# Density of states → Helmholz free energy for electrons in metals

The Helmholz free energy for electrons in metals is defined as:
## $f~=~\phi~+~\mu n$
with the grand potential density $\phi$, the chemical potential $\mu$ and the electron density n.

The calculation can therefore be carried out in two sub-steps: first the chemical potential is determined, then the grand potential. 

#### Calculation of the chemical potential

The chemical potential is implicitly defined by the electron density, which is given as the integral of the density of states times the probability that these states are occupied (the Fermi function):

### $n~ = ~ \int\limits_{-\infty}^\infty D(E)f(E) dE~=~\int\limits_{-\infty}^\infty \frac{D(E)}{exp\left(\frac{E-\mu}{k_B~T}\right)+1} dE$

If the density of states and the electron density of the metal is known, the chemical potential can be calculated based on the formular above. <br>
A more detailed description of the procedure can be found [here](http://lampx.tugraz.at/~hadley/ss1/materials/thermo/dos2mu.html?)

#### Calculation of the grand potential density

The grand potential can be derived by the grand partition function (a derivation can be found [here](http://lampx.tugraz.at/~hadley/ss2/fermigas/thermo/thermo.php)):

### $\phi~ = ~ -k_BT\int\limits_{-\infty}^\infty D(E)~ln\left(exp\left(-\frac{E-\mu}{k_B~T}\right)+1\right) dE$

since the chemical potential is known from the calculation above, the integral can be calculated rather simple.<br>
A more detailed description of the procedure can be found [here](http://lampx.tugraz.at/~hadley/ss1/materials/thermo/gp/gp/dos2phi.html?)

#### Explanation of the User Interface
The density of states is input as two columns of text in the textbox below. The first column is the energy in eV. The second column is the density of states in unit of eV-1 m-d, where d is the dimensionality. After the 'D(E) → f(T)' button is pressed, the density of states is plotted over the energy and the Helmholz free energy is plotted over temperature.<br>
Below are some buttons to load predefined data of the free electron model and some tight binding calculations.
At the bottom of the page you have the option to display the Python code of the jupyter notebook.

In [1]:
%matplotlib inline
from ipywidgets.widgets import Label, Button, Textarea, Output, Text #import all different widgets used
from ipywidgets.widgets import Layout, HBox, VBox #import layout settings
from IPython.display import Javascript, display, clear_output, HTML #some disp properties
import matplotlib.pyplot as plt
import numpy as np



In [2]:
def calcutlation(DOS,E,num_electrons,volume_unit,T_min,T_max):
    ec=1.602e-19
    E=E*ec
    DOS=DOS/ec
    nume=num_electrons
    vol=volume_unit
    k_B=1.38064852e-23
    n0= nume/vol
    K=np.zeros(np.size(DOS))
    Efi=0

    flag=2

    Efi=-1
    for i in range(1,np.size(DOS)):
        K[i] = K[i-1] + 0.5*(DOS[i]+DOS[i-1])*(E[i]-E[i-1])     #trapizoidal rule
        if ((K[i] > n0) and flag >0):
          Efi = i-1
          flag=0

    Ef = E[Efi]+ 2*(n0-K[Efi])/(DOS[Efi+1]+DOS[Efi])
    Ef=Ef




    def interval(mu,T,E,K,i):
      x1 = (E[i]-mu)/(k_B*T)
      x2 = (E[i+1]-mu)/(k_B*T)
      b = (K[i+1]-K[i])/(E[i+1]-E[i])
      It = (b*(E[i+1]-mu)*np.exp(x2)+b*(E[i]-mu)-K[i])/(np.exp(x2)+1)-k_B*T*b*np.log(np.exp(x2)+1)
      It = It - (b*(E[i]-mu)*np.exp(x1)+b*(E[i]-mu)-K[i])/(np.exp(x1)+1)+k_B*T*b*np.log(np.exp(x1)+1)
      return It

    def findmu(mu):
        mui=np.argmin(np.abs(mu-E))   
        if T==0:
            n = K[mui]+(K[mui+1]-K[mui])*(Ef-E[mui])/(E[mui+1]-E[mui])  
            #print(n)
        else:
            bound=np.int(32*k_B*T/(E[mui+2]-E[mui]))+1   
            n=0
            for i in range(-bound,bound+1,1):
                n=n+interval(mu,T,E,K,mui+i)
        f=n0-n
        return f

    mu_0=Ef*0.8
    mu_1=Ef
    mu_2=Ef
    T=0
    f0=findmu(mu_0)
    mu_fin=[]
    step_T=(T_max-T_min)/np.size(E)
    for T_i in range(np.size(E)):
        #print(find_mu(mu_guess))
        T=step_T*T_i
        f1=findmu(mu_1)
        #print(f1-f0)
        while (np.abs(f1/n0) > 1E-5):
            mu_2 = mu_1 - f1*(mu_1-mu_0)/np.float(f1-f0) #  //secant method     #dividing by 0???
            #mui2 = np.argmin(np.abs(mu_2-E*ec))
            f0 = f1
            f1 = findmu(mu_2)
            mu_0 = mu_1
            mu_1 = mu_2
            #mui1 = mui2
        mu_fin.append(mu_2)

    mu=np.array(mu_fin)
    T=np.linspace(T_min,T_max-1,np.int((T_max-T_min)/step_T))
    # now calculate grand potential

    K_2=np.zeros(np.size(DOS))
    K_int=-K#since we want to integrate over negative K
    for i in range(np.size(K_2)-1):
        K_2[i+1] = K_2[i] + 0.5*(K_int[i+1]+K_int[i])*(E[i+1]-E[i])     #trapizoidal rule

    # lets calculate the grand potential over a sum

    phi_k=[]
    for k in range(np.int((T_max-T_min)/step_T)):
        T_int=T[k]
        mu_int=mu[k]
        mui=np.argmin(np.abs(mu_int-E))   
        if T_int==0:
            phi = K_2[mui]+(K_2[mui+1]-K_2[mui])*(Ef-E[mui])/(E[mui+1]-E[mui])   
        else:
            bound=np.int(64*k_B*T_int/(E[mui]-E[mui-2]))+1   
            phi=0
            for i in range(-bound,bound+1,1):
                phi=phi+interval(mu_int,T_int,E,K_2,mui+i)

        phi_k.append(phi)
    phi=np.array(phi_k)
    phi=phi/ec
    mu=mu/ec
    f=phi+mu*n0
    return f,T

In [3]:
#########################################################################################################
##########################################   GUI    #####################################################
#########################################################################################################



#############################################DEFINE BUTTONS##############################################

#Button -> when pressed calculate Entropy from DOS in DOS_input -> write values in DOS_output and actualize plots
button_calc = Button(
    description='D(E) -> f(T)',
    disabled=False,
    button_style='', # 'success', 'info', 'warning', 'danger' or ''
    tooltip='Calculate Entropy',
    icon='' # (FontAwesome names without the `fa-` prefix)
)

############## DEFINE UNITS
vol_unit_3d='[$m^3$]'
vol_unit_2d='[$m^2$]'
vol_unit_1d='[$m^1$]'

DOS_unit_3d='[$eV^{-1}m^{-3}$]'
DOS_unit_2d='[$eV^{-1}m^{-2}$]'
DOS_unit_1d='[$eV^{-1}m^{-1}$]'

f_unit_3d='[$eVm^{-3}$]'
f_unit_2d='[$eVm^{-2}$]'
f_unit_1d='[$eVm^{-1}$]'

vol_unit=vol_unit_3d #default
DOS_unit=DOS_unit_3d #default
f_unit=f_unit_3d #default


#Button -> give predefined DOS over E -> default is 3Dim electron gas
#FREE ELECTRON MODEL
# 1 Dim electron gas
DOS_free_e_1='-0.1175094851155327\t0\n0\t0\n0.009400758809242618\t16819268126.841518\n0.018801517618485235\t11893018547.084398\n0.02820227642772785\t9710608980.604445\n0.03760303523697047\t8409634063.420759\n0.047003794046213083\t7521805372.682639\n0.0564045528554557\t6866437459.63639\n0.06580531166469832\t6357085813.962547\n0.07520607047394094\t5946509273.542199\n0.08460682928318355\t5606422708.947173\n0.09400758809242617\t5318719585.789301\n0.1034083469016688\t5071200147.737909\n0.1128091057109114\t4855304490.302222\n0.12220986452015403\t4664825665.161866\n0.13161062332939663\t4495138487.63772\n0.14101138213863926\t4342716356.710295\n0.15041214094788188\t4204817031.7103796\n0.1598128997571245\t4079271707.7971816\n0.1692136585663671\t3964339515.6947994\n0.17861441737560976\t3858604740.4850955\n0.18801517618485233\t3760902686.3413196\n0.19741593499409493\t3670265205.9528284\n0.2068166938033376\t3585880013.219698\n0.21621745261258024\t3507059838.3371925\n0.2256182114218228\t3433218729.818195\n0.2350189702310654\t3363853625.368304\n0.24441972904030806\t3298529860.8890023\n0.2538204878495507\t3236869660.201481\n0.26322124665879326\t3178542906.9812737\n0.2726220054680359\t3123259682.7043457\n0.2820227642772785\t3070764184.599587\n0.29142352308652114\t3020829731.7906795\n0.30082428189576377\t2973254636.7710996\n0.31022504070500634\t2927858770.410952\n0.319625799514249\t2884480686.8858156\n0.3290265583234916\t2842975203.7639675\n0.3384273171327342\t2803211354.4735866\n0.34782807594197684\t2765070647.2700195\n0.3572288347512195\t2728445577.91557\n0.3666295935604621\t2693238353.5038786\n0.37603035236970467\t2659359792.8946505\n0.38543111117894724\t2626728375.581969\n0.39483186998818987\t2595269415.882285\n0.40423262879743255\t2564914343.3840775\n0.4136333876066752\t2535600073.8689547\n0.4230341464159178\t2507268457.5608797\n0.4324349052251605\t2479865793.7152257\n0.44183566403440305\t2453342402.322547\n0.4512364228436456\t2427652245.151111\n0.4606371816528882\t2402752589.5487885\n0.4700379404621308\t2378603709.4168797\n0.4794386992713735\t2355168618.594327\n0.48883945808061613\t2332412832.580933\n0.4982402168898587\t2310304155.1071615\n0.5076409756991014\t2288812486.545463\n0.5170417345083439\t2267909651.569789\n0.5264424933175865\t2247569243.81886\n0.5358432521268292\t2227766485.615436\n0.5452440109360718\t2208478101.0467877\n0.5546447697453144\t2189682200.9279785\n0.564045528554557\t2171358178.3551474\n0.5734462873637997\t2153486613.715592\n0.5828470461730423\t2136049188.1591291\n0.5922478049822849\t2119028604.6541827\n0.6016485637915275\t2102408515.8551898\n0.61104932260077\t2086173458.0975213\n0.6204500814100127\t2070308790.9140913\n0.6298508402192554\t2054800641.5359428\n0.639251599028498\t2039635853.8985908\n0.6486523578377406\t2024801941.7281039\n0.6580531166469832\t2010287045.3267083\n0.6674538754562258\t1996079891.7180002\n0.6768546342654684\t1982169757.8473997\n0.6862553930747111\t1968546436.5648456\n0.6956561518839537\t1955200205.1445072\n0.7050569106931963\t1942121796.1208887\n0.714457669502439\t1929302370.2425478\n0.7238584283116815\t1916733491.3640747\n0.7332591871209242\t1904407103.1142845\n0.7426599459301667\t1892315507.1940103\n0.7520607047394093\t1880451343.1706598\n0.7614614635486521\t1868807569.6490576\n0.7708622223578945\t1857377446.7091348\n0.7802629811671373\t1846154519.5109448\n0.7896637399763797\t1835132602.9764142\n0.7990644987856225\t1824305767.4652312\n0.8084652575948651\t1813668325.369522\n0.8178660164041076\t1803214818.558459\n0.8272667752133503\t1792940006.609849\n0.836667534022593\t1782838855.7710552\n0.8460682928318356\t1772906528.5964336\n0.8554690516410781\t1763138374.2128227\n0.864869810450321\t1753529919.1685963\n0.8742705692595634\t1744076858.8253741\n0.8836713280688061\t1734775049.254768\n0.8930720868780486\t1725620499.6055217\n0.9024728456872912\t1716609364.9090974\n0.911873604496534\t1707737939.2942646\n0.9212743633057764\t1699002649.5834856\n0.9306751221150192\t1690400049.24597\n0.9400758809242616\t1681926812.684152\n0.9494766397335044\t1673579729.8320813\n0.958877398542747\t1665355701.045802\n0.9682781573519895\t1657251732.267246\n0.9776789161612323\t1649264930.4445012\n0.9870796749704749\t1641392499.1925576\n0.9964804337797174\t1633631734.6797311\n1.0058811925889601\t1625980021.7260406\n1.0152819513982028\t1618434830.1007404\n1.0246827102074452\t1610993711.0071127\n1.0340834690166878\t1603654293.7434177\n1.0434842278259304\t1596414282.5296783\n1.052884986635173\t1589271453.4906368\n1.062285745444416\t1582223651.7858913\n1.0716865042536583\t1575268788.8787982\n1.0810872630629011\t1568404839.9362772\n1.0904880218721436\t1561629841.3521729\n1.0998887806813862\t1554941888.387289\n1.1092895394906288\t1548339132.9196582\n1.1186902982998714\t1541819781.299012\n1.128091057109114\t1535382092.2997935\n1.1374918159183567\t1529024375.1674109\n1.1468925747275993\t1522744987.7527502\n1.156293333536842\t1516542334.730278\n1.1656940923460846\t1510414865.8953397\n1.1750948511553272\t1504361074.5365279\n1.1844956099645698\t1498379495.87924\n1.1938963687738124\t1492468705.5967789\n1.203297127583055\t1486627318.3855498\n1.2126978863922977\t1480853986.601129\n1.22209864520154\t1475147398.9521472\n1.2314994040107827\t1469506279.2491133\n1.2409001628200254\t1463929385.205476\n1.250300921629268\t1458415507.2883554\n1.2597016804385108\t1452963467.6165333\n1.2691024392477532\t1447572118.9034314\n1.278503198056996\t1442240343.4429078\n1.2879039568662387\t1436967052.1358495\n1.2973047156754811\t1431751183.555631\n1.3067054744847237\t1426591703.0506155\n1.3161062332939664\t1421487601.8819838\n1.325506992103209\t1416437896.3952456\n1.3349077509124516\t1411441627.2239075\n1.3443085097216942\t1406497858.523815\n1.3537092685309369\t1401605677.2367933\n1.3631100273401797\t1396764192.382268\n1.3725107861494221\t1391972534.375616\n1.381911544958665\t1387229854.3720632\n1.3913123037679074\t1382535323.6350098\n1.40071306257715\t1377888132.9277062\n1.4101138213863926\t1373287491.927278\n1.4195145801956353\t1368732628.6601248\n1.428915339004878\t1364222788.957785\n1.4383160978141203\t1359757235.9323938\n1.447716856623363\t1355335249.4709039\n1.4571176154326058\t1350956125.7472835\n1.4665183742418484\t1346619176.7519393\n1.475919133051091\t1342323729.837653\n1.4853198918603334\t1338069127.2813458\n1.4947206506695763\t1333854725.8610306\n1.5041214094788187\t1329679896.4473252\n1.5135221682880613\t1325544023.6089427\n1.5229229270973041\t1321446505.2316\n1.5323236859065466\t1317386752.1497998\n1.541724444715789\t1313364187.7909844\n1.5511252035250318\t1309378247.8315678\n1.5605259623342747\t1305428379.8643813\n1.569926721143517\t1301514043.077088\n1.5793274799527595\t1297634707.9411426\n1.5887282387620023\t1293789855.9108863\n1.598128997571245\t1289978979.1323938\n1.6075297563804876\t1286201580.1616986\n1.6169305151897302\t1282457171.6920388\n1.626331273998973\t1278745276.28979\n1.6357320328082152\t1275065426.1387565\n1.6451327916174578\t1271417162.7925093\n1.6545335504267007\t1267800036.9344773\n1.6639343092359433\t1264213608.1455007\n1.673335068045186\t1260657444.6785781\n1.6827358268544284\t1257131123.240547\n1.6921365856636712\t1253634228.7804399\n1.7015373444729138\t1250166354.2842844\n1.7109381032821562\t1246727100.5761116\n1.720338862091399\t1243316076.1249526\n1.729739620900642\t1239932896.8576128\n1.739140379709884\t1236577185.9770215\n1.7485411385191267\t1233248573.785955\n1.7579418973283696\t1229946697.515958\n1.7673426561376122\t1226671201.1612735\n1.7767434149468548\t1223421735.3176093\n1.7861441737560972\t1220197957.0255826\n1.7955449325653399\t1216999529.618676\n1.8049456913745825\t1213826122.5755556\n1.8143464501838251\t1210677411.376602\n1.823747208993068\t1207553077.364515\n1.8331479678023104\t1204452807.6088564\n1.8425487266115528\t1201376294.7743943\n1.8519494854207956\t1198323236.993133\n1.8613502442300385\t1195293337.7398994\n1.8707510030392809\t1192286305.7113714\n1.8801517618485233\t1189301854.7084398\n1.8895525206577661\t1186339703.5217924\n1.8989532794670088\t1183399575.8206148\n1.9083540382762512\t1180481200.0443141\n1.917754797085494\t1177584309.2971635\n1.9271555558947369\t1174708641.2457762\n1.936556314703979\t1171853938.0193222\n1.9459570735132217\t1169019946.1123974\n1.9553578323224645\t1166206416.2904665\n1.9647585911317071\t1163413103.497794\n1.9741593499409498\t1160639766.7677922\n1.9835601087501922\t1157886169.135709\n1.9929608675594348\t1155152077.5535808\n2.0023616263686774\t1152437262.8073866\n2.0117623851779203\t1149741499.4363332\n2.0211631439871627\t1147064565.654207\n2.0305639027964055\t1144406243.2727315\n2.039964661605648\t1141766317.6268694\n2.0493654204148903\t1139144577.5020106\n2.058766179224133\t1136540815.062992\n2.0681669380333756\t1133954825.7848945\n2.0775676968426184\t1131386408.385561\n2.086968455651861\t1128835364.7597926\n2.0963692144611037\t1126301499.915166\n2.105769973270346\t1123784621.90943\n2.115170732079589\t1121284541.7894347\n2.124571490888832\t1118801073.5315466\n2.1339722496980738\t1116334033.9835112\n2.1433730085073166\t1113883242.807718\n2.1527737673165595\t1111448522.4258313\n2.1621745261258023\t1109029697.9647431\n2.1715752849350447\t1106626597.2038198\n2.180976043744287\t1104239050.5233939\n2.19037680255353\t1101866890.8544796\n2.1997775613627724\t1099509953.6296675\n2.209178320172015\t1097168076.7351708\n2.2185790789812576\t1094841100.4639893\n2.2279798377905005\t1092528867.470165\n2.237380596599743\t1090231222.724091\n2.2467813554089853\t1087948013.4688532\n2.256182114218228\t1085679089.1775737\n2.2655828730274705\t1083424301.5117254\n2.2749836318367134\t1081183504.2804\n2.2843843906459558\t1078956553.4004936\n2.2937851494551986\t1076743306.857796\n2.303185908264441\t1074543624.6689484\n2.312586667073684\t1072357368.8442587\n2.3219874258829267\t1070184403.351341\n2.331388184692169\t1068024594.0795646\n2.3407889435014115\t1065877808.8052883\n2.3501897023106544\t1063743917.15786\n2.3595904611198972\t1061622790.5863639\n2.3689912199291396\t1059514302.3270913\n2.3783919787383825\t1057418327.3717214\n2.387792737547625\t1055334742.4361913\n2.3971934963568673\t1053263425.9302381\n2.40659425516611\t1051204257.9275949\n2.4159950139753525\t1049157120.1368275\n2.4253957727845954\t1047121895.8727914\n2.434796531593838\t1045098470.0286957\n2.44419729040308\t1043086729.0487607\n2.453598049212323\t1041086560.9014485\n2.4629988080215655\t1039097855.0532602\n2.4723995668308083\t1037120502.4430784\n2.4818003256400507\t1035154395.4570457\n2.4912010844492936\t1033199427.9039663\n2.500601843258536\t1031255494.9912149\n2.510002602067779\t1029322493.301143\n2.5194033608770217\t1027400320.7679714\n2.528804119686264\t1025488876.6551523\n2.5382048784955065\t1023588061.5331957\n2.5476056373047493\t1021697777.2579457\n2.557006396113992\t1019817926.9492954\n2.5664071549232346\t1017948414.9703323\n2.5758079137324774\t1016089146.9069023\n2.58520867254172\t1014240029.5475823\n2.5946094313509622\t1012400970.8640519\n2.604010190160205\t1010571879.991858\n2.6134109489694475\t1008752667.211556\n2.6228117077786903\t1006943243.9302264\n2.6322124665879327\t1005143522.6633542\n2.641613225397175\t1003353417.0170606\n2.651013984206418\t1001572841.6706866\n2.6604147430156604\t999801712.3597109\n2.6698155018249032\t998039945.8590001\n2.679216260634146\t996287459.9663845\n2.6886170194433885\t994544173.4865468\n2.698017778252631\t992810006.2152222\n2.7074185370618737\t991084878.9236999\n2.716819295871116\t989368713.3436188\n2.7262200546803594\t987661432.1520532\n2.735620813489602\t985962958.9568805\n2.7450215722988442\t984273218.2824228\n2.7544223311080867\t982592135.5553615\n2.76382308991733\t980919637.0909128\n2.7732238487265723\t979255650.0792626\n2.7826246075358148\t977600102.5722536\n2.7920253663450576\t975952923.4703174\n2.8014261251543\t974314042.509652\n2.810826883963542\t972683390.2496307\n2.8202276427727853\t971060898.0604444\n2.8296284015820277\t969446498.110971\n2.8390291603912705\t967840123.3568627\n2.848429919200513\t966241707.5288533\n2.857830678009756\t964651185.1212739\n2.8672314368189986\t963068491.3807788\n2.8766321956282406\t961493562.2952719\n2.8860329544374834\t959926334.5830327\n2.895433713246726\t958366745.6820374\n2.904834472055969\t956814733.739468\n2.9142352308652115\t955270237.6014103\n2.923635989674454\t953733196.8027323\n2.9330367484836968\t952203551.5571423\n2.9424375072929387\t950681242.7474204\n2.951838266102182\t949166211.9158235\n2.9612390249114244\t947658401.2546558\n2.970639783720667\t946157753.5970051\n2.9800405425299097\t944664212.4076389\n2.9894413013391525\t943177721.774058\n2.9988420601483954\t941698226.3977065\n3.0082428189576373\t940225671.5853299\n3.0176435777668797\t938760003.240483\n3.0270443365761226\t937301167.8551844\n3.0364450953853654\t935849112.5017102\n3.0458458541946083\t934403784.8245288\n3.0552466130038507\t932965133.0323733\n3.064647371813093\t931533105.8904449\n3.0740481306223355\t930107652.7127507\n3.083448889431578\t928688723.3545674\n3.092849648240821\t927276268.2050331\n3.1022504070500636\t925870238.1798614\n3.111651165859306\t924470584.7141776\n3.1210519246685493\t923077259.7554724\n3.1304526834777917\t921690215.7566731\n3.139853442287034\t920309405.6693293\n3.1492542010962765\t918934782.9369093\n3.158654959905519\t917566301.4882071\n3.168055718714762\t916203915.7308569\n3.1774564775240046\t914847580.5449538\n3.1868572363332475\t913497251.276777\n3.19625799514249\t912152883.7326156\n3.205658753951733\t910814434.1726928\n3.215059512760975\t909481859.30519\n3.2244602715702175\t908155116.2803638\n3.2338610303794604\t906834162.684761\n3.243261789188703\t905518956.5355214\n3.252662547997946\t904209456.2747756\n3.2620633068071885\t902905620.7641281\n3.2714640656164304\t901607409.2792295\n3.2808648244256733\t900314781.5044348\n3.2902655832349157\t899027697.5275441\n3.299666342044159\t897746117.8346263\n3.3090671008534014\t896470003.3049245\n3.318467859662644\t895199315.2058406\n3.3278686184718866\t893934015.1879964\n3.3372693772811286\t892674065.2803737\n3.346670136090372\t891419427.8855276\n3.3560708948996143\t890170065.7748744\n3.3654716537088567\t888925942.0840521\n3.3748724125180996\t887687020.3083514\n3.3842731713273424\t886453264.2982168\n3.3936739301365852\t885224638.2548169\n3.4030746889458277\t884001106.7256812\n3.4124754477550696\t882782634.6004041\n3.4218762065643125\t881569187.1064113\n3.4312769653735553\t880360729.8047944\n3.440677724182798\t879157228.5862036\n3.4500784829920406\t877958649.6668053\n3.459479241801284\t876764959.5842981\n3.4688800006105263\t875576125.1939896\n3.478280759419768\t874392113.6649305\n3.487681518229011\t873212892.4761063\n3.4970822770382535\t872038429.4126871\n3.5064830358474968\t870868692.5623287\n3.515883794656739\t869703650.3115333\n3.5252845534659816\t868543271.342059\n3.5346853122752244\t867387524.627384\n3.5440860710844664\t866236379.4292237\n3.5534868298937097\t865089805.2940949\n3.562887588702952\t863947772.0499341\n3.5722883475121945\t862810249.8027608\n3.5816891063214373\t861677208.9333925\n3.5910898651306797\t860548620.0942044\n3.600490623939923\t859424454.2059368\n3.609891382749165\t858304682.4545487\n3.6192921415584074\t857189276.2881153\n3.6286929003676502\t856078207.4137704\n3.6380936591768926\t854971447.7946925\n3.647494417986136\t853868969.6471323\n3.6568951767953783\t852770745.4374843\n3.6662959356046207\t851676747.8793983\n3.675696694413863\t850586949.930932\n3.6850974532231056\t849501324.7917428\n3.694498212032349\t848419845.9003209\n3.7038989708415913\t847342486.9312587\n3.7132997296508337\t846269221.7925599\n3.722700488460077\t845200024.622985\n3.7321012472693194\t844134869.7894347\n3.7415020060785618\t843073731.8843677\n3.750902764887804\t842016585.7232566\n3.7603035236970466\t840963406.342076\n3.7697042825062894\t839914168.9948276\n3.7791050413155323\t838868849.1510979\n3.788505800124775\t837827422.493648\n3.7979065589340175\t836789864.9160407\n3.80730731774326\t835756152.5202931\n3.8167080765525023\t834726261.614568\n3.826108835361745\t833700168.7108908\n3.835509594170988\t832677850.522901\n3.8449103529802304\t831659283.9636327\n3.8543111117894737\t830644446.1433235\n3.863711870598716\t829633314.3672556\n3.873112629407958\t828625866.133623\n3.882513388217201\t827622079.1314284\n3.8919141470264433\t826621931.2384088\n3.9013149058356866\t825625400.5189868\n3.910715664644929\t824632465.2222506\n3.9201164234541714\t823643103.7799597\n3.9295171822634143\t822657294.8045766\n3.9389179410726562\t821675017.0873266\n3.9483186998818995\t820696249.5962788\n3.957719458691142\t819720971.4744576\n3.9671202175003843\t818749162.0379736\n3.976520976309627\t817780800.7741823\n3.9859217351188696\t816815867.3398656\n3.995322493928113\t815854341.5594362\n4.004723252737355\t814896203.4231665\n4.014124011546597\t813941433.085439\n4.0235247703558406\t812990010.8630203\n4.032925529165083\t812041917.2333568\n4.042326287974325\t811097132.8328916\n4.051727046783568\t810155638.4554042\n4.061127805592811\t809217415.0503702\n4.0705285644020535\t808282443.7213428\n4.079929323211296\t807350705.7243528\n4.089330082020538\t806422182.4663328\n4.098730840829781\t805496855.5035564\n4.108131599639024\t804574706.5401008\n4.117532358448266\t803655717.4263275\n4.126933117257509\t802739870.1573813\n4.136333876066751\t801827146.8717089\n4.145734634875994\t800917529.8495963\n4.155135393685237\t800011001.5117227\n4.164536152494479\t799107544.4177356\n4.173936911303722\t798207141.2648392\n4.183337670112965\t797309774.8864044\n4.192738428922207\t796415428.2505934\n4.20213918773145\t795524084.459002\n4.211539946540692\t794635726.7453184\n4.220940705349935\t793750338.4739991\n4.230341464159178\t792867903.1389599\n4.23974222296842\t791988404.3622843\n4.249142981777664\t791111825.8929456\n4.258543740586906\t790238151.605547\n4.2679444993961475\t789367365.4990746\n4.277345258205391\t788499451.6956667\n4.286746017014633\t787634394.4393991\n4.2961467758238765\t786772178.0950819\n4.305547534633119\t785912787.1470737\n4.314948293442361\t785056206.198109\n4.324349052251605\t784202419.9681386\n4.333749811060846\t783351413.293186\n4.343150569870089\t782503171.124215\n4.352551328679332\t781657678.5260133\n4.361952087488574\t780814920.6760864\n4.3713528462978175\t779974882.863568\n4.38075360510706\t779137550.4881399\n4.390154363916302\t778302909.0589672\n4.399555122725545\t777470944.1936445\n4.408955881534788\t776641641.6171547\n4.41835664034403\t775814987.1608416\n4.427757399153273\t774990966.7613913\n4.437158157962515\t774169566.4598291\n4.446558916771758\t773350772.4005249\n4.455959675581001\t772534570.8302126\n4.465360434390243\t771720948.0970192\n4.474761193199486\t770909890.649506\n4.484161952008728\t770101385.0357206\n4.4935627108179705\t769295417.9022596\n4.502963469627214\t768491975.9933428\n4.512364228436456\t767691046.1498967\n4.521764987245699\t766892615.3086505\n4.531165746054941\t766096670.5012398\n4.5405665048641835\t765303198.8533229\n4.549967263673427\t764512187.5837054\n4.559368022482669\t763723624.003477\n4.5687687812919116\t762937495.5151545\n4.578169540101155\t762153789.611838\n4.587570298910397\t761372493.8763751\n4.59697105771964\t760593595.9805337\n4.606371816528882\t759817083.6841857\n4.6157725753381245\t759042944.8344992\n4.625173334147368\t758271167.365139\n4.63457409295661\t757501739.2954774\n4.6439748517658535\t756734648.7298126\n4.653375610575096\t755969883.8565962\n4.662776369384338\t755207432.9476699\n4.672177128193581\t754447284.3575094\n4.681577887002823\t753689426.5224776\n4.690978645812066\t752933847.9600861\n4.700379404621309\t752180537.2682639\n'
num_free_e_1='1'
vol_free_e_1='2e-10'
button_1dime = Button(
    description='1D',
    disabled=False,
    button_style='', # 'success', 'info', 'warning', 'danger' or ''
    tooltip='1 Dim electron gas',
    icon='' # (FontAwesome names without the `fa-` prefix)
)
# 2 Dim electron gas
DOS_free_e_2='-1.196941786644515\t0\n0\t0\n0\t4177312594304950000\n0.1915106858631224\t4177312594304950000\n0.2872660287946836\t4177312594304950000\n0.3830213717262448\t4177312594304950000\n0.47877671465780597\t4177312594304950000\n0.5745320575893672\t4177312594304950000\n0.6702874005209284\t4177312594304950000\n0.7660427434524896\t4177312594304950000\n0.8617980863840506\t4177312594304950000\n0.9575534293156119\t4177312594304950000\n1.0533087722471732\t4177312594304950000\n1.1490641151787344\t4177312594304950000\n1.2448194581102954\t4177312594304950000\n1.3405748010418568\t4177312594304950000\n1.436330143973418\t4177312594304950000\n1.5320854869049791\t4177312594304950000\n1.6278408298365403\t4177312594304950000\n1.7235961727681013\t4177312594304950000\n1.8193515156996627\t4177312594304950000\n1.9151068586312239\t4177312594304950000\n2.010862201562785\t4177312594304950000\n2.1066175444943465\t4177312594304950000\n2.2023728874259074\t4177312594304950000\n2.298128230357469\t4177312594304950000\n2.39388357328903\t4177312594304950000\n2.4896389162205907\t4177312594304950000\n2.585394259152152\t4177312594304950000\n2.6811496020837136\t4177312594304950000\n2.7769049450152745\t4177312594304950000\n2.872660287946836\t4177312594304950000\n2.9684156308783964\t4177312594304950000\n3.0641709738099583\t4177312594304950000\n3.1599263167415197\t4177312594304950000\n3.2556816596730807\t4177312594304950000\n3.3514370026046416\t4177312594304950000\n3.4471923455362026\t4177312594304950000\n3.542947688467764\t4177312594304950000\n3.6387030313993254\t4177312594304950000\n3.7344583743308863\t4177312594304950000\n3.8302137172624477\t4177312594304950000\n3.925969060194009\t4177312594304950000\n4.02172440312557\t4177312594304950000\n4.117479746057131\t4177312594304950000\n4.213235088988693\t4177312594304950000\n4.308990431920253\t4177312594304950000\n4.404745774851815\t4177312594304950000\n4.500501117783376\t4177312594304950000\n4.596256460714938\t4177312594304950000\n4.692011803646499\t4177312594304950000\n4.78776714657806\t4177312594304950000\n4.8835224895096205\t4177312594304950000\n4.9792778324411815\t4177312594304950000\n5.075033175372743\t4177312594304950000\n5.170788518304304\t4177312594304950000\n5.266543861235865\t4177312594304950000\n5.362299204167427\t4177312594304950000\n5.458054547098988\t4177312594304950000\n5.553809890030549\t4177312594304950000\n5.64956523296211\t4177312594304950000\n5.745320575893672\t4177312594304950000\n5.841075918825232\t4177312594304950000\n5.936831261756793\t4177312594304950000\n6.0325866046883565\t4177312594304950000\n6.128341947619917\t4177312594304950000\n6.2240972905514775\t4177312594304950000\n6.319852633483039\t4177312594304950000\n6.4156079764146\t4177312594304950000\n6.511363319346161\t4177312594304950000\n6.607118662277723\t4177312594304950000\n6.702874005209283\t4177312594304950000\n6.798629348140844\t4177312594304950000\n6.894384691072405\t4177312594304950000\n6.990140034003967\t4177312594304950000\n7.085895376935528\t4177312594304950000\n7.181650719867088\t4177312594304950000\n7.277406062798651\t4177312594304950000\n7.373161405730213\t4177312594304950000\n7.468916748661773\t4177312594304950000\n7.564672091593335\t4177312594304950000\n7.6604274345248955\t4177312594304950000\n7.7561827774564565\t4177312594304950000\n7.851938120388018\t4177312594304950000\n7.947693463319579\t4177312594304950000\n8.04344880625114\t4177312594304950000\n8.139204149182701\t4177312594304950000\n8.234959492114262\t4177312594304950000\n8.330714835045823\t4177312594304950000\n8.426470177977386\t4177312594304950000\n8.522225520908945\t4177312594304950000\n8.617980863840506\t4177312594304950000\n8.713736206772067\t4177312594304950000\n8.80949154970363\t4177312594304950000\n8.90524689263519\t4177312594304950000\n9.001002235566752\t4177312594304950000\n9.096757578498314\t4177312594304950000\n9.192512921429875\t4177312594304950000\n9.288268264361434\t4177312594304950000\n9.384023607292997\t4177312594304950000\n9.479778950224558\t4177312594304950000\n9.57553429315612\t4177312594304950000\n9.67128963608768\t4177312594304950000\n9.767044979019241\t4177312594304950000\n9.862800321950802\t4177312594304950000\n9.958555664882363\t4177312594304950000\n10.054311007813926\t4177312594304950000\n10.150066350745487\t4177312594304950000\n10.245821693677048\t4177312594304950000\n10.341577036608609\t4177312594304950000\n10.43733237954017\t4177312594304950000\n10.53308772247173\t4177312594304950000\n10.628843065403293\t4177312594304950000\n10.724598408334854\t4177312594304950000\n10.820353751266413\t4177312594304950000\n10.916109094197976\t4177312594304950000\n11.011864437129537\t4177312594304950000\n11.107619780061098\t4177312594304950000\n11.203375122992659\t4177312594304950000\n11.29913046592422\t4177312594304950000\n11.394885808855783\t4177312594304950000\n11.490641151787344\t4177312594304950000\n11.586396494718903\t4177312594304950000\n11.682151837650464\t4177312594304950000\n11.777907180582025\t4177312594304950000\n11.873662523513586\t4177312594304950000\n11.969417866445148\t4177312594304950000\n12.065173209376713\t4177312594304950000\n12.160928552308272\t4177312594304950000\n12.256683895239833\t4177312594304950000\n12.352439238171394\t4177312594304950000\n12.448194581102955\t4177312594304950000\n12.543949924034516\t4177312594304950000\n12.639705266966079\t4177312594304950000\n12.73546060989764\t4177312594304950000\n12.8312159528292\t4177312594304950000\n12.926971295760762\t4177312594304950000\n13.022726638692323\t4177312594304950000\n13.118481981623882\t4177312594304950000\n13.214237324555446\t4177312594304950000\n13.309992667487007\t4177312594304950000\n13.405748010418566\t4177312594304950000\n13.501503353350127\t4177312594304950000\n13.597258696281688\t4177312594304950000\n13.69301403921325\t4177312594304950000\n13.78876938214481\t4177312594304950000\n13.884524725076373\t4177312594304950000\n13.980280068007934\t4177312594304950000\n14.076035410939495\t4177312594304950000\n14.171790753871056\t4177312594304950000\n14.267546096802617\t4177312594304950000\n14.363301439734176\t4177312594304950000\n14.45905678266574\t4177312594304950000\n14.554812125597302\t4177312594304950000\n14.65056746852886\t4177312594304950000\n14.746322811460425\t4177312594304950000\n14.842078154391986\t4177312594304950000\n14.937833497323545\t4177312594304950000\n15.03358884025511\t4177312594304950000\n15.12934418318667\t4177312594304950000\n15.22509952611823\t4177312594304950000\n15.320854869049791\t4177312594304950000\n15.416610211981352\t4177312594304950000\n15.512365554912913\t4177312594304950000\n15.608120897844474\t4177312594304950000\n15.703876240776037\t4177312594304950000\n15.799631583707598\t4177312594304950000\n15.895386926639159\t4177312594304950000\n15.99114226957072\t4177312594304950000\n16.08689761250228\t4177312594304950000\n16.18265295543384\t4177312594304950000\n16.278408298365402\t4177312594304950000\n16.374163641296963\t4177312594304950000\n16.469918984228524\t4177312594304950000\n16.565674327160085\t4177312594304950000\n16.661429670091646\t4177312594304950000\n16.757185013023207\t4177312594304950000\n16.85294035595477\t4177312594304950000\n16.948695698886333\t4177312594304950000\n17.04445104181789\t4177312594304950000\n17.14020638474945\t4177312594304950000\n17.235961727681012\t4177312594304950000\n17.331717070612573\t4177312594304950000\n17.427472413544134\t4177312594304950000\n17.523227756475702\t4177312594304950000\n17.61898309940726\t4177312594304950000\n17.71473844233882\t4177312594304950000\n17.81049378527038\t4177312594304950000\n17.906249128201942\t4177312594304950000\n18.002004471133503\t4177312594304950000\n18.097759814065068\t4177312594304950000\n18.19351515699663\t4177312594304950000\n18.28927049992819\t4177312594304950000\n18.38502584285975\t4177312594304950000\n18.48078118579131\t4177312594304950000\n18.57653652872287\t4177312594304950000\n18.67229187165443\t4177312594304950000\n18.768047214585994\t4177312594304950000\n18.863802557517555\t4177312594304950000\n18.959557900449116\t4177312594304950000\n19.055313243380677\t4177312594304950000\n19.15106858631224\t4177312594304950000\n19.2468239292438\t4177312594304950000\n19.34257927217536\t4177312594304950000\n19.43833461510692\t4177312594304950000\n19.534089958038482\t4177312594304950000\n19.629845300970043\t4177312594304950000\n19.725600643901604\t4177312594304950000\n19.821355986833165\t4177312594304950000\n19.917111329764726\t4177312594304950000\n20.01286667269629\t4177312594304950000\n20.10862201562785\t4177312594304950000\n20.204377358559412\t4177312594304950000\n20.300132701490973\t4177312594304950000\n20.395888044422534\t4177312594304950000\n20.491643387354095\t4177312594304950000\n20.58739873028566\t4177312594304950000\n20.683154073217217\t4177312594304950000\n20.778909416148778\t4177312594304950000\n20.87466475908034\t4177312594304950000\n20.9704201020119\t4177312594304950000\n21.06617544494346\t4177312594304950000\n21.161930787875026\t4177312594304950000\n21.257686130806587\t4177312594304950000\n21.353441473738147\t4177312594304950000\n21.44919681666971\t4177312594304950000\n21.54495215960127\t4177312594304950000\n21.640707502532827\t4177312594304950000\n21.73646284546439\t4177312594304950000\n21.832218188395952\t4177312594304950000\n21.927973531327513\t4177312594304950000\n22.023728874259074\t4177312594304950000\n22.119484217190635\t4177312594304950000\n22.215239560122196\t4177312594304950000\n22.310994903053757\t4177312594304950000\n22.406750245985318\t4177312594304950000\n22.50250558891688\t4177312594304950000\n22.59826093184844\t4177312594304950000\n22.694016274780004\t4177312594304950000\n22.789771617711565\t4177312594304950000\n22.885526960643126\t4177312594304950000\n22.981282303574687\t4177312594304950000\n23.07703764650625\t4177312594304950000\n23.172792989437806\t4177312594304950000\n23.268548332369367\t4177312594304950000\n23.364303675300928\t4177312594304950000\n23.46005901823249\t4177312594304950000\n23.55581436116405\t4177312594304950000\n23.65156970409561\t4177312594304950000\n23.74732504702717\t4177312594304950000\n23.843080389958732\t4177312594304950000\n23.938835732890297\t4177312594304950000\n24.034591075821858\t4177312594304950000\n24.130346418753426\t4177312594304950000\n24.226101761684983\t4177312594304950000\n24.321857104616544\t4177312594304950000\n24.417612447548105\t4177312594304950000\n24.513367790479666\t4177312594304950000\n24.609123133411227\t4177312594304950000\n24.704878476342788\t4177312594304950000\n24.80063381927435\t4177312594304950000\n24.89638916220591\t4177312594304950000\n24.99214450513747\t4177312594304950000\n25.087899848069032\t4177312594304950000\n25.183655191000597\t4177312594304950000\n25.279410533932158\t4177312594304950000\n25.37516587686372\t4177312594304950000\n25.47092121979528\t4177312594304950000\n25.56667656272684\t4177312594304950000\n25.6624319056584\t4177312594304950000\n25.758187248589962\t4177312594304950000\n25.853942591521523\t4177312594304950000\n25.949697934453084\t4177312594304950000\n26.045453277384645\t4177312594304950000\n26.141208620316206\t4177312594304950000\n26.236963963247764\t4177312594304950000\n26.332719306179325\t4177312594304950000\n26.428474649110893\t4177312594304950000\n26.524229992042454\t4177312594304950000\n26.619985334974015\t4177312594304950000\n26.715740677905572\t4177312594304950000\n26.811496020837133\t4177312594304950000\n26.907251363768694\t4177312594304950000\n27.003006706700255\t4177312594304950000\n27.098762049631816\t4177312594304950000\n27.194517392563377\t4177312594304950000\n27.290272735494938\t4177312594304950000\n27.3860280784265\t4177312594304950000\n27.48178342135806\t4177312594304950000\n27.57753876428962\t4177312594304950000\n27.673294107221185\t4177312594304950000\n27.769049450152746\t4177312594304950000\n27.864804793084307\t4177312594304950000\n27.960560136015868\t4177312594304950000\n28.05631547894743\t4177312594304950000\n28.15207082187899\t4177312594304950000\n28.24782616481055\t4177312594304950000\n28.343581507742112\t4177312594304950000\n28.439336850673673\t4177312594304950000\n28.535092193605234\t4177312594304950000\n28.630847536536795\t4177312594304950000\n28.726602879468352\t4177312594304950000\n28.82235822239992\t4177312594304950000\n28.91811356533148\t4177312594304950000\n29.013868908263042\t4177312594304950000\n29.109624251194603\t4177312594304950000\n29.205379594126164\t4177312594304950000\n29.30113493705772\t4177312594304950000\n29.396890279989282\t4177312594304950000\n29.49264562292085\t4177312594304950000\n29.58840096585241\t4177312594304950000\n29.684156308783972\t4177312594304950000\n29.77991165171553\t4177312594304950000\n29.87566699464709\t4177312594304950000\n29.97142233757865\t4177312594304950000\n30.06717768051022\t4177312594304950000\n30.16293302344178\t4177312594304950000\n30.25868836637334\t4177312594304950000\n30.3544437093049\t4177312594304950000\n30.45019905223646\t4177312594304950000\n30.54595439516802\t4177312594304950000\n30.641709738099582\t4177312594304950000\n30.737465081031143\t4177312594304950000\n30.833220423962704\t4177312594304950000\n30.928975766894265\t4177312594304950000\n31.024731109825826\t4177312594304950000\n31.120486452757387\t4177312594304950000\n31.216241795688948\t4177312594304950000\n31.311997138620512\t4177312594304950000\n31.407752481552073\t4177312594304950000\n31.503507824483634\t4177312594304950000\n31.599263167415195\t4177312594304950000\n31.695018510346756\t4177312594304950000\n31.790773853278317\t4177312594304950000\n31.886529196209878\t4177312594304950000\n31.98228453914144\t4177312594304950000\n32.078039882073\t4177312594304950000\n32.17379522500456\t4177312594304950000\n32.26955056793612\t4177312594304950000\n32.36530591086768\t4177312594304950000\n32.461061253799244\t4177312594304950000\n32.556816596730805\t4177312594304950000\n32.652571939662366\t4177312594304950000\n32.74832728259393\t4177312594304950000\n32.84408262552549\t4177312594304950000\n32.93983796845705\t4177312594304950000\n33.03559331138861\t4177312594304950000\n33.13134865432017\t4177312594304950000\n33.22710399725173\t4177312594304950000\n33.32285934018329\t4177312594304950000\n33.41861468311485\t4177312594304950000\n33.514370026046414\t4177312594304950000\n33.610125368977975\t4177312594304950000\n33.70588071190954\t4177312594304950000\n33.801636054841104\t4177312594304950000\n33.897391397772665\t4177312594304950000\n33.993146740704226\t4177312594304950000\n34.08890208363578\t4177312594304950000\n34.18465742656734\t4177312594304950000\n34.2804127694989\t4177312594304950000\n34.37616811243046\t4177312594304950000\n34.471923455362024\t4177312594304950000\n34.567678798293585\t4177312594304950000\n34.663434141225146\t4177312594304950000\n34.75918948415671\t4177312594304950000\n34.85494482708827\t4177312594304950000\n34.95070017001984\t4177312594304950000\n35.046455512951404\t4177312594304950000\n35.14221085588296\t4177312594304950000\n35.23796619881452\t4177312594304950000\n35.33372154174608\t4177312594304950000\n35.42947688467764\t4177312594304950000\n35.5252322276092\t4177312594304950000\n35.62098757054076\t4177312594304950000\n35.71674291347232\t4177312594304950000\n35.812498256403885\t4177312594304950000\n35.908253599335445\t4177312594304950000\n36.004008942267006\t4177312594304950000\n36.09976428519857\t4177312594304950000\n36.195519628130135\t4177312594304950000\n36.291274971061696\t4177312594304950000\n36.38703031399326\t4177312594304950000\n36.48278565692482\t4177312594304950000\n36.57854099985638\t4177312594304950000\n36.67429634278794\t4177312594304950000\n36.7700516857195\t4177312594304950000\n36.86580702865106\t4177312594304950000\n36.96156237158262\t4177312594304950000\n37.057317714514184\t4177312594304950000\n37.15307305744574\t4177312594304950000\n37.2488284003773\t4177312594304950000\n37.34458374330886\t4177312594304950000\n37.44033908624043\t4177312594304950000\n37.53609442917199\t4177312594304950000\n37.63184977210355\t4177312594304950000\n37.72760511503511\t4177312594304950000\n37.82336045796667\t4177312594304950000\n37.91911580089823\t4177312594304950000\n38.014871143829794\t4177312594304950000\n38.110626486761355\t4177312594304950000\n38.206381829692916\t4177312594304950000\n38.30213717262448\t4177312594304950000\n38.39789251555604\t4177312594304950000\n38.4936478584876\t4177312594304950000\n38.58940320141916\t4177312594304950000\n38.68515854435072\t4177312594304950000\n38.78091388728228\t4177312594304950000\n38.87666923021384\t4177312594304950000\n38.9724245731454\t4177312594304950000\n39.068179916076964\t4177312594304950000\n39.163935259008525\t4177312594304950000\n39.259690601940086\t4177312594304950000\n39.35544594487165\t4177312594304950000\n39.45120128780321\t4177312594304950000\n39.54695663073477\t4177312594304950000\n39.64271197366633\t4177312594304950000\n39.73846731659789\t4177312594304950000\n39.83422265952945\t4177312594304950000\n39.92997800246102\t4177312594304950000\n40.02573334539258\t4177312594304950000\n40.12148868832414\t4177312594304950000\n40.2172440312557\t4177312594304950000\n40.312999374187264\t4177312594304950000\n40.408754717118825\t4177312594304950000\n40.504510060050386\t4177312594304950000\n40.60026540298195\t4177312594304950000\n40.69602074591351\t4177312594304950000\n40.79177608884507\t4177312594304950000\n40.88753143177663\t4177312594304950000\n40.98328677470819\t4177312594304950000\n41.07904211763976\t4177312594304950000\n41.17479746057132\t4177312594304950000\n41.27055280350287\t4177312594304950000\n41.366308146434434\t4177312594304950000\n41.462063489365995\t4177312594304950000\n41.557818832297556\t4177312594304950000\n41.65357417522912\t4177312594304950000\n41.74932951816068\t4177312594304950000\n41.84508486109224\t4177312594304950000\n41.9408402040238\t4177312594304950000\n42.03659554695536\t4177312594304950000\n42.13235088988692\t4177312594304950000\n42.22810623281848\t4177312594304950000\n42.32386157575005\t4177312594304950000\n42.41961691868161\t4177312594304950000\n42.51537226161317\t4177312594304950000\n42.611127604544734\t4177312594304950000\n42.706882947476295\t4177312594304950000\n42.802638290407856\t4177312594304950000\n42.89839363333942\t4177312594304950000\n42.99414897627098\t4177312594304950000\n43.08990431920254\t4177312594304950000\n43.1856596621341\t4177312594304950000\n43.281415005065654\t4177312594304950000\n43.37717034799722\t4177312594304950000\n43.47292569092878\t4177312594304950000\n43.568681033860344\t4177312594304950000\n43.664436376791905\t4177312594304950000\n43.760191719723466\t4177312594304950000\n43.85594706265503\t4177312594304950000\n43.95170240558659\t4177312594304950000\n44.04745774851815\t4177312594304950000\n44.14321309144971\t4177312594304950000\n44.23896843438127\t4177312594304950000\n44.33472377731283\t4177312594304950000\n44.43047912024439\t4177312594304950000\n44.52623446317596\t4177312594304950000\n44.621989806107514\t4177312594304950000\n44.71774514903908\t4177312594304950000\n44.813500491970636\t4177312594304950000\n44.909255834902204\t4177312594304950000\n45.00501117783376\t4177312594304950000\n45.100766520765326\t4177312594304950000\n45.19652186369688\t4177312594304950000\n45.29227720662845\t4177312594304950000\n45.38803254956001\t4177312594304950000\n45.48378789249157\t4177312594304950000\n45.57954323542313\t4177312594304950000\n45.67529857835469\t4177312594304950000\n45.77105392128625\t4177312594304950000\n45.866809264217814\t4177312594304950000\n45.962564607149375\t4177312594304950000\n46.058319950080936\t4177312594304950000\n46.1540752930125\t4177312594304950000\n46.24983063594406\t4177312594304950000\n46.34558597887561\t4177312594304950000\n46.44134132180717\t4177312594304950000\n46.53709666473873\t4177312594304950000\n46.63285200767031\t4177312594304950000\n46.728607350601855\t4177312594304950000\n46.82436269353343\t4177312594304950000\n46.92011803646498\t4177312594304950000\n47.01587337939655\t4177312594304950000\n47.1116287223281\t4177312594304950000\n47.207384065259674\t4177312594304950000\n47.30313940819122\t4177312594304950000\n47.39889475112279\t4177312594304950000\n47.49465009405434\t4177312594304950000\n47.59040543698591\t4177312594304950000\n47.686160779917465\t4177312594304950000\n47.78191612284903\t4177312594304950000\n47.877671465780594\t4177312594304950000'
num_free_e_2='1'
vol_free_e_2='2e-20'
button_2dime = Button(
    description='2D',
    disabled=False,
    button_style='', # 'success', 'info', 'warning', 'danger' or ''
    tooltip='2 Dim electron gas',
    icon='' # (FontAwesome names without the `fa-` prefix)
)
# 3 Dim electron gas
DOS_free_e_3='-0.39280212388434976\t0\n0\t0\n0.031424169910747986\t1.2075842267210155e+27\n0.06284833982149597\t1.7077819911366868e+27\n0.09427250973224395\t2.091597235099573e+27\n0.12569667964299194\t2.415168453442031e+27\n0.15712084955373992\t2.700240419504709e+27\n0.1885450194644879\t2.957965176899883e+27\n0.21996918937523588\t3.1949675510680467e+27\n0.2513933592859839\t3.4155639822733735e+27\n0.28281752919673186\t3.6227526801630466e+27\n0.31424169910747984\t3.8187166229315745e+27\n0.3456658690182278\t4.0051037827850755e+27\n0.3770900389289758\t4.183194470199146e+27\n0.40851420883972384\t4.3540068488841527e+27\n0.43993837875047176\t4.5183664420623854e+27\n0.4713625486612198\t4.676953599233255e+27\n0.5027867185719678\t4.830336906884062e+27\n0.5342108884827157\t4.97899731860057e+27\n0.5656350583934637\t5.12334597341006e+27\n0.5970592283042117\t5.263737610090615e+27\n0.6284833982149597\t5.400480839009418e+27\n0.6599075681257076\t5.533846126983768e+27\n0.6913317380364556\t5.664072088326441e+27\n0.7227559079472038\t5.791370501563861e+27\n0.7541800778579516\t5.915930353799766e+27\n0.7856042477686995\t6.037921133605077e+27\n0.8170284176794477\t6.157495536357312e+27\n0.8484525875901955\t6.274791705298719e+27\n0.8798767575009435\t6.389935102136093e+27\n0.9113009274116917\t6.503040079388747e+27\n0.9427250973224396\t6.61421121062533e+27\n0.9741492672331874\t6.72354442265292e+27\n1.0055734371439355\t6.831127964546747e+27\n1.0369976070546836\t6.937043241370055e+27\n1.0684217769654314\t7.041365534984202e+27\n1.0998459468761794\t7.144164630094183e+27\n1.1312701167869275\t7.245505360326093e+27\n1.1626942866976755\t7.345448086477744e+27\n1.1941184566084233\t7.444049116963491e+27\n1.2255426265191713\t7.54136107877022e+27\n1.2569667964299194\t7.637433245863149e+27\n1.2883909663406674\t7.732311830858938e+27\n1.3198151362514152\t7.826040244866269e+27\n1.3512393061621635\t7.918659329639829e+27\n1.3826634760729113\t8.010207565570151e+27\n1.4140876459836593\t8.100721258514126e+27\n1.4455118158944076\t8.190234708039085e+27\n1.476935985805155\t8.278780359291667e+27\n1.5083601557159032\t8.366388940398292e+27\n1.5397843256266512\t8.45308958704711e+27\n1.571208495537399\t8.538909955683433e+27\n1.6026326654481473\t8.623876326565394e+27\n1.6340568353588953\t8.708013697768305e+27\n1.6654810052696432\t8.791345871090832e+27\n1.696905175180391\t8.873895530699649e+27\n1.7283293450911392\t8.955684315248981e+27\n1.759753515001887\t9.036732884124771e+27\n1.791177684912635\t9.117060978388123e+27\n1.8226018548233833\t9.196687476927374e+27\n1.8540260247341311\t9.275630448271329e+27\n1.8854501946448792\t9.35390719846651e+27\n1.916874364555627\t9.431534315377798e+27\n1.9482985344663748\t9.508527709733739e+27\n1.979722704377123\t9.584902653204139e+27\n2.011146874287871\t9.660673813768124e+27\n2.042571044198619\t9.73585528860462e+27\n2.073995214109367\t9.810460634714148e+27\n2.105419384020115\t9.884502897460315e+27\n2.136843553930863\t9.95799463720114e+27\n2.168267723841611\t1.0030947954164257e+28\n2.199691893752359\t1.0103374511705361e+28\n2.231116063663107\t1.0175285558076634e+28\n2.262540233573855\t1.024669194682012e+28\n2.293964403484603\t1.0317604155890734e+28\n2.325388573395351\t1.0388032305604323e+28\n2.3568127433060986\t1.0457986175497866e+28\n2.3882369132168466\t1.052747522018123e+28\n2.4196610831275946\t1.0596508584253365e+28\n2.4510852530383427\t1.0665095116349439e+28\n2.4825094229490907\t1.0733243382380093e+28\n2.5139335928598388\t1.0800961678018836e+28\n2.545357762770587\t1.086825804048914e+28\n2.576781932681335\t1.093514025969865e+28\n2.6082061025920824\t1.1001615888764142e+28\n2.6396302725028304\t1.1067692253967536e+28\n2.671054442413579\t1.1133376464180056e+28\n2.702478612324327\t1.1198675419788887e+28\n2.7339027822350745\t1.1263595821158055e+28\n2.7653269521458226\t1.1328144176652881e+28\n2.796751122056571\t1.1392326810255224e+28\n2.8281752919673186\t1.1456149868794726e+28\n2.8595994618780667\t1.1519619328819455e+28\n2.891023631788815\t1.1582741003127723e+28\n2.9224478016995623\t1.164552054698121e+28\n2.95387197161031\t1.170796346401828e+28\n2.9852961415210584\t1.17700751118849e+28\n3.0167203114318064\t1.1831860707599532e+28\n3.048144481342554\t1.189332533266719e+28\n3.0795686512533025\t1.1954473937956808e+28\n3.1109928211640505\t1.2015311348355228e+28\n3.142416991074798\t1.2075842267210153e+28\n3.1738411609855466\t1.2136071280573655e+28\n3.2052653308962946\t1.2196002861257048e+28\n3.236689500807042\t1.2255641372707326e+28\n3.2681136707177907\t1.2314991072714623e+28\n3.2995378406285387\t1.2374056116959638e+28\n3.3309620105392863\t1.2432840562409366e+28\n3.3623861804500343\t1.249134837056901e+28\n3.393810350360782\t1.2549583410597437e+28\n3.42523452027153\t1.260754946229313e+28\n3.4566586901822784\t1.2665250218957113e+28\n3.488082860093026\t1.272268929013904e+28\n3.519507030003774\t1.2779870204272187e+28\n3.5509311999145226\t1.2836796411202813e+28\n3.58235536982527\t1.2893471284619003e+28\n3.613779539736018\t1.2949898124383843e+28\n3.6452037096467667\t1.3006080158777494e+28\n3.6766278795575142\t1.3062020546652458e+28\n3.7080520494682623\t1.3117722379506145e+28\n3.7394762193790108\t1.3173188683474542e+28\n3.7709003892897583\t1.322842242125066e+28\n3.8023245592005055\t1.328342649393117e+28\n3.833748729111254\t1.3338203742794527e+28\n3.865172899022002\t1.339275695101361e+28\n3.8965970689327496\t1.344708884530584e+28\n3.928021238843498\t1.3501202097523543e+28\n3.959445408754246\t1.3555099326187156e+28\n3.9908695786649937\t1.360878309796379e+28\n4.022293748575742\t1.3662255929093494e+28\n4.05371791848649\t1.371552028676549e+28\n4.085142088397238\t1.3768578590446478e+28\n4.116566258307986\t1.3821433213163044e+28\n4.147990428218734\t1.387408648274011e+28\n4.179414598129482\t1.392654068299724e+28\n4.21083876804023\t1.3978798054904531e+28\n4.242262937950978\t1.4030860797699765e+28\n4.273687107861726\t1.4082731069968404e+28\n4.305111277772474\t1.41344109906879e+28\n4.336535447683222\t1.4185902640237746e+28\n4.36795961759397\t1.4237208061376698e+28\n4.399383787504718\t1.4288329260188366e+28\n4.430807957415466\t1.4339268206996492e+28\n4.462232127326214\t1.4390026837251062e+28\n4.493656297236962\t1.444060705238638e+28\n4.52508046714771\t1.4491010720652186e+28\n4.556504637058458\t1.4541239677918866e+28\n4.587928806969206\t1.4591295728457683e+28\n4.619352976879954\t1.4641180645697013e+28\n4.650777146790702\t1.4690896172955488e+28\n4.68220131670145\t1.4740444024152854e+28\n4.713625486612197\t1.478982588449942e+28\n4.745049656522945\t1.483904341116483e+28\n4.776473826433693\t1.4888098233926982e+28\n4.807897996344441\t1.4936991955801714e+28\n4.839322166255189\t1.4985726153654036e+28\n4.870746336165937\t1.5034302378791503e+28\n4.902170506076685\t1.508272215754044e+28\n4.933594675987433\t1.5130986991805483e+28\n4.965018845898181\t1.5179098359613198e+28\n4.9964430158089295\t1.5227057715640192e+28\n5.0278671857196775\t1.5274866491726298e+28\n5.0592913556304255\t1.5322526097373378e+28\n5.090715525541174\t1.5370037920230178e+28\n5.1221396954519225\t1.5417403326563753e+28\n5.15356386536267\t1.5464623661717877e+28\n5.184988035273417\t1.5511700250558925e+28\n5.216412205184165\t1.555863439790958e+28\n5.247836375094914\t1.560542738897082e+28\n5.279260545005661\t1.5652080489732539e+28\n5.310684714916409\t1.5698594947373202e+28\n5.342108884827158\t1.574497199064885e+28\n5.373533054737905\t1.5791212830271848e+28\n5.404957224648654\t1.5837318659279658e+28\n5.436381394559402\t1.5883290653393993e+28\n5.467805564470149\t1.592912997137064e+28\n5.499229734380897\t1.5974837755340233e+28\n5.530653904291645\t1.6020415131140302e+28\n5.562078074202394\t1.6065863208638823e+28\n5.593502244113142\t1.611118308204956e+28\n5.62492641402389\t1.6156375830239445e+28\n5.656350583934637\t1.6201442517028252e+28\n5.687774753845385\t1.6246384191480765e+28\n5.719198923756133\t1.6291201888191722e+28\n5.750623093666882\t1.6335896627563696e+28\n5.78204726357763\t1.638046941607817e+28\n5.813471433488377\t1.6424921246559987e+28\n5.844895603399125\t1.646925309843537e+28\n5.876319773309873\t1.651346593798372e+28\n5.90774394322062\t1.6557560718583333e+28\n5.93916811313137\t1.6601538380951306e+28\n5.970592283042117\t1.664539985337765e+28\n6.002016452952865\t1.6689146051953947e+28\n6.033440622863613\t1.6732777880796585e+28\n6.064864792774361\t1.677629623226476e+28\n6.096288962685108\t1.6819701987173442e+28\n6.127713132595858\t1.6862996015001354e+28\n6.159137302506605\t1.690617917409422e+28\n6.190561472417353\t1.694925231186327e+28\n6.221985642328101\t1.699221626497932e+28\n6.253409812238849\t1.7035071859562355e+28\n6.284833982149596\t1.7077819911366866e+28\n6.316258152060345\t1.7120461225963046e+28\n6.347682321971093\t1.716299659891388e+28\n6.379106491881841\t1.7205426815948358e+28\n6.410530661792589\t1.7247752653130788e+28\n6.441954831703337\t1.7289974877026443e+28\n6.473379001614084\t1.7332094244863512e+28\n6.504803171524833\t1.7374111504691582e+28\n6.536227341435581\t1.741602739553661e+28\n6.567651511346329\t1.7457842647552622e+28\n6.599075681257077\t1.7499557982170081e+28\n6.630499851167825\t1.7541174112241115e+28\n6.661924021078573\t1.7582691742181663e+28\n6.6933481909893215\t1.7624111568110568e+28\n6.724772360900069\t1.7665434277985755e+28\n6.756196530810817\t1.770666055173757e+28\n6.787620700721564\t1.7747791061399298e+28\n6.819044870632312\t1.7788826471234976e+28\n6.85046904054306\t1.782976743786457e+28\n6.881893210453809\t1.7870614610386546e+28\n6.913317380364557\t1.7911368630497962e+28\n6.944741550275304\t1.7952030132612074e+28\n6.976165720186052\t1.7992599743973551e+28\n7.0075898900968\t1.8033078084771402e+28\n7.039014060007548\t1.8073465768249541e+28\n7.070438229918297\t1.811376340081523e+28\n7.101862399829045\t1.8153971582145291e+28\n7.133286569739792\t1.819409090529022e+28\n7.16471073965054\t1.8234121956776245e+28\n7.196134909561288\t1.8274065316705394e+28\n7.227559079472036\t1.8313921558853536e+28\n7.258983249382785\t1.8353691250766581e+28\n7.290407419293533\t1.8393374953854748e+28\n7.3218315892042805\t1.8432973223485044e+28\n7.3532557591150285\t1.8472486609071935e+28\n7.3846799290257765\t1.8511915654166301e+28\n7.416104098936525\t1.8551260896542658e+28\n7.4475282688472735\t1.859052286828475e+28\n7.4789524387580215\t1.8629702095869477e+28\n7.510376608668769\t1.8668799100249295e+28\n7.541800778579517\t1.870781439693302e+28\n7.573224948490265\t1.8746748496065116e+28\n7.604649118401011\t1.8785601902503553e+28\n7.63607328831176\t1.882437511589616e+28\n7.667497458222508\t1.8863068630755595e+28\n7.698921628133256\t1.890168293653296e+28\n7.730345798044004\t1.8940218517689987e+28\n7.761769967954751\t1.897867585376999e+28\n7.793194137865499\t1.9017055419467477e+28\n7.824618307776248\t1.9055357684696525e+28\n7.856042477686996\t1.9093583114657872e+28\n7.887466647597744\t1.9131732169904889e+28\n7.918890817508492\t1.9169805306408278e+28\n7.950314987419239\t1.9207802975619684e+28\n7.981739157329987\t1.9245725624534133e+28\n8.013163327240736\t1.9283573695751399e+28\n8.044587497151484\t1.9321347627536248e+28\n8.076011667062232\t1.935904785387768e+28\n8.10743583697298\t1.9396674804547078e+28\n8.138860006883728\t1.9434228905155378e+28\n8.170284176794476\t1.947171057720924e+28\n8.201708346705225\t1.9509120238166239e+28\n8.233132516615973\t1.9546458301489124e+28\n8.26455668652672\t1.9583725176699106e+28\n8.295980856437469\t1.9620921269428295e+28\n8.327405026348217\t1.9658046981471203e+28\n8.358829196258965\t1.9695102710835364e+28\n8.390253366169713\t1.9732088851791135e+28\n8.42167753608046\t1.976900579492063e+28\n8.453101705991209\t1.9805853927165845e+28\n8.484525875901957\t1.984263363187599e+28\n8.515950045812703\t1.9879345288853993e+28\n8.547374215723451\t1.991598927440228e+28\n8.5787983856342\t1.9952565961367784e+28\n8.610222555544947\t1.9989075719186163e+28\n8.641646725455695\t2.002551891392538e+28\n8.673070895366443\t2.0061895908328515e+28\n8.704495065277191\t2.0098207061855887e+28\n8.73591923518794\t2.013445273072649e+28\n8.767343405098687\t2.017063326795876e+28\n8.798767575009435\t2.0206749023410723e+28\n8.830191744920183\t2.0242800343819415e+28\n8.861615914830931\t2.0278787572839772e+28\n8.89304008474168\t2.0314711051082817e+28\n8.924464254652428\t2.035057111615327e+28\n8.955888424563176\t2.0386368102686584e+28\n8.987312594473924\t2.0422102342385377e+28\n9.018736764384672\t2.0457774164055283e+28\n9.05016093429542\t2.049338389364024e+28\n9.081585104206168\t2.0528931854257267e+28\n9.113009274116916\t2.0564418366230636e+28\n9.144433444027664\t2.0599843747125593e+28\n9.175857613938412\t2.0635208311781468e+28\n9.20728178384916\t2.0670512372344337e+28\n9.238705953759908\t2.0705756238299183e+28\n9.270130123670656\t2.074094021650154e+28\n9.301554293581404\t2.0776064611208646e+28\n9.332978463492152\t2.081112972411017e+28\n9.3644026334029\t2.0846135854358405e+28\n9.395826803313646\t2.08810832985981e+28\n9.427250973224394\t2.091597235099573e+28\n9.458675143135142\t2.095080330326843e+28\n9.49009931304589\t2.0985576444712418e+28\n9.52152348295664\t2.102029206223106e+28\n9.552947652867386\t2.105495044036246e+28\n9.584371822778134\t2.10895518613067e+28\n9.615795992688883\t2.1124096604952606e+28\n9.64722016259963\t2.1158584948904207e+28\n9.678644332510379\t2.119301716850673e+28\n9.710068502421128\t2.1227393536872264e+28\n9.741492672331875\t2.126171432490503e+28\n9.772916842242623\t2.129597980132629e+28\n9.80434101215337\t2.1330190232698877e+28\n9.835765182064119\t2.136434588345143e+28\n9.867189351974867\t2.1398447015902194e+28\n9.898613521885617\t2.1432493890282547e+28\n9.930037691796363\t2.1466486764760185e+28\n9.961461861707111\t2.1500425895461926e+28\n9.992886031617859\t2.1534311536496236e+28\n10.024310201528607\t2.156814393997546e+28\n10.055734371439355\t2.1601923356037672e+28\n10.087158541350105\t2.1635650032868235e+28\n10.118582711260851\t2.1669324216721126e+28\n10.150006881171599\t2.170294615193988e+28\n10.181431051082347\t2.173651608097828e+28\n10.212855220993095\t2.177003424442076e+28\n10.244279390903845\t2.180350088100253e+28\n10.275703560814591\t2.1836916227629384e+28\n10.30712773072534\t2.18702805193973e+28\n10.338551900636087\t2.1903593989611713e+28\n10.369976070546834\t2.193685686980657e+28\n10.401400240457582\t2.197006938976309e+28\n10.43282441036833\t2.2003231777528284e+28\n10.46424858027908\t2.203634425943323e+28\n10.495672750189827\t2.206940706011109e+28\n10.527096920100576\t2.2102420402514894e+28\n10.558521090011322\t2.213538450793507e+28\n10.58994525992207\t2.2168299596016772e+28\n10.621369429832818\t2.2201165884776923e+28\n10.652793599743568\t2.22339835906211e+28\n10.684217769654316\t2.226675292836011e+28\n10.715641939565064\t2.229947411122646e+28\n10.74706610947581\t2.2332147350890473e+28\n10.778490279386558\t2.2364772857476327e+28\n10.809914449297308\t2.2397350839577775e+28\n10.841338619208054\t2.2429881504273727e+28\n10.872762789118804\t2.24623650571436e+28\n10.904186959029552\t2.2494801702282495e+28\n10.935611128940298\t2.252719164231611e+28\n10.967035298851048\t2.2559535078415563e+28\n10.998459468761794\t2.259183221031193e+28\n11.029883638672544\t2.262408323631066e+28\n11.06130780858329\t2.2656288353305763e+28\n11.092731978494037\t2.2688447756793844e+28\n11.124156148404788\t2.2720561640887955e+28\n11.155580318315534\t2.2752630198331235e+28\n11.187004488226284\t2.278465362051045e+28\n11.21842865813703\t2.2816632097469275e+28\n11.24985282804778\t2.28485658179215e+28\n11.281276997958527\t2.2880454969263965e+28\n11.312701167869275\t2.291229973758945e+28\n11.344125337780023\t2.2944100307699294e+28\n11.37554950769077\t2.297585686311595e+28\n11.406973677601517\t2.3007569586095306e+28\n11.438397847512267\t2.303923865763891e+28\n11.469822017423015\t2.307086425750601e+28\n11.501246187333765\t2.3102446564225485e+28\n11.53267035724451\t2.313398575510756e+28\n11.56409452715526\t2.3165482006255446e+28\n11.595518697066007\t2.3196935492576814e+28\n11.626942866976753\t2.3228346387795136e+28\n11.658367036887503\t2.3259714864460847e+28\n11.68979120679825\t2.329104109396242e+28\n11.721215376708997\t2.3322325246537312e+28\n11.752639546619745\t2.335356749128272e+28\n11.784063716530493\t2.338476799616627e+28\n11.81548788644124\t2.341592692803656e+28\n11.846912056351991\t2.344704445263354e+28\n11.87833622626274\t2.347812073459881e+28\n11.909760396173487\t2.35091559374858e+28\n11.941184566084234\t2.35401502237698e+28\n11.972608735994983\t2.357110375485787e+28\n12.00403290590573\t2.3602016691098666e+28\n12.03545707581648\t2.363288919179213e+28\n12.066881245727226\t2.3663721415199064e+28\n12.098305415637974\t2.3694513518550584e+28\n12.129729585548722\t2.3725265658057476e+28\n12.16115375545947\t2.3755977988919487e+28\n12.192577925370216\t2.378665066533438e+28\n12.224002095280968\t2.3817283840507043e+28\n12.255426265191716\t2.3847877666658377e+28\n12.286850435102464\t2.387843229503413e+28\n12.31827460501321\t2.3908947875913616e+28\n12.34969877492396\t2.393942455861835e+28\n12.381122944834706\t2.3969862491520575e+28\n12.412547114745456\t2.400026182205166e+28\n12.443971284656202\t2.4030622696710455e+28\n12.47539545456695\t2.406094526107154e+28\n12.506819624477698\t2.409122965979334e+28\n12.538243794388444\t2.4121476036626195e+28\n12.569667964299192\t2.4151684534420307e+28\n12.601092134209942\t2.418185529513363e+28\n12.63251630412069\t2.4211988459839643e+28\n12.663940474031438\t2.4242084168735027e+28\n12.695364643942186\t2.427214256114731e+28\n12.726788813852933\t2.430216377554238e+28\n12.758212983763682\t2.43321479495319e+28\n12.789637153674429\t2.436209521988072e+28\n12.821061323585178\t2.4392005722514095e+28\n12.852485493495925\t2.442187959252493e+28\n12.883909663406675\t2.445171696418088e+28\n12.91533383331742\t2.4481517970931386e+28\n12.946758003228169\t2.451128274541465e+28\n12.978182173138919\t2.4541011419464505e+28\n13.009606343049667\t2.4570704124117254e+28\n13.041030512960415\t2.4600360989618386e+28\n13.072454682871163\t2.4629982145429247e+28\n13.103878852781909\t2.4659567720233637e+28\n13.135303022692659\t2.468911784194434e+28\n13.166727192603405\t2.471863263770955e+28\n13.198151362514155\t2.4748112233919275e+28\n13.229575532424901\t2.4777556756211666e+28\n13.26099970233565\t2.480696632947922e+28\n13.292423872246397\t2.4836341077875e+28\n13.323848042157145\t2.4865681124818733e+28\n13.355272212067895\t2.4894986593002857e+28\n13.386696381978643\t2.492425760439852e+28\n13.418120551889391\t2.4953494280261487e+28\n13.449544721800137\t2.498269674113802e+28\n13.480968891710885\t2.501186510687065e+28\n13.512393061621633\t2.504099949660394e+28\n13.543817231532381\t2.5070100028790158e+28\n13.575241401443128\t2.5099166821194875e+28\n13.606665571353878\t2.512819999090256e+28\n13.638089741264624\t2.515719965432203e+28\n13.669513911175374\t2.5186165927191975e+28\n13.70093808108612\t2.521509892458626e+28\n13.732362250996871\t2.5243998760919334e+28\n13.763786420907618\t2.527286554995144e+28\n13.795210590818368\t2.530169940479389e+28\n13.826634760729114\t2.5330500437914227e+28\n13.858058930639862\t2.5359268761141324e+28\n13.889483100550608\t2.538800448567047e+28\n13.920907270461358\t2.5416707722068354e+28\n13.952331440372104\t2.544537858027808e+28\n13.983755610282854\t2.547401716962403e+28\n14.0151797801936\t2.5502623598816757e+28\n14.04660395010435\t2.553119797595778e+28\n14.078028120015096\t2.5559740408544374e+28\n14.109452289925848\t2.5588251003474262e+28\n14.140876459836594\t2.56167298670503e+28\n14.172300629747342\t2.564517710498511e+28\n14.20372479965809\t2.5673592822405626e+28\n14.235148969568838\t2.570197712385767e+28\n14.266573139479584\t2.5730330113310408e+28\n14.297997309390334\t2.5758651894160802e+28\n14.32942147930108\t2.5786942569238006e+28\n14.360845649211827\t2.581520224080773e+28\n14.392269819122577\t2.5843431010576554e+28\n14.423693989033323\t2.5871628979696183e+28\n14.455118158944073\t2.5899796248767686e+28\n14.48654232885482\t2.5927932917845696e+28\n14.51796649876557\t2.5956039086442515e+28\n14.549390668676317\t2.5984114853532285e+28\n14.580814838587067\t2.601216031755499e+28\n14.612239008497813\t2.604017557642052e+28\n14.643663178408561\t2.6068160727512657e+28\n14.675087348319309\t2.6096115867693003e+28\n14.706511518230057\t2.6124041093304915e+28\n14.737935688140803\t2.615193650017737e+28\n14.769359858051553\t2.617980218362879e+28\n14.8007840279623\t2.620763823847086e+28\n14.83220819787305\t2.623544475901229e+28\n14.863632367783797\t2.626322183906253e+28\n14.895056537694547\t2.629096957193546e+28\n14.926480707605293\t2.6318688050453078e+28\n14.957904877516043\t2.6346377366949085e+28\n14.98932904742679\t2.63740376132725e+28\n15.020753217337537\t2.640166888079119e+28\n15.052177387248285\t2.642927126039542e+28\n15.083601557159033\t2.645684484250132e+28\n15.11502572706978\t2.648438971705435e+28\n15.14644989698053\t2.651190597353271e+28\n15.177874066891276\t2.653939370095076e+28\n15.209298236802022\t2.656685298786234e+28\n15.240722406712774\t2.6594283922364134e+28\n15.27214657662352\t2.662168659209895e+28\n15.30357074653427\t2.664906108425898e+28\n15.334994916445016\t2.6676407485589055e+28\n15.366419086355766\t2.6703725882389844e+28\n15.397843256266512\t2.673101636052102e+28\n15.42926742617726\t2.675827900540444e+28\n15.460691596088008\t2.678551390202722e+28\n15.492115765998756\t2.681272113494486e+28\n15.523539935909502\t2.6839900788284297e+28\n15.554964105820252\t2.686705294574694e+28\n15.586388275730998\t2.689417769061168e+28\n15.61781244564175\t2.692127510573785e+28\n15.649236615552496\t2.69483452735682e+28\n15.680660785463246\t2.697538827613184e+28\n15.712084955373992\t2.7002404195047086e+28'
num_free_e_3='1'
vol_free_e_3='1e-29'
button_3dime = Button(
    description='3D',
    disabled=False,
    button_style='', # 'success', 'info', 'warning', 'danger' or ''
    tooltip='3 dim electron gas',
    icon='' # (FontAwesome names without the `fa-` prefix)
)


#TIGHT BINDING
DOS_2d_square='-4.2\t0\n-4\t0\n-3.9604\t5329999999999999000\n-3.8812\t5379999999999999000\n-3.802\t5440000000000000000\n-3.7228\t5496666666666666000\n-3.6436\t5550000000000000000\n-3.5644\t5616666666666666000\n-3.4851\t5673333333333332000\n-3.4059\t5733333333333332000\n-3.3267\t5806666666666666000\n-3.2475\t5870000000000000000\n-3.1683\t5939999999999999000\n-3.0891\t6006666666666666000\n-3.0099\t6086666666666666000\n-2.9307\t6153333333333332000\n-2.8515\t6236666666666666000\n-2.7723\t6316666666666666000\n-2.6931\t6406666666666666000\n-2.6139\t6483333333333333000\n-2.5347\t6576666666666666000\n-2.4554\t6669999999999999000\n-2.3762\t6763333333333333000\n-2.297\t6866666666666666000\n-2.2178\t6970000000000000000\n-2.1386\t7076666666666666000\n-2.0594\t7193333333333332000\n-1.9802\t7309999999999999000\n-1.901\t7440000000000000000\n-1.8218\t7559999999999999000\n-1.7426\t7700000000000000000\n-1.6634\t7849999999999999000\n-1.5842\t7993333333333333000\n-1.5049\t8159999999999999000\n-1.4257\t8326666666666666000\n-1.3465\t8503333333333332000\n-1.2673\t8700000000000000000\n-1.1881\t8906666666666666000\n-1.1089\t9119999999999999000\n-1.0297\t9363333333333332000\n-0.9505\t9620000000000000000\n-0.8713\t9910000000000000000\n-0.7921\t10216666666666666000\n-0.7129\t10563333333333332000\n-0.6337\t10950000000000000000\n-0.5545\t11390000000000000000\n-0.4752\t11903333333333332000\n-0.396\t12519999999999998000\n-0.3168\t13266666666666666000\n-0.2376\t14233333333333332000\n-0.1584\t15629999999999998000\n-0.0792\t18066666666666666000\n0\t23666666666666664000\n0.0792\t18083333333333332000\n0.1584\t15633333333333330000\n0.2376\t14246666666666666000\n0.3168\t13270000000000000000\n0.396\t12526666666666666000\n0.4752\t11910000000000000000\n0.5545\t11400000000000000000\n0.6337\t10956666666666666000\n0.7129\t10566666666666666000\n0.7921\t10219999999999998000\n0.8713\t9916666666666666000\n0.9505\t9623333333333332000\n1.0297\t9370000000000000000\n1.1089\t9126666666666665000\n1.1881\t8906666666666666000\n1.2673\t8703333333333332000\n1.3465\t8510000000000000000\n1.4257\t8330000000000000000\n1.505\t8159999999999999000\n1.5842\t7996666666666666000\n1.6634\t7853333333333333000\n1.7426\t7703333333333333000\n1.8218\t7569999999999999000\n1.901\t7440000000000000000\n1.9802\t7316666666666666000\n2.0594\t7193333333333332000\n2.1386\t7083333333333332000\n2.2178\t6973333333333333000\n2.297\t6873333333333333000\n2.3762\t6769999999999999000\n2.4554\t6676666666666666000\n2.5347\t6583333333333333000\n2.6139\t6490000000000000000\n2.6931\t6400000000000000000\n2.7723\t6319999999999999000\n2.8515\t6240000000000000000\n2.9307\t6163333333333333000\n3.0099\t6089999999999999000\n3.0891\t6013333333333333000\n3.1683\t5946666666666666000\n3.2475\t5873333333333333000\n3.3267\t5806666666666666000\n3.4059\t5743333333333333000\n3.4851\t5683333333333333000\n3.5644\t5616666666666666000\n3.6436\t5563333333333333000\n3.7228\t5503333333333333000\n3.802\t5446666666666666000\n3.8812\t5396666666666666000\n3.9604\t5359999999999999000\n4\t0\n4.2\t0'
num_2d_square='1'
vol_2d_square='3e-20'
button_2d_square = Button(
    description='2d square',
    disabled=False,
    button_style='', # 'success', 'info', 'warning', 'danger' or ''
    tooltip='2d square',
    icon='' # (FontAwesome names without the `fa-` prefix)
)

DOS_2d_hexagonal='-6.1\t0\n-6\t0\n-5.95544045073133\t3074650140578266600\n-5.86633159416396\t3099045085432799700\n-5.7772227375966\t3115899774605067000\n-5.68811388102923\t3147834975141933000\n-5.59900502446186\t3167794475477466600\n-5.5098961678945\t3193963598139633000\n-5.42078731132713\t3218802087446100000\n-5.33167845475976\t3241866398944966000\n-5.2425695981924\t3270253243866632700\n-5.15346074162503\t3302631988855400000\n-5.06435188505766\t3323478578094766000\n-4.9752430284903\t3348760611853133000\n-4.88613417192293\t3384687712457100000\n-4.79702531535556\t3409082657311666000\n-4.70791645878819\t3443235580108066300\n-4.61880760222083\t3469404702770199600\n-4.52969874565346\t3500009269951399400\n-4.44058988908609\t3534605737199666000\n-4.35148103251873\t3560774859861833000\n-4.26237217595136\t3593153604850599400\n-4.17326331938399\t3640169316752133000\n-4.08415446281663\t3662346539347166000\n-3.99504560624926\t3694725284335966000\n-3.90593674968189\t3737749096170366000\n-3.81682789311453\t3774563285678166000\n-3.72771903654716\t3806054941763133000\n-3.63861017997979\t3850409386953233000\n-3.54950132341243\t3884562309749633000\n-3.46039246684506\t3930247388295433000\n-3.37128361027769\t3966174488899433000\n-3.28217475371033\t4018956278675633000\n-3.19306589714296\t4050891479212533000\n-3.10395704057559\t4101455546729233000\n-3.01484818400822\t4147584169726966300\n-2.92573932744086\t4186172537042366500\n-2.83663047087349\t4247825215856599600\n-2.74752161430612\t4281978138653000000\n-2.65841275773876\t4347179173082433000\n-2.56930390117139\t4399073873954866000\n-2.48019504460402\t4440767052433566000\n-2.39108618803666\t4503750364603533000\n-2.30197733146929\t4559193421091166000\n-2.21286847490192\t4619959011001600000\n-2.12375961833456\t4682942323171566000\n-2.03465076176719\t4745925635341499000\n-1.94554190519982\t4809352491963366000\n-1.85643304863246\t4874553526392833000\n-1.76732419206509\t4945520638697000000\n-1.67821533549772\t5017818384356866000\n-1.58910647893035\t5087454863305333000\n-1.49999762236299\t5170841220262733000\n-1.41088876579562\t5244913143730233000\n-1.32177990922825\t5329630134043333000\n-1.23267105266089\t5417895479971633000\n-1.14356219609352\t5503943103640433000\n-1.05445333952615\t5605071238673900000\n-0.965344482958792\t5696884940217400000\n-0.876235626391425\t5795795352991366000\n-0.787126769824058\t5910673366033733000\n-0.69801791325669\t6009583778807666000\n-0.608909056689324\t6138211669858999000\n-0.519800200121957\t6252202593997567000\n-0.43069134355459\t6372403140462766000\n-0.341582486987223\t6520103442945799000\n-0.252473630419856\t6652723234064232000\n-0.16336477385249\t6813729870104332000\n-0.074255917285123\t6970744606077300000\n0.014852939282244\t7132194786569299000\n0.103961795849611\t7300298133839799000\n0.193070652416977\t7495457692676266000\n0.282179508984345\t7689730162608932000\n0.371288365551712\t7925252266568433000\n0.460397222119079\t8139927781288533000\n0.549506078686445\t8398514196746866000\n0.638614935253812\t8662866690079899000\n0.727723791821179\t8948952861556099000\n0.816832648388546\t9282498289385700000\n0.905941504955913\t9632898406387567000\n0.995050361523279\t10008137012695865000\n1.08415921809064\t10445471842270333000\n1.17326807465801\t10933814283813399000\n1.26237693122538\t11470946615065633000\n1.35148578779274\t12125618226071600000\n1.44059464436011\t12837507071372833000\n1.52970350092748\t13725926608530698000\n1.61881235749484\t14823255582533933000\n1.70792121406221\t16211549716984300000\n1.79703007062958\t18147621249532500000\n1.88613892719694\t21288359513444033000\n1.97524778376431\t30435576744999900000\n2.06435664033168\t25228808424133165000\n2.15346549689904\t20624373468948128000\n2.24257435346641\t18463868443737965000\n2.33168321003378\t17019687708348066000\n2.42079206660114\t15956955201593098000\n2.50990092316851\t15116882009692465000\n2.59900977973588\t14405880253295032000\n2.68811863630325\t13817740310074198000\n2.77722749287061\t13309881912647465000\n2.86633634943798\t12854361760545065000\n2.95544520600535\t12467147454035433000\n3.04455406257271\t0\n3.1\t0'
num_2d_hexagonal='1'
vol_2d_hexagonal='3e-20'
button_2d_hexagonal = Button(
    description='2d hexagonal',
    disabled=False,
    button_style='', # 'success', 'info', 'warning', 'danger' or ''
    tooltip='2d hexagonal',
    icon='' # (FontAwesome names without the `fa-` prefix)
)

DOS_graphene='-8.95999999999999\t0\n-8.39999999999999\t0\n-8.39999999999999\t3762700401025880000\n-8.35842184616182\t3762700401025880000\n-8.27527031807221\t3783362628661580000\n-8.19211878998256\t3797771813723310000\n-8.10896726189295\t3821696498354100000\n-8.0258157338033\t3839911883243470000\n-7.94266420571366\t3859214753797860000\n-7.85951267762404\t3879605110017290000\n-7.7763611495344\t3902714180399310000\n-7.69320962144478\t3917123365461050000\n-7.61005809335514\t3945397992751990000\n-7.5269065652655\t3965788348971420000\n-7.44375503717588\t3988081805104670000\n-7.36060350908624\t4009287775572880000\n-7.27745198099659\t4037562402863830000\n-7.19430045290698\t4054962173504410000\n-7.11114892481733\t4078614986718950000\n-7.02799739672772\t4106345871177380000\n-6.94484586863807\t4129183070143140000\n-6.86169434054843\t4155282726104010000\n-6.77854281245881\t4181926124897410000\n-6.69539128436917\t4208569523690800000\n-6.61223975627955\t4237116022398010000\n-6.52908822818991\t4260496964196290000\n-6.44593670010026\t4291490305649830000\n-6.36278517201065\t4315143118864370000\n-6.279633643921\t4352389502891870000\n-6.19648211583136\t4380392258766550000\n-6.11333058774174\t4412201214468860000\n-6.0301790596521\t4444282041587440000\n-5.94702753156248\t4475547254457230000\n-5.86387600347284\t4504093753164440000\n-5.7807244753832\t4551127508177250000\n-5.69757294729358\t4576411549889360000\n-5.61442141920393\t4621814076404630000\n-5.53126989111432\t4653894903523200000\n-5.44811836302468\t4692772516048250000\n-5.36496683493503\t4740621885309840000\n-5.28181530684542\t4777052655088570000\n-5.19866377875577\t4816474010446140000\n-5.11551225066613\t4868401450951620000\n-5.03236072257651\t4918153920127040000\n-4.94920919448687\t4963828318058570000\n-4.86605766639725\t5018746344142910000\n-4.78290613830761\t5064692613490690000\n-4.69975461021796\t5123416839402650000\n-4.61660308212835\t5188937850721100000\n-4.5334515540387\t5250108919379390000\n-4.45030002594909\t5304483202631210000\n-4.36714849785944\t5384685270427640000\n-4.2839969697698\t5455371838655010000\n-4.20084544168018\t5539108234862820000\n-4.11769391359054\t5616047845664140000\n-4.0345423855009\t5708484127192230000\n-3.95139085741128\t5811523393954430000\n-3.86823932932163\t5916193889214170000\n-3.78508780123202\t6033098598205590000\n-3.70193627314237\t6165228106507510000\n-3.61878474505273\t6304698143048420000\n-3.53563321696311\t6469995964133960000\n-3.45248168887347\t6646712384702370000\n-3.36933016078385\t6874540631527490000\n-3.28617863269421\t7126565434399670000\n-3.20302710460457\t7427798963614750000\n-3.11987557651495\t7838868544998500000\n-3.03672404842531\t8366027221124890000\n-2.95357252033566\t9161794856515260000\n-2.87042099224605\t10780517268921900000\n-2.78726946415642\t13536749686956600000\n-2.70411793606679\t9726199916669150000\n-2.62096640797715\t8280115853587020000\n-2.53781487988752\t7358199881052430000\n-2.45466335179789\t6683686897313600000\n-2.37151182370826\t6139128450546640000\n-2.28836029561862\t5683200085480130000\n-2.20520876752899\t5275392961091480000\n-2.12205723943935\t4927941291112360000\n-2.03890571134972\t4601967463017710000\n-1.95575418326009\t4303180776548970000\n-1.87260265517046\t4034299945868710000\n-1.78945112708082\t3775750229006310000\n-1.70629959899119\t3535144025617020000\n-1.62314807090156\t3308403264456930000\n-1.53999654281192\t3094984202693540000\n-1.45684501472229\t2884827597925260000\n-1.37369348663266\t2685273978391090000\n-1.29054195854302\t2494963987009720000\n-1.20739043045339\t2311994523867350000\n-1.12423890236376\t2128481317892450000\n-1.04108737427412\t1953667997237850000\n-0.957935846184494\t1786195204822250000\n-0.874784318094861\t1621712997985510000\n-0.791632790005229\t1453968334153640000\n-0.708481261915596\t1298186012637170000\n-0.625329733825963\t1135878777130500000\n-0.54217820573633\t984174526857932000\n-0.459026677646695\t828392205341468000\n-0.375875149557062\t679678540647746000\n-0.292723621467429\t527158676126392000\n-0.209572093377796\t377085654351368000\n-0.126420565288163\t227284503992605000\n-0.0432690371985311\t79386453547650800\n0.0432690371985311\t79386453547650800\n0.126420565288163\t227284503992605000\n0.209572093377796\t377085654351368000\n0.292723621467429\t527158676126392000\n0.375875149557062\t679678540647746000\n0.459026677646695\t828392205341468000\n0.54217820573633\t984174526857932000\n0.625329733825963\t1135878777130500000\n0.708481261915596\t1298186012637170000\n0.791632790005229\t1453968334153640000\n0.874784318094861\t1621712997985510000\n0.957935846184494\t1786195204822250000\n1.04108737427412\t1953667997237850000\n1.12423890236376\t2128481317892450000\n1.20739043045339\t2311994523867350000\n1.29054195854302\t2494963987009720000\n1.37369348663266\t2685273978391090000\n1.45684501472229\t2884827597925260000\n1.53999654281192\t3094984202693540000\n1.62314807090156\t3308403264456930000\n1.70629959899119\t3535144025617020000\n1.78945112708082\t3775750229006310000\n1.87260265517046\t4034299945868710000\n1.95575418326009\t4303180776548970000\n2.03890571134972\t4601967463017710000\n2.12205723943935\t4927941291112360000\n2.20520876752899\t5275392961091480000\n2.28836029561862\t5683200085480130000\n2.37151182370826\t6139128450546640000\n2.45466335179789\t6683686897313600000\n2.53781487988752\t7358199881052430000\n2.62096640797715\t8280115853587020000\n2.70411793606679\t9726199916669150000\n2.78726946415642\t13536749686956600000\n2.87042099224605\t10780517268921900000\n2.95357252033566\t9161794856515260000\n3.03672404842531\t8366027221124890000\n3.11987557651495\t7838868544998500000\n3.20302710460457\t7427798963614750000\n3.28617863269421\t7126565434399670000\n3.36933016078385\t6874540631527490000\n3.45248168887347\t6646712384702370000\n3.53563321696311\t6469995964133960000\n3.61878474505273\t6304698143048420000\n3.70193627314237\t6165228106507510000\n3.78508780123202\t6033098598205590000\n3.86823932932163\t5916193889214170000\n3.95139085741128\t5811523393954430000\n4.0345423855009\t5708484127192230000\n4.11769391359054\t5616047845664140000\n4.20084544168018\t5539108234862820000\n4.2839969697698\t5455371838655010000\n4.36714849785944\t5384685270427640000\n4.45030002594909\t5304483202631210000\n4.5334515540387\t5250108919379390000\n4.61660308212835\t5188937850721100000\n4.69975461021796\t5123416839402650000\n4.78290613830761\t5064692613490690000\n4.86605766639725\t5018746344142910000\n4.94920919448687\t4963828318058570000\n5.03236072257651\t4918153920127040000\n5.11551225066613\t4868401450951620000\n5.19866377875577\t4816474010446140000\n5.28181530684542\t4777052655088570000\n5.36496683493503\t4740621885309840000\n5.44811836302468\t4692772516048250000\n5.53126989111432\t4653894903523200000\n5.61442141920393\t4621814076404630000\n5.69757294729358\t4576411549889360000\n5.7807244753832\t4551127508177250000\n5.86387600347284\t4504093753164440000\n5.94702753156248\t4475547254457230000\n6.0301790596521\t4444282041587440000\n6.11333058774174\t4412201214468860000\n6.19648211583136\t4380392258766550000\n6.279633643921\t4352389502891870000\n6.36278517201065\t4315143118864370000\n6.44593670010026\t4291490305649830000\n6.52908822818991\t4260496964196290000\n6.61223975627955\t4237116022398010000\n6.69539128436917\t4208569523690800000\n6.77854281245881\t4181926124897410000\n6.86169434054843\t4155282726104010000\n6.94484586863807\t4129183070143140000\n7.02799739672772\t4106345871177380000\n7.11114892481733\t4078614986718950000\n7.19430045290698\t4054962173504410000\n7.27745198099659\t4037562402863830000\n7.36060350908624\t4009287775572880000\n7.44375503717588\t3988081805104670000\n7.5269065652655\t3965788348971420000\n7.61005809335514\t3945397992751990000\n7.69320962144478\t3917123365461050000\n7.7763611495344\t3902714180399310000\n7.85951267762404\t3879605110017290000\n7.94266420571366\t3859214753797860000\n8.0258157338033\t3839911883243470000\n8.10896726189295\t3821696498354100000\n8.19211878998256\t3797771813723310000\n8.27527031807221\t3783362628661580000\n8.35842184616182\t3762700401025880000\n8.39999999999999\t3762700401025880000\n8.39999999999999\t0\n8.95999999999999\t0'
num_graphene='2'
vol_graphene='5.2450e-20'
button_graphene = Button(
    description='graphene',
    disabled=False,
    button_style='', # 'success', 'info', 'warning', 'danger' or ''
    tooltip='graphene',
    icon='' # (FontAwesome names without the `fa-` prefix)
)

DOS_simple_cubic='-6.5\t0\n-6\t0\n-5.999198\t3.0680000000000003e+26\n-5.938901\t1.2372e+27\n-5.878605\t1.7787e+27\n-5.818308\t2.2165e+27\n-5.758012\t2.5383000000000003e+27\n-5.697715\t2.9347000000000005e+27\n-5.637419\t3.1254e+27\n-5.577122\t3.3941000000000003e+27\n-5.516826\t3.7630999999999997e+27\n-5.456529\t3.9513e+27\n-5.396233\t4.322e+27\n-5.335936\t4.4306e+27\n-5.27564\t4.7548000000000003e+27\n-5.215344\t5.0675e+27\n-5.155047\t5.185200000000001e+27\n-5.094751\t5.414900000000001e+27\n-5.034454\t5.668700000000001e+27\n-4.974158\t5.7939e+27\n-4.913861\t6.143e+27\n-4.853565\t6.3636e+27\n-4.793268\t6.486300000000001e+27\n-4.732972\t6.893399999999999e+27\n-4.672675\t7.0278e+27\n-4.612379\t7.099900000000001e+27\n-4.552082\t7.42e+27\n-4.491786\t7.6281e+27\n-4.43149\t7.9789e+27\n-4.371193\t8.1215e+27\n-4.310897\t8.5146e+27\n-4.2506\t8.724400000000001e+27\n-4.190304\t8.7708e+27\n-4.130007\t9.0843e+27\n-4.069711\t9.216100000000001e+27\n-4.009414\t9.6133e+27\n-3.949118\t9.9658e+27\n-3.888821\t1.01689e+28\n-3.828525\t1.06151e+28\n-3.768228\t1.06457e+28\n-3.707932\t1.09028e+28\n-3.647636\t1.13547e+28\n-3.587339\t1.14086e+28\n-3.527043\t1.1839e+28\n-3.466746\t1.21342e+28\n-3.40645\t1.2289300000000001e+28\n-3.346153\t1.26624e+28\n-3.285857\t1.29875e+28\n-3.22556\t1.32794e+28\n-3.165264\t1.3649200000000002e+28\n-3.104967\t1.41012e+28\n-3.044671\t1.4442e+28\n-2.984374\t1.4806e+28\n-2.924078\t1.53301e+28\n-2.863782\t1.56659e+28\n-2.803485\t1.6058200000000002e+28\n-2.743189\t1.6457800000000002e+28\n-2.682892\t1.6982800000000003e+28\n-2.622596\t1.75292e+28\n-2.562299\t1.8093100000000002e+28\n-2.502003\t1.86437e+28\n-2.441706\t1.9081600000000003e+28\n-2.38141\t1.9846900000000003e+28\n-2.321113\t2.0516100000000003e+28\n-2.260817\t2.15237e+28\n-2.20052\t2.22965e+28\n-2.140224\t2.30892e+28\n-2.079928\t2.45172e+28\n-2.019631\t2.7242100000000004e+28\n-1.959335\t2.8772e+28\n-1.899038\t2.87786e+28\n-1.838742\t2.86949e+28\n-1.778445\t2.91029e+28\n-1.718149\t2.8676600000000002e+28\n-1.657852\t2.84279e+28\n-1.597556\t2.85589e+28\n-1.537259\t2.8687400000000003e+28\n-1.476963\t2.88093e+28\n-1.416666\t2.88383e+28\n-1.35637\t2.90962e+28\n-1.296074\t2.8668300000000006e+28\n-1.235777\t2.88342e+28\n-1.175481\t2.8874000000000002e+28\n-1.115184\t2.8877300000000004e+28\n-1.054888\t2.85664e+28\n-0.994591\t2.87579e+28\n-0.934295\t2.8765400000000002e+28\n-0.873998\t2.82413e+28\n-0.813702\t2.8777000000000005e+28\n-0.753405\t2.86211e+28\n-0.693109\t2.87612e+28\n-0.632812\t2.83914e+28\n-0.572516\t2.83707e+28\n-0.51222\t2.8759600000000006e+28\n-0.451923\t2.85871e+28\n-0.391627\t2.8700700000000003e+28\n-0.33133\t2.85556e+28\n-0.271034\t2.84942e+28\n-0.210737\t2.8460200000000004e+28\n-0.150441\t2.85788e+28\n-0.090144\t2.85e+28\n-0.029848\t2.8617800000000002e+28\n0.030449\t2.8526500000000003e+28\n0.090745\t2.8482600000000002e+28\n0.151042\t2.8612e+28\n0.211338\t2.8682400000000003e+28\n0.271635\t2.86136e+28\n0.331931\t2.8420400000000003e+28\n0.392227\t2.8274500000000005e+28\n0.452524\t2.8474300000000006e+28\n0.51282\t2.8666700000000002e+28\n0.573117\t2.85556e+28\n0.633413\t2.82612e+28\n0.69371\t2.8840800000000004e+28\n0.754006\t2.8482600000000002e+28\n0.814303\t2.85755e+28\n0.874599\t2.8636000000000003e+28\n0.934896\t2.8607e+28\n0.995192\t2.86203e+28\n1.055489\t2.89097e+28\n1.115785\t2.8497499999999997e+28\n1.176081\t2.86377e+28\n1.236378\t2.8456900000000003e+28\n1.296674\t2.87786e+28\n1.356971\t2.85962e+28\n1.417267\t2.8830000000000003e+28\n1.477564\t2.8785300000000005e+28\n1.53786\t2.8860700000000002e+28\n1.598157\t2.8954400000000003e+28\n1.658453\t2.88342e+28\n1.71875\t2.8879800000000003e+28\n1.779046\t2.87703e+28\n1.839343\t2.8768700000000004e+28\n1.899639\t2.9012500000000004e+28\n1.959935\t2.9040700000000003e+28\n2.020232\t2.67802e+28\n2.080528\t2.50703e+28\n2.140825\t2.35835e+28\n2.201121\t2.2261700000000004e+28\n2.261418\t2.14648e+28\n2.321714\t2.06861e+28\n2.382011\t1.9788900000000003e+28\n2.442307\t1.9152e+28\n2.502604\t1.8683500000000001e+28\n2.5629\t1.8275500000000002e+28\n2.623197\t1.7672700000000001e+28\n2.683493\t1.7020900000000002e+28\n2.743789\t1.6593800000000002e+28\n2.804086\t1.62066e+28\n2.864382\t1.5913900000000001e+28\n2.924679\t1.5250500000000002e+28\n2.984975\t1.47861e+28\n3.045272\t1.43474e+28\n3.105568\t1.40564e+28\n3.165865\t1.3602e+28\n3.226161\t1.33407e+28\n3.286458\t1.31492e+28\n3.346754\t1.2775200000000001e+28\n3.407051\t1.23631e+28\n3.467347\t1.21558e+28\n3.527643\t1.18672e+28\n3.58794\t1.15894e+28\n3.648236\t1.1392e+28\n3.708533\t1.0989000000000002e+28\n3.768829\t1.0634100000000002e+28\n3.829126\t1.03389e+28\n3.889422\t1.01772e+28\n3.949719\t9.9044e+27\n4.010015\t9.665600000000001e+27\n4.070312\t9.402700000000001e+27\n4.130608\t9.1315e+27\n4.190905\t8.849600000000001e+27\n4.251201\t8.540300000000001e+27\n4.311497\t8.3786e+27\n4.371794\t8.194500000000001e+27\n4.43209\t7.9789e+27\n4.492387\t7.8247e+27\n4.552683\t7.436600000000001e+27\n4.61298\t7.2351e+27\n4.673276\t6.9747e+27\n4.733573\t6.867700000000001e+27\n4.793869\t6.4622e+27\n4.854166\t6.3718e+27\n4.914462\t6.1339e+27\n4.974759\t5.8917e+27\n5.035055\t5.6811e+27\n5.095351\t5.4746e+27\n5.155648\t5.2433e+27\n5.215944\t4.9414000000000004e+27\n5.276241\t4.7258e+27\n5.336537\t4.5061e+27\n5.396834\t4.3983e+27\n5.45713\t4.0450000000000003e+27\n5.517427\t3.7183000000000005e+27\n5.577723\t3.5981e+27\n5.63802\t3.2231999999999997e+27\n5.698316\t2.8924e+27\n5.758613\t2.5283e+27\n5.818909\t2.2398000000000004e+27\n5.879205\t1.729e+27\n5.939502\t1.2546e+27\n5.999798\t2.8769999999999998e+26\n6\t0\n6.5\t0'
num_simple_cubic='1'
vol_simple_cubic='1e-29'
button_simple_cubic = Button(
    description='simple cubic',
    disabled=False,
    button_style='', # 'success', 'info', 'warning', 'danger' or ''
    tooltip='simple cubic',
    icon='' # (FontAwesome names without the `fa-` prefix)
)

DOS_al_fcc='-11.35077\t0\n-11.33717\t0\n-11.32356\t0\n-11.30996\t0\n-11.29635\t0\n-11.28275\t0\n-11.26914\t0\n-11.25553\t0\n-11.24193\t0\n-11.22832\t0\n-11.21472\t0\n-11.20111\t0\n-11.1875\t6.6697075282883295e+22\n-11.1739\t5.327730230427907e+23\n-11.16029\t2.273593473900054e+24\n-11.14669\t7.266052596312932e+24\n-11.13308\t1.8730985191726472e+25\n-11.11948\t4.003253102253488e+25\n-11.10587\t7.236338022478737e+25\n-11.09226\t1.1309011440706044e+26\n-11.07866\t1.5675303777364087e+26\n-11.06505\t1.9814415339792185e+26\n-11.05145\t2.34612810578534e+26\n-11.03784\t2.6600963286708606e+26\n-11.02423\t2.9338811262135938e+26\n-11.01063\t3.179514757938469e+26\n-10.99702\t3.406058918852795e+26\n-10.98342\t3.61837883470244e+26\n-10.96981\t3.8172968348894884e+26\n-10.95621\t4.0035664981493957e+26\n-10.9426\t4.180423570142474e+26\n-10.92899\t4.351949340441923e+26\n-10.91539\t4.519555429878028e+26\n-10.90178\t4.6814150350233606e+26\n-10.88818\t4.8351808116889166e+26\n-10.87457\t4.981003654194948e+26\n-10.86097\t5.1219068061412905e+26\n-10.84736\t5.2613599440279354e+26\n-10.83375\t5.4008764753864026e+26\n-10.82015\t5.539154601879845e+26\n-10.80654\t5.673328224289279e+26\n-10.79294\t5.801198214148551e+26\n-10.77933\t5.922861893829892e+26\n-10.76573\t6.0406782147777144e+26\n-10.75212\t6.157710599552867e+26\n-10.73851\t6.27593853163463e+26\n-10.72491\t6.39529415322218e+26\n-10.7113\t6.513884588818868e+26\n-10.6977\t6.629148206443615e+26\n-10.68409\t6.739300167361607e+26\n-10.67048\t6.844378864802258e+26\n-10.65688\t6.946126279941967e+26\n-10.64327\t7.046896007030341e+26\n-10.62967\t7.148523778152809e+26\n-10.61606\t7.251863173014464e+26\n-10.60246\t7.356657046264817e+26\n-10.58885\t7.461560742008609e+26\n-10.57524\t7.564457275433312e+26\n-10.56164\t7.663393949033657e+26\n-10.54803\t7.757688613338208e+26\n-10.53443\t7.848301099082297e+26\n-10.52082\t7.93711892456777e+26\n-10.50721\t8.025920678468838e+26\n-10.49361\t8.115769763953664e+26\n-10.48\t8.20701886301337e+26\n-10.4664\t8.2995001168775e+26\n-10.45279\t8.392543876195823e+26\n-10.43919\t8.484861735618497e+26\n-10.42558\t8.574855465362972e+26\n-10.41197\t8.661319696598839e+26\n-10.39837\t8.74416335701446e+26\n-10.38476\t8.824468599959813e+26\n-10.37116\t8.903813119304036e+26\n-10.35755\t8.983530856552786e+26\n-10.34395\t9.064372711844124e+26\n-10.33034\t9.146551187238518e+26\n-10.31673\t9.229895745368113e+26\n-10.30313\t9.31394566747995e+26\n-10.28952\t9.39794737483857e+26\n-10.27592\t9.480861571652416e+26\n-10.26231\t9.561558782684105e+26\n-10.2487\t9.639275607674368e+26\n-10.2351\t9.714054011315824e+26\n-10.22149\t9.786754716239967e+26\n-10.20789\t9.85857951981401e+26\n-10.19428\t9.9305400389897e+26\n-10.18068\t1.0003232708121639e+27\n-10.16707\t1.0076912886828718e+27\n-10.15346\t1.015165111150916e+27\n-10.13986\t1.022737238143574e+27\n-10.12625\t1.0303785622357556e+27\n-10.11265\t1.0380272078274998e+27\n-10.09904\t1.045588084711074e+27\n-10.08543\t1.0529569954475823e+27\n-10.07183\t1.0600677786812219e+27\n-10.05822\t1.0669280237712955e+27\n-10.04462\t1.0736138028839895e+27\n-10.03101\t1.0802227955378569e+27\n-10.01741\t1.0868346453622853e+27\n-10.0038\t1.0934962278117909e+27\n-9.99019\t1.100229418098481e+27\n-9.97659\t1.1070401984232178e+27\n-9.96298\t1.1139292830786413e+27\n-9.94938\t1.1208914934431102e+27\n-9.93577\t1.1279150436880598e+27\n-9.92216\t1.1349660941996588e+27\n-9.90856\t1.1419744657260035e+27\n-9.89495\t1.1488445323398804e+27\n-9.88135\t1.1554921860829012e+27\n-9.86774\t1.1618943017308378e+27\n-9.85414\t1.1681044512317084e+27\n-9.84053\t1.1742185283724661e+27\n-9.82693\t1.1803232304223206e+27\n-9.81332\t1.1864687364392491e+27\n-9.79971\t1.1926708501479171e+27\n-9.78611\t1.1989310001336048e+27\n-9.7725\t1.2052487399634125e+27\n-9.7589\t1.2116226410520592e+27\n-9.74529\t1.2180502926618844e+27\n-9.73168\t1.2245234804275254e+27\n-9.71808\t1.2310231863074354e+27\n-9.70447\t1.2375119099380018e+27\n-9.69087\t1.2439269721400427e+27\n-9.67726\t1.2501959614971536e+27\n-9.66366\t1.256271466835338e+27\n-9.65005\t1.2621565238983172e+27\n-9.63644\t1.267903543908569e+27\n-9.62284\t1.2735841347032778e+27\n-9.60923\t1.279258832583705e+27\n-9.59563\t1.2849680843706036e+27\n-9.58202\t1.290730997392101e+27\n-9.56841\t1.296552214550358e+27\n-9.55481\t1.3024284322419142e+27\n-9.5412\t1.3083544718451272e+27\n-9.5276\t1.3143279226223368e+27\n-9.51399\t1.320344855964021e+27\n-9.50039\t1.3263943789074166e+27\n-9.48678\t1.3324539912343557e+27\n-9.47317\t1.338482888977764e+27\n-9.45957\t1.3444241072995824e+27\n-9.44596\t1.3502223778067718e+27\n-9.43236\t1.3558519859642832e+27\n-9.41875\t1.3613323069599834e+27\n-9.40514\t1.3667163770224108e+27\n-9.39154\t1.3720615181359448e+27\n-9.37793\t1.3774087128408194e+27\n-9.36433\t1.382779389916242e+27\n-9.35072\t1.3881849780444566e+27\n-9.33712\t1.3936319951458054e+27\n-9.32351\t1.3991257984150904e+27\n-9.30991\t1.404666387852311e+27\n-9.2963\t1.410249834847947e+27\n-9.28269\t1.415870425060875e+27\n-9.26909\t1.4215227120097143e+27\n-9.25548\t1.4272003563472824e+27\n-9.24188\t1.4328869293428533e+27\n-9.22827\t1.4385471627973155e+27\n-9.21466\t1.4441264133236895e+27\n-9.20106\t1.449569323242357e+27\n-9.18745\t1.4548516066035495e+27\n-9.17385\t1.4599938886072537e+27\n-9.16024\t1.4650506340672885e+27\n-9.14664\t1.470079254254614e+27\n-9.13303\t1.475118856691283e+27\n-9.11942\t1.4801871201201417e+27\n-9.10582\t1.4852872588580717e+27\n-9.09221\t1.490415165722391e+27\n-9.07861\t1.4955672692498987e+27\n-9.065\t1.5007431230076944e+27\n-9.05139\t1.5059462091723995e+27\n-9.03779\t1.511182242085136e+27\n-9.02418\t1.5164525610446041e+27\n-9.01058\t1.5217548445997235e+27\n-8.99697\t1.527081771250931e+27\n-8.98337\t1.532420840877023e+27\n-8.96976\t1.5377449103576696e+27\n-8.95615\t1.5430109435612963e+27\n-8.94255\t1.548171440027327e+27\n-8.92894\t1.553196756611191e+27\n-8.91534\t1.5580920719345306e+27\n-8.90173\t1.5628947970743784e+27\n-8.88812\t1.5676543075094914e+27\n-8.87452\t1.5724109607740432e+27\n-8.86091\t1.5771881499520023e+27\n-8.84731\t1.5819974822987723e+27\n-8.8337\t1.5868418149849142e+27\n-8.8201\t1.591719540851988e+27\n-8.80649\t1.5966275348696916e+27\n-8.79288\t1.6015610648492843e+27\n-8.77928\t1.6065163807544046e+27\n-8.76567\t1.611493214725312e+27\n-8.75207\t1.6164933524936075e+27\n-8.73846\t1.6215178654982516e+27\n-8.72485\t1.6265663965929235e+27\n-8.71125\t1.6316301956927808e+27\n-8.69764\t1.636688012591776e+27\n-8.68404\t1.6417049362371174e+27\n-8.67043\t1.64663882336303e+27\n-8.65683\t1.6514577986604436e+27\n-8.64322\t1.6561585585258966e+27\n-8.62961\t1.6607664603481175e+27\n-8.61601\t1.6653217723747002e+27\n-8.6024\t1.6698600306644973e+27\n-8.5888\t1.674403735435676e+27\n-8.57519\t1.6789640475107408e+27\n-8.56158\t1.683545788365013e+27\n-8.54798\t1.6881503865837726e+27\n-8.53437\t1.692779985044941e+27\n-8.52077\t1.6974366373398588e+27\n-8.50716\t1.7021223970598662e+27\n-8.49356\t1.7068358356196834e+27\n-8.47995\t1.711571327964768e+27\n-8.46634\t1.716324766912439e+27\n-8.45274\t1.7210940095847753e+27\n-8.43913\t1.7258787881220372e+27\n-8.42553\t1.7306775846523634e+27\n-8.41192\t1.7354824526701317e+27\n-8.39832\t1.7402719633961352e+27\n-8.38471\t1.7450115629239013e+27\n-8.3711\t1.749664911615358e+27\n-8.3575\t1.7542101342583973e+27\n-8.34389\t1.7586551773586425e+27\n-8.33029\t1.7630311126459435e+27\n-8.31668\t1.7673753511973342e+27\n-8.30308\t1.771714857559983e+27\n-8.28947\t1.776064006873275e+27\n-8.27586\t1.780426906319892e+27\n-8.26226\t1.7848058773509142e+27\n-8.24865\t1.789201991405303e+27\n-8.23505\t1.7936148020501567e+27\n-8.22144\t1.7980450235781167e+27\n-8.20783\t1.802493370281823e+27\n-8.19423\t1.8069618957526162e+27\n-8.18062\t1.8114536357342173e+27\n-8.16702\t1.8159703759582267e+27\n-8.15341\t1.8205103306930445e+27\n-8.13981\t1.8250713570607492e+27\n-8.1262\t1.8296476514336395e+27\n-8.11259\t1.8342332316108526e+27\n-8.09899\t1.838816490336985e+27\n-8.08538\t1.8433756416865093e+27\n-8.07178\t1.8478773817650738e+27\n-8.05817\t1.8522897459770276e+27\n-8.04456\t1.8565993413353663e+27\n-8.03096\t1.8608203644063146e+27\n-8.01735\t1.8649862083708036e+27\n-8.00375\t1.8691310699889856e+27\n-7.99014\t1.8732784316314087e+27\n-7.97654\t1.8774402576997968e+27\n-7.96293\t1.8816218161023712e+27\n-7.94932\t1.885823821131773e+27\n-7.93572\t1.8900455584953616e+27\n-7.92211\t1.8942855996078562e+27\n-7.90851\t1.898543319463197e+27\n-7.8949\t1.9028170216163632e+27\n-7.8813\t1.9071035810370538e+27\n-7.86769\t1.9114007655607684e+27\n-7.85408\t1.9157085751875062e+27\n-7.84048\t1.9200296885146688e+27\n-7.82687\t1.924367944865197e+27\n-7.81327\t1.9287257549767524e+27\n-7.79966\t1.933102850989594e+27\n-7.78605\t1.9374930721297002e+27\n-7.77245\t1.9418824004040063e+27\n-7.75884\t1.9462472641553838e+27\n-7.74524\t1.9505568595137225e+27\n-7.73163\t1.9547833290660525e+27\n-7.71803\t1.9589172977214707e+27\n-7.70442\t1.962974569204643e+27\n-7.69081\t1.9669855009527792e+27\n-7.67721\t1.9709796468238694e+27\n-7.6636\t1.9749761141460405e+27\n-7.65\t1.9789838315772955e+27\n-7.63639\t1.9830062812942557e+27\n-7.62278\t1.9870449811687812e+27\n-7.60918\t1.9910998419142925e+27\n-7.59557\t1.995170684957629e+27\n-7.58197\t1.999256438859831e+27\n-7.56836\t2.0033571036208978e+27\n-7.55476\t2.00747312567373e+27\n-7.54115\t2.0116052193109675e+27\n-7.52754\t2.0157532059594509e+27\n-7.51394\t2.019915389174159e+27\n-7.50033\t2.024089893936911e+27\n-7.48673\t2.0282743095100468e+27\n-7.47312\t2.0324689037533058e+27\n-7.45952\t2.0366737659532687e+27\n-7.44591\t2.0408876460978144e+27\n-7.4323\t2.0451038476934408e+27\n-7.4187\t2.0493057634362624e+27\n-7.40509\t2.0534644644743492e+27\n-7.39149\t2.0575521826813118e+27\n-7.37788\t2.061555167923825e+27\n-7.36427\t2.0654832417256928e+27\n-7.35067\t2.069363368634084e+27\n-7.33706\t2.0732227810559083e+27\n-7.32346\t2.0770821934777323e+27\n-7.30985\t2.0809510702770396e+27\n-7.29625\t2.0848330722036116e+27\n-7.28264\t2.0887273063916476e+27\n-7.26903\t2.0926325228290277e+27\n-7.25543\t2.0965498822412915e+27\n-7.24182\t2.1004809917868803e+27\n-7.22822\t2.1044258514657938e+27\n-7.21461\t2.108383746985392e+27\n-7.20101\t2.1123535176201338e+27\n-7.1874\t2.11633560980292e+27\n-7.17379\t2.1203305592532305e+27\n-7.16019\t2.1243401517026662e+27\n-7.14658\t2.1283637621451667e+27\n-7.13298\t2.1324004977149316e+27\n-7.11937\t2.1364470548085002e+27\n-7.10576\t2.140500576255311e+27\n-7.09216\t2.144558383457963e+27\n-7.07855\t2.148612976343734e+27\n-7.06495\t2.15265247979748e+27\n-7.05134\t2.1566568043386938e+27\n-7.03774\t2.1606033604626278e+27\n-7.02413\t2.1644808980601984e+27\n-7.01052\t2.168292988594606e+27\n-6.99692\t2.1720600786926789e+27\n-6.98331\t2.1758048471457433e+27\n-6.96971\t2.1795436333979462e+27\n-6.9561\t2.18328572325361e+27\n-6.9425\t2.1870357596148967e+27\n-6.92889\t2.190796063932887e+27\n-6.91528\t2.194568600512341e+27\n-6.90168\t2.19835426221906e+27\n-6.88807\t2.2021509061751225e+27\n-6.87447\t2.205959068100009e+27\n-6.86086\t2.2097778551279193e+27\n-6.84725\t2.2136090529904537e+27\n-6.83365\t2.2174527509741925e+27\n-6.82004\t2.2213093955120355e+27\n-6.80644\t2.2251776473052828e+27\n-6.79283\t2.2290566134881337e+27\n-6.77923\t2.2329460262008483e+27\n-6.76562\t2.2368464211629062e+27\n-6.75201\t2.2407588698132686e+27\n-6.73841\t2.2446848007372156e+27\n-6.7248\t2.2486218924836662e+27\n-6.7112\t2.2525648771443994e+27\n-6.69759\t2.2565020581774303e+27\n-6.68398\t2.2604141496814722e+27\n-6.67038\t2.264278383578618e+27\n-6.65677\t2.2680769025528614e+27\n-6.64317\t2.2718078315860213e+27\n-6.62956\t2.2754866172564436e+27\n-6.61596\t2.2791368312212558e+27\n-6.60235\t2.2827781165280652e+27\n-6.58874\t2.286423598304136e+27\n-6.57514\t2.2900792587503303e+27\n-6.56153\t2.2937457228727083e+27\n-6.54793\t2.2974218299457292e+27\n-6.53432\t2.3011069549633338e+27\n-6.52072\t2.304800919352361e+27\n-6.50711\t2.3085047052651918e+27\n-6.4935\t2.312218044842086e+27\n-6.4799\t2.3159409380830432e+27\n-6.46629\t2.3196724028356834e+27\n-6.45269\t2.3234123498134268e+27\n-6.43908\t2.3271614040223328e+27\n-6.42547\t2.3309192083160823e+27\n-6.41187\t2.3346862984141543e+27\n-6.39826\t2.33846187073733e+27\n-6.38466\t2.342246014572188e+27\n-6.37105\t2.3460383727724096e+27\n-6.35745\t2.3498387667648333e+27\n-6.34384\t2.3536479108421002e+27\n-6.33023\t2.3574653585713098e+27\n-6.31663\t2.3612848598918602e+27\n-6.30302\t2.3650956111275678e+27\n-6.28942\t2.3688778799442454e+27\n-6.27581\t2.372611130428486e+27\n-6.26221\t2.3762827731725063e+27\n-6.2486\t2.3798981653711064e+27\n-6.23499\t2.3834736464684333e+27\n-6.22139\t2.3870284130791927e+27\n-6.20778\t2.3905787153609507e+27\n-6.19418\t2.3941334819717107e+27\n-6.18057\t2.3976972665270532e+27\n-6.16696\t2.4012730154841197e+27\n-6.15336\t2.4048618895684515e+27\n-6.13975\t2.408464245926367e+27\n-6.12615\t2.4120778523933672e+27\n-6.11254\t2.415702798256031e+27\n-6.09894\t2.419337922788818e+27\n-6.08533\t2.4229831367051485e+27\n-6.07172\t2.4266385292916028e+27\n-6.05812\t2.4303040112616004e+27\n-6.04451\t2.433978779035921e+27\n-6.03091\t2.4376617611756046e+27\n-6.0173\t2.441352779107491e+27\n-6.0037\t2.4450525471242205e+27\n-5.99009\t2.4487607973660526e+27\n-5.97648\t2.4524776191195676e+27\n-5.96288\t2.4562045302566264e+27\n-5.94927\t2.459939209326148e+27\n-5.93567\t2.4636812991818117e+27\n-5.92206\t2.467426603354357e+27\n-5.90845\t2.471169496789241e+27\n-5.89485\t2.4748953364873393e+27\n-5.88124\t2.4785884972971464e+27\n-5.86764\t2.482233175493997e+27\n-5.85403\t2.4858257103281096e+27\n-5.84043\t2.4893756554635476e+27\n-5.82682\t2.492900064637097e+27\n-5.81321\t2.4964157237258024e+27\n-5.79961\t2.4999321863937295e+27\n-5.786\t2.503454720549098e+27\n-5.7724\t2.506983683338229e+27\n-5.75879\t2.5105211283524623e+27\n-5.74518\t2.514066073439419e+27\n-5.73158\t2.5176195007514775e+27\n-5.71797\t2.5211838210263e+27\n-5.70437\t2.5247593914102075e+27\n-5.69076\t2.528344158311857e+27\n-5.67716\t2.5319388360238907e+27\n-5.66355\t2.5355436031194675e+27\n-5.64994\t2.5391588167449075e+27\n-5.63634\t2.5427848340465315e+27\n-5.62273\t2.546421833597499e+27\n-5.60913\t2.550069190391751e+27\n-5.59552\t2.5537256544171656e+27\n-5.58191\t2.557390779240843e+27\n-5.56831\t2.561065011295683e+27\n-5.5547\t2.564748618441427e+27\n-5.5411\t2.5684424935438747e+27\n-5.52749\t2.5721468151761855e+27\n-5.51389\t2.5758601547530797e+27\n-5.50028\t2.579579119384516e+27\n-5.48667\t2.58329460183933e+27\n-5.47307\t2.58699356627684e+27\n-5.45946\t2.590659048246837e+27\n-5.44586\t2.5942787262012786e+27\n-5.43225\t2.597850546548824e+27\n-5.41865\t2.6013863844046173e+27\n-5.40504\t2.6049044542309843e+27\n-5.39143\t2.608421363331811e+27\n-5.37783\t2.6119458617919405e+27\n-5.36422\t2.615483306806174e+27\n-5.35062\t2.619033251941612e+27\n-5.33701\t2.622597304356695e+27\n-5.3234\t2.6261744818990425e+27\n-5.3098\t2.629762730977313e+27\n-5.29619\t2.633361962304928e+27\n-5.28259\t2.6369719973087264e+27\n-5.26898\t2.6405946217203093e+27\n-5.25538\t2.6442302819725766e+27\n-5.24177\t2.6478803173642295e+27\n-5.22816\t2.651544192175786e+27\n-5.21456\t2.655222977846208e+27\n-5.20095\t2.658917388668136e+27\n-5.18735\t2.662628138934209e+27\n-5.17374\t2.6663576393820885e+27\n-5.16014\t2.6701080328896953e+27\n-5.14653\t2.673878873024129e+27\n-5.13292\t2.6776717669438306e+27\n-5.11932\t2.6814857324964194e+27\n-5.10571\t2.6853204125355745e+27\n-5.09211\t2.689177146359998e+27\n-5.0785\t2.693056826835489e+27\n-5.06489\t2.6969580253767674e+27\n-5.05129\t2.7008784205327523e+27\n-5.03768\t2.704808637212541e+27\n-5.02408\t2.70873992533129e+27\n-5.01047\t2.712668534852638e+27\n-4.99687\t2.716602501568788e+27\n-4.98326\t2.720559325649425e+27\n-4.96965\t2.7245629358979986e+27\n-4.95605\t2.728636368252156e+27\n-4.94244\t2.7327975693144837e+27\n-4.92884\t2.737065199980208e+27\n-4.91523\t2.741455510406894e+27\n-4.90162\t2.745987607922669e+27\n-4.88802\t2.7506871177760015e+27\n-4.87441\t2.755591183184184e+27\n-4.86081\t2.7607574832779164e+27\n-4.8472\t2.766268518857147e+27\n-4.8336\t2.7722378624516753e+27\n-4.81999\t2.778807479723749e+27\n-4.80638\t2.786144247291447e+27\n-4.79278\t2.79443280980227e+27\n-4.77917\t2.803859240489005e+27\n-4.76557\t2.8145887195247055e+27\n-4.75196\t2.826734819439173e+27\n-4.73836\t2.840319772590834e+27\n-4.72475\t2.855161523643006e+27\n-4.71114\t2.8707304246029476e+27\n-4.69754\t2.8860763769725527e+27\n-4.68393\t2.8999947262140477e+27\n-4.67033\t2.911331711140278e+27\n-4.65672\t2.9192006267249576e+27\n-4.64311\t2.9230561105372596e+27\n-4.62951\t2.9228299476300425e+27\n-4.6159\t2.9191639299405646e+27\n-4.6023\t2.913419499241134e+27\n-4.58869\t2.9071374740433384e+27\n-4.57509\t2.9011990236055013e+27\n-4.56148\t2.8953130736767215e+27\n-4.54787\t2.8884009530836506e+27\n-4.53427\t2.8795121168952806e+27\n-4.52066\t2.868582993066631e+27\n-4.50706\t2.856525465439554e+27\n-4.49345\t2.8447986553049107e+27\n-4.47985\t2.8349060593838364e+27\n-4.46624\t2.827888402053169e+27\n-4.45263\t2.8237989874011856e+27\n-4.43903\t2.821485572112592e+27\n-4.42542\t2.818838760734164e+27\n-4.41182\t2.8135301378318625e+27\n-4.39821\t2.80407977834168e+27\n-4.3846\t2.790857328704944e+27\n-4.371\t2.7762609371746956e+27\n-4.35739\t2.763706083296848e+27\n-4.34379\t2.7557735063806065e+27\n-4.33018\t2.753191338486121e+27\n-4.31658\t2.7554401102907724e+27\n-4.30297\t2.762070353150687e+27\n-4.28936\t2.7732900155107565e+27\n-4.27576\t2.7893288317413995e+27\n-4.26215\t2.8093625974223525e+27\n-4.24855\t2.8312070949463273e+27\n-4.23494\t2.8518544380052514e+27\n-4.22133\t2.8683286156001236e+27\n-4.20773\t2.878475946134025e+27\n-4.19412\t2.8817057988800533e+27\n-4.18052\t2.8795623852398376e+27\n-4.16691\t2.875726633761722e+27\n-4.15331\t2.8747000166645294e+27\n-4.1397\t2.879493456000054e+27\n-4.12609\t2.8899403430099583e+27\n-4.11249\t2.9031862750172426e+27\n-4.09888\t2.915853987132249e+27\n-4.08528\t2.925981228185644e+27\n-4.07167\t2.933376567749841e+27\n-4.05807\t2.9388839425792906e+27\n-4.04446\t2.943590059639545e+27\n-4.03085\t2.9483760881889276e+27\n-4.01725\t2.9535558705562445e+27\n-4.00364\t2.958949315709575e+27\n-3.99004\t2.964392582774563e+27\n-3.97643\t2.970064423484428e+27\n-3.96282\t2.9761351073472913e+27\n-3.94922\t2.9819800747358366e+27\n-3.93561\t2.986065471491718e+27\n-3.92201\t2.9869195869162915e+27\n-3.9084\t2.9844215269801944e+27\n-3.8948\t2.980168271453855e+27\n-3.88119\t2.97662546924482e+27\n-3.86758\t2.9756893887397785e+27\n-3.85398\t2.9776520863420117e+27\n-3.84037\t2.981457748242657e+27\n-3.82677\t2.9858683267230103e+27\n-3.81316\t2.990543818486315e+27\n-3.79956\t2.996234766524307e+27\n-3.78595\t3.004085378360081e+27\n-3.77234\t3.0147073563534254e+27\n-3.75874\t3.027657124774748e+27\n-3.74513\t3.041655564078531e+27\n-3.73153\t3.0551058730675055e+27\n-3.71792\t3.066530090982425e+27\n-3.70431\t3.0747005273478687e+27\n-3.69071\t3.07884467467341e+27\n-3.6771\t3.079052265971981e+27\n-3.6635\t3.0763620613156584e+27\n-3.64989\t3.0722655037372727e+27\n-3.63629\t3.0680290340879795e+27\n-3.62268\t3.0643832844521687e+27\n-3.60907\t3.061592721679891e+27\n-3.59547\t3.0596063631339495e+27\n-3.58186\t3.0582250104542957e+27\n-3.56826\t3.05745178867123e+27\n-3.55465\t3.057895900120303e+27\n-3.54105\t3.0608154820007245e+27\n-3.52744\t3.06753626145279e+27\n-3.51383\t3.0785206536744786e+27\n-3.50023\t3.0927487380621e+27\n-3.48662\t3.10802040399712e+27\n-3.47302\t3.1221396480436845e+27\n-3.45941\t3.13416610394091e+27\n-3.4458\t3.1446853130806393e+27\n-3.4322\t3.1547668394050584e+27\n-3.41859\t3.1646823819772004e+27\n-3.40499\t3.173569164574229e+27\n-3.39138\t3.1802233362375924e+27\n-3.37778\t3.183944443746949e+27\n-3.36417\t3.184657843521394e+27\n-3.35056\t3.182624609520936e+27\n-3.33696\t3.178338853679466e+27\n-3.32335\t3.1726388876968903e+27\n-3.30975\t3.166786598808782e+27\n-3.29614\t3.1623585201587434e+27\n-3.28253\t3.1609298455916733e+27\n-3.26893\t3.1635948714324276e+27\n-3.25532\t3.1706130644825754e+27\n-3.24172\t3.181414419215201e+27\n-3.22811\t3.195017140396288e+27\n-3.21451\t3.21035407482131e+27\n-3.2009\t3.2262670862606896e+27\n-3.18729\t3.241389465033898e+27\n-3.17369\t3.254303340250049e+27\n-3.16008\t3.2640466490093115e+27\n-3.14648\t3.2706252842259686e+27\n-3.13287\t3.275097024013643e+27\n-3.11927\t3.279166706331439e+27\n-3.10566\t3.2846000625860434e+27\n-3.09205\t3.2927433558311575e+27\n-3.07845\t3.3044055224818585e+27\n-3.06484\t3.3198068325310826e+27\n-3.05124\t3.338523621156584e+27\n-3.03763\t3.359421145212754e+27\n-3.02402\t3.381000640167198e+27\n-3.01042\t3.402012808192127e+27\n-2.99681\t3.421874072200461e+27\n-2.98321\t3.440343447712698e+27\n-2.9696\t3.4567219100937775e+27\n-2.956\t3.4696061421653576e+27\n-2.94239\t3.4775743444270316e+27\n-2.92878\t3.480406961178503e+27\n-2.91518\t3.479554631485531e+27\n-2.90157\t3.4771605904151693e+27\n-2.88797\t3.4745539579977554e+27\n-2.87436\t3.4717753596272017e+27\n-2.86076\t3.4688655992705837e+27\n-2.84715\t3.4669894203643997e+27\n-2.83354\t3.467892554121409e+27\n-2.81994\t3.4717867883094455e+27\n-2.80633\t3.4762806711689676e+27\n-2.79273\t3.477636666459893e+27\n-2.77912\t3.4735468053750096e+27\n-2.76551\t3.46486145330253e+27\n-2.75191\t3.4546072467323314e+27\n-2.7383\t3.445732964256507e+27\n-2.7247\t3.4390012918416776e+27\n-2.71109\t3.4332363252288396e+27\n-2.69749\t3.42670795835674e+27\n-2.68388\t3.418435378143741e+27\n-2.67027\t3.408690462226038e+27\n-2.65667\t3.3989697429715226e+27\n-2.64306\t3.391271096894962e+27\n-2.62946\t3.386774892584359e+27\n-2.61585\t3.385017821975936e+27\n-2.60225\t3.3838515606675756e+27\n-2.58864\t3.381713504222162e+27\n-2.57503\t3.378941870204851e+27\n-2.56143\t3.3772239071184817e+27\n-2.54782\t3.3773856944014974e+27\n-2.53422\t3.3777417692826596e+27\n-2.52061\t3.3752061196963696e+27\n-2.507\t3.3677400651607877e+27\n-2.4934\t3.356135399067627e+27\n-2.47979\t3.3434067935050393e+27\n-2.46619\t3.3325418667274316e+27\n-2.45258\t3.32434616225984e+27\n-2.43898\t3.3176767225912914e+27\n-2.42537\t3.3115017520029534e+27\n-2.41176\t3.306248754640011e+27\n-2.39816\t3.303392744804571e+27\n-2.38455\t3.303252029154443e+27\n-2.37095\t3.3041612343988945e+27\n-2.35734\t3.3032889937985754e+27\n-2.34373\t3.298672788324412e+27\n-2.33013\t3.2904328869997045e+27\n-2.31652\t3.2804335936154935e+27\n-2.30292\t3.270960823193724e+27\n-2.28931\t3.2634168214737757e+27\n-2.27571\t3.257586139938035e+27\n-2.2621\t3.2518917097234215e+27\n-2.24849\t3.244817087554694e+27\n-2.23489\t3.2359504837247523e+27\n-2.22128\t3.226466909626798e+27\n-2.20768\t3.2181924543956196e+27\n-2.19407\t3.212883027914098e+27\n-2.18046\t3.2114221208916364e+27\n-2.16686\t3.213412050900779e+27\n-2.15325\t3.2172158377832446e+27\n-2.13965\t3.2206375673897585e+27\n-2.12604\t3.222203832576656e+27\n-2.11244\t3.221903383234853e+27\n-2.09883\t3.220915337940234e+27\n-2.08522\t3.220457119211516e+27\n-2.07162\t3.2205388164322445e+27\n-2.05801\t3.219546842528104e+27\n-2.04441\t3.215168764362882e+27\n-2.0308\t3.2062995712221187e+27\n-2.01719\t3.193842039716505e+27\n-2.00359\t3.1802789617769517e+27\n-1.98998\t3.168021878643506e+27\n-1.97638\t3.1583375883136434e+27\n-1.96277\t3.151220912165722e+27\n-1.94917\t3.145989165008827e+27\n-1.93556\t3.1418229638980176e+27\n-1.92195\t3.137711763320507e+27\n-1.90835\t3.132133137800193e+27\n-1.89474\t3.1231774259633806e+27\n-1.88114\t3.10959381211042e+27\n-1.86753\t3.091673638351952e+27\n-1.85393\t3.071071027869623e+27\n-1.84032\t3.0497930536959427e+27\n-1.82671\t3.029327944546861e+27\n-1.81311\t3.010572226972466e+27\n-1.7995\t2.9943111764441273e+27\n-1.7859\t2.98149551646601e+27\n-1.77229\t2.9727953428212453e+27\n-1.75868\t2.968081457828528e+27\n-1.74508\t2.966234207774274e+27\n-1.73147\t2.965742774437786e+27\n-1.71787\t2.9657738461676366e+27\n-1.70426\t2.9669752863885284e+27\n-1.69066\t2.971816047611469e+27\n-1.67705\t2.9838499142948384e+27\n-1.66344\t3.005734680066407e+27\n-1.64984\t3.037577131675892e+27\n-1.63623\t3.075664108119559e+27\n-1.62263\t3.1131336678623145e+27\n-1.60902\t3.1428745812376184e+27\n-1.59542\t3.161696995887296e+27\n-1.58181\t3.173204339608224e+27\n-1.5682\t3.184961953612978e+27\n-1.5546\t3.20152238204416e+27\n-1.54099\t3.2200773833866463e+27\n-1.52739\t3.23358305005524e+27\n-1.51378\t3.2378355020023586e+27\n-1.50017\t3.2350127960612706e+27\n-1.48657\t3.2311390085000615e+27\n-1.47296\t3.231176776723414e+27\n-1.45936\t3.237378354712602e+27\n-1.44575\t3.249800439445944e+27\n-1.43215\t3.2669947133087634e+27\n-1.41854\t3.2859689151444933e+27\n-1.40493\t3.302350234696133e+27\n-1.39133\t3.312783550145873e+27\n-1.37772\t3.3177983309132936e+27\n-1.36412\t3.321827298550596e+27\n-1.35051\t3.329230048900936e+27\n-1.3369\t3.3403349780056654e+27\n-1.3233\t3.3511312434032296e+27\n-1.30969\t3.3568314772455454e+27\n-1.29609\t3.355543339755444e+27\n-1.28248\t3.3492339928641585e+27\n-1.26888\t3.342801162632692e+27\n-1.25527\t3.3413809702907244e+27\n-1.24166\t3.3479163015160667e+27\n-1.22806\t3.361483129491982e+27\n-1.21445\t3.378139540996696e+27\n-1.20085\t3.393483886207861e+27\n-1.18724\t3.404833906974775e+27\n-1.17364\t3.412095405955506e+27\n-1.16003\t3.416608664002894e+27\n-1.14642\t3.419748783735992e+27\n-1.13282\t3.422402559467662e+27\n-1.11921\t3.425403838568812e+27\n-1.10561\t3.429629415255342e+27\n-1.092\t3.4355627763581176e+27\n-1.07839\t3.443859642520884e+27\n-1.06479\t3.4555313628356486e+27\n-1.05118\t3.4719113430885885e+27\n-1.03758\t3.4934264624188306e+27\n-1.02397\t3.518133844844907e+27\n-1.01037\t3.5419158611555464e+27\n-0.99676\t3.560399343947428e+27\n-0.98315\t3.572316602357277e+27\n-0.96955\t3.580644629536474e+27\n-0.95594\t3.5896085557386493e+27\n-0.94234\t3.600279730637591e+27\n-0.92873\t3.6101126831232043e+27\n-0.91513\t3.617022660838355e+27\n-0.90152\t3.6220805670239305e+27\n-0.88791\t3.6272460635384423e+27\n-0.87431\t3.632770402818098e+27\n-0.8607\t3.636917764460521e+27\n-0.8471\t3.638550280289801e+27\n-0.83349\t3.6373656259459547e+27\n-0.81988\t3.633196210518264e+27\n-0.80628\t3.6254283673421793e+27\n-0.79267\t3.613640306613635e+27\n-0.77907\t3.597631847820202e+27\n-0.76546\t3.577618260906336e+27\n-0.75186\t3.555060363607916e+27\n-0.73825\t3.532704968273006e+27\n-0.72464\t3.513154421563179e+27\n-0.71104\t3.49756391325087e+27\n-0.69743\t3.48538209870439e+27\n-0.68383\t3.475865756431565e+27\n-0.67022\t3.4682797007324226e+27\n-0.65662\t3.461915264021259e+27\n-0.64301\t3.4560617251210305e+27\n-0.6294\t3.450207114781842e+27\n-0.6158\t3.443588211317591e+27\n-0.60219\t3.4346107135552507e+27\n-0.58859\t3.421488532747889e+27\n-0.57498\t3.404184614964792e+27\n-0.56137\t3.385149608968061e+27\n-0.54777\t3.367498991394705e+27\n-0.53416\t3.3527535805623865e+27\n-0.52056\t3.340548908651419e+27\n-0.50695\t3.329693535537875e+27\n-0.49335\t3.3192828988794625e+27\n-0.47974\t3.3091994975368633e+27\n-0.46613\t3.2999869974958825e+27\n-0.45253\t3.293111127254304e+27\n-0.43892\t3.290456815803153e+27\n-0.42532\t3.293789705262536e+27\n-0.41171\t3.304277217666355e+27\n-0.3981\t3.321758101451072e+27\n-0.3845\t3.344043496107238e+27\n-0.37089\t3.3670596121343747e+27\n-0.35729\t3.386692927503891e+27\n-0.34368\t3.4012134254411127e+27\n-0.33008\t3.4123796051397434e+27\n-0.31647\t3.4238637343498635e+27\n-0.30286\t3.438394321670629e+27\n-0.28926\t3.4556332388234635e+27\n-0.27565\t3.471934468312816e+27\n-0.26205\t3.4823074260344555e+27\n-0.24844\t3.483585206281274e+27\n-0.23484\t3.476573352578308e+27\n-0.22123\t3.4656030676362644e+27\n-0.20762\t3.455940384658769e+27\n-0.19402\t3.450819085001372e+27\n-0.18041\t3.451096855551847e+27\n-0.16681\t3.4563767281753787e+27\n-0.1532\t3.465768515669061e+27\n-0.13959\t3.4773875569016075e+27\n-0.12599\t3.488145518356339e+27\n-0.11238\t3.495590322685873e+27\n-0.09878\t3.5002813503141017e+27\n-0.08517\t3.5055297940614626e+27\n-0.07157\t3.5151884591428566e+27\n-0.05796\t3.531583618114402e+27\n-0.04435\t3.554780985899001e+27\n-0.03075\t3.582389914316333e+27\n-0.01714\t3.6101566121205796e+27\n-0.00354\t3.633327104644589e+27\n0.01007\t3.6492733306917404e+27\n0.02367\t3.6584307409128424e+27\n0.03728\t3.663266769947041e+27\n0.05089\t3.6663885859312326e+27\n0.06449\t3.669467812216749e+27\n0.0781\t3.6733149923771085e+27\n0.0917\t3.6785142392188726e+27\n0.10531\t3.6854558243833546e+27\n0.11892\t3.6942263558531834e+27\n0.13252\t3.70444725852903e+27\n0.14613\t3.715395489685806e+27\n0.15973\t3.7263255956668364e+27\n0.17334\t3.736701678418776e+27\n0.18694\t3.7462451638119306e+27\n0.20055\t3.7547988181788653e+27\n0.21416\t3.762114781973415e+27\n0.22776\t3.767940731320414e+27\n0.24137\t3.772336309655322e+27\n0.25497\t3.775799021802071e+27\n0.26858\t3.7788982482815134e+27\n0.28218\t3.7817307757464054e+27\n0.29579\t3.7838270460723643e+27\n0.3094\t3.7846312502987004e+27\n0.323\t3.78407669135013e+27\n0.33661\t3.7826110521389273e+27\n0.35021\t3.780779784382499e+27\n0.36382\t3.77897539188666e+27\n0.37743\t3.7774876096036096e+27\n0.39103\t3.7765730471643557e+27\n0.40464\t3.776267597774071e+27\n0.41824\t3.7761867041325633e+27\n0.43185\t3.775721342477444e+27\n0.44545\t3.7744865983622e+27\n0.45906\t3.7725830084759466e+27\n0.47267\t3.7704480770608346e+27\n0.48627\t3.7685885947451166e+27\n0.49988\t3.767269296238584e+27\n0.51348\t3.766341965818385e+27\n0.52709\t3.7652781162173206e+27\n0.54069\t3.7634471163206326e+27\n0.5543\t3.760568784840185e+27\n0.56791\t3.75693982108142e+27\n0.58151\t3.7532993393538303e+27\n0.59512\t3.7504809191685834e+27\n0.60872\t3.749120370262077e+27\n0.62233\t3.749469748649737e+27\n0.63594\t3.7514004816563193e+27\n0.64954\t3.754542565694177e+27\n0.66315\t3.758472514514226e+27\n0.67675\t3.762850592679448e+27\n0.69036\t3.767342511234209e+27\n0.70396\t3.7714819263710093e+27\n0.71757\t3.774698743276353e+27\n0.73118\t3.7766129582656295e+27\n0.74478\t3.777322161570813e+27\n0.75839\t3.777327161619294e+27\n0.77199\t3.7772372500332035e+27\n0.7856\t3.7774839488538284e+27\n0.79921\t3.778241456198808e+27\n0.81281\t3.779482539661234e+27\n0.82642\t3.781021126008322e+27\n0.84002\t3.782580158982237e+27\n0.85363\t3.783859546387496e+27\n0.86723\t3.7845639282173577e+27\n0.88084\t3.7844353555421133e+27\n0.89445\t3.7832723085506344e+27\n0.90805\t3.780954071786719e+27\n0.92166\t3.777486002445169e+27\n0.93526\t3.773123728004612e+27\n0.94887\t3.7684077001339745e+27\n0.96247\t3.7640301576882324e+27\n0.97608\t3.760549945371798e+27\n0.98969\t3.758161707929139e+27\n1.00329\t3.756655621897182e+27\n1.0169\t3.7555007892710657e+27\n1.0305\t3.754134079590537e+27\n1.04411\t3.752317722692974e+27\n1.05772\t3.7503885968448317e+27\n1.07132\t3.749293586227336e+27\n1.08493\t3.7502124344224315e+27\n1.09853\t3.753870684179447e+27\n1.11214\t3.75991181418432e+27\n1.12574\t3.767009918723595e+27\n1.13935\t3.7737931987816817e+27\n1.15296\t3.7797276313234185e+27\n1.16656\t3.785075629607513e+27\n1.18017\t3.790221304501259e+27\n1.19377\t3.7952611747976676e+27\n1.20738\t3.800141579262142e+27\n1.22098\t3.804934482878187e+27\n1.23459\t3.8098098872941794e+27\n1.2482\t3.8148242216286993e+27\n1.2618\t3.819873109869692e+27\n1.27541\t3.824790746838039e+27\n1.28901\t3.829469810064544e+27\n1.30262\t3.833877084941437e+27\n1.31623\t3.8380731970565564e+27\n1.32983\t3.8422168086626176e+27\n1.34344\t3.8464860464867825e+27\n1.35704\t3.850912517978381e+27\n1.37065\t3.8552830960708806e+27\n1.38425\t3.859291795654516e+27\n1.39786\t3.862849508722417e+27\n1.41147\t3.8662340058250576e+27\n1.42507\t3.86994252392663e+27\n1.43868\t3.8743934599411574e+27\n1.45228\t3.879723868768986e+27\n1.46589\t3.885748302183393e+27\n1.4795\t3.892026220198507e+27\n1.4931\t3.897976902897809e+27\n1.50671\t3.903084363135301e+27\n1.52031\t3.9070819018964323e+27\n1.53392\t3.910020948251301e+27\n1.54752\t3.912191683585006e+27\n1.56113\t3.9139976832392855e+27\n1.57474\t3.9158449332935386e+27\n1.58834\t3.9180013827744386e+27\n1.60195\t3.9204422100127365e+27\n1.61555\t3.922862412051047e+27\n1.62916\t3.9248998425207654e+27\n1.64277\t3.9263769997007925e+27\n1.65637\t3.9273596878006096e+27\n1.66998\t3.9280323728945606e+27\n1.68358\t3.928534699193813e+27\n1.69719\t3.9289727391554434e+27\n1.71079\t3.929502208575025e+27\n1.7244\t3.930366502669721e+27\n1.73801\t3.9317943736575713e+27\n1.75161\t3.9338132325186435e+27\n1.76522\t3.9362352202885547e+27\n1.77882\t3.938817656042781e+27\n1.79243\t3.9414251813259956e+27\n1.80603\t3.9441092252082963e+27\n1.81964\t3.9470597002454087e+27\n1.83325\t3.950452679573153e+27\n1.84685\t3.95426289508938e+27\n1.86046\t3.9581928439094286e+27\n1.87406\t3.961834397075978e+27\n1.88767\t3.9649421057805237e+27\n1.90128\t3.967591327896613e+27\n1.91488\t3.9700739412543644e+27\n1.92849\t3.972720574059633e+27\n1.94209\t3.9757580142256946e+27\n1.9557\t3.9792508159499136e+27\n1.9693\t3.983111835530178e+27\n1.98291\t3.987108838571829e+27\n1.99652\t3.9909361078248424e+27\n2.01012\t3.994329355012327e+27\n2.02373\t3.997216704437357e+27\n2.03733\t3.999801818788984e+27\n2.05094\t4.002486487677345e+27\n2.06455\t4.0056577684268734e+27\n2.07815\t4.009468519662581e+27\n2.09176\t4.013814097512672e+27\n2.10536\t4.018426285090734e+27\n2.11897\t4.02301990106015e+27\n2.13257\t4.0273612824409795e+27\n2.14618\t4.0312677488904796e+27\n2.15979\t4.034637870853736e+27\n2.17339\t4.037496827146317e+27\n2.187\t4.0400143515568606e+27\n2.2006\t4.0424006246947594e+27\n2.21421\t4.0447156471417936e+27\n2.22781\t4.046802095943949e+27\n2.24142\t4.0484322010355687e+27\n2.25503\t4.049563908437457e+27\n2.26863\t4.0504479348663406e+27\n2.28224\t4.051463301854449e+27\n2.29584\t4.052872511947072e+27\n2.30945\t4.0547349407199315e+27\n2.32305\t4.0569896054388646e+27\n2.33666\t4.059566951858029e+27\n2.35027\t4.062411800870965e+27\n2.36387\t4.065466562633553e+27\n2.37748\t4.068661593613369e+27\n2.39108\t4.071944393301356e+27\n2.40469\t4.0753113009477307e+27\n2.4183\t4.0788109777386117e+27\n2.4319\t4.082465477459266e+27\n2.44551\t4.086186317108882e+27\n2.45911\t4.0897767090650736e+27\n2.47272\t4.093056830155659e+27\n2.48633\t4.096017662436055e+27\n2.49993\t4.098826886103559e+27\n2.51354\t4.10165727069053e+27\n2.52714\t4.1045526559077636e+27\n2.54075\t4.1074342017050923e+27\n2.55435\t4.110209853618504e+27\n2.56796\t4.112809878828997e+27\n2.58157\t4.1151474907807784e+27\n2.59517\t4.117128849278238e+27\n2.60878\t4.1187416327733313e+27\n2.62238\t4.120093431594995e+27\n2.63599\t4.1213278185639186e+27\n2.64959\t4.122523365870529e+27\n2.6632\t4.1237053416169746e+27\n2.67681\t4.1249211569772515e+27\n2.69041\t4.1262825094629784e+27\n2.70402\t4.127883328556348e+27\n2.71762\t4.1297436144512864e+27\n2.73123\t4.1318327418508426e+27\n2.74483\t4.13415517508402e+27\n2.75844\t4.1368158258823525e+27\n2.77205\t4.1400007674786255e+27\n2.78565\t4.1438955373861415e+27\n2.79926\t4.1485453146143973e+27\n2.81286\t4.153765008082988e+27\n2.82647\t4.159183274905567e+27\n2.84008\t4.164436272268509e+27\n2.85368\t4.169362212888799e+27\n2.86729\t4.174020472342157e+27\n2.88089\t4.1785599806440747e+27\n2.8945\t4.1830777923070445e+27\n2.90811\t4.1875566750211216e+27\n2.92171\t4.191867431105e+27\n2.93532\t4.1958269337830385e+27\n2.94892\t4.19929839601463e+27\n2.96253\t4.2022788713426325e+27\n2.97613\t4.2048788965531245e+27\n2.98974\t4.207220526401008e+27\n3.00335\t4.20938260093645e+27\n3.01695\t4.211443960209617e+27\n3.03056\t4.213543980571937e+27\n3.04416\t4.215844717166167e+27\n3.05777\t4.218416170671049e+27\n3.07137\t4.221161822293571e+27\n3.08498\t4.2238580984373364e+27\n3.09859\t4.2262936577674115e+27\n3.11219\t4.2283801065695677e+27\n3.1258\t4.230166998895721e+27\n3.1394\t4.2317584428981867e+27\n3.15301\t4.2332243499691296e+27\n3.16661\t4.2345647201085494e+27\n3.18022\t4.23573151713639e+27\n3.19383\t4.2367035801331834e+27\n3.20743\t4.2375603741551573e+27\n3.22104\t4.238510651226423e+27\n3.23464\t4.23981155669747e+27\n3.24825\t4.241643628033118e+27\n3.26185\t4.244034990506079e+27\n3.27546\t4.246897964694761e+27\n3.28907\t4.2501352282269317e+27\n3.30267\t4.2537222272930824e+27\n3.31628\t4.2577087838048703e+27\n3.32988\t4.262156059069616e+27\n3.34349\t4.267059142325418e+27\n3.3571\t4.272318211175803e+27\n3.3707\t4.277748174540365e+27\n3.38431\t4.283112065835706e+27\n3.39791\t4.288173186338162e+27\n3.41152\t4.2927192125604216e+27\n3.42513\t4.296578089262766e+27\n3.43873\t4.299663476322305e+27\n3.45234\t4.3020210884680134e+27\n3.46594\t4.3038379810850565e+27\n3.47955\t4.3053988890771527e+27\n3.49315\t4.306989797360138e+27\n3.50676\t4.3088354402559514e+27\n3.52037\t4.3110480509956904e+27\n3.53397\t4.313646469047742e+27\n3.54758\t4.316595069066674e+27\n3.56118\t4.319821975355561e+27\n3.57479\t4.3232162939820053e+27\n3.58839\t4.326626862766015e+27\n3.602\t4.329916537520664e+27\n3.61561\t4.333044782138617e+27\n3.62921\t4.3360936509869234e+27\n3.64282\t4.3392157348308543e+27\n3.65642\t4.342539338485915e+27\n3.67003\t4.346116158881942e+27\n3.68363\t4.349888338315076e+27\n3.69724\t4.3537048931784854e+27\n3.71085\t4.3573560000090985e+27\n3.72445\t4.360659246323912e+27\n3.73806\t4.3635466850355223e+27\n3.75166\t4.3660835846339326e+27\n3.76527\t4.368430839536358e+27\n3.77888\t4.370770862225801e+27\n3.79248\t4.3732322253775053e+27\n3.80609\t4.3758314470087774e+27\n3.81969\t4.3784908477949893e+27\n3.8333\t4.3811352484357574e+27\n3.84691\t4.3838033993068125e+27\n3.86051\t4.386646909021048e+27\n3.87412\t4.3898464043298656e+27\n3.88772\t4.393537690121492e+27\n3.90133\t4.3977736240513056e+27\n3.91493\t4.402484562586882e+27\n3.92854\t4.407478361007995e+27\n3.94215\t4.412512606249862e+27\n3.95575\t4.4174343504008906e+27\n3.96936\t4.422261807923407e+27\n3.98296\t4.427102837006088e+27\n3.99657\t4.431982795037662e+27\n4.01017\t4.4367352518329527e+27\n4.02378\t4.441055829440635e+27\n4.03739\t4.4446787217119584e+27\n4.05099\t4.4474886596721023e+27\n4.0646\t4.4495333223548034e+27\n4.0782\t4.4509950329564853e+27\n4.09181\t4.4521445083877996e+27\n4.10541\t4.4532525548459796e+27\n4.11902\t4.454463548730935e+27\n4.13263\t4.4557527576599975e+27\n4.14623\t4.4570326807847373e+27\n4.15984\t4.4582884072462875e+27\n4.17344\t4.4596077057528203e+27\n4.18705\t4.461096202328511e+27\n4.20065\t4.46284282640707e+27\n4.21426\t4.464922400142564e+27\n4.22787\t4.467436442376487e+27\n4.24147\t4.4705003113702375e+27\n4.25508\t4.4742016865454076e+27\n4.26868\t4.4785741396560875e+27\n4.28229\t4.483570884534342e+27\n4.2959\t4.4890354018053765e+27\n4.3095\t4.4947500107870775e+27\n4.32311\t4.5005338168683017e+27\n4.33671\t4.506311283602344e+27\n4.35032\t4.512094643250668e+27\n4.36393\t4.517921039030567e+27\n4.37753\t4.5238033282095655e+27\n4.39114\t4.529718564136595e+27\n4.40474\t4.535615764174458e+27\n4.41835\t4.541453410063441e+27\n4.43195\t4.547229716071943e+27\n4.44556\t4.5529512894068856e+27\n4.45917\t4.55855955807177e+27\n4.47277\t4.563882466826876e+27\n4.48638\t4.5687062635996116e+27\n4.49998\t4.5729068400437323e+27\n4.51359\t4.5765039284934266e+27\n4.52719\t4.5795996727962493e+27\n4.5408\t4.5823010382750747e+27\n4.55441\t4.584696418644137e+27\n4.56801\t4.586877868367446e+27\n4.58162\t4.588955567084759e+27\n4.59522\t4.591010854870484e+27\n4.60883\t4.5930741784484116e+27\n4.62244\t4.595136877020279e+27\n4.63604\t4.5972050220735293e+27\n4.64965\t4.5993246854834557e+27\n4.66325\t4.601565242922745e+27\n4.67686\t4.6039999986735996e+27\n4.69046\t4.6067301144311964e+27\n4.70407\t4.60991737747855e+27\n4.71768\t4.6137619683280893e+27\n4.73128\t4.618432995762392e+27\n4.74489\t4.623987424619518e+27\n4.75849\t4.6303482005809e+27\n4.7721\t4.6373166610059716e+27\n4.78571\t4.6446311069286603e+27\n4.79931\t4.6520385894677423e+27\n4.81292\t4.659376428474399e+27\n4.82652\t4.66657908759889e+27\n4.84013\t4.6736258523546484e+27\n4.85373\t4.6804927046516443e+27\n4.86734\t4.687168483667375e+27\n4.88095\t4.6936792610832086e+27\n4.89455\t4.700112894893896e+27\n4.90816\t4.7065630467218885e+27\n4.92176\t4.713075431296163e+27\n4.93537\t4.719616030429727e+27\n4.94897\t4.7260805573971056e+27\n4.96258\t4.732348118168936e+27\n4.97619\t4.738319336781644e+27\n4.98979\t4.74393287335475e+27\n5.0034\t4.749140334561877e+27\n5.017\t4.753935381055842e+27\n5.03061\t4.758368459754363e+27\n5.04421\t4.7625568039370197e+27\n5.05782\t4.766646129302423e+27\n5.07143\t4.770730186759604e+27\n5.08503\t4.7748317443864714e+27\n5.09864\t4.7789472307198233e+27\n5.11224\t4.783124860512877e+27\n5.12585\t4.787510617323981e+27\n5.13946\t4.79228494933138e+27\n5.15306\t4.797558929040629e+27\n5.16667\t4.803337467213632e+27\n5.18027\t4.809565652603668e+27\n5.19388\t4.816208395584788e+27\n5.20748\t4.823295607161299e+27\n5.22109\t4.830931484772099e+27\n5.2347\t4.8392868336447856e+27\n5.2483\t4.8485287982571766e+27\n5.26191\t4.858697378997126e+27\n5.27551\t4.869642395837021e+27\n5.28912\t4.881090810415128e+27\n5.30273\t4.8928517280233436e+27\n5.31633\t4.905009613766375e+27\n5.32994\t4.918080633363379e+27\n5.34354\t4.9329883671981944e+27\n5.35715\t4.9508065756822676e+27\n5.37075\t4.972243212108662e+27\n5.38436\t4.997228454371794e+27\n5.39797\t5.024918812150114e+27\n5.41157\t5.05419829247982e+27\n5.42518\t5.084269655487817e+27\n5.43878\t5.114893434566464e+27\n5.45239\t5.146179720068938e+27\n5.46599\t5.178236191610757e+27\n5.4796\t5.211164368033414e+27\n5.49321\t5.245034517875394e+27\n5.50681\t5.280198876694919e+27\n5.52042\t5.316363334497367e+27\n5.53402\t5.35134679870575e+27\n5.54763\t5.380620921840653e+27\n5.56123\t5.399042171886254e+27\n5.57484\t5.404108024577452e+27\n5.58845\t5.397629747476749e+27\n5.60205\t5.384352654453033e+27\n5.61566\t5.369101167285101e+27\n5.62926\t5.354770849763344e+27\n5.64287\t5.341980815033695e+27\n5.65648\t5.330032038461097e+27\n5.67008\t5.318406390021628e+27\n5.68369\t5.307273514217348e+27\n5.69729\t5.297386989783717e+27\n5.7109\t5.288978961828812e+27\n5.72451\t5.281352191449175e+27\n5.73811\t5.273333631556364e+27\n5.75172\t5.264207114491953e+27\n5.76532\t5.254372286988158e+27\n5.77893\t5.245071750379267e+27\n5.79253\t5.237506141306952e+27\n5.80614\t5.232068767156246e+27\n5.81975\t5.228188015241794e+27\n5.83335\t5.224693159926236e+27\n5.84696\t5.22030472451773e+27\n5.86056\t5.214049842440264e+27\n5.87417\t5.205631725101816e+27\n5.88777\t5.195533948619832e+27\n5.90138\t5.184720361625741e+27\n5.91499\t5.174170795048802e+27\n5.92859\t5.164598827236617e+27\n5.9422\t5.156438748114459e+27\n5.9558\t5.149871005860564e+27\n5.96941\t5.144653455269895e+27\n5.98302\t5.139957963312664e+27\n5.99662\t5.134614250784411e+27\n6.01023\t5.127742041292613e+27\n6.02383\t5.11931267384508e+27\n6.03744\t5.110105263139161e+27\n6.05104\t5.101114461676397e+27\n6.06465\t5.092929918031309e+27\n6.07826\t5.085576632446306e+27\n6.09186\t5.078760941359667e+27\n6.10547\t5.072230967329126e+27\n6.11907\t5.066015549920035e+27\n6.13268\t5.060438710131322e+27\n6.14628\t5.05586295147791e+27\n6.15989\t5.0522748809728e+27\n6.1735\t5.049048242543654e+27\n6.1871\t5.045187758682869e+27\n6.20071\t5.039907350339858e+27\n6.21431\t5.033023533592655e+27\n6.22792\t5.024864525909456e+27\n6.24153\t5.015935957192973e+27\n6.25513\t5.006676403124316e+27\n6.26874\t4.997387027337928e+27\n6.28234\t4.988260510273517e+27\n6.29595\t4.979411763759581e+27\n6.30956\t4.970942485210775e+27\n6.32316\t4.963055980169829e+27\n6.33677\t4.956090198342159e+27\n6.35037\t4.9503749643543997e+27\n6.36398\t4.9459684930567273e+27\n6.37758\t4.942522031067545e+27\n6.39119\t4.939437983306707e+27\n6.4048\t4.9361799160013893e+27\n6.4184\t4.932438094005465e+27\n6.43201\t4.9281055519960584e+27\n6.44561\t4.923212022404319e+27\n6.45922\t4.9179162567695424e+27\n6.47282\t4.912425132097659e+27\n6.48643\t4.906914275091588e+27\n6.50004\t4.9014731509045213e+27\n6.51364\t4.896147563552014e+27\n6.52725\t4.8909634954288554e+27\n6.54085\t4.8859007677679585e+27\n6.55446\t4.880856165282808e+27\n6.56806\t4.8757481693258354e+27\n6.58167\t4.870615262413034e+27\n6.59528\t4.8656036066759146e+27\n6.60888\t4.86078034562266e+27\n6.62249\t4.8559917277624566e+27\n6.63609\t4.8509881078175406e+27\n6.6497\t4.8457034137186864e+27\n6.66331\t4.8403347009480247e+27\n6.67691\t4.8351565257391483e+27\n6.69052\t4.830287549956918e+27\n6.70412\t4.825647862112206e+27\n6.71773\t4.8210848714397407e+27\n6.73133\t4.8165383987845807e+27\n6.74494\t4.8120738912098887e+27\n6.75855\t4.8078088498549853e+27\n6.77215\t4.8037908644670266e+27\n6.78576\t4.7999383271118653e+27\n6.79937\t4.7961315937722593e+27\n6.81297\t4.7923275390300545e+27\n6.82657\t4.788635717518947e+27\n6.84018\t4.7852775599574157e+27\n6.85379\t4.782485747173017e+27\n6.86739\t4.7803596551293277e+27\n6.881\t4.7787486573658346e+27\n6.89461\t4.7772324819503353e+27\n6.90821\t4.7753070168519743e+27\n6.92181\t4.772646633913381e+27\n6.93542\t4.769267761865283e+27\n6.94903\t4.765457814208795e+27\n6.96263\t4.761592508872689e+27\n6.97624\t4.7579815810030906e+27\n6.98985\t4.7548256575453274e+27\n7.00345\t4.752223310883754e+27\n7.01706\t4.750182308950834e+27\n7.03066\t4.7486208652392587e+27\n7.04427\t4.747409067775083e+27\n7.05787\t4.746420843907304e+27\n7.07148\t4.745598068072321e+27\n7.08509\t4.74495091894026e+27\n7.09869\t4.7445076110704075e+27\n7.1123\t4.7442809124437096e+27\n7.1259\t4.744314930630702e+27\n7.13951\t4.7446843092122876e+27\n7.15311\t4.7454053876326154e+27\n7.16672\t4.7462792353913756e+27\n7.18033\t4.746939688223862e+27\n7.19393\t4.7471137077683417e+27\n7.20754\t4.746859866021314e+27\n7.22114\t4.7465102197739146e+27\n7.23475\t4.746406468767919e+27\n7.24836\t4.746680042849133e+27\n7.26196\t4.7472180837803975e+27\n7.27557\t4.7477428210112375e+27\n7.28917\t4.747941840798126e+27\n7.30278\t4.7475841587585227e+27\n7.31638\t4.7466369174309783e+27\n7.32999\t4.7452718149088896e+27\n7.3436\t4.7437540323349493e+27\n7.3572\t4.7423043754215716e+27\n7.37081\t4.741012220035368e+27\n7.38441\t4.739847208739128e+27\n7.39802\t4.738729072897405e+27\n7.41162\t4.7376078120253805e+27\n7.42523\t4.736517355023466e+27\n7.43884\t4.7355710958483016e+27\n7.45244\t4.734951625556049e+27\n7.46605\t4.734829213654827e+27\n7.47965\t4.7352752001220803e+27\n7.49326\t4.73618154819597e+27\n7.50686\t4.7372900410870506e+27\n7.52047\t4.738354426407596e+27\n7.53408\t4.739290596199218e+27\n7.54768\t4.7401984621449694e+27\n7.56129\t4.7412713296906163e+27\n7.57489\t4.742683218380642e+27\n7.5885\t4.7445395756660586e+27\n7.6021\t4.74684602660141e+27\n7.61571\t4.749485159333955e+27\n7.62932\t4.7521801854656e+27\n7.64292\t4.754561190695277e+27\n7.65653\t4.7563025468656144e+27\n7.67013\t4.7572481810347184e+27\n7.68374\t4.757419075548897e+27\n7.69735\t4.7569304993829696e+27\n7.71095\t4.7559113823585e+27\n7.72456\t4.7544925293152334e+27\n7.73816\t4.752813495177757e+27\n7.75177\t4.7510066919442566e+27\n7.76537\t4.74917756706575e+27\n7.77898\t4.74740165698894e+27\n7.79259\t4.745730569357087e+27\n7.80619\t4.7442021616801225e+27\n7.8198\t4.742845005663657e+27\n7.83341\t4.7416599048869106e+27\n7.84701\t4.740611948297091e+27\n7.86061\t4.7396412245989974e+27\n7.87422\t4.7386997868991555e+27\n7.88783\t4.737796742428725e+27\n7.90143\t4.737010127658655e+27\n7.91504\t4.7364880690252165e+27\n7.92865\t4.736410836133489e+27\n7.94225\t4.736950484223195e+27\n7.95585\t4.7382251394397124e+27\n7.96946\t4.740238373246243e+27\n7.98307\t4.742864737997844e+27\n7.99667\t4.7458583384531105e+27\n8.01028\t4.748876849864206e+27\n8.02389\t4.7515463400339626e+27\n8.03749\t4.7535622524378935e+27\n8.0511\t4.75480494305876e+27\n8.0647\t4.755356287690449e+27\n8.07831\t4.755421199034131e+27\n8.09191\t4.7551865539018116e+27\n8.10552\t4.754741103154039e+27\n8.11913\t4.754081721760512e+27\n8.13273\t4.7531998382095495e+27\n8.14634\t4.752132327858704e+27\n8.15994\t4.7509843702992493e+27\n8.17355\t4.749890163260974e+27\n8.18716\t4.748941850494469e+27\n8.20076\t4.748172289461185e+27\n8.21437\t4.7475357654321463e+27\n8.22797\t4.746926384523437e+27\n8.24158\t4.746211109730812e+27\n8.25518\t4.7452766363842115e+27\n8.26879\t4.7440706425477374e+27\n8.2824\t4.742622592792801e+27\n8.296\t4.7410286487660944e+27\n8.30961\t4.7394198831671016e+27\n8.32321\t4.7379042434710816e+27\n8.33682\t4.736531640876271e+27\n8.35042\t4.7353050218398095e+27\n8.36403\t4.734244297269046e+27\n8.37764\t4.733445003804612e+27\n8.39124\t4.7330698215953236e+27\n8.40485\t4.7332683056627306e+27\n8.41845\t4.73408250998603e+27\n8.43206\t4.735414130040607e+27\n8.44566\t4.737067092496715e+27\n8.45927\t4.738793984241087e+27\n8.47288\t4.7403661423422665e+27\n8.48648\t4.7416018686098904e+27\n8.50009\t4.742421965847472e+27\n8.51369\t4.742857327211701e+27\n8.5273\t4.742995096404689e+27\n8.5409\t4.742910006293919e+27\n8.55451\t4.7426247356707215e+27\n8.56812\t4.742121248645928e+27\n8.58172\t4.7413767771416334e+27\n8.59533\t4.740403910565619e+27\n8.60893\t4.7392703281455503e+27\n8.62254\t4.7380686200649183e+27\n8.63615\t4.736869590581687e+27\n8.64975\t4.7356849362378406e+27\n8.66336\t4.7344864424740895e+27\n8.67697\t4.733248573328545e+27\n8.69057\t4.731979900312889e+27\n8.70417\t4.7307350668141015e+27\n8.71778\t4.7295839842243473e+27\n8.73139\t4.728581295930603e+27\n8.74499\t4.7277281626584105e+27\n8.7586\t4.7269884233428565e+27\n8.77221\t4.726297702359739e+27\n8.78581\t4.725591981231177e+27\n8.79942\t4.724829384551136e+27\n8.81302\t4.72402625176376e+27\n8.82663\t4.723241869158191e+27\n8.84023\t4.7225382909075507e+27\n8.85384\t4.7219124812681157e+27\n8.86745\t4.7213031003594066e+27\n8.88105\t4.7206612191355655e+27\n8.89466\t4.7200295165818486e+27\n8.90826\t4.719530315312898e+27\n8.92187\t4.7192717413771294e+27\n8.93547\t4.708795032649495e+27\n8.94908\t4.6675248110545756e+27\n8.96269\t4.5401154506616824e+27\n8.97629\t4.234198287984104e+27\n8.9899\t3.6625591738002986e+27'
num_al_fcc='3'
vol_al_fcc='1.1200e-28'
button_al_fcc = Button(
    description='Al fcc',
    disabled=False,
    button_style='', # 'success', 'info', 'warning', 'danger' or ''
    tooltip='Al fcc',
    icon='' # (FontAwesome names without the `fa-` prefix)
)

DOS_au_fcc='-10.8\t0\n-10.74913\t0\n-10.73552\t0\n-10.72192\t0\n-10.70831\t0\n-10.6947\t0\n-10.6811\t0\n-10.66749\t0\n-10.65388\t0\n-10.64028\t0\n-10.62667\t0\n-10.61307\t0\n-10.59946\t0\n-10.58586\t0\n-10.57225\t0\n-10.55865\t0\n-10.54504\t0\n-10.53143\t0\n-10.51783\t0\n-10.50422\t0\n-10.49062\t0\n-10.47701\t0\n-10.4634\t0\n-10.4498\t0\n-10.43619\t0\n-10.42259\t0\n-10.40898\t0\n-10.39538\t0\n-10.38177\t0\n-10.36816\t0\n-10.35456\t0\n-10.34095\t0\n-10.32735\t0\n-10.31374\t0\n-10.30013\t0\n-10.28653\t0\n-10.27292\t0\n-10.25932\t0\n-10.24571\t0\n-10.23211\t0\n-10.2185\t0\n-10.20489\t0\n-10.19129\t0\n-10.17768\t0\n-10.16408\t0\n-10.15047\t0\n-10.13686\t0\n-10.12326\t0\n-10.10965\t0\n-10.09605\t0\n-10.08244\t0\n-10.06884\t0\n-10.05523\t0\n-10.04163\t0\n-10.02802\t6.55414272286668e+21\n-10.01441\t1.095852663263309e+23\n-10.00081\t6.576863750972617e+23\n-9.9872\t2.4583278524928346e+24\n-9.9736\t7.194263995466659e+24\n-9.95999\t1.7198769613359275e+25\n-9.94638\t3.427038885789493e+25\n-9.93278\t5.805205203353186e+25\n-9.91917\t8.565801379367668e+25\n-9.90557\t1.1340484592807832e+26\n-9.89196\t1.3903215569447451e+26\n-9.87836\t1.622009628312386e+26\n-9.86475\t1.8327323079381207e+26\n-9.85114\t2.022237042855695e+26\n-9.83754\t2.187190833019107e+26\n-9.82393\t2.3284413475538477e+26\n-9.81033\t2.45448100765736e+26\n-9.79672\t2.576119779393891e+26\n-9.78311\t2.7011352454612426e+26\n-9.76951\t2.8312148791391295e+26\n-9.7559\t2.9631314205508114e+26\n-9.7423\t3.091479886664165e+26\n-9.72869\t3.2112336869536e+26\n-9.71509\t3.31986729175657e+26\n-9.70148\t3.418258956197941e+26\n-9.68787\t3.5098133389508176e+26\n-9.67427\t3.598427970221064e+26\n-9.66066\t3.687252334058443e+26\n-9.64706\t3.77848512687505e+26\n-9.63345\t3.873445916072425e+26\n-9.61984\t3.9724746431864584e+26\n-9.60624\t4.0746816925782345e+26\n-9.59263\t4.1780073156613794e+26\n-9.57903\t4.279425246269322e+26\n-9.56542\t4.375614718755809e+26\n-9.55182\t4.464262557682519e+26\n-9.53821\t4.545374006363628e+26\n-9.5246\t4.6213872058920426e+26\n-9.511\t4.695697202198209e+26\n-9.49739\t4.7708338943731525e+26\n-9.48379\t4.8477471961688406e+26\n-9.47018\t4.9263785572436176e+26\n-9.45657\t5.006532227201492e+26\n-9.44297\t5.0882702519269066e+26\n-9.42936\t5.1718207155866176e+26\n-9.41576\t5.2572334296653205e+26\n-9.40215\t5.344224381311688e+26\n-9.38855\t5.431956388028589e+26\n-9.37494\t5.5190120072164896e+26\n-9.36133\t5.603578799941094e+26\n-9.34773\t5.6840767808633434e+26\n-9.33412\t5.759944041480462e+26\n-9.32052\t5.831907654691841e+26\n-9.30691\t5.9015012898946324e+26\n-9.29331\t5.9703460050556245e+26\n-9.2797\t6.039747385405211e+26\n-9.26609\t6.110579316639776e+26\n-9.25249\t6.183235047322691e+26\n-9.23888\t6.257655153226601e+26\n-9.22528\t6.3334551246451e+26\n-9.21167\t6.410216370329617e+26\n-9.19806\t6.487677598456937e+26\n-9.18446\t6.565798610285026e+26\n-9.17085\t6.644688641525931e+26\n-9.15725\t6.724443819606255e+26\n-9.14364\t6.804936557214324e+26\n-9.13004\t6.885607567504458e+26\n-9.11643\t6.96541867426935e+26\n-9.10282\t7.043180519076226e+26\n-9.08922\t7.118166029025695e+26\n-9.07561\t7.190562215656785e+26\n-9.06201\t7.261345209292352e+26\n-9.0484\t7.331629214195285e+26\n-9.0348\t7.402143924922063e+26\n-9.02119\t7.473185588723759e+26\n-9.00758\t7.544920243882686e+26\n-8.99398\t7.617591704508137e+26\n-8.98037\t7.691493596194091e+26\n-8.96677\t7.7668076871654e+26\n-8.95316\t7.84351562582244e+26\n-8.93955\t7.921429526740486e+26\n-8.92595\t8.000307323581642e+26\n-8.91234\t8.079962878692579e+26\n-8.89874\t8.160293947446818e+26\n-8.88513\t8.241241979502703e+26\n-8.87153\t8.322751920061363e+26\n-8.85792\t8.404664721926053e+26\n-8.84431\t8.486608983675815e+26\n-8.83071\t8.567973859208874e+26\n-8.8171\t8.648117916424088e+26\n-8.8035\t8.726717817613795e+26\n-8.78989\t8.803993781973482e+26\n-8.77629\t8.880597728232651e+26\n-8.76268\t8.957306540775387e+26\n-8.74907\t9.034744173988905e+26\n-8.73547\t9.113262803808847e+26\n-8.72186\t9.192954188233335e+26\n-8.70826\t9.273737055892604e+26\n-8.69465\t9.355459350675484e+26\n-8.68104\t9.438052035611961e+26\n-8.66744\t9.521554435558372e+26\n-8.65383\t9.606102876683351e+26\n-8.64023\t9.691830189612752e+26\n-8.62662\t9.778794924688229e+26\n-8.61302\t9.866967369796106e+26\n-8.59941\t9.956258388595352e+26\n-8.5858\t1.0046554375945438e+27\n-8.5722\t1.013773560950596e+27\n-8.55859\t1.0229671006422459e+27\n-8.54499\t1.0322184041784266e+27\n-8.53138\t1.0415014297653862e+27\n-8.51777\t1.0507818336952564e+27\n-8.50417\t1.0600307777400569e+27\n-8.49056\t1.0692457276312683e+27\n-8.47696\t1.0784592793053652e+27\n-8.46335\t1.0877223802984473e+27\n-8.44975\t1.0970805600552956e+27\n-8.43614\t1.1065630063581695e+27\n-8.42253\t1.1161874590867055e+27\n-8.40893\t1.1259691238520207e+27\n-8.39532\t1.1359176133967753e+27\n-8.38172\t1.1460310051724368e+27\n-8.36811\t1.1562973269449656e+27\n-8.35451\t1.1667030334860673e+27\n-8.3409\t1.1772417454301585e+27\n-8.32729\t1.1879184439257082e+27\n-8.31369\t1.1987469363667197e+27\n-8.30008\t1.2097448752442596e+27\n-8.28648\t1.2209247571237862e+27\n-8.27287\t1.2322893784395281e+27\n-8.25926\t1.2438320102716232e+27\n-8.24566\t1.2555409425517397e+27\n-8.23205\t1.2674021931087357e+27\n-8.21845\t1.2794028284343043e+27\n-8.20484\t1.291528167248747e+27\n-8.19124\t1.3037645769352e+27\n-8.17763\t1.3161032312481295e+27\n-8.16402\t1.3285531312102084e+27\n-8.15042\t1.3411484457521655e+27\n-8.13681\t1.3539430062328977e+27\n-8.12321\t1.366991605285568e+27\n-8.1096\t1.380330683943716e+27\n-8.09599\t1.3939778073098385e+27\n-8.08239\t1.4079423259608872e+27\n-8.06878\t1.422234813913788e+27\n-8.05518\t1.4368666316825943e+27\n-8.04157\t1.4518420613072179e+27\n-8.02797\t1.4671558594734807e+27\n-8.01436\t1.4827962287244815e+27\n-8.00075\t1.498759236574587e+27\n-7.98715\t1.5150552822635832e+27\n-7.97354\t1.531707785928134e+27\n-7.95994\t1.5487443623562445e+27\n-7.94633\t1.566182314484704e+27\n-7.93273\t1.5840218170906504e+27\n-7.91912\t1.6022497618886393e+27\n-7.90551\t1.6208473603361973e+27\n-7.89191\t1.6398008924278923e+27\n-7.8783\t1.6591072121752166e+27\n-7.8647\t1.6787821369092747e+27\n-7.85109\t1.6988680500863417e+27\n-7.83749\t1.7194444753047877e+27\n-7.82388\t1.7406306105736e+27\n-7.81027\t1.762578337226809e+27\n-7.79667\t1.785447488958284e+27\n-7.78306\t1.809371158559583e+27\n-7.76946\t1.8344406670859782e+27\n-7.75585\t1.860707486404987e+27\n-7.74224\t1.8881942501561453e+27\n-7.72864\t1.9169109206363918e+27\n-7.71503\t1.9468660619255513e+27\n-7.70143\t1.9780802977260583e+27\n-7.68782\t2.0105863987515272e+27\n-7.67422\t2.04441040679571e+27\n-7.66061\t2.079553807464291e+27\n-7.647\t2.1159985113233546e+27\n-7.6334\t2.1537342065216835e+27\n-7.61979\t2.1927760986703948e+27\n-7.60619\t2.233157570203091e+27\n-7.59258\t2.2749623393694845e+27\n-7.57897\t2.3184141209078493e+27\n-7.56537\t2.364136432262555e+27\n-7.55176\t2.4135540566729824e+27\n-7.53816\t2.469045885781823e+27\n-7.52455\t2.5333834480751537e+27\n-7.51095\t2.6085110518388547e+27\n-7.49734\t2.69486275609832e+27\n-7.48373\t2.7920007441196607e+27\n-7.47013\t2.9029020823047434e+27\n-7.45652\t3.0379950234456356e+27\n-7.44292\t3.2182013523879946e+27\n-7.42931\t3.475568030612409e+27\n-7.41571\t3.833125179595628e+27\n-7.4021\t4.275081597415454e+27\n-7.38849\t4.7329810111029386e+27\n-7.37489\t5.117607119085876e+27\n-7.36128\t5.376550898826551e+27\n-7.34768\t5.518535652123391e+27\n-7.33407\t5.584694217430844e+27\n-7.32047\t5.610089510544851e+27\n-7.30686\t5.615108673042022e+27\n-7.29325\t5.61513576349861e+27\n-7.27965\t5.624608946613102e+27\n-7.26604\t5.6504313950555e+27\n-7.25244\t5.686618826965549e+27\n-7.23883\t5.722228008710302e+27\n-7.22522\t5.747945765646273e+27\n-7.21162\t5.762817814593015e+27\n-7.19801\t5.776206442570147e+27\n-7.18441\t5.806942837671872e+27\n-7.1708\t5.879049855526028e+27\n-7.1572\t6.012872865972938e+27\n-7.14359\t6.213892705323171e+27\n-7.12998\t6.466145841395206e+27\n-7.11638\t6.738466276878973e+27\n-7.10277\t7.000836475046594e+27\n-7.08917\t7.237210758461085e+27\n-7.07556\t7.447505234095592e+27\n-7.06195\t7.641880745719093e+27\n-7.04835\t7.83330278585453e+27\n-7.03474\t8.031421849024192e+27\n-7.02114\t8.240671943862953e+27\n-7.00753\t8.462492971832742e+27\n-6.99393\t8.699226597045585e+27\n-6.98032\t8.955973865088404e+27\n-6.96671\t9.238036815258289e+27\n-6.95311\t9.543906946066145e+27\n-6.9395\t9.859006008936355e+27\n-6.9259\t1.0156836915668913e+28\n-6.91229\t1.0410976683570868e+28\n-6.89868\t1.0610406750062243e+28\n-6.88508\t1.0763836085216043e+28\n-6.87147\t1.0894806295807114e+28\n-6.85787\t1.1036420172014409e+28\n-6.84426\t1.1224671143123384e+28\n-6.83066\t1.1484619716637759e+28\n-6.81705\t1.1815252359926873e+28\n-6.80344\t1.218884164111878e+28\n-6.78984\t1.2568816842037e+28\n-6.77623\t1.292945400115712e+28\n-6.76263\t1.3261035596923933e+28\n-6.74902\t1.3565030543804493e+28\n-6.73541\t1.3848306097766678e+28\n-6.72181\t1.4119168105411752e+28\n-6.7082\t1.438507553071262e+28\n-6.6946\t1.4651010046470075e+28\n-6.68099\t1.4919583347476327e+28\n-6.66739\t1.5191381898422214e+28\n-6.65378\t1.546372217111129e+28\n-6.64017\t1.5730320315666577e+28\n-6.62657\t1.5982634885903068e+28\n-6.61296\t1.621085904914739e+28\n-6.59936\t1.6404081293817373e+28\n-6.58575\t1.655171222259854e+28\n-6.57215\t1.6646756555268488e+28\n-6.55854\t1.6688458992419837e+28\n-6.54493\t1.668188763414875e+28\n-6.53133\t1.6636076536007293e+28\n-6.51772\t1.6562240185748566e+28\n-6.50412\t1.6471461813494076e+28\n-6.49051\t1.637164422976192e+28\n-6.4769\t1.6266504245195944e+28\n-6.4633\t1.6157834811079423e+28\n-6.44969\t1.604777886991702e+28\n-6.43609\t1.593821562551024e+28\n-6.42248\t1.5828954483388697e+28\n-6.40888\t1.5718192180417906e+28\n-6.39527\t1.5605200507647078e+28\n-6.38166\t1.5492038077611175e+28\n-6.36806\t1.5382132095234274e+28\n-6.35445\t1.5277344199215372e+28\n-6.34085\t1.517657128363993e+28\n-6.32724\t1.5077285983685438e+28\n-6.31364\t1.4978330925135608e+28\n-6.30003\t1.4881433343069342e+28\n-6.28642\t1.4789940307092353e+28\n-6.27282\t1.470592607229357e+28\n-6.25921\t1.4628369678013915e+28\n-6.24561\t1.4553867689020252e+28\n-6.232\t1.4479214605189686e+28\n-6.21839\t1.4403651019852061e+28\n-6.20479\t1.4329287629129845e+28\n-6.19118\t1.425972658986353e+28\n-6.17758\t1.4198061107864027e+28\n-6.16397\t1.4145857798019242e+28\n-6.15037\t1.4103901234907387e+28\n-6.13676\t1.4073987253634528e+28\n-6.12315\t1.4060095529661987e+28\n-6.10955\t1.4067055504902254e+28\n-6.09594\t1.4099149743599017e+28\n-6.08234\t1.415624200697221e+28\n-6.06873\t1.4228016686096035e+28\n-6.05512\t1.428615691319633e+28\n-6.04152\t1.4287025730355674e+28\n-6.02791\t1.4190486528813496e+28\n-6.01431\t1.3984265234409825e+28\n-6.0007\t1.3691810822035689e+28\n-5.9871\t1.3357084199036164e+28\n-5.97349\t1.3021006373972895e+28\n-5.95988\t1.2709545122479584e+28\n-5.94628\t1.243193881458411e+28\n-5.93267\t1.218338072940209e+28\n-5.91907\t1.1948127903501765e+28\n-5.90546\t1.17071558452729e+28\n-5.89186\t1.1446112380369526e+28\n-5.87825\t1.1161989943778976e+28\n-5.86464\t1.0863699547947262e+28\n-5.85104\t1.0569022057750098e+28\n-5.83743\t1.0295635831271024e+28\n-5.82383\t1.005132710267623e+28\n-5.81022\t9.831930845348193e+27\n-5.79661\t9.631223594911556e+27\n-5.78301\t9.450686762398825e+27\n-5.7694\t9.302741147378391e+27\n-5.7558\t9.206346748696101e+27\n-5.74219\t9.187501403653619e+27\n-5.72859\t9.286187742351811e+27\n-5.71498\t9.555475619691993e+27\n-5.70137\t1.0042050281677716e+28\n-5.68777\t1.0750199535866847e+28\n-5.67416\t1.1617533885960433e+28\n-5.66056\t1.2526332015021682e+28\n-5.64695\t1.3346460370625247e+28\n-5.63335\t1.3987173875561663e+28\n-5.61974\t1.4426805058320555e+28\n-5.60613\t1.4705843752260971e+28\n-5.59253\t1.4888845379380348e+28\n-5.57892\t1.5023895150567837e+28\n-5.56532\t1.5128916286679103e+28\n-5.55171\t1.520604561301894e+28\n-5.5381\t1.5261635666880052e+28\n-5.5245\t1.5308854157935535e+28\n-5.51089\t1.5362492912425197e+28\n-5.49729\t1.5428462980587938e+28\n-5.48368\t1.5499492846932735e+28\n-5.47008\t1.5559091501871724e+28\n-5.45647\t1.5595438243144222e+28\n-5.44286\t1.5621503981364492e+28\n-5.42926\t1.5680276552154693e+28\n-5.41565\t1.5823347807537845e+28\n-5.40205\t1.6069865020064535e+28\n-5.38844\t1.638493174916398e+28\n-5.37484\t1.6689814301746355e+28\n-5.36123\t1.6905127939878035e+28\n-5.34762\t1.699298631046663e+28\n-5.33402\t1.6968690540335812e+28\n-5.32041\t1.6885484649806183e+28\n-5.30681\t1.6803449766109708e+28\n-5.2932\t1.6761630665217895e+28\n-5.27959\t1.6767224844503285e+28\n-5.26599\t1.680296327394253e+28\n-5.25238\t1.683992365775103e+28\n-5.23878\t1.6845407377884398e+28\n-5.22517\t1.679352600753016e+28\n-5.21157\t1.6674910967691684e+28\n-5.19796\t1.6510869252029585e+28\n-5.18435\t1.6350670623494466e+28\n-5.17075\t1.6249427819580077e+28\n-5.15714\t1.6239083197649153e+28\n-5.14354\t1.6313483116793478e+28\n-5.12993\t1.643968732957362e+28\n-5.11632\t1.658584112936219e+28\n-5.10272\t1.6739938287965166e+28\n-5.08911\t1.690497902975537e+28\n-5.07551\t1.7081494677236197e+28\n-5.0619\t1.7260940725622705e+28\n-5.0483\t1.7428499394269892e+28\n-5.03469\t1.7567498429696474e+28\n-5.02108\t1.765984778626735e+28\n-5.00748\t1.7689385647136487e+28\n-4.99387\t1.7654576507746773e+28\n-4.98027\t1.7576295050504827e+28\n-4.96666\t1.7490208745331353e+28\n-4.95305\t1.74292828327967e+28\n-4.93945\t1.7411393868260339e+28\n-4.92584\t1.7438820071732736e+28\n-4.91224\t1.750457236757994e+28\n-4.89863\t1.7600701192399098e+28\n-4.88503\t1.7723713450284634e+28\n-4.87142\t1.7874321795021944e+28\n-4.85781\t1.8054051244539785e+28\n-4.84421\t1.8258205624494374e+28\n-4.8306\t1.8477792563681363e+28\n-4.817\t1.8707786607626565e+28\n-4.80339\t1.8952019308165774e+28\n-4.78979\t1.9221297922317573e+28\n-4.77618\t1.9522110264880479e+28\n-4.76257\t1.9846720524892973e+28\n-4.74897\t2.0171351583385044e+28\n-4.73536\t2.046649476726981e+28\n-4.72176\t2.071297763608863e+28\n-4.70815\t2.091491313287153e+28\n-4.69455\t2.1098376259027164e+28\n-4.68094\t2.1293259061297417e+28\n-4.66733\t2.151869858777022e+28\n-4.65373\t2.177934513379029e+28\n-4.64012\t2.2075515482922585e+28\n-4.62652\t2.2411157850743347e+28\n-4.61291\t2.279489591608162e+28\n-4.5993\t2.324169750575647e+28\n-4.5857\t2.3776743898274855e+28\n-4.57209\t2.4437227756263372e+28\n-4.55849\t2.525049296316183e+28\n-4.54488\t2.62014800215416e+28\n-4.53128\t2.721893098089115e+28\n-4.51767\t2.82115881426515e+28\n-4.50406\t2.9142594416303483e+28\n-4.49046\t3.0044027436715626e+28\n-4.47685\t3.0944164484640033e+28\n-4.46325\t3.1772366320638195e+28\n-4.44964\t3.2332177322963503e+28\n-4.43604\t3.2381183434599504e+28\n-4.42243\t3.17520188534722e+28\n-4.40882\t3.045420098131231e+28\n-4.39522\t2.8699503607461184e+28\n-4.38161\t2.6813380728571173e+28\n-4.36801\t2.507285952848676e+28\n-4.3544\t2.3596774829299064e+28\n-4.34079\t2.2367118818017015e+28\n-4.32719\t2.131165016055492e+28\n-4.31358\t2.0377479022464923e+28\n-4.29998\t1.9554192094400355e+28\n-4.28637\t1.886173476871831e+28\n-4.27277\t1.8321700498810682e+28\n-4.25916\t1.7912985382052692e+28\n-4.24555\t1.7561752106911343e+28\n-4.23195\t1.7165195361847118e+28\n-4.21834\t1.6641009183820522e+28\n-4.20474\t1.5967519110235605e+28\n-4.19113\t1.5193154925111606e+28\n-4.17753\t1.4420699306348504e+28\n-4.16392\t1.376841197186063e+28\n-4.15031\t1.3323955367063453e+28\n-4.13671\t1.3126465064652339e+28\n-4.1231\t1.3154142335485308e+28\n-4.1095\t1.33284130580007e+28\n-4.09589\t1.3538620057677e+28\n-4.08228\t1.3704117055189282e+28\n-4.06868\t1.3836133219570351e+28\n-4.05507\t1.4038029129331207e+28\n-4.04147\t1.44208639464137e+28\n-4.02786\t1.5001997497565031e+28\n-4.01426\t1.5660763471051605e+28\n-4.00065\t1.6184685997763601e+28\n-3.98704\t1.63829149083653e+28\n-3.97344\t1.6205604461843613e+28\n-3.95983\t1.576355742207707e+28\n-3.94623\t1.5247296950373814e+28\n-3.93262\t1.4804048754717596e+28\n-3.91901\t1.448351080205024e+28\n-3.90541\t1.426287170448481e+28\n-3.8918\t1.40963495516621e+28\n-3.8782\t1.3946876733998668e+28\n-3.86459\t1.3795947585822216e+28\n-3.85099\t1.3644661105784512e+28\n-3.83738\t1.3510547965286404e+28\n-3.82377\t1.3417726710439482e+28\n-3.81017\t1.338608654275056e+28\n-3.79656\t1.342234065213924e+28\n-3.78296\t1.3518362076406315e+28\n-3.76935\t1.3654382734602486e+28\n-3.75575\t1.3812804229185443e+28\n-3.74214\t1.398991158467129e+28\n-3.72853\t1.4198595488967363e+28\n-3.71493\t1.4454984463874666e+28\n-3.70132\t1.477436303238863e+28\n-3.68772\t1.5168034119494832e+28\n-3.67411\t1.5634132066620065e+28\n-3.6605\t1.6137336249076522e+28\n-3.6469\t1.6606619946507918e+28\n-3.63329\t1.6971927238178073e+28\n-3.61969\t1.720700502477341e+28\n-3.60608\t1.7334551001651775e+28\n-3.59248\t1.7397406279026905e+28\n-3.57887\t1.742720036318222e+28\n-3.56526\t1.7436241759374128e+28\n-3.55166\t1.742724624218128e+28\n-3.53805\t1.7411756356047196e+28\n-3.52445\t1.7412570031019098e+28\n-3.51084\t1.7454523448142445e+28\n-3.49723\t1.754171093668193e+28\n-3.48363\t1.7650261522343744e+28\n-3.47002\t1.7747736305912471e+28\n-3.45642\t1.7819344335033993e+28\n-3.44281\t1.7884762194825193e+28\n-3.42921\t1.7994877560214947e+28\n-3.4156\t1.820674302016584e+28\n-3.40199\t1.8574263077807805e+28\n-3.38839\t1.9128223502784408e+28\n-3.37478\t1.9823045650549434e+28\n-3.36118\t2.0483375355101114e+28\n-3.34757\t2.0834831471095037e+28\n-3.33397\t2.0664063195062176e+28\n-3.32036\t1.9983052635951336e+28\n-3.30675\t1.902248560562497e+28\n-3.29315\t1.8063406190919557e+28\n-3.27954\t1.7294371659880655e+28\n-3.26594\t1.6790004859893728e+28\n-3.25233\t1.6554512501924026e+28\n-3.23872\t1.654856404937732e+28\n-3.22512\t1.6678604008644596e+28\n-3.21151\t1.6819751142501453e+28\n-3.19791\t1.6873928472745796e+28\n-3.1843\t1.681036491101375e+28\n-3.1707\t1.6658859697386242e+28\n-3.15709\t1.6468056368323844e+28\n-3.14348\t1.6271939115118885e+28\n-3.12988\t1.6083220352996637e+28\n-3.11627\t1.5902728263431563e+28\n-3.10267\t1.5727439813634162e+28\n-3.08906\t1.5554277615124631e+28\n-3.07545\t1.5382638337218187e+28\n-3.06185\t1.5214335904454808e+28\n-3.04824\t1.5052514120627228e+28\n-3.03464\t1.490049008106178e+28\n-3.02103\t1.4759622153684914e+28\n-3.00743\t1.462956873657792e+28\n-2.99382\t1.4510290067941609e+28\n-2.98021\t1.4404471948075243e+28\n-2.96661\t1.4316656310497198e+28\n-2.953\t1.4249724793291295e+28\n-2.9394\t1.4203352136201341e+28\n-2.92579\t1.417494150049197e+28\n-2.91219\t1.4160766375388093e+28\n-2.89858\t1.415587532453401e+28\n-2.88497\t1.4152770932986183e+28\n-2.87137\t1.4143451378977115e+28\n-2.85776\t1.4122859049038993e+28\n-2.84416\t1.4091719006134109e+28\n-2.83055\t1.4054194004777179e+28\n-2.81694\t1.401276762811732e+28\n-2.80334\t1.39663116897205e+28\n-2.78973\t1.3913695905827022e+28\n-2.77613\t1.3858544455196923e+28\n-2.76252\t1.3809540353498023e+28\n-2.74892\t1.3775310512936442e+28\n-2.73531\t1.3760164413435313e+28\n-2.7217\t1.3763179231699262e+28\n-2.7081\t1.378041715139182e+28\n-2.69449\t1.3805384852234586e+28\n-2.68089\t1.3829716014736108e+28\n-2.66728\t1.3845422537134327e+28\n-2.65368\t1.3850051072725215e+28\n-2.64007\t1.3849466617971473e+28\n-2.62646\t1.3855287920149354e+28\n-2.61286\t1.387833569411717e+28\n-2.59925\t1.3924668676796507e+28\n-2.58565\t1.3995030719692127e+28\n-2.57204\t1.4086664363877664e+28\n-2.55843\t1.419622970561012e+28\n-2.54483\t1.4319968075120777e+28\n-2.53122\t1.4452610291214734e+28\n-2.51762\t1.4586346350034856e+28\n-2.50401\t1.4713323602102015e+28\n-2.49041\t1.4829016455560361e+28\n-2.4768\t1.493203228616414e+28\n-2.46319\t1.5021357386505546e+28\n-2.44959\t1.5098948211881638e+28\n-2.43598\t1.5177069223709727e+28\n-2.42238\t1.5276065966607275e+28\n-2.40877\t1.5412374133197555e+28\n-2.39516\t1.5588423125716515e+28\n-2.38156\t1.5795382940922197e+28\n-2.36795\t1.6026478168233412e+28\n-2.35435\t1.628372337634603e+28\n-2.34074\t1.6572629638015715e+28\n-2.32714\t1.6891461241472311e+28\n-2.31353\t1.7227064022271028e+28\n-2.29992\t1.7560256189376274e+28\n-2.28632\t1.7877005323218392e+28\n-2.27271\t1.8176690528010105e+28\n-2.25911\t1.8476340340431115e+28\n-2.2455\t1.8813261989522811e+28\n-2.23189\t1.9242926768080172e+28\n-2.21829\t1.981805567583452e+28\n-2.20468\t2.0572145188471034e+28\n-2.19108\t2.1505128628511087e+28\n-2.17747\t2.2575754833376928e+28\n-2.16387\t2.369215980261346e+28\n-2.15026\t2.471589242712574e+28\n-2.13665\t2.551423979346696e+28\n-2.12305\t2.6031461801601947e+28\n-2.10944\t2.6310962081967194e+28\n-2.09584\t2.6445433602989387e+28\n-2.08223\t2.6504284299160844e+28\n-2.06863\t2.6509305558983686e+28\n-2.05502\t2.642963016666744e+28\n-2.04141\t2.618869568552352e+28\n-2.02781\t2.5674005149473816e+28\n-2.0142\t2.480151828192579e+28\n-2.0006\t2.3596037269771317e+28\n-1.98699\t2.2203128137279585e+28\n-1.97338\t2.080372891788653e+28\n-1.95978\t1.9514684683341179e+28\n-1.94617\t1.8364279006372652e+28\n-1.93257\t1.7328408896034755e+28\n-1.91896\t1.6374046454152703e+28\n-1.90536\t1.548165491732104e+28\n-1.89175\t1.4643206334589952e+28\n-1.87814\t1.386677951705678e+28\n-1.86454\t1.3163949430324388e+28\n-1.85093\t1.2538970586905611e+28\n-1.83733\t1.1984682017850016e+28\n-1.82372\t1.1490594210978218e+28\n-1.81012\t1.105093279177423e+28\n-1.79651\t1.067202014847424e+28\n-1.7829\t1.0364149868084502e+28\n-1.7693\t1.011039661982606e+28\n-1.75569\t9.84562987752468e+27\n-1.74209\t9.438091972188286e+27\n-1.72848\t8.735491542616903e+27\n-1.71487\t7.662340769362781e+27\n-1.70127\t6.310430858202516e+27\n-1.68766\t4.9326287625212826e+27\n-1.67406\t3.8072816705079467e+27\n-1.66045\t3.076341215191457e+27\n-1.64685\t2.7011442464839153e+27\n-1.63324\t2.5509625327435784e+27\n-1.61963\t2.5051821953786336e+27\n-1.60603\t2.4958827407405816e+27\n-1.59242\t2.4980203525425026e+27\n-1.57882\t2.500040601495399e+27\n-1.56521\t2.5019298549824077e+27\n-1.5516\t2.5036367285245816e+27\n-1.538\t2.5050647451410393e+27\n-1.52439\t2.5060809868173627e+27\n-1.51079\t2.506533834385228e+27\n-1.49718\t2.506260657716539e+27\n-1.48358\t2.505062385649659e+27\n-1.46997\t2.5025920855631257e+27\n-1.45636\t2.4983191340620956e+27\n-1.44276\t2.4913630913074623e+27\n-1.42915\t2.4807533324562555e+27\n-1.41555\t2.4662394018678913e+27\n-1.40194\t2.4492517630387782e+27\n-1.38834\t2.4328871173226158e+27\n-1.37473\t2.4203592667564198e+27\n-1.36112\t2.4131537296354694e+27\n-1.34752\t2.4106219953844805e+27\n-1.33391\t2.4110991369747053e+27\n-1.32031\t2.4131430682299738e+27\n-1.3067\t2.4159716614520237e+27\n-1.29309\t2.4192651618645488e+27\n-1.27949\t2.422825110025901e+27\n-1.26588\t2.426534230475626e+27\n-1.25228\t2.4302769955246614e+27\n-1.23867\t2.433971347306117e+27\n-1.22507\t2.4375763005808334e+27\n-1.21146\t2.441081281331883e+27\n-1.19785\t2.4444831435707597e+27\n-1.18425\t2.4477707015605497e+27\n-1.17064\t2.4509269145301734e+27\n-1.15704\t2.4539378003084887e+27\n-1.14343\t2.4568305367406528e+27\n-1.12983\t2.4597109513844987e+27\n-1.11622\t2.4627778532359516e+27\n-1.10261\t2.4662570543589583e+27\n-1.08901\t2.4702636454997317e+27\n-1.0754\t2.4746788655921331e+27\n-1.0618\t2.479139964683595e+27\n-1.04819\t2.483159751498383e+27\n-1.03458\t2.486238450806738e+27\n-1.02098\t2.4879359737719605e+27\n-1.00737\t2.487968744485575e+27\n-0.99377\t2.4863884095922376e+27\n-0.98016\t2.4836942199902906e+27\n-0.96656\t2.480705705685803e+27\n-0.95295\t2.4781924104230076e+27\n-0.93934\t2.476550641365214e+27\n-0.92574\t2.4757581144271652e+27\n-0.91213\t2.4755614901454793e+27\n-0.89853\t2.4756831350344158e+27\n-0.88492\t2.4759230166580725e+27\n-0.87132\t2.476149789996284e+27\n-0.85771\t2.476278513359361e+27\n-0.8441\t2.4762550058341286e+27\n-0.8305\t2.476079005254877e+27\n-0.81689\t2.475842269619727e+27\n-0.80329\t2.4757424718731998e+27\n-0.78968\t2.4760243000102833e+27\n-0.77607\t2.4768530058161624e+27\n-0.76247\t2.4782310361707877e+27\n-0.74886\t2.480011578277167e+27\n-0.73526\t2.481998270019322e+27\n-0.72165\t2.4840268208863336e+27\n-0.70805\t2.4859865969490407e+27\n-0.69444\t2.4878015701518567e+27\n-0.68083\t2.4894118793245803e+27\n-0.66723\t2.4907762770623423e+27\n-0.65362\t2.4918631287029325e+27\n-0.64002\t2.492643159075523e+27\n-0.62641\t2.493066119752572e+27\n-0.6128\t2.4930402527359594e+27\n-0.5992\t2.492437096828317e+27\n-0.58559\t2.491095857061509e+27\n-0.57199\t2.4888751387298623e+27\n-0.55838\t2.485764717370729e+27\n-0.54478\t2.481988832053801e+27\n-0.53117\t2.477994475312777e+27\n-0.51756\t2.4742718096347586e+27\n-0.50396\t2.4711398032989244e+27\n-0.49035\t2.4686742221951516e+27\n-0.47675\t2.4667844443767253e+27\n-0.46314\t2.4653406104291625e+27\n-0.44954\t2.4642501758572167e+27\n-0.43593\t2.4634630670104853e+27\n-0.42232\t2.4629547277008995e+27\n-0.40872\t2.462711700088736e+27\n-0.39511\t2.4627158947400784e+27\n-0.38151\t2.4629502708838478e+27\n-0.3679\t2.463396214754712e+27\n-0.35429\t2.4640365981930207e+27\n-0.34069\t2.4648546425934044e+27\n-0.32708\t2.4658320837448076e+27\n-0.31348\t2.4669454141219985e+27\n-0.29987\t2.4681663198284143e+27\n-0.28627\t2.4694560877277045e+27\n-0.27266\t2.4707707613693422e+27\n-0.25905\t2.4720651608628235e+27\n-0.24545\t2.4733024956203312e+27\n-0.23184\t2.4744624914937092e+27\n-0.21824\t2.4755380700088163e+27\n-0.20463\t2.476530629382767e+27\n-0.19103\t2.4774385092327386e+27\n-0.17742\t2.4782502616561077e+27\n-0.16381\t2.478928746510779e+27\n-0.15021\t2.479392779815558e+27\n-0.1366\t2.479520192350091e+27\n-0.123\t2.479112874227007e+27\n-0.10939\t2.477905426360315e+27\n-0.09578\t2.4756448588409144e+27\n-0.08218\t2.472280748464121e+27\n-0.06857\t2.4681088181495925e+27\n-0.05497\t2.463693073725773e+27\n-0.04136\t2.459582315409991e+27\n-0.02776\t2.4560900933901086e+27\n-0.01415\t2.4532703264135918e+27\n-0.00054\t2.4510302952080553e+27\n0.01306\t2.4492439854560806e+27\n0.02667\t2.4478084534226332e+27\n0.04027\t2.4466487197149647e+27\n0.05388\t2.44572467297961e+27\n0.06748\t2.445008698428564e+27\n0.08109\t2.4444680253482122e+27\n0.0947\t2.4440643775450536e+27\n0.1083\t2.4437625374255228e+27\n0.12191\t2.443535676698742e+27\n0.13551\t2.4433723474620885e+27\n0.14912\t2.443269491115624e+27\n0.16273\t2.443235409573465e+27\n0.17633\t2.4432903769837677e+27\n0.18994\t2.4434512593404714e+27\n0.20354\t2.4437275819976676e+27\n0.21715\t2.4441057997270617e+27\n0.23075\t2.4445599581234716e+27\n0.24436\t2.4450602576846505e+27\n0.25797\t2.445586074708164e+27\n0.27157\t2.4461226405257426e+27\n0.28518\t2.446663837937512e+27\n0.29878\t2.4472096669434722e+27\n0.31239\t2.4477633609207e+27\n0.32599\t2.4483292892976772e+27\n0.3396\t2.4489077142401125e+27\n0.35321\t2.4494913824967263e+27\n0.36681\t2.4500549513823232e+27\n0.38042\t2.4505448517037148e+27\n0.39402\t2.450861547880084e+27\n0.40763\t2.450861023548666e+27\n0.42124\t2.4503948055296461e+27\n0.43484\t2.449361435693674e+27\n0.44845\t2.4477415137782902e+27\n0.46205\t2.4455886963652526e+27\n0.47566\t2.4430048785267596e+27\n0.48926\t2.4401281342028391e+27\n0.50287\t2.4371416298354526e+27\n0.51648\t2.4342625260201516e+27\n0.53008\t2.431690156084281e+27\n0.54369\t2.429538387334079e+27\n0.55729\t2.4278177063979022e+27\n0.5709\t2.4264623970713835e+27\n0.58451\t2.4253919744818846e+27\n0.59811\t2.4245422080307226e+27\n0.61172\t2.4238697529873567e+27\n0.62532\t2.4233428873010076e+27\n0.63893\t2.4229367926178986e+27\n0.65253\t2.4226297965727595e+27\n0.66614\t2.4224068683316126e+27\n0.67975\t2.4222639006316845e+27\n0.69335\t2.422212516152737e+27\n0.70696\t2.4222778828028265e+27\n0.72056\t2.422485255878578e+27\n0.73417\t2.4228514139853625e+27\n0.74777\t2.4233735606889505e+27\n0.76138\t2.4240361408239475e+27\n0.77499\t2.4248236866135274e+27\n0.78859\t2.4257245753779276e+27\n0.8022\t2.4267413413856683e+27\n0.8158\t2.427890326299272e+27\n0.82941\t2.429214175740721e+27\n0.84302\t2.4307778194172579e+27\n0.85662\t2.432639982447679e+27\n0.87023\t2.4348066072547191e+27\n0.88383\t2.4371929269258305e+27\n0.89744\t2.4396384960471557e+27\n0.91104\t2.4419623328909756e+27\n0.92465\t2.444012293957549e+27\n0.93826\t2.4456891932203371e+27\n0.95186\t2.4469450543546076e+27\n0.96547\t2.4477724493319423e+27\n0.97907\t2.4481907784148008e+27\n0.99268\t2.4482264329512132e+27\n1.00629\t2.447888676129561e+27\n1.01989\t2.447153388704625e+27\n1.0335\t2.4459431444037055e+27\n1.0471\t2.4441057997270617e+27\n1.06071\t2.44151437908301e+27\n1.07431\t2.4382670198352536e+27\n1.08792\t2.4348221624201147e+27\n1.10153\t2.4318333859499178e+27\n1.11513\t2.429737633272854e+27\n1.12874\t2.428494356092611e+27\n1.14234\t2.4277281331140234e+27\n1.15595\t2.4270572510649105e+27\n1.16955\t2.4262826387836375e+27\n1.18316\t2.4253571064425987e+27\n1.19677\t2.4242666718706532e+27\n1.21037\t2.4229787391313251e+27\n1.22398\t2.4214445454027564e+27\n1.23758\t2.4196060646747074e+27\n1.25119\t2.4173915509315057e+27\n1.2648\t2.4147095957293082e+27\n1.2784\t2.4114606634872985e+27\n1.29201\t2.407591796732275e+27\n1.30561\t2.403164866571542e+27\n1.31922\t2.398357708744313e+27\n1.33282\t2.3933991939144708e+27\n1.34643\t2.3884824508209155e+27\n1.36004\t2.3837237062612662e+27\n1.37364\t2.3791756555430145e+27\n1.38725\t2.3748549898829614e+27\n1.40085\t2.3707673895381337e+27\n1.41446\t2.366916786994165e+27\n1.42807\t2.3633110472223218e+27\n1.44167\t2.3599693957079256e+27\n1.45528\t2.356917000359032e+27\n1.46888\t2.3541667946839478e+27\n1.48249\t2.3516868818547545e+27\n1.49609\t2.349386727313307e+27\n1.5097\t2.347137869862237e+27\n1.52331\t2.344817878115481e+27\n1.53691\t2.3423442572633015e+27\n1.55052\t2.339676284232247e+27\n1.56412\t2.3368036471710993e+27\n1.57773\t2.3337434742395077e+27\n1.59133\t2.3305559761619537e+27\n1.60494\t2.3273641086559173e+27\n1.61855\t2.32435130032907e+27\n1.63215\t2.3217201178858328e+27\n1.64576\t2.3196158011289446e+27\n1.65936\t2.3180768884176153e+27\n1.67297\t2.3170384500446048e+27\n1.68658\t2.3163600525785033e+27\n1.70018\t2.3158508393832211e+27\n1.71379\t2.315289892154713e+27\n1.72739\t2.3144526222690095e+27\n1.741\t2.3131389099016385e+27\n1.7546\t2.3111536163765968e+27\n1.76821\t2.3082669097557376e+27\n1.78182\t2.3042704556890426e+27\n1.79542\t2.299141445759836e+27\n1.80903\t2.2931839048018894e+27\n1.82263\t2.286944885261138e+27\n1.83624\t2.280930017401509e+27\n1.84985\t2.2753746386410375e+27\n1.86345\t2.2702505224717307e+27\n1.87706\t2.265412866033698e+27\n1.89066\t2.2607367036723565e+27\n1.90427\t2.256156581349048e+27\n1.91787\t2.2516421752301066e+27\n1.93148\t2.24718710594995e+27\n1.94509\t2.2427909365657297e+27\n1.95869\t2.2384512201974958e+27\n1.9723\t2.2341602666511198e+27\n1.9859\t2.2299083757953718e+27\n1.99951\t2.2256834880076425e+27\n2.01311\t2.221480796916601e+27\n2.02672\t2.2173080801049458e+27\n2.04033\t2.213179844075236e+27\n2.05393\t2.209104565518727e+27\n2.06754\t2.2050773506755194e+27\n2.08114\t2.2010955778885231e+27\n2.09475\t2.19717593837454e+27\n2.10836\t2.1933813519037093e+27\n2.12196\t2.1898178208110021e+27\n2.13557\t2.1866042809396957e+27\n2.14917\t2.18382287754525e+27\n2.16278\t2.1814635609421574e+27\n2.17638\t2.1794144737612803e+27\n2.18999\t2.1774993532576588e+27\n2.2036\t2.1755394898063822e+27\n2.2172\t2.1733968968559924e+27\n2.23081\t2.1710011392193605e+27\n2.24441\t2.1683558872164113e+27\n2.25802\t2.1655317508114133e+27\n2.27162\t2.162632897179374e+27\n2.28523\t2.159774067512229e+27\n2.29884\t2.1570688669505083e+27\n2.31244\t2.1546250456005754e+27\n2.32605\t2.1525298172549294e+27\n2.33965\t2.1508190986156916e+27\n2.35326\t2.1494512927237142e+27\n2.36687\t2.1482891121360955e+27\n2.38047\t2.1471139980401702e+27\n2.39408\t2.145678291229584e+27\n2.40768\t2.1438197985190877e+27\n2.42129\t2.1415807285878173e+27\n2.43489\t2.1392297138988402e+27\n2.4485\t2.1371211151020395e+27\n2.46211\t2.135465626038813e+27\n2.47571\t2.1341929862991717e+27\n2.48932\t2.13302425156883e+27\n2.50292\t2.1316822253048958e+27\n2.51653\t2.1300429031270524e+27\n2.53014\t2.1281301421148108e+27\n2.54374\t2.1260296704549867e+27\n2.55735\t2.1238146323803666e+27\n2.57095\t2.1215363249813285e+27\n2.58456\t2.119254522039505e+27\n2.59816\t2.1170566995131037e+27\n2.61177\t2.1150846890506477e+27\n2.62538\t2.113556525133384e+27\n2.63898\t2.1127573566640422e+27\n2.65259\t2.1129222588949498e+27\n2.66619\t2.1140637283915643e+27\n2.6798\t2.1158813232514695e+27\n2.6934\t2.1178615482394718e+27\n2.70701\t2.119491694617503e+27\n2.72062\t2.120411808867224e+27\n2.73422\t2.1204406470952045e+27\n2.74783\t2.11953110686241e+27\n2.76143\t2.1177241734080004e+27\n2.77504\t2.1151158867700082e+27\n2.78865\t2.1118131231691013e+27\n2.80225\t2.107899513466423e+27\n2.81586\t2.1034770401227417e+27\n2.82946\t2.0988062084641482e+27\n2.84307\t2.0945444427000317e+27\n2.85667\t2.091934408290647e+27\n2.87028\t2.092761016770855e+27\n2.88389\t2.098637461136177e+27\n2.89749\t2.1096241268882334e+27\n2.9111\t2.1231999411815312e+27\n2.9247\t2.1351161591488296e+27\n2.93831\t2.1419973972878523e+27\n2.95192\t2.1442009000712802e+27\n2.96552\t2.147349073292497e+27\n2.97913\t2.1617189875180975e+27\n2.99273\t2.202563094138458e+27\n3.00634\t2.2920408623110212e+27\n3.01994\t2.4590835888430658e+27\n3.03355\t2.7302156271683234e+27\n3.04716\t3.109711938724927e+27\n3.06076\t3.561727217852961e+27\n3.07437\t4.011616333081697e+27\n3.08797\t4.371854213827138e+27\n3.10158\t4.57929484094297e+27\n3.11518\t4.6211201464232283e+27\n3.12879\t4.53404469003002e+27\n3.1424\t4.3793167607313937e+27\n3.156\t4.212405816162364e+27\n3.16961\t4.0654340593619783e+27\n3.18321\t3.947881314976022e+27\n3.19682\t3.856485717254178e+27\n3.21042\t3.7843219842183266e+27\n3.22403\t3.725550462090963e+27\n3.23764\t3.676452068125425e+27\n3.25124\t3.6347413290599615e+27\n3.26485\t3.598688388158586e+27\n3.27845\t3.5665057122293487e+27\n3.29206\t3.536359976469808e+27\n3.30566\t3.5060398131252695e+27\n3.31927\t3.4728852015245155e+27\n3.33288\t3.434711252649451e+27\n3.34648\t3.391211844340633e+27\n3.36009\t3.3443508599235415e+27\n3.3737\t3.2973940976341263e+27\n3.3873\t3.253413964803729e+27\n3.40091\t3.2141838376760164e+27\n3.41451\t3.1797838515693477e+27\n3.42812\t3.1489680202578214e+27\n3.44172\t3.120057871484396e+27\n3.45533\t3.092134951382173e+27\n3.46894\t3.065463173431461e+27\n3.48254\t3.040919744094288e+27\n3.49615\t3.018930420481931e+27\n3.50975\t2.9988665292244126e+27\n3.52336\t2.979051345836085e+27\n3.53696\t2.957355036097725e+27\n3.55057\t2.932030003393707e+27\n3.56418\t2.9026624628467953e+27\n3.57778\t2.870593392058087e+27\n3.59139\t2.8382232676469756e+27\n3.60499\t2.80774292105429e+27\n3.6186\t2.780394056466021e+27\n3.6322\t2.7567157739682664e+27\n3.64581\t2.7370365671942954e+27\n3.65942\t2.721507356203874e+27\n3.67302\t2.7097535935875336e+27\n3.68663\t2.7005978057579675e+27\n3.70023\t2.6923219334360887e+27\n3.71384\t2.683192012623135e+27\n3.72744\t2.672028821960409e+27\n3.74105\t2.65845580410134e+27\n3.75466\t2.642804511279134e+27\n3.76826\t2.6258658974375884e+27\n3.78187\t2.6086194136652066e+27\n3.79547\t2.591935974447004e+27\n3.80908\t2.5763325705609595e+27\n3.82269\t2.56182720405242e+27\n3.83629\t2.547901573314861e+27\n3.8499\t2.533624378361646e+27\n3.8635\t2.5180059436416245e+27\n3.87711\t2.5004935364518335e+27\n3.89072\t2.4812836062968203e+27\n3.90432\t2.461124374109827e+27\n3.91793\t2.440815095748765e+27\n3.93153\t2.420878879191488e+27\n3.94514\t2.401615554620426e+27\n3.95874\t2.383277587613263e+27\n3.97235\t2.366145145924259e+27\n3.98596\t2.3504133682294169e+27\n3.99956\t2.3361041016711453e+27\n4.01317\t2.3229978261625137e+27\n4.02677\t2.3105811338568968e+27\n4.04038\t2.298084568398631e+27\n4.05398\t2.2847232930437954e+27\n4.06759\t2.2701025736233334e+27\n4.0812\t2.2544770604291707e+27\n4.0948\t2.2385973338859306e+27\n4.10841\t2.2232953331765693e+27\n4.12201\t2.209164426688929e+27\n4.13562\t2.196493346257096e+27\n4.14922\t2.1853577703823758e+27\n4.16283\t2.1757291230024973e+27\n4.17644\t2.1675256958048485e+27\n4.19004\t2.160666130031096e+27\n4.20365\t2.155101488082243e+27\n4.21725\t2.1508507332779006e+27\n4.23086\t2.148050803506692e+27\n4.24446\t2.1469889449970178e+27\n4.25807\t2.148092575242979e+27\n4.27168\t2.1518607703657792e+27\n4.28528\t2.1587663025271613e+27\n4.29889\t2.1691913219421528e+27\n4.31249\t2.1834530491185412e+27\n4.3261\t2.2018294670963452e+27\n4.33971\t2.224405779730962e+27\n4.35331\t2.2506798523012508e+27\n4.36692\t2.2792259402935638e+27\n4.38052\t2.3078139747993028e+27\n4.39413\t2.334051344170343e+27\n4.40774\t2.3560653987479076e+27\n4.42134\t2.372878784769163e+27\n4.43495\t2.3845813376836956e+27\n4.44855\t2.3924775066704966e+27\n4.46216\t2.3991040945175932e+27\n4.47576\t2.4077402699120908e+27\n4.48937\t2.4214127359634083e+27\n4.50298\t2.441863409030145e+27\n4.51658\t2.4693013225708758e+27\n4.53019\t2.5028691947174486e+27\n4.54379\t2.540893971304141e+27\n4.5574\t2.5807201758653556e+27\n4.571\t2.6175224737513786e+27\n4.58461\t2.644471360856414e+27\n4.59822\t2.655292774823284e+27\n4.61182\t2.6483213516803955e+27\n4.62543\t2.6286947528253467e+27\n4.63903\t2.606077804505848e+27\n4.65264\t2.589966061310219e+27\n4.66624\t2.585967247752143e+27\n4.67985\t2.594892766700713e+27\n4.69346\t2.613570587855199e+27\n4.70706\t2.6370243691175534e+27\n4.72067\t2.6616381462532856e+27\n4.73427\t2.686375053883638e+27\n4.74788\t2.710805751965978e+27\n4.76149\t2.731919179944851e+27\n4.77509\t2.7446783480548795e+27\n4.7887\t2.746364947448897e+27\n4.8023\t2.7399175061695586e+27\n4.81591\t2.7323301683878594e+27\n4.82952\t2.7296450671971554e+27\n4.84312\t2.733937069406367e+27\n4.85673\t2.743918853996154e+27\n4.87033\t2.757376518943301e+27\n4.88394\t2.7728259441696423e+27\n4.89754\t2.789636446368099e+27\n4.91115\t2.807589554114575e+27\n4.92476\t2.826601986102206e+27\n4.93836\t2.84657997439577e+27\n4.95197\t2.8673030376340687e+27\n4.96557\t2.888444692120935e+27\n4.97918\t2.9092356562778436e+27\n4.99278\t2.928349022063406e+27\n5.00639\t2.9443706676437384e+27\n5.02\t2.956960738871517e+27\n5.0336\t2.9677050761199673e+27\n5.04721\t2.979416542668603e+27\n5.06081\t2.9943221488260863e+27\n5.07442\t3.01294718728451e+27\n5.08803\t3.034542388447799e+27\n5.10163\t3.0580691391658015e+27\n5.11524\t3.082613092834393e+27\n5.12884\t3.1075200586212613e+27\n5.14245\t3.132011666536639e+27\n5.15605\t3.1548161507265813e+27\n5.16966\t3.1736675255803687e+27\n5.18327\t3.185828431542654e+27\n5.19687\t3.189950113429641e+27\n5.21048\t3.1875860778437875e+27\n5.22408\t3.182472360914268e+27\n5.23769\t3.1779756946749636e+27\n5.25129\t3.1750191645869634e+27\n5.2649\t3.172232168324061e+27\n5.27851\t3.1679698782285265e+27\n5.29211\t3.1622957384019166e+27\n5.30572\t3.1572057037747684e+27\n5.31932\t3.155453213399244e+27\n5.33293\t3.158922539613881e+27\n5.34654\t3.16791831897244e+27\n5.36014\t3.181384023667994e+27\n5.37375\t3.1972066854752595e+27\n5.38735\t3.2125139294987995e+27\n5.40096\t3.224225832990284e+27\n5.41457\t3.230375541412865e+27\n5.42817\t3.231358225878447e+27\n5.44178\t3.229535125538654e+27\n5.45538\t3.227076360743313e+27\n5.46899\t3.224084962616027e+27\n5.48259\t3.219149605757139e+27\n5.4962\t3.2118045090904764e+27\n5.50981\t3.1967941240379976e+27\n5.52341\t3.1632140174916754e+27\n5.53702\t3.0753414025662265e+27\n5.55062\t2.8699447067056625e+27\n5.56423\t2.4855748220089053e+27\n5.57783\t1.9237832451413113e+27\n'
num_au_fcc='11'
vol_au_fcc='1.1443e-28'
button_au_fcc = Button(
    description='Au fcc',
    disabled=False,
    button_style='', # 'success', 'info', 'warning', 'danger' or ''
    tooltip='Au fcc',
    icon='' # (FontAwesome names without the `fa-` prefix)
)

DOS_cu_fcc='-9.624\t0\n-9.614\t0\n-9.604\t0\n-9.594\t0\n-9.584\t0\n-9.574\t0\n-9.564\t0\n-9.554\t0\n-9.544\t0\n-9.534\t0\n-9.524\t0\n-9.514\t0\n-9.504\t0\n-9.494\t0\n-9.484\t0\n-9.474\t0\n-9.464\t0\n-9.454\t0\n-9.444\t0\n-9.434\t0\n-9.424\t0\n-9.414\t0\n-9.404\t0\n-9.394\t0\n-9.384\t0\n-9.374\t0\n-9.364\t0\n-9.354\t0\n-9.344\t0\n-9.334\t0\n-9.324\t0\n-9.314\t0\n-9.304\t0\n-9.294\t0\n-9.284\t3.438983050847458e+24\n-9.274\t4.79322033898305e+25\n-9.264\t1.438135593220339e+26\n-9.254\t2.9110169491525427e+26\n-9.244\t4.8974576271186445e+26\n-9.234\t1.340677966101695e+27\n-9.224\t1.676271186440678e+27\n-9.214\t1.2177966101694916e+27\n-9.204\t1.3372881355932202e+27\n-9.194\t1.4601694915254237e+27\n-9.184\t1.588135593220339e+27\n-9.174\t1.7203389830508473e+27\n-9.164\t1.8567796610169492e+27\n-9.154\t1.998305084745763e+27\n-9.144\t2.209322033898305e+27\n-9.134\t2.3813559322033898e+27\n-9.124\t2.5093220338983054e+27\n-9.114\t2.5923728813559325e+27\n-9.104\t2.6322033898305084e+27\n-9.094\t2.490677966101695e+27\n-9.084\t2.5127118644067796e+27\n-9.074\t2.585593220338983e+27\n-9.064\t2.6635593220338986e+27\n-9.054\t2.7449152542372883e+27\n-9.044\t2.8305084745762714e+27\n-9.034\t2.9194915254237293e+27\n-9.024\t3.0127118644067795e+27\n-9.014\t3.1093220338983055e+27\n-9.004\t3.206779661016949e+27\n-8.994\t3.305084745762712e+27\n-8.984\t3.4033898305084747e+27\n-8.974\t3.5025423728813557e+27\n-8.964\t3.574576271186441e+27\n-8.954\t3.583050847457627e+27\n-8.944\t3.63135593220339e+27\n-8.934\t3.6771186440677967e+27\n-8.924\t3.721186440677966e+27\n-8.914\t3.761864406779661e+27\n-8.904\t3.800847457627119e+27\n-8.894\t3.8364406779661014e+27\n-8.884\t3.8618644067796613e+27\n-8.874\t3.882203389830508e+27\n-8.864\t3.913559322033898e+27\n-8.854\t3.9567796610169494e+27\n-8.844\t4.0110169491525424e+27\n-8.834\t4.0779661016949156e+27\n-8.824\t4.1500000000000003e+27\n-8.814\t4.222881355932203e+27\n-8.804\t4.297457627118644e+27\n-8.794\t4.372033898305085e+27\n-8.784\t4.448305084745763e+27\n-8.774\t4.5245762711864406e+27\n-8.764\t4.6016949152542375e+27\n-8.754\t4.6788135593220343e+27\n-8.744\t4.7440677966101696e+27\n-8.734\t4.7923728813559324e+27\n-8.724\t4.822881355932204e+27\n-8.714\t4.835593220338983e+27\n-8.704\t4.8313559322033896e+27\n-8.694\t4.86271186440678e+27\n-8.684\t4.9084745762711864e+27\n-8.674\t4.948305084745763e+27\n-8.664\t4.98728813559322e+27\n-8.654\t5.027966101694916e+27\n-8.644\t5.067796610169491e+27\n-8.634\t5.109322033898306e+27\n-8.624\t5.15e+27\n-8.614\t5.188983050847458e+27\n-8.604\t5.226271186440679e+27\n-8.594\t5.263559322033899e+27\n-8.584\t5.299152542372882e+27\n-8.574\t5.333050847457627e+27\n-8.564\t5.373728813559322e+27\n-8.554\t5.422881355932204e+27\n-8.544\t5.474576271186441e+27\n-8.534\t5.528813559322035e+27\n-8.524\t5.584745762711865e+27\n-8.514\t5.643220338983051e+27\n-8.504\t5.703389830508475e+27\n-8.494\t5.766101694915255e+27\n-8.484\t5.829661016949154e+27\n-8.474\t5.89406779661017e+27\n-8.464\t5.959322033898305e+27\n-8.454\t6.026271186440679e+27\n-8.444\t6.07457627118644e+27\n-8.434\t6.086440677966102e+27\n-8.424\t6.114406779661018e+27\n-8.414\t6.144067796610169e+27\n-8.404\t6.172033898305085e+27\n-8.394\t6.196610169491526e+27\n-8.384\t6.218644067796611e+27\n-8.374\t6.237288135593221e+27\n-8.364\t6.258474576271186e+27\n-8.354\t6.287288135593222e+27\n-8.344\t6.322033898305085e+27\n-8.334\t6.361864406779661e+27\n-8.324\t6.407627118644068e+27\n-8.314\t6.45e+27\n-8.304\t6.490677966101696e+27\n-8.294\t6.53135593220339e+27\n-8.284\t6.572033898305085e+27\n-8.274\t6.61271186440678e+27\n-8.264\t6.652542372881356e+27\n-8.254\t6.69322033898305e+27\n-8.244\t6.733050847457628e+27\n-8.234\t6.772881355932204e+27\n-8.224\t6.81271186440678e+27\n-8.214\t6.852542372881356e+27\n-8.204\t6.892372881355933e+27\n-8.194\t6.932203389830509e+27\n-8.184\t6.976271186440678e+27\n-8.174\t7.024576271186442e+27\n-8.164\t7.072881355932204e+27\n-8.154\t7.123728813559321e+27\n-8.144\t7.176271186440679e+27\n-8.134\t7.229661016949153e+27\n-8.124\t7.285593220338984e+27\n-8.114\t7.342372881355932e+27\n-8.104\t7.394915254237289e+27\n-8.094\t7.441525423728814e+27\n-8.084\t7.479661016949153e+27\n-8.074\t7.511016949152543e+27\n-8.064\t7.528813559322034e+27\n-8.054\t7.552542372881356e+27\n-8.044\t7.586440677966103e+27\n-8.034\t7.61864406779661e+27\n-8.024\t7.650847457627119e+27\n-8.014\t7.68135593220339e+27\n-8.004\t7.711864406779661e+27\n-7.994\t7.741525423728813e+27\n-7.984\t7.770338983050847e+27\n-7.974\t7.798305084745763e+27\n-7.964\t7.824576271186441e+27\n-7.954\t7.850847457627118e+27\n-7.944\t7.880508474576272e+27\n-7.934\t7.92457627118644e+27\n-7.924\t7.966949152542373e+27\n-7.914\t8.006779661016948e+27\n-7.904\t8.047457627118644e+27\n-7.894\t8.088983050847457e+27\n-7.884\t8.132203389830509e+27\n-7.874\t8.177118644067798e+27\n-7.864\t8.21949152542373e+27\n-7.854\t8.26186440677966e+27\n-7.844\t8.305084745762713e+27\n-7.834\t8.347457627118645e+27\n-7.824\t8.390677966101695e+27\n-7.814\t8.433898305084746e+27\n-7.804\t8.474576271186442e+27\n-7.794\t8.516949152542374e+27\n-7.784\t8.559322033898306e+27\n-7.774\t8.610169491525423e+27\n-7.764\t8.652542372881356e+27\n-7.754\t8.694915254237288e+27\n-7.744\t8.73728813559322e+27\n-7.734\t8.779661016949152e+27\n-7.724\t8.830508474576272e+27\n-7.714\t8.881355932203391e+27\n-7.704\t8.932203389830509e+27\n-7.694\t8.97457627118644e+27\n-7.684\t9.000000000000001e+27\n-7.674\t9.042372881355933e+27\n-7.664\t9.076271186440678e+27\n-7.654\t9.118644067796611e+27\n-7.644\t9.152542372881356e+27\n-7.634\t9.186440677966101e+27\n-7.624\t9.220338983050848e+27\n-7.614\t9.254237288135594e+27\n-7.604\t9.28813559322034e+27\n-7.594\t9.322033898305085e+27\n-7.584\t9.35593220338983e+27\n-7.574\t9.389830508474576e+27\n-7.564\t9.432203389830508e+27\n-7.554\t9.466101694915253e+27\n-7.544\t9.508474576271187e+27\n-7.534\t9.542372881355933e+27\n-7.524\t9.576271186440679e+27\n-7.514\t9.618644067796611e+27\n-7.504\t9.652542372881356e+27\n-7.494\t9.686440677966102e+27\n-7.484\t9.720338983050847e+27\n-7.474\t9.754237288135593e+27\n-7.464\t9.78813559322034e+27\n-7.454\t9.847457627118644e+27\n-7.444\t9.889830508474576e+27\n-7.434\t9.93220338983051e+27\n-7.424\t9.983050847457628e+27\n-7.414\t1.002542372881356e+28\n-7.404\t1.0076271186440678e+28\n-7.394\t1.011864406779661e+28\n-7.384\t1.016949152542373e+28\n-7.374\t1.0220338983050848e+28\n-7.364\t1.026271186440678e+28\n-7.354\t1.0313559322033898e+28\n-7.344\t1.0364406779661017e+28\n-7.334\t1.0415254237288136e+28\n-7.324\t1.0457627118644069e+28\n-7.314\t1.0508474576271187e+28\n-7.304\t1.0559322033898306e+28\n-7.294\t1.0610169491525425e+28\n-7.284\t1.0661016949152542e+28\n-7.274\t1.0703389830508475e+28\n-7.264\t1.0754237288135596e+28\n-7.254\t1.0796610169491526e+28\n-7.244\t1.083898305084746e+28\n-7.234\t1.0881355932203388e+28\n-7.224\t1.090677966101695e+28\n-7.214\t1.0949152542372883e+28\n-7.204\t1.0991525423728816e+28\n-7.194\t1.1033898305084747e+28\n-7.184\t1.107627118644068e+28\n-7.174\t1.111864406779661e+28\n-7.164\t1.1161016949152544e+28\n-7.154\t1.1211864406779662e+28\n-7.144\t1.1254237288135593e+28\n-7.134\t1.1296610169491526e+28\n-7.124\t1.1347457627118643e+28\n-7.114\t1.1389830508474576e+28\n-7.104\t1.143220338983051e+28\n-7.094\t1.1483050847457628e+28\n-7.084\t1.152542372881356e+28\n-7.074\t1.1576271186440677e+28\n-7.064\t1.161864406779661e+28\n-7.054\t1.166949152542373e+28\n-7.044\t1.171186440677966e+28\n-7.034\t1.176271186440678e+28\n-7.024\t1.1813559322033898e+28\n-7.014\t1.185593220338983e+28\n-7.004\t1.1906779661016952e+28\n-6.994\t1.194915254237288e+28\n-6.984\t1.2000000000000001e+28\n-6.974\t1.2042372881355932e+28\n-6.964\t1.209322033898305e+28\n-6.954\t1.2135593220338984e+28\n-6.944\t1.2186440677966103e+28\n-6.934\t1.2245762711864407e+28\n-6.924\t1.2305084745762712e+28\n-6.914\t1.2364406779661018e+28\n-6.904\t1.2423728813559323e+28\n-6.894\t1.2483050847457627e+28\n-6.884\t1.2542372881355932e+28\n-6.874\t1.2601694915254239e+28\n-6.864\t1.2661016949152543e+28\n-6.854\t1.272033898305085e+28\n-6.844\t1.2779661016949152e+28\n-6.834\t1.2838983050847457e+28\n-6.824\t1.2898305084745763e+28\n-6.814\t1.2966101694915254e+28\n-6.804\t1.302542372881356e+28\n-6.794\t1.3084745762711865e+28\n-6.784\t1.3152542372881357e+28\n-6.774\t1.3211864406779662e+28\n-6.764\t1.326271186440678e+28\n-6.754\t1.3313559322033897e+28\n-6.744\t1.3364406779661018e+28\n-6.734\t1.3423728813559323e+28\n-6.724\t1.3474576271186441e+28\n-6.714\t1.3525423728813558e+28\n-6.704\t1.357627118644068e+28\n-6.694\t1.3627118644067798e+28\n-6.684\t1.3686440677966102e+28\n-6.674\t1.374576271186441e+28\n-6.664\t1.3805084745762711e+28\n-6.654\t1.3872881355932206e+28\n-6.644\t1.3932203389830508e+28\n-6.634\t1.4e+28\n-6.624\t1.4067796610169493e+28\n-6.614\t1.4135593220338983e+28\n-6.604\t1.4203389830508476e+28\n-6.594\t1.4271186440677966e+28\n-6.584\t1.4338983050847456e+28\n-6.574\t1.440677966101695e+28\n-6.564\t1.4474576271186441e+28\n-6.554\t1.4542372881355934e+28\n-6.544\t1.4610169491525424e+28\n-6.534\t1.4677966101694914e+28\n-6.524\t1.4745762711864407e+28\n-6.514\t1.48135593220339e+28\n-6.504\t1.4889830508474577e+28\n-6.494\t1.4957627118644067e+28\n-6.484\t1.5025423728813562e+28\n-6.474\t1.5101694915254238e+28\n-6.464\t1.5169491525423728e+28\n-6.454\t1.5245762711864409e+28\n-6.444\t1.5313559322033899e+28\n-6.434\t1.5389830508474577e+28\n-6.424\t1.545762711864407e+28\n-6.414\t1.5533898305084745e+28\n-6.404\t1.5601694915254238e+28\n-6.394\t1.569491525423729e+28\n-6.384\t1.578813559322034e+28\n-6.374\t1.5881355932203391e+28\n-6.364\t1.5966101694915255e+28\n-6.354\t1.6050847457627121e+28\n-6.344\t1.614406779661017e+28\n-6.334\t1.6228813559322035e+28\n-6.324\t1.6322033898305084e+28\n-6.314\t1.6415254237288136e+28\n-6.304\t1.6500000000000002e+28\n-6.294\t1.6593220338983052e+28\n-6.284\t1.669491525423729e+28\n-6.274\t1.678813559322034e+28\n-6.264\t1.6872881355932203e+28\n-6.254\t1.6966101694915255e+28\n-6.244\t1.7059322033898307e+28\n-6.234\t1.7152542372881356e+28\n-6.224\t1.7245762711864406e+28\n-6.214\t1.7338983050847458e+28\n-6.204\t1.743220338983051e+28\n-6.194\t1.7525423728813561e+28\n-6.184\t1.7627118644067797e+28\n-6.174\t1.7720338983050849e+28\n-6.164\t1.7813559322033898e+28\n-6.154\t1.7923728813559322e+28\n-6.144\t1.802542372881356e+28\n-6.134\t1.8135593220338982e+28\n-6.124\t1.8254237288135594e+28\n-6.114\t1.8364406779661017e+28\n-6.104\t1.8483050847457626e+28\n-6.094\t1.8601694915254237e+28\n-6.084\t1.8728813559322034e+28\n-6.074\t1.8847457627118643e+28\n-6.064\t1.897457627118644e+28\n-6.054\t1.9101694915254237e+28\n-6.044\t1.9228813559322034e+28\n-6.034\t1.935593220338983e+28\n-6.024\t1.9483050847457628e+28\n-6.014\t1.9610169491525425e+28\n-6.004\t1.9745762711864407e+28\n-5.994\t1.9872881355932202e+28\n-5.984\t2e+28\n-5.974\t2.0135593220338984e+28\n-5.964\t2.0271186440677965e+28\n-5.954\t2.040677966101695e+28\n-5.944\t2.0542372881355934e+28\n-5.934\t2.0677966101694915e+28\n-5.924\t2.0822033898305088e+28\n-5.914\t2.095762711864407e+28\n-5.904\t2.1101694915254236e+28\n-5.894\t2.127118644067797e+28\n-5.884\t2.144915254237288e+28\n-5.874\t2.161864406779661e+28\n-5.864\t2.178813559322034e+28\n-5.854\t2.1957627118644068e+28\n-5.844\t2.2135593220338984e+28\n-5.834\t2.23135593220339e+28\n-5.824\t2.2491525423728815e+28\n-5.814\t2.267796610169492e+28\n-5.804\t2.285593220338983e+28\n-5.794\t2.304237288135593e+28\n-5.784\t2.323728813559322e+28\n-5.774\t2.3432203389830512e+28\n-5.764\t2.3635593220338983e+28\n-5.754\t2.383898305084746e+28\n-5.744\t2.405084745762712e+28\n-5.734\t2.427118644067797e+28\n-5.724\t2.4483050847457627e+28\n-5.714\t2.4703389830508473e+28\n-5.704\t2.4940677966101696e+28\n-5.694\t2.5186440677966106e+28\n-5.684\t2.54406779661017e+28\n-5.674\t2.5703389830508477e+28\n-5.664\t2.5974576271186443e+28\n-5.654\t2.6245762711864404e+28\n-5.644\t2.6533898305084745e+28\n-5.634\t2.6822033898305086e+28\n-5.624\t2.71271186440678e+28\n-5.614\t2.7432203389830507e+28\n-5.604\t2.774576271186441e+28\n-5.594\t2.805932203389831e+28\n-5.584\t2.8372881355932204e+28\n-5.574\t2.8686440677966105e+28\n-5.564\t2.9008474576271185e+28\n-5.554\t2.9330508474576273e+28\n-5.544\t2.966101694915254e+28\n-5.534\t3e+28\n-5.524\t3.0355932203389832e+28\n-5.514\t3.0805084745762713e+28\n-5.504\t3.1262711864406783e+28\n-5.494\t3.1686440677966104e+28\n-5.484\t3.211864406779661e+28\n-5.474\t3.255084745762712e+28\n-5.464\t3.3000000000000005e+28\n-5.454\t3.344915254237288e+28\n-5.444\t3.391525423728814e+28\n-5.434\t3.438983050847458e+28\n-5.424\t3.4872881355932203e+28\n-5.414\t3.538135593220339e+28\n-5.404\t3.5940677966101693e+28\n-5.394\t3.652542372881356e+28\n-5.384\t3.7135593220338984e+28\n-5.374\t3.7779661016949152e+28\n-5.364\t3.8440677966101696e+28\n-5.354\t3.9135593220338983e+28\n-5.344\t3.984745762711864e+28\n-5.334\t4.06271186440678e+28\n-5.324\t4.165254237288135e+28\n-5.314\t4.3144067796610175e+28\n-5.304\t4.455932203389831e+28\n-5.294\t4.586440677966102e+28\n-5.284\t4.723728813559322e+28\n-5.274\t4.85677966101695e+28\n-5.264\t5.0093220338983045e+28\n-5.254\t5.170338983050847e+28\n-5.244\t5.338135593220339e+28\n-5.234\t5.606779661016949e+28\n-5.224\t6.13135593220339e+28\n-5.214\t6.349152542372881e+28\n-5.204\t6.511016949152543e+28\n-5.194\t6.393220338983051e+28\n-5.184\t6.48135593220339e+28\n-5.174\t6.568644067796611e+28\n-5.164\t6.655932203389831e+28\n-5.154\t6.8067796610169494e+28\n-5.144\t6.7567796610169495e+28\n-5.134\t6.770338983050848e+28\n-5.124\t6.856779661016949e+28\n-5.114\t6.988983050847457e+28\n-5.104\t7.128813559322034e+28\n-5.094\t7.285593220338984e+28\n-5.084\t7.465254237288136e+28\n-5.074\t7.711864406779662e+28\n-5.064\t8.635593220338982e+28\n-5.054\t1.0372881355932203e+29\n-5.044\t1.0177966101694916e+29\n-5.034\t1.0076271186440678e+29\n-5.024\t1.0254237288135593e+29\n-5.014\t1.040677966101695e+29\n-5.004\t1.043220338983051e+29\n-4.994\t1.0347457627118644e+29\n-4.984\t1.0372881355932203e+29\n-4.974\t1.0449152542372882e+29\n-4.964\t1.0508474576271187e+29\n-4.954\t1.0559322033898306e+29\n-4.944\t1.0618644067796609e+29\n-4.934\t1.0686440677966102e+29\n-4.924\t1.0669491525423728e+29\n-4.914\t1.0661016949152543e+29\n-4.904\t1.0686440677966102e+29\n-4.894\t1.0711864406779662e+29\n-4.884\t1.073728813559322e+29\n-4.874\t1.0779661016949153e+29\n-4.864\t1.0830508474576272e+29\n-4.854\t1.0889830508474575e+29\n-4.844\t1.0949152542372882e+29\n-4.834\t1.1008474576271187e+29\n-4.824\t1.1033898305084747e+29\n-4.814\t1.1067796610169492e+29\n-4.804\t1.1110169491525424e+29\n-4.794\t1.116949152542373e+29\n-4.784\t1.1220338983050848e+29\n-4.774\t1.1262711864406779e+29\n-4.764\t1.1330508474576272e+29\n-4.754\t1.1398305084745763e+29\n-4.744\t1.1440677966101696e+29\n-4.734\t1.1516949152542373e+29\n-4.724\t1.1559322033898307e+29\n-4.714\t1.1601694915254238e+29\n-4.704\t1.161864406779661e+29\n-4.694\t1.164406779661017e+29\n-4.684\t1.1661016949152541e+29\n-4.674\t1.1686440677966102e+29\n-4.664\t1.1728813559322034e+29\n-4.654\t1.1779661016949153e+29\n-4.644\t1.1838983050847458e+29\n-4.634\t1.2686440677966103e+29\n-4.624\t1.3449152542372881e+29\n-4.614\t1.3932203389830509e+29\n-4.604\t1.4389830508474576e+29\n-4.594\t1.4813559322033899e+29\n-4.584\t1.533050847457627e+29\n-4.574\t1.5576271186440679e+29\n-4.564\t1.578813559322034e+29\n-4.554\t1.613559322033898e+29\n-4.544\t1.6330508474576272e+29\n-4.534\t1.666949152542373e+29\n-4.524\t1.689830508474576e+29\n-4.514\t1.707627118644068e+29\n-4.504\t1.7228813559322034e+29\n-4.494\t1.745762711864407e+29\n-4.484\t1.7762711864406783e+29\n-4.474\t1.7974576271186442e+29\n-4.464\t1.8211864406779662e+29\n-4.454\t1.8389830508474577e+29\n-4.444\t1.852542372881356e+29\n-4.434\t1.8728813559322034e+29\n-4.424\t1.8923728813559325e+29\n-4.414\t1.914406779661017e+29\n-4.404\t1.933898305084746e+29\n-4.394\t1.957627118644068e+29\n-4.384\t1.9805084745762715e+29\n-4.374\t2.002542372881356e+29\n-4.364\t2.0296610169491527e+29\n-4.354\t2.0677966101694917e+29\n-4.344\t2.109322033898305e+29\n-4.334\t2.1796610169491526e+29\n-4.324\t2.202542372881356e+29\n-4.314\t2.1754237288135597e+29\n-4.304\t2.171186440677966e+29\n-4.294\t2.1635593220338984e+29\n-4.284\t2.1533898305084746e+29\n-4.274\t2.1491525423728813e+29\n-4.264\t2.1338983050847455e+29\n-4.254\t2.1237288135593218e+29\n-4.244\t2.183898305084746e+29\n-4.234\t2.107627118644068e+29\n-4.224\t2.0296610169491527e+29\n-4.214\t1.978813559322034e+29\n-4.204\t1.9389830508474576e+29\n-4.194\t1.8966101694915254e+29\n-4.184\t1.8601694915254236e+29\n-4.174\t1.8347457627118644e+29\n-4.164\t1.7974576271186442e+29\n-4.154\t1.7186440677966102e+29\n-4.144\t1.623728813559322e+29\n-4.134\t1.5194915254237289e+29\n-4.124\t1.4474576271186441e+29\n-4.114\t1.4228813559322035e+29\n-4.104\t1.4398305084745764e+29\n-4.094\t1.4745762711864407e+29\n-4.084\t1.533050847457627e+29\n-4.074\t1.6305084745762712e+29\n-4.064\t1.7338983050847456e+29\n-4.054\t1.772033898305085e+29\n-4.044\t1.8110169491525424e+29\n-4.034\t1.8559322033898304e+29\n-4.024\t1.8949152542372885e+29\n-4.014\t1.936440677966102e+29\n-4.004\t1.9635593220338984e+29\n-3.994\t1.9728813559322034e+29\n-3.984\t1.9796610169491523e+29\n-3.974\t1.9864406779661016e+29\n-3.964\t1.9398305084745764e+29\n-3.954\t1.910169491525424e+29\n-3.944\t1.8974576271186442e+29\n-3.934\t1.8889830508474577e+29\n-3.924\t1.8847457627118647e+29\n-3.914\t1.8703389830508474e+29\n-3.904\t1.848305084745763e+29\n-3.894\t1.8110169491525424e+29\n-3.884\t1.7754237288135595e+29\n-3.874\t1.73728813559322e+29\n-3.864\t1.7042372881355935e+29\n-3.854\t1.676271186440678e+29\n-3.844\t1.6449152542372882e+29\n-3.834\t1.616949152542373e+29\n-3.824\t1.6033898305084744e+29\n-3.814\t1.5966101694915255e+29\n-3.804\t1.590677966101695e+29\n-3.794\t1.5627118644067797e+29\n-3.784\t1.5822033898305084e+29\n-3.774\t1.614406779661017e+29\n-3.764\t1.6567796610169492e+29\n-3.754\t1.722033898305085e+29\n-3.744\t1.8220338983050846e+29\n-3.734\t1.8855932203389832e+29\n-3.724\t1.942372881355932e+29\n-3.714\t2.0288135593220342e+29\n-3.704\t2.109322033898305e+29\n-3.694\t2.0042372881355934e+29\n-3.684\t2.0372881355932204e+29\n-3.674\t2.092372881355932e+29\n-3.664\t2.1940677966101696e+29\n-3.654\t2.244915254237288e+29\n-3.644\t2.276271186440678e+29\n-3.634\t2.3169491525423728e+29\n-3.624\t2.3542372881355933e+29\n-3.614\t2.3966101694915253e+29\n-3.604\t2.4457627118644068e+29\n-3.594\t2.5101694915254238e+29\n-3.584\t2.5923728813559323e+29\n-3.574\t2.5584745762711866e+29\n-3.564\t2.5754237288135596e+29\n-3.554\t2.590677966101695e+29\n-3.544\t2.605932203389831e+29\n-3.534\t2.6305084745762713e+29\n-3.524\t2.6669491525423727e+29\n-3.514\t2.676271186440678e+29\n-3.504\t2.6923728813559323e+29\n-3.494\t2.7059322033898305e+29\n-3.484\t2.7398305084745766e+29\n-3.474\t2.7271186440677968e+29\n-3.464\t2.6822033898305085e+29\n-3.454\t2.6347457627118646e+29\n-3.444\t2.6203389830508475e+29\n-3.434\t2.6177966101694915e+29\n-3.424\t2.629661016949153e+29\n-3.414\t2.6347457627118646e+29\n-3.404\t2.643220338983051e+29\n-3.394\t2.6635593220338982e+29\n-3.384\t2.6898305084745762e+29\n-3.374\t2.7271186440677968e+29\n-3.364\t2.759322033898305e+29\n-3.354\t2.7822033898305085e+29\n-3.344\t2.819491525423729e+29\n-3.334\t2.8661016949152546e+29\n-3.324\t2.948305084745763e+29\n-3.314\t3.0415254237288137e+29\n-3.304\t3.1483050847457626e+29\n-3.294\t3.245762711864407e+29\n-3.284\t3.4211864406779665e+29\n-3.274\t3.3881355932203395e+29\n-3.264\t3.2703389830508474e+29\n-3.254\t3.285593220338983e+29\n-3.244\t3.495762711864407e+29\n-3.234\t3.4423728813559324e+29\n-3.224\t3.499152542372881e+29\n-3.214\t3.455932203389831e+29\n-3.204\t3.438983050847458e+29\n-3.194\t3.4898305084745764e+29\n-3.184\t3.5169491525423735e+29\n-3.174\t3.617796610169492e+29\n-3.164\t3.6949152542372884e+29\n-3.154\t3.787288135593221e+29\n-3.144\t3.639830508474576e+29\n-3.134\t3.572881355932204e+29\n-3.124\t3.548305084745763e+29\n-3.114\t3.617796610169492e+29\n-3.104\t3.704237288135594e+29\n-3.094\t3.839830508474576e+29\n-3.084\t4.024576271186441e+29\n-3.074\t4.539830508474577e+29\n-3.064\t5.150847457627119e+29\n-3.054\t4.844915254237288e+29\n-3.044\t3.709322033898305e+29\n-3.034\t3.272033898305085e+29\n-3.024\t2.9279661016949155e+29\n-3.014\t2.7389830508474578e+29\n-3.004\t2.6533898305084745e+29\n-2.994\t2.6305084745762713e+29\n-2.984\t2.578813559322034e+29\n-2.974\t2.5305084745762713e+29\n-2.964\t2.5245762711864408e+29\n-2.954\t2.578813559322034e+29\n-2.944\t2.7110169491525422e+29\n-2.934\t2.755084745762712e+29\n-2.924\t2.7440677966101695e+29\n-2.914\t2.732203389830509e+29\n-2.904\t2.7177966101694915e+29\n-2.894\t2.6923728813559323e+29\n-2.884\t2.636440677966102e+29\n-2.874\t2.5728813559322036e+29\n-2.864\t2.5177966101694915e+29\n-2.854\t2.4508474576271185e+29\n-2.844\t2.385593220338983e+29\n-2.834\t2.328813559322034e+29\n-2.824\t2.288135593220339e+29\n-2.814\t2.2584745762711866e+29\n-2.804\t2.243220338983051e+29\n-2.794\t2.2296610169491526e+29\n-2.784\t2.2305084745762714e+29\n-2.774\t2.205084745762712e+29\n-2.764\t2.194915254237288e+29\n-2.754\t2.207627118644068e+29\n-2.744\t2.202542372881356e+29\n-2.734\t2.183898305084746e+29\n-2.724\t2.1550847457627122e+29\n-2.714\t2.128813559322034e+29\n-2.704\t2.1237288135593218e+29\n-2.694\t2.1135593220338987e+29\n-2.684\t2.2084745762711863e+29\n-2.674\t2.166949152542373e+29\n-2.664\t2.210169491525424e+29\n-2.654\t2.2703389830508473e+29\n-2.644\t2.3169491525423728e+29\n-2.634\t2.3754237288135593e+29\n-2.624\t2.5483050847457628e+29\n-2.614\t2.7754237288135592e+29\n-2.604\t2.9186440677966102e+29\n-2.594\t2.9661016949152542e+29\n-2.584\t3.010169491525424e+29\n-2.574\t3.0296610169491527e+29\n-2.564\t3.0389830508474577e+29\n-2.554\t3.0516949152542375e+29\n-2.544\t3.0415254237288137e+29\n-2.534\t3.0508474576271187e+29\n-2.524\t3.0830508474576272e+29\n-2.514\t3.1177966101694914e+29\n-2.504\t3.1423728813559325e+29\n-2.494\t3.1500000000000002e+29\n-2.484\t3.16271186440678e+29\n-2.474\t3.1940677966101694e+29\n-2.464\t3.1355932203389832e+29\n-2.454\t3.1661016949152545e+29\n-2.444\t3.188135593220339e+29\n-2.434\t3.23135593220339e+29\n-2.424\t3.482203389830508e+29\n-2.414\t3.26271186440678e+29\n-2.404\t3.007627118644068e+29\n-2.394\t3.0686440677966102e+29\n-2.384\t3.238983050847458e+29\n-2.374\t3.0754237288135595e+29\n-2.364\t3.014406779661017e+29\n-2.354\t2.9415254237288138e+29\n-2.344\t2.914406779661017e+29\n-2.334\t2.8728813559322035e+29\n-2.324\t2.8449152542372883e+29\n-2.314\t2.8135593220338982e+29\n-2.304\t2.7720338983050847e+29\n-2.294\t2.7423728813559326e+29\n-2.284\t2.7152542372881358e+29\n-2.274\t2.6898305084745762e+29\n-2.264\t2.6847457627118645e+29\n-2.254\t2.6474576271186443e+29\n-2.244\t2.6322033898305085e+29\n-2.234\t2.6228813559322036e+29\n-2.224\t2.6161016949152546e+29\n-2.214\t2.6245762711864408e+29\n-2.204\t2.6186440677966103e+29\n-2.194\t2.619491525423729e+29\n-2.184\t2.6127118644067798e+29\n-2.174\t2.614406779661017e+29\n-2.164\t2.619491525423729e+29\n-2.154\t2.6415254237288135e+29\n-2.144\t2.643220338983051e+29\n-2.134\t2.657627118644068e+29\n-2.124\t2.6881355932203394e+29\n-2.114\t2.691525423728814e+29\n-2.104\t2.702542372881356e+29\n-2.094\t2.7177966101694915e+29\n-2.084\t2.740677966101695e+29\n-2.074\t2.761864406779661e+29\n-2.064\t2.7635593220338986e+29\n-2.054\t2.8059322033898305e+29\n-2.044\t2.8601694915254237e+29\n-2.034\t2.9254237288135595e+29\n-2.024\t2.955084745762712e+29\n-2.014\t3.0033898305084747e+29\n-2.004\t3.072033898305085e+29\n-1.994\t3.116949152542373e+29\n-1.984\t3.174576271186441e+29\n-1.974\t3.2279661016949155e+29\n-1.964\t3.2635593220338984e+29\n-1.954\t3.317796610169491e+29\n-1.944\t3.408474576271187e+29\n-1.934\t3.507627118644068e+29\n-1.924\t3.620338983050848e+29\n-1.914\t3.88728813559322e+29\n-1.904\t3.990677966101695e+29\n-1.894\t4.243220338983051e+29\n-1.884\t4.567796610169492e+29\n-1.874\t4.997457627118645e+29\n-1.864\t5.63135593220339e+29\n-1.854\t5.757627118644068e+29\n-1.844\t5.816949152542373e+29\n-1.834\t5.9144067796610176e+29\n-1.824\t5.772881355932204e+29\n-1.814\t5.138135593220339e+29\n-1.804\t4.426271186440678e+29\n-1.794\t4.032203389830509e+29\n-1.784\t3.704237288135594e+29\n-1.774\t3.415254237288136e+29\n-1.764\t3.1101694915254236e+29\n-1.754\t2.852542372881356e+29\n-1.744\t2.5915254237288135e+29\n-1.734\t2.438983050847458e+29\n-1.724\t2.2627118644067795e+29\n-1.714\t2.1635593220338984e+29\n-1.704\t2.098305084745763e+29\n-1.694\t2.05e+29\n-1.684\t1.8322033898305084e+29\n-1.674\t1.8415254237288137e+29\n-1.664\t3.540677966101695e+28\n-1.654\t3.5228813559322034e+28\n-1.644\t3.5050847457627123e+28\n-1.634\t3.488983050847458e+28\n-1.624\t3.4737288135593222e+28\n-1.614\t3.4593220338983054e+28\n-1.604\t3.444915254237288e+28\n-1.594\t3.433050847457627e+28\n-1.584\t3.4228813559322034e+28\n-1.574\t3.414406779661017e+28\n-1.564\t3.405084745762712e+28\n-1.554\t3.3966101694915253e+28\n-1.544\t3.388135593220339e+28\n-1.534\t3.3796610169491525e+28\n-1.524\t3.3703389830508475e+28\n-1.514\t3.3610169491525426e+28\n-1.504\t3.3508474576271184e+28\n-1.494\t3.343220338983051e+28\n-1.484\t3.335593220338983e+28\n-1.474\t3.32542372881356e+28\n-1.464\t3.31271186440678e+28\n-1.454\t3.298305084745763e+28\n-1.444\t3.2805084745762713e+28\n-1.434\t3.2584745762711866e+28\n-1.424\t3.2313559322033897e+28\n-1.414\t3.190677966101695e+28\n-1.404\t3.143220338983051e+28\n-1.394\t3.114406779661017e+28\n-1.384\t3.0923728813559323e+28\n-1.374\t3.0771186440677966e+28\n-1.364\t3.064406779661017e+28\n-1.354\t3.052542372881356e+28\n-1.344\t3.0423728813559323e+28\n-1.334\t3.0338983050847457e+28\n-1.324\t3.026271186440678e+28\n-1.314\t3.0186440677966105e+28\n-1.304\t3.01271186440678e+28\n-1.294\t3.0059322033898308e+28\n-1.284\t3e+28\n-1.274\t2.9940677966101694e+28\n-1.264\t2.988983050847458e+28\n-1.254\t2.9847457627118645e+28\n-1.244\t2.979661016949153e+28\n-1.234\t2.973728813559322e+28\n-1.224\t2.9686440677966105e+28\n-1.214\t2.964406779661017e+28\n-1.204\t2.959322033898305e+28\n-1.194\t2.9542372881355936e+28\n-1.184\t2.9491525423728813e+28\n-1.174\t2.943220338983051e+28\n-1.164\t2.9372881355932204e+28\n-1.154\t2.9313559322033897e+28\n-1.144\t2.9245762711864407e+28\n-1.134\t2.9177966101694917e+28\n-1.124\t2.9110169491525427e+28\n-1.114\t2.903389830508475e+28\n-1.104\t2.8949152542372882e+28\n-1.094\t2.8847457627118645e+28\n-1.084\t2.8728813559322036e+28\n-1.074\t2.857627118644068e+28\n-1.064\t2.8355932203389833e+28\n-1.054\t2.822033898305085e+28\n-1.044\t2.828813559322034e+28\n-1.034\t2.8245762711864407e+28\n-1.024\t2.8228813559322036e+28\n-1.014\t2.821186440677966e+28\n-1.004\t2.819491525423729e+28\n-0.994\t2.8177966101694917e+28\n-0.984\t2.816101694915254e+28\n-0.974\t2.815254237288136e+28\n-0.964\t2.8135593220338986e+28\n-0.954\t2.811864406779661e+28\n-0.944\t2.810169491525424e+28\n-0.934\t2.807627118644068e+28\n-0.924\t2.805084745762712e+28\n-0.914\t2.8033898305084744e+28\n-0.904\t2.802542372881356e+28\n-0.894\t2.8e+28\n-0.884\t2.7983050847457626e+28\n-0.874\t2.796610169491526e+28\n-0.864\t2.795762711864407e+28\n-0.854\t2.7940677966101695e+28\n-0.844\t2.7923728813559323e+28\n-0.834\t2.791525423728814e+28\n-0.824\t2.7906779661016947e+28\n-0.814\t2.7889830508474576e+28\n-0.804\t2.7881355932203392e+28\n-0.794\t2.7864406779661017e+28\n-0.784\t2.7847457627118645e+28\n-0.774\t2.783898305084746e+28\n-0.764\t2.7822033898305086e+28\n-0.754\t2.763559322033898e+28\n-0.744\t2.7610169491525423e+28\n-0.734\t2.757627118644068e+28\n-0.724\t2.7542372881355932e+28\n-0.714\t2.75e+28\n-0.704\t2.745762711864407e+28\n-0.694\t2.7415254237288136e+28\n-0.684\t2.7372881355932205e+28\n-0.674\t2.7322033898305086e+28\n-0.664\t2.7271186440677967e+28\n-0.654\t2.7203389830508477e+28\n-0.644\t2.71271186440678e+28\n-0.634\t2.7042372881355933e+28\n-0.624\t2.6898305084745764e+28\n-0.614\t2.678813559322034e+28\n-0.604\t2.6703389830508473e+28\n-0.594\t2.6627118644067794e+28\n-0.584\t2.657627118644068e+28\n-0.574\t2.6516949152542373e+28\n-0.564\t2.646610169491526e+28\n-0.554\t2.6415254237288136e+28\n-0.544\t2.63728813559322e+28\n-0.534\t2.633050847457627e+28\n-0.524\t2.628813559322034e+28\n-0.514\t2.6254237288135596e+28\n-0.504\t2.6211864406779665e+28\n-0.494\t2.6177966101694918e+28\n-0.484\t2.652542372881356e+28\n-0.474\t2.63135593220339e+28\n-0.464\t2.6177966101694918e+28\n-0.454\t2.6110169491525423e+28\n-0.444\t2.6076271186440676e+28\n-0.434\t2.6033898305084745e+28\n-0.424\t2.6e+28\n-0.414\t2.5966101694915255e+28\n-0.404\t2.5940677966101695e+28\n-0.394\t2.5906779661016952e+28\n-0.384\t2.5881355932203393e+28\n-0.374\t2.585593220338983e+28\n-0.364\t2.5830508474576274e+28\n-0.354\t2.580508474576271e+28\n-0.344\t2.5779661016949155e+28\n-0.334\t2.576271186440678e+28\n-0.324\t2.5737288135593225e+28\n-0.314\t2.572033898305085e+28\n-0.304\t2.5703389830508477e+28\n-0.294\t2.56864406779661e+28\n-0.284\t2.5661016949152546e+28\n-0.274\t2.56271186440678e+28\n-0.264\t2.5601694915254235e+28\n-0.254\t2.5584745762711864e+28\n-0.244\t2.5567796610169492e+28\n-0.234\t2.5542372881355933e+28\n-0.224\t2.552542372881356e+28\n-0.214\t2.5508474576271186e+28\n-0.204\t2.5491525423728814e+28\n-0.194\t2.547457627118644e+28\n-0.184\t2.5457627118644067e+28\n-0.174\t2.54406779661017e+28\n-0.164\t2.5432203389830507e+28\n-0.154\t2.5415254237288136e+28\n-0.144\t2.5398305084745765e+28\n-0.134\t2.5372881355932205e+28\n-0.124\t2.5355932203389834e+28\n-0.114\t2.533050847457627e+28\n-0.104\t2.530508474576271e+28\n-0.094\t2.5279661016949156e+28\n-0.084\t2.5228813559322037e+28\n-0.074\t2.516949152542373e+28\n-0.064\t2.5067796610169492e+28\n-0.054\t2.4991525423728814e+28\n-0.044\t2.4940677966101696e+28\n-0.034\t2.4881355932203393e+28\n-0.024\t2.483050847457627e+28\n-0.014\t2.477966101694915e+28\n-0.004\t2.473728813559322e+28\n0.006\t2.4703389830508473e+28\n0.016\t2.4661016949152542e+28\n0.026\t2.461864406779661e+28\n0.036\t2.458474576271187e+28\n0.046\t2.4542372881355933e+28\n0.056\t2.4500000000000002e+28\n0.066\t2.445762711864407e+28\n0.076\t2.4415254237288136e+28\n0.086\t2.4372881355932205e+28\n0.096\t2.433898305084746e+28\n0.106\t2.4296610169491527e+28\n0.116\t2.426271186440678e+28\n0.126\t2.4228813559322033e+28\n0.136\t2.4203389830508478e+28\n0.146\t2.416949152542373e+28\n0.156\t2.414406779661017e+28\n0.166\t2.4110169491525424e+28\n0.176\t2.4084745762711864e+28\n0.186\t2.4059322033898305e+28\n0.196\t2.4042372881355933e+28\n0.206\t2.4016949152542374e+28\n0.216\t2.4008474576271186e+28\n0.226\t2.3991525423728815e+28\n0.236\t2.397457627118644e+28\n0.246\t2.3957627118644067e+28\n0.256\t2.394067796610169e+28\n0.266\t2.393220338983051e+28\n0.276\t2.3915254237288136e+28\n0.286\t2.389830508474576e+28\n0.296\t2.388135593220339e+28\n0.306\t2.3864406779661018e+28\n0.316\t2.384745762711864e+28\n0.326\t2.383050847457627e+28\n0.336\t2.3813559322033903e+28\n0.346\t2.378813559322034e+28\n0.356\t2.377118644067797e+28\n0.366\t2.375423728813559e+28\n0.376\t2.373728813559322e+28\n0.386\t2.371186440677966e+28\n0.396\t2.369491525423729e+28\n0.406\t2.3677966101694914e+28\n0.416\t2.3661016949152543e+28\n0.426\t2.365254237288136e+28\n0.436\t2.364406779661017e+28\n0.446\t2.3627118644067795e+28\n0.456\t2.361864406779661e+28\n0.466\t2.360169491525424e+28\n0.476\t2.3584745762711864e+28\n0.486\t2.3567796610169493e+28\n0.496\t2.3550847457627117e+28\n0.506\t2.3533898305084746e+28\n0.516\t2.3516949152542374e+28\n0.526\t2.35e+28\n0.536\t2.348305084745763e+28\n0.546\t2.3466101694915255e+28\n0.556\t2.3449152542372884e+28\n0.566\t2.3432203389830512e+28\n0.576\t2.3415254237288137e+28\n0.586\t2.3389830508474577e+28\n0.596\t2.3364406779661018e+28\n0.606\t2.333050847457627e+28\n0.616\t2.326271186440678e+28\n0.626\t2.317796610169492e+28\n0.636\t2.3127118644067795e+28\n0.646\t2.3076271186440677e+28\n0.656\t2.3033898305084746e+28\n0.666\t2.2991525423728815e+28\n0.676\t2.2957627118644068e+28\n0.686\t2.2915254237288132e+28\n0.696\t2.2881355932203394e+28\n0.706\t2.285593220338983e+28\n0.716\t2.2822033898305083e+28\n0.726\t2.2788135593220335e+28\n0.736\t2.276271186440678e+28\n0.746\t2.273728813559322e+28\n0.756\t2.271186440677966e+28\n0.766\t2.26864406779661e+28\n0.776\t2.2661016949152547e+28\n0.786\t2.2635593220338983e+28\n0.796\t2.261864406779661e+28\n0.806\t2.2593220338983053e+28\n0.816\t2.257627118644068e+28\n0.826\t2.2559322033898305e+28\n0.836\t2.2542372881355934e+28\n0.846\t2.252542372881356e+28\n0.856\t2.2508474576271186e+28\n0.866\t2.2491525423728815e+28\n0.876\t2.2483050847457627e+28\n0.886\t2.2466101694915256e+28\n0.896\t2.2449152542372884e+28\n0.906\t2.243220338983051e+28\n0.916\t2.2415254237288137e+28\n0.926\t2.239830508474576e+28\n0.936\t2.238135593220339e+28\n0.946\t2.236440677966102e+28\n0.956\t2.234745762711864e+28\n0.966\t2.2330508474576275e+28\n0.976\t2.23135593220339e+28\n0.986\t2.2296610169491528e+28\n0.996\t2.2279661016949156e+28\n1.006\t2.2254237288135593e+28\n1.016\t2.223728813559322e+28\n1.026\t2.2220338983050845e+28\n1.036\t2.219491525423729e+28\n1.046\t2.2177966101694914e+28\n1.056\t2.2161016949152543e+28\n1.066\t2.2135593220338984e+28\n1.076\t2.211864406779661e+28\n1.086\t2.2093220338983053e+28\n1.096\t2.2067796610169493e+28\n1.106\t2.2050847457627117e+28\n1.116\t2.2025423728813562e+28\n1.126\t2.201694915254237e+28\n1.136\t2.2033898305084746e+28\n1.146\t2.207627118644068e+28\n1.156\t2.2050847457627117e+28\n1.166\t2.2033898305084746e+28\n1.176\t2.201694915254237e+28\n1.186\t2.2008474576271187e+28\n1.196\t2.1991525423728815e+28\n1.206\t2.197457627118644e+28\n1.216\t2.1966101694915256e+28\n1.226\t2.1949152542372884e+28\n1.236\t2.1940677966101696e+28\n1.246\t2.193220338983051e+28\n1.256\t2.192372881355932e+28\n1.266\t2.1915254237288137e+28\n1.276\t2.190677966101695e+28\n1.286\t2.190677966101695e+28\n1.296\t2.190677966101695e+28\n1.306\t2.190677966101695e+28\n1.316\t2.190677966101695e+28\n1.326\t2.190677966101695e+28\n1.336\t2.1915254237288137e+28\n1.346\t2.192372881355932e+28\n1.356\t2.193220338983051e+28\n1.366\t2.1940677966101696e+28\n1.376\t2.1949152542372884e+28\n1.386\t2.1966101694915256e+28\n1.396\t2.197457627118644e+28\n1.406\t2.197457627118644e+28\n1.416\t2.1966101694915256e+28\n1.426\t2.1940677966101696e+28\n1.436\t2.1915254237288137e+28\n1.446\t2.1898305084745765e+28\n1.456\t2.1889830508474573e+28\n1.466\t2.1889830508474573e+28\n1.476\t2.1889830508474573e+28\n1.486\t2.1898305084745765e+28\n1.496\t2.190677966101695e+28\n1.506\t2.192372881355932e+28\n1.516\t2.1940677966101696e+28\n1.526\t2.1957627118644068e+28\n1.536\t2.198305084745763e+28\n1.546\t2.2025423728813562e+28\n1.556\t2.2084745762711865e+28\n1.566\t2.2161016949152543e+28\n1.576\t2.2254237288135593e+28\n1.586\t2.236440677966102e+28\n1.596\t2.2500000000000003e+28\n1.606\t2.2593220338983053e+28\n1.616\t2.2389830508474577e+28\n1.626\t2.1940677966101696e+28\n1.636\t2.1889830508474573e+28\n1.646\t2.183898305084746e+28\n1.656\t2.177966101694915e+28\n1.666\t2.1728813559322038e+28\n1.676\t2.1669491525423727e+28\n1.686\t2.1610169491525424e+28\n1.696\t2.1559322033898305e+28\n1.706\t2.15e+28\n1.716\t2.144915254237288e+28\n1.726\t2.1398305084745766e+28\n1.736\t2.133898305084746e+28\n1.746\t2.128813559322034e+28\n1.756\t2.123728813559322e+28\n1.766\t2.1203389830508474e+28\n1.776\t2.1186440677966103e+28\n1.786\t2.1161016949152543e+28\n1.796\t2.1135593220338984e+28\n1.806\t2.1110169491525424e+28\n1.816\t2.1076271186440677e+28\n1.826\t2.1033898305084746e+28\n1.836\t2.1e+28\n1.846\t2.0966101694915256e+28\n1.856\t2.093220338983051e+28\n1.866\t2.0898305084745766e+28\n1.876\t2.086440677966102e+28\n1.886\t2.083898305084746e+28\n1.896\t2.080508474576271e+28\n1.906\t2.077118644067797e+28\n1.916\t2.073728813559322e+28\n1.926\t2.0703389830508474e+28\n1.936\t2.066949152542373e+28\n1.946\t2.0635593220338984e+28\n1.956\t2.0593220338983053e+28\n1.966\t2.0559322033898306e+28\n1.976\t2.0516949152542375e+28\n1.986\t2.049152542372881e+28\n1.996\t2.045762711864407e+28\n2.006\t2.043220338983051e+28\n2.016\t2.040677966101695e+28\n2.026\t2.038135593220339e+28\n2.036\t2.036440677966102e+28\n2.046\t2.0347457627118647e+28\n2.056\t2.033050847457627e+28\n2.066\t2.023728813559322e+28\n2.076\t2.0161016949152543e+28\n2.086\t2.0118644067796613e+28\n2.096\t2.0084745762711865e+28\n2.106\t2.004237288135593e+28\n2.116\t2e+28\n2.126\t1.995762711864407e+28\n2.136\t1.9915254237288133e+28\n2.146\t1.9872881355932202e+28\n2.156\t1.983050847457627e+28\n2.166\t1.978813559322034e+28\n2.176\t1.9737288135593222e+28\n2.186\t1.9694915254237289e+28\n2.196\t1.964406779661017e+28\n2.206\t1.9610169491525425e+28\n2.216\t1.9635593220338982e+28\n2.226\t1.9627118644067796e+28\n2.236\t1.9593220338983051e+28\n2.246\t1.9542372881355932e+28\n2.256\t1.9474576271186442e+28\n2.266\t1.9398305084745762e+28\n2.276\t1.9347457627118645e+28\n2.286\t1.9296610169491526e+28\n2.296\t1.9245762711864408e+28\n2.306\t1.9203389830508475e+28\n2.316\t1.9161016949152544e+28\n2.326\t1.9152542372881358e+28\n2.336\t1.9101694915254237e+28\n2.346\t1.9050847457627118e+28\n2.356\t1.9000000000000002e+28\n2.366\t1.894915254237288e+28\n2.376\t1.8898305084745764e+28\n2.386\t1.8847457627118643e+28\n2.396\t1.878813559322034e+28\n2.406\t1.873728813559322e+28\n2.416\t1.8677966101694917e+28\n2.426\t1.8627118644067797e+28\n2.436\t1.8567796610169492e+28\n2.446\t1.8508474576271187e+28\n2.456\t1.8457627118644069e+28\n2.466\t1.8398305084745762e+28\n2.476\t1.833898305084746e+28\n2.486\t1.8279661016949153e+28\n2.496\t1.8220338983050848e+28\n2.506\t1.816949152542373e+28\n2.516\t1.8110169491525425e+28\n2.526\t1.8050847457627118e+28\n2.536\t1.7991525423728814e+28\n2.546\t1.7940677966101695e+28\n2.556\t1.788135593220339e+28\n2.566\t1.7830508474576272e+28\n2.576\t1.7788135593220339e+28\n2.586\t1.7745762711864408e+28\n2.596\t1.771186440677966e+28\n2.606\t1.7677966101694916e+28\n2.616\t1.7652542372881358e+28\n2.626\t1.761864406779661e+28\n2.636\t1.7593220338983052e+28\n2.646\t1.7567796610169492e+28\n2.656\t1.7542372881355933e+28\n2.666\t1.7516949152542373e+28\n2.676\t1.7483050847457628e+28\n2.686\t1.7457627118644067e+28\n2.696\t1.743220338983051e+28\n2.706\t1.740677966101695e+28\n2.716\t1.7364406779661017e+28\n2.726\t1.73135593220339e+28\n2.736\t1.7254237288135594e+28\n2.746\t1.7203389830508477e+28\n2.756\t1.714406779661017e+28\n2.766\t1.709322033898305e+28\n2.776\t1.7033898305084747e+28\n2.786\t1.6974576271186443e+28\n2.796\t1.690677966101695e+28\n2.806\t1.6855932203389832e+28\n2.816\t1.6813559322033898e+28\n2.826\t1.6779661016949153e+28\n2.836\t1.6754237288135592e+28\n2.846\t1.669491525423729e+28\n2.856\t1.6644067796610168e+28\n2.866\t1.6584745762711866e+28\n2.876\t1.6533898305084745e+28\n2.886\t1.647457627118644e+28\n2.896\t1.6423728813559322e+28\n2.906\t1.6364406779661017e+28\n2.916\t1.630508474576271e+28\n2.926\t1.6245762711864408e+28\n2.936\t1.6194915254237287e+28\n2.946\t1.6135593220338985e+28\n2.956\t1.6076271186440678e+28\n2.966\t1.602542372881356e+28\n2.976\t1.5966101694915255e+28\n2.986\t1.5915254237288136e+28\n2.996\t1.585593220338983e+28\n3.006\t1.5805084745762713e+28\n3.016\t1.5754237288135594e+28\n3.026\t1.569491525423729e+28\n3.036\t1.5644067796610169e+28\n3.046\t1.5593220338983052e+28\n3.056\t1.5542372881355933e+28\n3.066\t1.5491525423728812e+28\n3.076\t1.5440677966101696e+28\n3.086\t1.5389830508474577e+28\n3.096\t1.5347457627118646e+28\n3.106\t1.5313559322033899e+28\n3.116\t1.5271186440677966e+28\n3.126\t1.523728813559322e+28\n3.136\t1.5203389830508476e+28\n3.146\t1.5161016949152543e+28\n3.156\t1.5127118644067797e+28\n3.166\t1.5093220338983052e+28\n3.176\t1.5059322033898305e+28\n3.186\t1.5033898305084746e+28\n3.196\t1.5033898305084746e+28\n3.206\t1.5033898305084746e+28\n3.216\t1.4991525423728815e+28\n3.226\t1.4949152542372882e+28\n3.236\t1.4898305084745765e+28\n3.246\t1.4838983050847458e+28\n3.256\t1.4779661016949154e+28\n3.266\t1.4711864406779661e+28\n3.276\t1.4644067796610171e+28\n3.286\t1.4576271186440677e+28\n3.296\t1.4516949152542374e+28\n3.306\t1.4466101694915253e+28\n3.316\t1.4423728813559322e+28\n3.326\t1.4389830508474577e+28\n3.336\t1.4364406779661018e+28\n3.346\t1.4322033898305087e+28\n3.356\t1.428813559322034e+28\n3.366\t1.4245762711864407e+28\n3.376\t1.419491525423729e+28\n3.386\t1.4152542372881357e+28\n3.396\t1.4110169491525424e+28\n3.406\t1.4067796610169493e+28\n3.416\t1.4033898305084746e+28\n3.426\t1.3991525423728813e+28\n3.436\t1.3949152542372882e+28\n3.446\t1.3898305084745763e+28\n3.456\t1.3855932203389832e+28\n3.466\t1.3805084745762711e+28\n3.476\t1.3754237288135595e+28\n3.486\t1.3694915254237288e+28\n3.496\t1.3618644067796612e+28\n3.506\t1.3542372881355932e+28\n3.516\t1.3466101694915256e+28\n3.526\t1.3398305084745763e+28\n3.536\t1.333050847457627e+28\n3.546\t1.3254237288135595e+28\n3.556\t1.31864406779661e+28\n3.566\t1.3110169491525424e+28\n3.576\t1.305084745762712e+28\n3.586\t1.2983050847457627e+28\n3.596\t1.2915254237288137e+28\n3.606\t1.2847457627118645e+28\n3.616\t1.2779661016949152e+28\n3.626\t1.2711864406779662e+28\n3.636\t1.2652542372881355e+28\n3.646\t1.2584745762711865e+28\n3.656\t1.2525423728813558e+28\n3.666\t1.2457627118644068e+28\n3.676\t1.2398305084745764e+28\n3.686\t1.233898305084746e+28\n3.696\t1.2279661016949152e+28'
num_cu_fcc='11'
vol_cu_fcc='1.1800e-29'
button_cu_fcc = Button(
    description='Cu fcc',
    disabled=False,
    button_style='', # 'success', 'info', 'warning', 'danger' or ''
    tooltip='Cu fcc',
    icon='' # (FontAwesome names without the `fa-` prefix)
)

DOS_na_bcc='-3.5\t0\n-3.49\t0\n-3.48\t0\n-3.47\t0\n-3.46\t0\n-3.45\t0\n-3.44\t0\n-3.43\t0\n-3.42\t0\n-3.41\t0\n-3.4\t0\n-3.39\t0\n-3.38\t0\n-3.37\t0\n-3.36\t0\n-3.35\t0\n-3.34\t0\n-3.33\t0\n-3.32\t0\n-3.31\t0\n-3.3\t0\n-3.29\t0\n-3.28\t0\n-3.27\t0\n-3.26\t0\n-3.25\t0\n-3.24\t0\n-3.23\t4.0952380952380954e+23\n-3.22\t2.833333333333333e+25\n-3.21\t1.0013227513227514e+26\n-3.2\t2.1582010582010583e+26\n-3.19\t8.296296296296296e+26\n-3.18\t1.0563492063492064e+27\n-3.17\t1.2198412698412699e+27\n-3.16\t1.3195767195767195e+27\n-3.15\t1.3616402116402117e+27\n-3.14\t1.4494708994708995e+27\n-3.13\t1.6219576719576721e+27\n-3.12\t1.8796296296296298e+27\n-3.11\t2.115079365079365e+27\n-3.1\t2.1843915343915347e+27\n-3.09\t2.2648148148148152e+27\n-3.08\t2.356613756613757e+27\n-3.07\t2.453968253968254e+27\n-3.06\t2.5087301587301586e+27\n-3.05\t2.510582010582011e+27\n-3.04\t2.4595238095238095e+27\n-3.03\t2.4701058201058202e+27\n-3.02\t2.6007936507936506e+27\n-3.01\t2.7566137566137567e+27\n-3\t2.9391534391534397e+27\n-2.99\t3.1349206349206347e+27\n-2.98\t3.288359788359788e+27\n-2.97\t3.391534391534392e+27\n-2.96\t3.444444444444445e+27\n-2.95\t3.2407407407407407e+27\n-2.94\t3.3439153439153445e+27\n-2.93\t3.4259259259259264e+27\n-2.92\t3.484126984126985e+27\n-2.91\t3.529100529100529e+27\n-2.9\t3.5740740740740745e+27\n-2.89\t3.6190476190476193e+27\n-2.88\t3.666666666666667e+27\n-2.87\t3.6640211640211646e+27\n-2.86\t3.6851851851851854e+27\n-2.85\t3.740740740740741e+27\n-2.84\t3.830687830687831e+27\n-2.83\t3.947089947089947e+27\n-2.82\t4.0740740740740744e+27\n-2.81\t4.216931216931217e+27\n-2.8\t4.3677248677248677e+27\n-2.79\t4.3968253968253967e+27\n-2.78\t4.425925925925926e+27\n-2.77\t4.4576719576719584e+27\n-2.76\t4.486772486772487e+27\n-2.75\t4.507936507936508e+27\n-2.74\t4.507936507936508e+27\n-2.73\t4.4894179894179895e+27\n-2.72\t4.4735449735449737e+27\n-2.71\t4.5264550264550267e+27\n-2.7\t4.5793650793650797e+27\n-2.69\t4.6296296296296294e+27\n-2.68\t4.67989417989418e+27\n-2.67\t4.73015873015873e+27\n-2.66\t4.780423280423281e+27\n-2.65\t4.828042328042328e+27\n-2.64\t4.8862433862433867e+27\n-2.63\t4.9497354497354495e+27\n-2.62\t5.010582010582011e+27\n-2.61\t5.068783068783069e+27\n-2.6\t5.129629629629629e+27\n-2.59\t5.198412698412699e+27\n-2.58\t5.280423280423281e+27\n-2.57\t5.373015873015873e+27\n-2.56\t5.423280423280424e+27\n-2.55\t5.44973544973545e+27\n-2.54\t5.473544973544973e+27\n-2.53\t5.500000000000001e+27\n-2.52\t5.526455026455027e+27\n-2.51\t5.55026455026455e+27\n-2.5\t5.571428571428572e+27\n-2.49\t5.58994708994709e+27\n-2.48\t5.621693121693122e+27\n-2.47\t5.653439153439154e+27\n-2.46\t5.682539682539683e+27\n-2.45\t5.711640211640213e+27\n-2.44\t5.735449735449735e+27\n-2.43\t5.756613756613757e+27\n-2.42\t5.772486772486773e+27\n-2.41\t5.788359788359789e+27\n-2.4\t5.841269841269841e+27\n-2.39\t5.894179894179895e+27\n-2.38\t5.941798941798942e+27\n-2.37\t5.992063492063492e+27\n-2.36\t6.042328042328042e+27\n-2.35\t6.097883597883598e+27\n-2.34\t6.156084656084656e+27\n-2.33\t6.21957671957672e+27\n-2.32\t6.285714285714286e+27\n-2.31\t6.351851851851853e+27\n-2.3\t6.417989417989419e+27\n-2.29\t6.481481481481481e+27\n-2.28\t6.531746031746032e+27\n-2.27\t6.568783068783069e+27\n-2.26\t6.58994708994709e+27\n-2.25\t6.544973544973546e+27\n-2.24\t6.560846560846561e+27\n-2.23\t6.582010582010582e+27\n-2.22\t6.605820105820106e+27\n-2.21\t6.632275132275132e+27\n-2.2\t6.658730158730159e+27\n-2.19\t6.690476190476192e+27\n-2.18\t6.722222222222222e+27\n-2.17\t6.738095238095238e+27\n-2.16\t6.761904761904762e+27\n-2.15\t6.793650793650794e+27\n-2.14\t6.830687830687831e+27\n-2.13\t6.870370370370371e+27\n-2.12\t6.91005291005291e+27\n-2.11\t6.944444444444445e+27\n-2.1\t6.978835978835979e+27\n-2.09\t7.013227513227514e+27\n-2.08\t7.044973544973545e+27\n-2.07\t7.076719576719577e+27\n-2.06\t7.105820105820106e+27\n-2.05\t7.134920634920635e+27\n-2.04\t7.164021164021164e+27\n-2.03\t7.19047619047619e+27\n-2.02\t7.23015873015873e+27\n-2.01\t7.280423280423281e+27\n-2\t7.333333333333334e+27\n-1.99\t7.386243386243387e+27\n-1.98\t7.43915343915344e+27\n-1.97\t7.497354497354498e+27\n-1.96\t7.552910052910053e+27\n-1.95\t7.613756613756614e+27\n-1.94\t7.645502645502645e+27\n-1.93\t7.66931216931217e+27\n-1.92\t7.690476190476191e+27\n-1.91\t7.70899470899471e+27\n-1.9\t7.727513227513229e+27\n-1.89\t7.743386243386244e+27\n-1.88\t7.756613756613758e+27\n-1.87\t7.767195767195768e+27\n-1.86\t7.788359788359789e+27\n-1.85\t7.806878306878306e+27\n-1.84\t7.828042328042328e+27\n-1.83\t7.846560846560846e+27\n-1.82\t7.865079365079366e+27\n-1.81\t7.88888888888889e+27\n-1.8\t7.915343915343916e+27\n-1.79\t7.941798941798943e+27\n-1.78\t7.96825396825397e+27\n-1.77\t7.997354497354498e+27\n-1.76\t8.026455026455027e+27\n-1.75\t8.055555555555556e+27\n-1.74\t8.089947089947091e+27\n-1.73\t8.124338624338624e+27\n-1.72\t8.161375661375661e+27\n-1.71\t8.201058201058201e+27\n-1.7\t8.238095238095239e+27\n-1.69\t8.275132275132277e+27\n-1.68\t8.30952380952381e+27\n-1.67\t8.343915343915344e+27\n-1.66\t8.378306878306879e+27\n-1.65\t8.410052910052911e+27\n-1.64\t8.444444444444445e+27\n-1.63\t8.478835978835979e+27\n-1.62\t8.513227513227514e+27\n-1.61\t8.550264550264551e+27\n-1.6\t8.587301587301588e+27\n-1.59\t8.626984126984128e+27\n-1.58\t8.664021164021165e+27\n-1.57\t8.698412698412698e+27\n-1.56\t8.730158730158731e+27\n-1.55\t8.756613756613757e+27\n-1.54\t8.783068783068785e+27\n-1.53\t8.806878306878307e+27\n-1.52\t8.833333333333333e+27\n-1.51\t8.854497354497355e+27\n-1.5\t8.87037037037037e+27\n-1.49\t8.886243386243386e+27\n-1.48\t8.91005291005291e+27\n-1.47\t8.933862433862435e+27\n-1.46\t8.957671957671958e+27\n-1.45\t8.981481481481483e+27\n-1.44\t9.005291005291005e+27\n-1.43\t9.026455026455027e+27\n-1.42\t9.050264550264552e+27\n-1.41\t9.074074074074075e+27\n-1.4\t9.097883597883598e+27\n-1.39\t9.121693121693122e+27\n-1.38\t9.142857142857144e+27\n-1.37\t9.161375661375662e+27\n-1.36\t9.185185185185186e+27\n-1.35\t9.20899470899471e+27\n-1.34\t9.232804232804233e+27\n-1.33\t9.256613756613757e+27\n-1.32\t9.280423280423281e+27\n-1.31\t9.306878306878308e+27\n-1.3\t9.333333333333334e+27\n-1.29\t9.35978835978836e+27\n-1.28\t9.388888888888889e+27\n-1.27\t9.417989417989418e+27\n-1.26\t9.449735449735451e+27\n-1.25\t9.484126984126984e+27\n-1.24\t9.521164021164022e+27\n-1.23\t9.558201058201059e+27\n-1.22\t9.597883597883599e+27\n-1.21\t9.634920634920636e+27\n-1.2\t9.671957671957672e+27\n-1.19\t9.708994708994709e+27\n-1.18\t9.746031746031747e+27\n-1.17\t9.783068783068784e+27\n-1.16\t9.822751322751324e+27\n-1.15\t9.85978835978836e+27\n-1.14\t9.896825396825397e+27\n-1.13\t9.931216931216933e+27\n-1.12\t9.957671957671958e+27\n-1.11\t9.97883597883598e+27\n-1.1\t9.976190476190476e+27\n-1.09\t9.994708994708996e+27\n-1.08\t1.0013227513227514e+28\n-1.07\t1.0029100529100529e+28\n-1.06\t1.0044973544973545e+28\n-1.05\t1.0058201058201057e+28\n-1.04\t1.0071428571428572e+28\n-1.03\t1.0084656084656085e+28\n-1.02\t1.0105820105820107e+28\n-1.01\t1.0126984126984126e+28\n-1\t1.0150793650793652e+28\n-0.99\t1.0177248677248677e+28\n-0.98\t1.02010582010582e+28\n-0.97\t1.0227513227513228e+28\n-0.96\t1.0251322751322751e+28\n-0.95\t1.0277777777777779e+28\n-0.94\t1.0301587301587302e+28\n-0.93\t1.032804232804233e+28\n-0.92\t1.0354497354497357e+28\n-0.91\t1.0378306878306878e+28\n-0.9\t1.0404761904761905e+28\n-0.89\t1.042857142857143e+28\n-0.88\t1.0452380952380952e+28\n-0.87\t1.0476190476190478e+28\n-0.86\t1.05e+28\n-0.85\t1.0523809523809525e+28\n-0.84\t1.055026455026455e+28\n-0.83\t1.0576719576719578e+28\n-0.82\t1.0603174603174603e+28\n-0.81\t1.0632275132275132e+28\n-0.8\t1.065873015873016e+28\n-0.79\t1.0685185185185186e+28\n-0.78\t1.0711640211640211e+28\n-0.77\t1.0735449735449735e+28\n-0.76\t1.0761904761904762e+28\n-0.75\t1.0791005291005291e+28\n-0.74\t1.082010582010582e+28\n-0.73\t1.0849206349206351e+28\n-0.72\t1.0880952380952382e+28\n-0.71\t1.0915343915343916e+28\n-0.7\t1.094973544973545e+28\n-0.69\t1.0986772486772487e+28\n-0.68\t1.1026455026455027e+28\n-0.67\t1.1066137566137567e+28\n-0.66\t1.1105820105820106e+28\n-0.65\t1.1132275132275134e+28\n-0.64\t1.1156084656084657e+28\n-0.63\t1.1177248677248677e+28\n-0.62\t1.1198412698412699e+28\n-0.61\t1.1216931216931217e+28\n-0.6\t1.1235449735449737e+28\n-0.59\t1.1251322751322753e+28\n-0.58\t1.1269841269841271e+28\n-0.57\t1.129100529100529e+28\n-0.56\t1.1312169312169313e+28\n-0.55\t1.133068783068783e+28\n-0.54\t1.134920634920635e+28\n-0.53\t1.136772486772487e+28\n-0.52\t1.1386243386243387e+28\n-0.51\t1.1402116402116404e+28\n-0.5\t1.1420634920634922e+28\n-0.49\t1.143915343915344e+28\n-0.48\t1.1455026455026456e+28\n-0.47\t1.1473544973544974e+28\n-0.46\t1.148941798941799e+28\n-0.45\t1.1505291005291007e+28\n-0.44\t1.1523809523809525e+28\n-0.43\t1.1547619047619048e+28\n-0.42\t1.1574074074074076e+28\n-0.41\t1.1603174603174605e+28\n-0.4\t1.162962962962963e+28\n-0.39\t1.1658730158730159e+28\n-0.38\t1.1685185185185186e+28\n-0.37\t1.1714285714285715e+28\n-0.36\t1.174074074074074e+28\n-0.35\t1.1767195767195767e+28\n-0.34\t1.1793650793650795e+28\n-0.33\t1.1822751322751324e+28\n-0.32\t1.184920634920635e+28\n-0.31\t1.187830687830688e+28\n-0.3\t1.190740740740741e+28\n-0.29\t1.1936507936507938e+28\n-0.28\t1.1965608465608467e+28\n-0.27\t1.1994708994708996e+28\n-0.26\t1.2023809523809525e+28\n-0.25\t1.2055555555555555e+28\n-0.24\t1.2087301587301588e+28\n-0.23\t1.211904761904762e+28\n-0.22\t1.2150793650793651e+28\n-0.21\t1.2185185185185186e+28\n-0.2\t1.2216931216931216e+28\n-0.19\t1.224867724867725e+28\n-0.18\t1.2277777777777778e+28\n-0.17\t1.230952380952381e+28\n-0.16\t1.2341269841269844e+28\n-0.15\t1.2373015873015874e+28\n-0.14\t1.2404761904761905e+28\n-0.13\t1.2425925925925927e+28\n-0.12\t1.2447089947089946e+28\n-0.11\t1.2468253968253968e+28\n-0.1\t1.248941798941799e+28\n-0.09\t1.2510582010582012e+28\n-0.08\t1.2534391534391536e+28\n-0.07\t1.2555555555555557e+28\n-0.06\t1.2582010582010583e+28\n-0.05\t1.2611111111111111e+28\n-0.04\t1.264021164021164e+28\n-0.03\t1.2671957671957673e+28\n-0.02\t1.2701058201058202e+28\n-0.01\t1.2730158730158731e+28\n0\t1.275925925925926e+28\n0.01\t1.2785714285714287e+28\n0.02\t1.2814814814814816e+28\n0.03\t1.2843915343915345e+28\n0.04\t1.2873015873015874e+28\n0.05\t1.2902116402116403e+28\n0.06\t1.2931216931216932e+28\n0.07\t1.2962962962962963e+28\n0.08\t1.2994708994708996e+28\n0.09\t1.302910052910053e+28\n0.1\t1.3063492063492064e+28\n0.11\t1.31005291005291e+28\n0.12\t1.3134920634920635e+28\n0.13\t1.3174603174603175e+28\n0.14\t1.3211640211640213e+28\n0.15\t1.3251322751322753e+28\n0.16\t1.329100529100529e+28\n0.17\t1.3333333333333334e+28\n0.18\t1.3373015873015872e+28\n0.19\t1.3415343915343916e+28\n0.2\t1.345767195767196e+28\n0.21\t1.3502645502645502e+28\n0.22\t1.3544973544973546e+28\n0.23\t1.3603174603174604e+28\n0.24\t1.3674603174603177e+28\n0.25\t1.374867724867725e+28\n0.26\t1.3825396825396825e+28\n0.27\t1.38994708994709e+28\n0.28\t1.3976190476190477e+28\n0.29\t1.4055555555555557e+28\n0.3\t1.4134920634920637e+28\n0.31\t1.4230158730158733e+28\n0.32\t1.4325396825396827e+28\n0.33\t1.4420634920634923e+28\n0.34\t1.4521164021164022e+28\n0.35\t1.4621693121693122e+28\n0.36\t1.4722222222222224e+28\n0.37\t1.4828042328042328e+28\n0.38\t1.492857142857143e+28\n0.39\t1.5026455026455026e+28\n0.4\t1.5121693121693122e+28\n0.41\t1.5214285714285714e+28\n0.42\t1.5304232804232805e+28\n0.43\t1.538888888888889e+28\n0.44\t1.546825396825397e+28\n0.45\t1.5544973544973546e+28\n0.46\t1.560846560846561e+28\n0.47\t1.5677248677248678e+28\n0.48\t1.573809523809524e+28\n0.49\t1.5788359788359788e+28\n0.5\t1.5830687830687832e+28\n0.51\t1.5865079365079366e+28\n0.52\t1.5891534391534394e+28\n0.53\t1.5910052910052912e+28\n0.54\t1.5925925925925926e+28\n0.55\t1.5947089947089948e+28\n0.56\t1.596825396825397e+28\n0.57\t1.5994708994708997e+28\n0.58\t1.6034391534391535e+28\n0.59\t1.6076719576719578e+28\n0.6\t1.611904761904762e+28\n0.61\t1.6166666666666667e+28\n0.62\t1.6211640211640212e+28\n0.63\t1.6248677248677248e+28\n0.64\t1.6272486772486774e+28\n0.65\t1.6322751322751323e+28\n0.66\t1.6365079365079366e+28\n0.67\t1.6415343915343917e+28\n0.68\t1.646031746031746e+28\n0.69\t1.650793650793651e+28\n0.7\t1.6547619047619047e+28\n0.71\t1.6579365079365082e+28\n0.72\t1.66005291005291e+28\n0.73\t1.6616402116402118e+28\n0.74\t1.661904761904762e+28\n0.75\t1.6611111111111113e+28\n0.76\t1.6626984126984127e+28\n0.77\t1.6632275132275134e+28\n0.78\t1.6597883597883598e+28\n0.79\t1.6505291005291006e+28\n0.8\t1.6407407407407408e+28\n0.81\t1.6306878306878306e+28\n0.82\t1.6195767195767196e+28\n0.83\t1.6095238095238099e+28\n0.84\t1.5978835978835978e+28\n0.85\t1.5846560846560846e+28\n0.86\t1.5722222222222225e+28\n0.87\t1.5632275132275133e+28\n0.88\t1.553174603174603e+28\n0.89\t1.5412698412698413e+28\n0.9\t1.5272486772486774e+28\n0.91\t1.5111111111111113e+28\n0.92\t1.4947089947089946e+28\n0.93\t1.4796296296296298e+28\n0.94\t1.466931216931217e+28\n0.95\t1.4531746031746033e+28\n0.96\t1.4396825396825397e+28\n0.97\t1.4320105820105821e+28\n0.98\t1.426984126984127e+28\n0.99\t1.4246031746031747e+28\n1\t1.4235449735449736e+28\n1.01\t1.4224867724867725e+28\n1.02\t1.420899470899471e+28\n1.03\t1.419047619047619e+28\n1.04\t1.417195767195767e+28\n1.05\t1.4153439153439155e+28\n1.06\t1.4134920634920637e+28\n1.07\t1.412698412698413e+28\n1.08\t1.4132275132275133e+28\n1.09\t1.4150793650793653e+28\n1.1\t1.417195767195767e+28\n1.11\t1.4137566137566138e+28\n1.12\t1.406084656084656e+28\n1.13\t1.391798941798942e+28\n1.14\t1.3722222222222224e+28\n1.15\t1.3574074074074075e+28\n1.16\t1.33994708994709e+28\n1.17\t1.3193121693121693e+28\n1.18\t1.2947089947089949e+28\n1.19\t1.2756613756613758e+28\n1.2\t1.2523809523809525e+28\n1.21\t1.2269841269841271e+28\n1.22\t1.217989417989418e+28\n1.23\t1.217989417989418e+28\n1.24\t1.2206349206349206e+28\n1.25\t1.2230158730158731e+28\n1.26\t1.225925925925926e+28\n1.27\t1.228835978835979e+28\n1.28\t1.2314814814814816e+28\n1.29\t1.2341269841269844e+28\n1.3\t1.2365079365079365e+28\n1.31\t1.2256613756613756e+28\n1.32\t1.210846560846561e+28\n1.33\t1.217989417989418e+28\n1.34\t1.225925925925926e+28\n1.35\t1.2343915343915345e+28\n1.36\t1.243915343915344e+28\n1.37\t1.2542328042328043e+28\n1.38\t1.2576719576719577e+28\n1.39\t1.2444444444444445e+28\n1.4\t1.2510582010582012e+28\n1.41\t1.2576719576719577e+28\n1.42\t1.2642857142857144e+28\n1.43\t1.2711640211640213e+28\n1.44\t1.282010582010582e+28\n1.45\t1.292857142857143e+28\n1.46\t1.3002645502645503e+28\n1.47\t1.3044973544973546e+28\n1.48\t1.3050264550264552e+28\n1.49\t1.2743386243386244e+28\n1.5\t1.2682539682539684e+28\n1.51\t1.2743386243386244e+28\n1.52\t1.280952380952381e+28\n1.53\t1.287830687830688e+28\n1.54\t1.2955026455026456e+28\n1.55\t1.3050264550264552e+28\n1.56\t1.3145502645502646e+28\n1.57\t1.3243386243386246e+28\n1.58\t1.3343915343915343e+28\n1.59\t1.3447089947089946e+28\n1.6\t1.3544973544973546e+28\n1.61\t1.3642857142857144e+28\n1.62\t1.3738095238095238e+28\n1.63\t1.382010582010582e+28\n1.64\t1.3878306878306877e+28\n1.65\t1.392063492063492e+28\n1.66\t1.5021164021164022e+28\n1.67\t1.428835978835979e+28\n1.68\t1.4605820105820108e+28\n1.69\t1.4891534391534392e+28\n1.7\t1.5037037037037039e+28\n1.71\t1.367989417989418e+28\n1.72\t1.3645502645502648e+28\n1.73\t1.3642857142857144e+28\n1.74\t1.362962962962963e+28\n1.75\t1.364814814814815e+28\n1.76\t1.36984126984127e+28\n1.77\t1.372751322751323e+28\n1.78\t1.3714285714285714e+28\n1.79\t1.3658730158730158e+28\n1.8\t1.367989417989418e+28\n1.81\t1.367989417989418e+28\n1.82\t1.3661375661375662e+28\n1.83\t1.3693121693121693e+28\n1.84\t1.375925925925926e+28\n1.85\t1.3841269841269841e+28\n1.86\t1.392063492063492e+28\n1.87\t1.4026455026455028e+28\n1.88\t1.4105820105820108e+28\n1.89\t1.3894179894179896e+28\n1.9\t1.3957671957671957e+28\n1.91\t1.4034391534391535e+28\n1.92\t1.411111111111111e+28\n1.93\t1.418783068783069e+28\n1.94\t1.4264550264550265e+28\n1.95\t1.4335978835978838e+28\n1.96\t1.4404761904761904e+28\n1.97\t1.446825396825397e+28\n1.98\t1.452910052910053e+28\n1.99\t1.4582010582010584e+28\n2\t1.4629629629629631e+28\n2.01\t1.4677248677248678e+28\n2.02\t1.471957671957672e+28\n2.03\t1.4761904761904763e+28\n2.04\t1.480952380952381e+28\n2.05\t1.486772486772487e+28\n2.06\t1.4931216931216932e+28\n2.07\t1.5005291005291008e+28\n2.08\t1.5113756613756615e+28\n2.09\t1.529100529100529e+28\n2.1\t1.5502645502645502e+28\n2.11\t1.5822751322751323e+28\n2.12\t1.6277777777777777e+28\n2.13\t1.670899470899471e+28\n2.14\t1.7034391534391537e+28\n2.15\t1.7253968253968256e+28\n2.16\t1.737566137566138e+28\n2.17\t1.7497354497354498e+28\n2.18\t1.7492063492063493e+28\n2.19\t1.7637566137566137e+28\n2.2\t1.7822751322751322e+28\n2.21\t1.8015873015873018e+28\n2.22\t1.8214285714285715e+28\n2.23\t1.8423280423280426e+28\n2.24\t1.8629629629629632e+28\n2.25\t1.9039682539682542e+28\n2.26\t1.9169312169312172e+28\n2.27\t1.910846560846561e+28\n2.28\t1.9174603174603175e+28\n2.29\t1.9373015873015873e+28\n2.3\t1.9608465608465608e+28\n2.31\t1.9539682539682541e+28\n2.32\t1.9632275132275134e+28\n2.33\t1.9674603174603177e+28\n2.34\t1.9724867724867728e+28\n2.35\t1.9375661375661379e+28\n2.36\t1.9375661375661379e+28\n2.37\t1.9357142857142858e+28\n2.38\t1.9317460317460318e+28\n2.39\t1.9261904761904762e+28\n2.4\t1.9243386243386246e+28\n2.41\t1.9253968253968255e+28\n2.42\t1.9275132275132277e+28\n2.43\t1.9296296296296299e+28\n2.44\t1.9314814814814815e+28\n2.45\t1.9330687830687833e+28\n2.46\t1.933862433862434e+28\n2.47\t1.9349206349206351e+28\n2.48\t1.9359788359788362e+28\n2.49\t1.936772486772487e+28\n2.5\t2.2100529100529105e+28\n2.51\t2.0563492063492065e+28\n2.52\t1.980952380952381e+28\n2.53\t1.9764550264550266e+28\n2.54\t1.9703703703703706e+28\n2.55\t1.9626984126984128e+28\n2.56\t1.9534391534391534e+28\n2.57\t1.9444444444444445e+28\n2.58\t1.9346560846560847e+28\n2.59\t1.924074074074074e+28\n2.6\t1.9124338624338625e+28\n2.61\t1.8997354497354498e+28\n2.62\t1.8843915343915346e+28\n2.63\t1.8671957671957672e+28\n2.64\t1.847883597883598e+28\n2.65\t1.8269841269841272e+28\n2.66\t1.8105820105820107e+28\n2.67\t1.7994708994708996e+28\n2.68\t1.7873015873015873e+28\n2.69\t1.775925925925926e+28\n2.7\t1.7650793650793652e+28\n2.71\t1.7555555555555556e+28\n2.72\t1.7465608465608468e+28\n2.73\t1.7383597883597886e+28\n2.74\t1.7325396825396828e+28\n2.75\t1.7291005291005292e+28\n2.76\t1.7261904761904763e+28\n2.77\t1.721693121693122e+28\n2.78\t1.7214285714285714e+28\n2.79\t1.723015873015873e+28\n2.8\t1.7920634920634922e+28\n2.81\t1.7232804232804234e+28\n2.82\t1.7177248677248678e+28\n2.83\t1.7084656084656087e+28\n2.84\t1.6955026455026457e+28\n2.85\t1.678835978835979e+28\n2.86\t1.6648148148148149e+28\n2.87\t1.6584656084656085e+28\n2.88\t1.6521164021164024e+28\n2.89\t1.6473544973544975e+28\n2.9\t1.6431216931216931e+28\n2.91\t1.6391534391534394e+28\n2.92\t1.6370370370370372e+28\n2.93\t1.632010582010582e+28\n2.94\t1.6272486772486774e+28\n2.95\t1.6227513227513226e+28\n2.96\t1.6182539682539683e+28\n2.97\t1.6134920634920636e+28\n2.98\t1.608994708994709e+28\n2.99\t1.6052910052910055e+28\n3\t1.6013227513227513e+28\n3.01\t1.5970899470899471e+28\n3.02\t1.5931216931216931e+28\n3.03\t1.5896825396825397e+28\n3.04\t1.5865079365079366e+28\n3.05\t1.583862433862434e+28\n3.06\t1.5817460317460317e+28\n3.07\t1.5806878306878308e+28\n3.08\t1.5804232804232807e+28\n3.09\t1.5804232804232807e+28\n3.1\t1.5806878306878308e+28\n3.11\t1.5812169312169314e+28\n3.12\t1.5825396825396824e+28\n3.13\t1.5846560846560846e+28\n3.14\t1.585714285714286e+28\n3.15\t1.5875661375661375e+28\n3.16\t1.5952380952380953e+28\n3.17\t1.6198412698412697e+28\n3.18\t1.6343915343915344e+28\n3.19\t1.6470899470899473e+28\n3.2\t1.6560846560846562e+28\n3.21\t1.6624338624338625e+28\n3.22\t1.6690476190476192e+28\n3.23\t1.7195767195767198e+28\n3.24\t1.7211640211640212e+28\n3.25\t1.720899470899471e+28\n3.26\t1.7219576719576721e+28\n3.27\t1.724867724867725e+28\n3.28\t1.727777777777778e+28\n3.29\t1.7304232804232806e+28\n3.3\t1.7330687830687832e+28\n3.31\t1.7357142857142859e+28\n3.32\t1.7394179894179895e+28\n3.33\t1.743915343915344e+28\n3.34\t1.7492063492063493e+28\n3.35\t1.7555555555555556e+28\n3.36\t1.7645502645502647e+28\n3.37\t1.7859788359788363e+28\n3.38\t1.788095238095238e+28\n3.39\t1.7907407407407407e+28\n3.4\t1.7939153439153442e+28\n3.41\t1.796825396825397e+28\n3.42\t1.7994708994708996e+28\n3.43\t1.8021164021164024e+28\n3.44\t1.8137566137566137e+28\n3.45\t1.8164021164021165e+28\n3.46\t1.8436507936507936e+28\n3.47\t1.841798941798942e+28\n3.48\t1.8394179894179897e+28\n3.49\t1.8370370370370371e+28\n3.5\t1.8330687830687831e+28\n3.51\t1.8312169312169313e+28\n3.52\t1.8296296296296297e+28\n3.53\t1.828042328042328e+28\n3.54\t1.8264550264550266e+28\n3.55\t1.824867724867725e+28\n3.56\t1.8232804232804236e+28\n3.57\t1.8216931216931217e+28\n3.58\t1.82010582010582e+28\n3.59\t1.8185185185185187e+28\n3.6\t1.833597883597884e+28\n3.61\t1.8306878306878306e+28\n3.62\t1.8301587301587302e+28\n3.63\t1.8328042328042327e+28\n3.64\t1.836772486772487e+28\n3.65\t1.8412698412698413e+28\n3.66\t1.8502645502645503e+28\n3.67\t1.8722222222222222e+28\n3.68\t1.8875661375661377e+28\n3.69\t1.892063492063492e+28\n3.7\t1.9002645502645505e+28\n3.71\t1.8978835978835982e+28\n3.72\t1.8917989417989418e+28\n3.73\t1.881746031746032e+28\n3.74\t1.8727513227513228e+28\n3.75\t1.871957671957672e+28\n3.76\t1.86984126984127e+28\n3.77\t1.8685185185185186e+28\n3.78\t1.8671957671957672e+28\n3.79\t1.8642857142857145e+28\n3.8\t1.8597883597883597e+28\n3.81\t1.8566137566137567e+28\n3.82\t1.853968253968254e+28\n3.83\t1.8507936507936509e+28\n3.84\t1.8492063492063492e+28\n3.85\t1.8492063492063492e+28\n3.86\t1.8494708994708996e+28\n3.87\t1.8500000000000002e+28\n3.88\t1.8505291005291007e+28\n3.89\t1.8515873015873016e+28\n3.9\t1.852910052910053e+28\n3.91\t1.8542328042328043e+28\n3.92\t1.8560846560846561e+28\n3.93\t1.8579365079365082e+28\n3.94\t1.8605820105820109e+28\n3.95\t1.8703703703703704e+28\n3.96\t1.8793650793650795e+28\n3.97\t1.8870370370370373e+28\n3.98\t1.8933862433862434e+28\n3.99\t1.8984126984126985e+28\n4\t1.9010582010582013e+28\n4.01\t1.9047619047619049e+28\n4.02\t1.9140211640211643e+28\n4.03\t1.921693121693122e+28\n4.04\t1.9277777777777779e+28\n4.05\t1.9309523809523811e+28\n4.06\t1.9343915343915344e+28\n4.07\t1.9365079365079365e+28\n4.08\t1.937830687830688e+28\n4.09\t1.9420634920634922e+28\n4.1\t1.9433862433862436e+28\n4.11\t1.9415343915343916e+28\n4.12\t1.9362433862433864e+28\n4.13\t1.9280423280423282e+28\n4.14\t1.9166666666666668e+28\n4.15\t1.9021164021164021e+28\n4.16\t1.8753968253968255e+28\n4.17\t1.873809523809524e+28\n4.18\t1.873015873015873e+28\n4.19\t1.8724867724867726e+28\n4.2\t1.8727513227513228e+28\n4.21\t1.8732804232804233e+28\n4.22\t1.897089947089947e+28\n4.23\t1.905026455026455e+28\n4.24\t1.9052910052910052e+28\n4.25\t1.9052910052910052e+28\n4.26\t1.9063492063492065e+28\n4.27\t1.8875661375661377e+28\n4.28\t1.8857142857142858e+28\n4.29\t1.8835978835978837e+28\n4.3\t1.880952380952381e+28\n4.31\t1.878042328042328e+28\n4.32\t1.8751322751322751e+28\n4.33\t1.8722222222222222e+28\n4.34\t1.87010582010582e+28\n4.35\t1.8690476190476192e+28\n4.36\t1.8574074074074074e+28\n4.37\t1.841798941798942e+28\n4.38\t1.8396825396825399e+28\n4.39\t1.8388888888888891e+28\n4.4\t1.8391534391534393e+28\n4.41\t1.841005291005291e+28\n4.42\t1.842857142857143e+28\n4.43\t1.844973544973545e+28\n4.44\t1.8481481481481484e+28\n4.45\t1.8521164021164021e+28\n4.46\t1.8568783068783068e+28\n4.47\t1.8624338624338625e+28\n4.48\t1.868783068783069e+28\n4.49\t1.8761904761904765e+28\n4.5\t1.8838624338624338e+28\n4.51\t1.8931216931216933e+28\n4.52\t1.902910052910053e+28\n4.53\t1.9121693121693123e+28\n4.54\t1.921957671957672e+28\n4.55\t1.9296296296296299e+28\n4.56\t1.937037037037037e+28\n4.57\t1.951851851851852e+28\n4.58\t1.9674603174603177e+28\n4.59\t1.981746031746032e+28\n4.6\t1.9955026455026456e+28\n4.61\t2.008994708994709e+28\n4.62\t2.057671957671958e+28\n4.63\t2.0629629629629634e+28\n4.64\t2.0693121693121695e+28\n4.65\t2.077777777777778e+28\n4.66\t2.0875661375661376e+28\n4.67\t2.094179894179894e+28\n4.68\t2.09973544973545e+28\n4.69\t2.1113756613756615e+28\n4.7\t2.1285714285714285e+28\n4.71\t2.145238095238095e+28\n4.72\t2.161111111111111e+28\n4.73\t2.1764550264550268e+28\n4.74\t2.1796296296296296e+28\n4.75\t2.181481481481482e+28\n4.76\t2.182010582010582e+28\n4.77\t2.182010582010582e+28\n4.78\t2.181481481481482e+28\n4.79\t2.1801587301587304e+28\n4.8\t2.178571428571429e+28\n4.81\t2.1761904761904764e+28\n4.82\t2.173015873015873e+28\n4.83\t2.169047619047619e+28\n4.84\t2.164550264550265e+28\n4.85\t2.165608465608466e+28\n4.86\t2.1642857142857144e+28\n4.87\t2.1603174603174604e+28\n4.88\t2.1539682539682543e+28\n4.89\t2.145238095238095e+28\n4.9\t2.1341269841269844e+28\n4.91\t2.137301587301587e+28\n4.92\t2.1333333333333337e+28\n4.93\t2.1380952380952384e+28\n4.94\t2.1396825396825398e+28\n4.95\t2.137301587301587e+28\n4.96\t2.135978835978836e+28\n4.97\t2.1351851851851855e+28\n4.98\t2.1335978835978836e+28\n4.99\t2.133862433862434e+28\n5\t2.135978835978836e+28\n5.01\t2.1396825396825398e+28\n5.02\t2.144708994708995e+28\n5.03\t2.153703703703704e+28\n5.04\t2.156878306878307e+28\n5.05\t2.1613756613756615e+28\n5.06\t2.1669312169312174e+28\n5.07\t2.1732804232804235e+28\n5.08\t2.1767195767195767e+28\n5.09\t2.175661375661376e+28\n5.1\t2.1703703703703706e+28\n5.11\t2.162698412698413e+28\n5.12\t2.156084656084656e+28\n5.13\t2.14973544973545e+28\n5.14\t2.1436507936507938e+28\n5.15\t2.1589947089947094e+28\n5.16\t2.1539682539682543e+28\n5.17\t2.1489417989417992e+28\n5.18\t2.1441798941798945e+28\n5.19\t2.1391534391534394e+28\n5.2\t2.133862433862434e+28\n5.21\t2.1293650793650792e+28\n5.22\t2.132804232804233e+28\n5.23\t2.136772486772487e+28\n5.24\t2.1362433862433866e+28\n5.25\t2.12989417989418e+28\n5.26\t2.124867724867725e+28\n5.27\t2.1203703703703706e+28\n5.28\t2.1132275132275133e+28\n5.29\t2.111904761904762e+28\n5.3\t2.111111111111111e+28\n5.31\t2.1105820105820104e+28\n5.32\t2.11005291005291e+28\n5.33\t2.1092592592592593e+28\n5.34\t2.1124338624338626e+28\n5.35\t2.111111111111111e+28\n5.36\t2.10978835978836e+28\n5.37\t2.1084656084656086e+28\n5.38\t2.111111111111111e+28\n5.39\t2.115873015873016e+28\n5.4\t2.1211640211640213e+28\n5.41\t2.1272486772486775e+28\n5.42\t2.132539682539683e+28\n5.43\t2.1391534391534394e+28\n5.44\t2.145238095238095e+28\n5.45\t2.146825396825397e+28\n5.46\t2.145767195767196e+28\n5.47\t2.1431216931216934e+28\n5.48\t2.1425925925925927e+28\n5.49\t2.1436507936507938e+28\n5.5\t2.1441798941798945e+28\n5.51\t2.1449735449735452e+28\n5.52\t2.145767195767196e+28\n5.53\t2.1462962962962963e+28\n5.54\t2.1465608465608467e+28\n5.55\t2.146825396825397e+28\n5.56\t2.15e+28\n5.57\t2.1484126984126985e+28\n5.58\t2.1425925925925927e+28\n5.59\t2.1396825396825398e+28\n5.6\t2.1412698412698416e+28\n5.61\t2.1473544973544974e+28\n5.62\t2.1515873015873017e+28\n5.63\t2.1301587301587304e+28\n5.64\t2.128042328042328e+28\n5.65\t2.1261904761904764e+28\n5.66\t2.124867724867725e+28\n5.67\t2.124074074074074e+28\n5.68\t2.1232804232804235e+28\n5.69\t2.1227513227513227e+28\n5.7\t2.1222222222222224e+28\n5.71\t2.1214285714285713e+28\n5.72\t2.12010582010582e+28\n5.73\t2.117989417989418e+28\n5.74\t2.1214285714285713e+28\n5.75\t2.1293650793650792e+28\n5.76\t2.1293650793650792e+28\n5.77\t2.1322751322751326e+28\n5.78\t2.1362433862433866e+28\n5.79\t2.140740740740741e+28\n5.8\t2.1460317460317463e+28\n5.81\t2.1478835978835977e+28\n5.82\t2.149206349206349e+28\n5.83\t2.1502645502645503e+28\n5.84\t2.1515873015873017e+28\n5.85\t2.1534391534391535e+28\n5.86\t2.1552910052910053e+28\n5.87\t2.156613756613757e+28\n5.88\t2.157936507936508e+28\n5.89\t2.1589947089947094e+28\n5.9\t2.1619047619047623e+28\n5.91\t2.1634920634920637e+28\n5.92\t2.1642857142857144e+28\n5.93\t2.16005291005291e+28\n5.94\t2.1555555555555557e+28\n5.95\t2.1513227513227514e+28\n5.96\t2.1473544973544974e+28\n5.97\t2.143386243386244e+28\n5.98\t2.1396825396825398e+28\n5.99\t2.1362433862433866e+28\n6\t2.1330687830687833e+28\n6.01\t2.12989417989418e+28\n6.02\t2.1264550264550263e+28\n6.03\t2.1243386243386246e+28\n6.04\t2.1264550264550263e+28\n6.05\t2.1330687830687833e+28\n6.06\t2.141798941798942e+28\n6.07\t2.138888888888889e+28\n6.08\t2.137830687830688e+28\n6.09\t2.138888888888889e+28\n6.1\t2.1412698412698416e+28\n6.11\t2.1431216931216934e+28\n6.12\t2.1444444444444445e+28\n6.13\t2.145767195767196e+28\n6.14\t2.1465608465608467e+28\n6.15\t2.146825396825397e+28\n6.16\t2.1462962962962963e+28\n6.17\t2.1449735449735452e+28\n6.18\t2.1431216931216934e+28\n6.19\t2.1396825396825398e+28\n6.2\t2.137566137566138e+28\n6.21\t2.137301587301587e+28\n6.22\t2.1383597883597887e+28\n6.23\t2.1412698412698416e+28\n6.24\t2.1716931216931216e+28\n6.25\t2.1883597883597887e+28\n6.26\t2.201851851851852e+28\n6.27\t2.2134920634920637e+28\n6.28\t2.223544973544974e+28\n6.29\t2.2306878306878307e+28\n6.3\t2.235978835978836e+28\n6.31\t2.23941798941799e+28\n6.32\t2.241269841269841e+28\n6.33\t2.240740740740741e+28\n6.34\t2.237830687830688e+28\n6.35\t2.233597883597884e+28\n6.36\t2.22989417989418e+28\n6.37\t2.225396825396825e+28\n6.38\t2.220634920634921e+28\n6.39\t2.2164021164021166e+28\n6.4\t2.2121693121693127e+28\n6.41\t2.2074074074074075e+28\n6.42\t2.201851851851852e+28\n6.43\t2.1489417989417992e+28\n6.44\t2.145767195767196e+28\n6.45\t2.1423280423280423e+28\n6.46\t2.1386243386243387e+28\n6.47\t2.135449735449736e+28\n6.48\t2.133862433862434e+28\n6.49\t2.132010582010582e+28\n6.5\t2.1304232804232808e+28\n6.51\t2.12989417989418e+28\n6.52\t2.12989417989418e+28\n6.53\t2.12962962962963e+28\n6.54\t2.1306878306878307e+28\n6.55\t2.1383597883597887e+28\n6.56\t2.1523809523809524e+28\n6.57\t2.1703703703703706e+28\n6.58\t2.175925925925926e+28\n6.59\t2.180687830687831e+28\n6.6\t2.185185185185185e+28\n6.61\t2.188888888888889e+28\n6.62\t2.1925925925925927e+28\n6.63\t2.196825396825397e+28\n6.64\t2.2005291005291006e+28\n6.65\t2.203703703703704e+28\n6.66\t2.2055555555555557e+28\n6.67\t2.2063492063492064e+28\n6.68\t2.206613756613757e+28\n6.69\t2.2052910052910053e+28\n6.7\t2.205820105820106e+28\n6.71\t2.2074074074074075e+28\n6.72\t2.20978835978836e+28\n6.73\t2.2129629629629634e+28\n6.74\t2.2174603174603177e+28\n6.75\t2.2227513227513227e+28\n6.76\t2.2291005291005293e+28\n6.77\t2.2354497354497354e+28\n6.78\t2.2420634920634923e+28\n6.79\t2.248677248677249e+28\n6.8\t2.252380952380953e+28\n6.81\t2.2465608465608466e+28\n6.82\t2.234920634920635e+28\n6.83\t2.232804232804233e+28\n6.84\t2.2330687830687832e+28\n6.85\t2.2391534391534394e+28\n6.86\t2.2552910052910053e+28\n6.87\t2.2751322751322753e+28\n6.88\t2.300793650793651e+28\n6.89\t2.4063492063492064e+28\n6.9\t2.3095238095238097e+28\n6.91\t2.2420634920634923e+28\n6.92\t2.202910052910053e+28\n6.93\t2.1955026455026455e+28\n6.94\t2.1944444444444445e+28\n6.95\t2.1944444444444445e+28\n6.96\t2.194708994708995e+28\n6.97\t2.1949735449735452e+28\n6.98\t2.195238095238095e+28\n6.99\t2.195238095238095e+28\n7\t2.1955026455026455e+28\n7.01\t2.196031746031746e+28\n7.02\t2.196825396825397e+28\n7.03\t2.1984126984126984e+28\n7.04\t2.2005291005291006e+28\n7.05\t2.203174603174603e+28\n7.06\t2.206613756613757e+28\n7.07\t2.210846560846561e+28\n7.08\t2.215608465608466e+28\n7.09\t2.220634920634921e+28\n7.1\t2.2301587301587304e+28\n7.11\t2.23941798941799e+28\n7.12\t2.2642857142857144e+28\n7.13\t2.2862433862433865e+28\n7.14\t2.2965608465608466e+28\n7.15\t2.3039682539682543e+28\n7.16\t2.307936507936508e+28\n7.17\t2.3089947089947093e+28\n7.18\t2.3082010582010586e+28\n7.19\t2.307936507936508e+28\n7.2\t2.3060846560846565e+28\n7.21\t2.3031746031746036e+28\n7.22\t2.303703703703704e+28\n7.23\t2.3031746031746036e+28\n7.24\t2.297089947089947e+28\n7.25\t2.284656084656085e+28\n7.26\t2.26957671957672e+28\n7.27\t2.2642857142857144e+28\n7.28\t2.2603174603174604e+28\n7.29\t2.257142857142857e+28\n7.3\t2.2544973544973546e+28\n7.31\t2.2542328042328042e+28\n7.32\t2.250793650793651e+28\n7.33\t2.2470899470899474e+28\n7.34\t2.2433862433862434e+28\n7.35\t2.2402116402116405e+28\n7.36\t2.2373015873015876e+28\n7.37\t2.2346560846560847e+28\n7.38\t2.2325396825396825e+28\n7.39\t2.231481481481482e+28\n7.4\t2.2343915343915347e+28\n7.41\t2.234920634920635e+28\n7.42\t2.2375661375661376e+28\n7.43\t2.241534391534392e+28\n7.44\t2.2455026455026455e+28\n7.45\t2.24973544973545e+28\n7.46\t2.253703703703704e+28\n7.47\t2.257671957671958e+28\n7.48\t2.2613756613756615e+28\n7.49\t2.2653439153439155e+28\n7.5\t2.268783068783069e+28\n7.51\t2.2714285714285717e+28\n7.52\t2.2738095238095242e+28\n7.53\t2.2764550264550267e+28\n7.54\t2.2791005291005292e+28\n7.55\t2.281746031746032e+28\n7.56\t2.2843915343915347e+28\n7.57\t2.2886243386243386e+28\n7.58\t2.2960317460317463e+28\n7.59\t2.3044973544973546e+28\n7.6\t2.312169312169312e+28\n7.61\t2.31957671957672e+28\n7.62\t2.3251322751322752e+28\n7.63\t2.3341269841269843e+28\n7.64\t2.348677248677249e+28\n7.65\t2.3687830687830687e+28\n7.66\t2.375661375661376e+28\n7.67\t2.373544973544974e+28\n7.68\t2.3743386243386245e+28\n7.69\t2.3767195767195766e+28\n7.7\t2.3833333333333336e+28\n7.71\t2.3891534391534394e+28\n7.72\t2.394973544973545e+28\n7.73\t2.3984126984126984e+28\n7.74\t2.3931216931216934e+28\n7.75\t2.378571428571429e+28\n7.76\t2.3619047619047622e+28\n7.77\t2.348677248677249e+28\n7.78\t2.334920634920635e+28\n7.79\t2.324074074074074e+28\n7.8\t2.314814814814815e+28\n7.81\t2.3066137566137568e+28\n7.82\t2.298941798941799e+28\n7.83\t2.2933862433862433e+28\n7.84\t2.288888888888889e+28\n7.85\t2.284656084656085e+28\n7.86\t2.2801587301587303e+28\n7.87\t2.2753968253968256e+28\n7.88\t2.2708994708994713e+28\n7.89\t2.2664021164021166e+28\n7.9\t2.261640211640212e+28\n7.91\t2.257671957671958e+28\n7.92\t2.2539682539682543e+28\n7.93\t2.2505291005291006e+28\n7.94\t2.2470899470899474e+28\n7.95\t2.2391534391534394e+28\n7.96\t2.232804232804233e+28\n7.97\t2.228571428571429e+28\n7.98\t2.2272486772486775e+28\n7.99\t2.227777777777778e+28\n8\t2.227777777777778e+28\n8.01\t2.2272486772486775e+28\n8.02\t2.226984126984127e+28\n8.03\t2.226984126984127e+28\n8.04\t2.226984126984127e+28\n8.05\t2.2272486772486775e+28\n8.06\t2.227777777777778e+28\n8.07\t2.2293650793650796e+28\n8.08\t2.230952380952381e+28\n8.09\t2.2325396825396825e+28\n8.1\t2.2341269841269843e+28\n8.11\t2.235978835978836e+28\n8.12\t2.2380952380952383e+28\n8.13\t2.241269841269841e+28\n8.14\t2.244708994708995e+28\n8.15\t2.248677248677249e+28\n8.16\t2.2542328042328042e+28\n8.17\t2.2613756613756615e+28\n8.18\t2.2693121693121695e+28\n8.19\t2.276719576719577e+28\n8.2\t2.2801587301587303e+28\n8.21\t2.2925925925925926e+28\n8.22\t2.3063492063492064e+28\n8.23\t2.3214285714285716e+28\n8.24\t2.3365079365079364e+28\n8.25\t2.3521164021164025e+28\n8.26\t2.3687830687830687e+28\n8.27\t2.3873015873015876e+28\n8.28\t2.4050264550264553e+28\n8.29\t2.4142857142857143e+28\n8.3\t2.414021164021164e+28\n8.31\t2.405820105820106e+28\n8.32\t2.4074074074074075e+28\n8.33\t2.4132275132275133e+28\n8.34\t2.4211640211640212e+28\n8.35\t2.429100529100529e+28\n8.36\t2.437037037037037e+28\n8.37\t2.4455026455026455e+28\n8.38\t2.453703703703704e+28\n8.39\t2.462169312169312e+28\n8.4\t2.47010582010582e+28\n8.41\t2.476719576719577e+28\n8.42\t2.4843915343915347e+28\n8.43\t2.4915343915343915e+28\n8.44\t2.4986772486772487e+28\n8.45\t2.505555555555556e+28\n8.46\t2.5113756613756614e+28\n8.47\t2.516666666666667e+28\n8.48\t2.521164021164021e+28\n8.49\t2.5238095238095237e+28\n8.5\t2.5238095238095237e+28\n8.51\t2.524074074074074e+28\n8.52\t2.525132275132275e+28\n8.53\t2.528571428571429e+28\n8.54\t2.5322751322751325e+28\n8.55\t2.5367724867724868e+28\n8.56\t2.541798941798942e+28\n8.57\t2.5470899470899473e+28\n8.58\t2.5526455026455027e+28\n8.59\t2.558201058201058e+28\n8.6\t2.564021164021164e+28\n8.61\t2.5703703703703705e+28\n8.62\t2.5772486772486774e+28\n8.63\t2.5841269841269842e+28\n8.64\t2.5923280423280426e+28\n8.65\t2.6010582010582013e+28\n8.66\t2.60978835978836e+28\n8.67\t2.619047619047619e+28\n8.68\t2.628571428571429e+28\n8.69\t2.6383597883597886e+28\n8.7\t2.648148148148148e+28\n8.71\t2.6587301587301584e+28\n8.72\t2.666666666666667e+28\n8.73\t2.6772486772486773e+28\n8.74\t2.6904761904761903e+28\n8.75\t2.7037037037037038e+28\n8.76\t2.7169312169312168e+28\n8.77\t2.738095238095238e+28\n8.78\t2.756613756613757e+28\n8.79\t2.777777777777778e+28\n8.8\t2.798941798941799e+28\n8.81\t2.825396825396826e+28\n8.82\t2.8518518518518524e+28\n8.83\t2.8703703703703704e+28\n8.84\t2.880952380952381e+28\n8.85\t2.8994708994709e+28\n8.86\t2.8994708994709e+28\n8.87\t2.891534391534392e+28\n8.88\t2.8862433862433864e+28\n8.89\t2.8703703703703704e+28\n8.9\t2.8544973544973544e+28\n8.91\t2.830687830687831e+28\n8.92\t2.822751322751323e+28\n8.93\t2.8174603174603175e+28\n8.94\t2.812169312169312e+28\n8.95\t2.8174603174603175e+28\n8.96\t2.8359788359788364e+28\n8.97\t2.8333333333333335e+28\n8.98\t2.8174603174603175e+28\n8.99\t2.798941798941799e+28\n9\t2.7804232804232806e+28\n9.01\t2.761904761904762e+28\n9.02\t2.7433862433862432e+28\n9.03\t2.7275132275132273e+28\n9.04\t2.7089947089947092e+28\n9.05\t2.6904761904761903e+28\n9.06\t2.6719576719576723e+28\n9.07\t2.6534391534391534e+28\n9.08\t2.637830687830688e+28\n9.09\t2.6208994708994712e+28\n9.1\t2.603703703703704e+28\n9.11\t2.594973544973545e+28\n9.12\t2.588624338624339e+28\n9.13\t2.5761904761904763e+28\n9.14\t2.5589947089947093e+28\n9.15\t2.5367724867724868e+28\n9.16\t2.5105820105820107e+28\n9.17\t2.4793650793650796e+28\n9.18\t2.4470899470899473e+28\n9.19\t2.42010582010582e+28\n9.2\t2.397883597883598e+28\n9.21\t2.3764550264550267e+28\n9.22\t2.3552910052910053e+28\n9.23\t2.3346560846560846e+28\n9.24\t2.3145502645502648e+28\n9.25\t2.2944444444444444e+28\n9.26\t2.2751322751322753e+28\n9.27\t2.2568783068783067e+28\n9.28\t2.2420634920634923e+28\n9.29\t2.2317460317460318e+28\n9.3\t2.217724867724868e+28\n9.31\t2.205820105820106e+28\n9.32\t2.195238095238095e+28\n9.33\t2.196825396825397e+28\n9.34\t2.2002645502645502e+28\n9.35\t2.196825396825397e+28\n9.36\t2.188888888888889e+28\n9.37\t2.178042328042328e+28\n9.38\t2.1664021164021166e+28\n9.39\t2.1584656084656086e+28\n9.4\t2.152645502645503e+28\n9.41\t2.1465608465608467e+28\n9.42\t2.1055555555555557e+28\n9.43\t2.0973544973544974e+28\n9.44\t2.0965608465608467e+28\n9.45\t2.170899470899471e+28\n9.46\t2.252910052910053e+28\n9.47\t2.2542328042328042e+28\n9.48\t2.2246031746031745e+28\n9.49\t2.245767195767196e+28\n9.5\t2.2452380952380956e+28\n9.51\t2.2134920634920637e+28\n9.52\t2.157671957671958e+28\n9.53\t2.144708994708995e+28\n9.54\t2.1365079365079365e+28\n9.55\t2.1333333333333337e+28\n9.56\t2.1351851851851855e+28\n9.57\t2.1425925925925927e+28\n9.58\t2.149206349206349e+28\n9.59\t2.1425925925925927e+28\n9.6\t2.132010582010582e+28\n9.61\t2.1460317460317463e+28\n9.62\t2.1187830687830687e+28\n9.63\t2.096825396825397e+28\n9.64\t2.0835978835978836e+28\n9.65\t2.0796296296296296e+28\n9.66\t2.078306878306878e+28\n9.67\t2.078835978835979e+28\n9.68\t2.080952380952381e+28\n9.69\t2.0843915343915348e+28\n9.7\t2.089153439153439e+28\n9.71\t2.0955026455026456e+28\n9.72\t2.103703703703704e+28\n9.73\t2.1132275132275133e+28\n9.74\t2.1243386243386246e+28\n9.75\t2.1370370370370373e+28\n9.76\t2.1394179894179894e+28\n9.77\t2.135978835978836e+28\n9.78\t2.1264550264550263e+28\n9.79\t2.1153439153439155e+28\n9.8\t2.09973544973545e+28\n9.81\t2.0902116402116406e+28\n9.82\t2.0835978835978836e+28\n9.83\t2.081216931216931e+28\n9.84\t2.081216931216931e+28\n9.85\t2.0825396825396825e+28\n9.86\t2.0854497354497354e+28\n9.87\t2.08968253968254e+28\n9.88\t2.0944444444444445e+28\n9.89\t2.1023809523809525e+28\n9.9\t2.11984126984127e+28\n9.91\t2.1412698412698416e+28\n9.92\t2.16957671957672e+28\n9.93\t2.2044973544973546e+28\n9.94\t2.235978835978836e+28\n9.95\t2.257671957671958e+28\n9.96\t2.2822751322751325e+28\n9.97\t2.30978835978836e+28\n9.98\t2.3574074074074075e+28\n9.99\t2.416666666666667e+28\n10\t2.4640211640211644e+28\n10.01\t2.5082010582010586e+28\n10.02\t2.5396825396825397e+28\n10.03\t2.571164021164021e+28\n10.04\t2.6031746031746035e+28\n10.05\t2.6354497354497357e+28\n10.06\t2.666666666666667e+28\n10.07\t2.701058201058201e+28\n10.08\t2.7328042328042327e+28\n10.09\t2.7645502645502646e+28\n10.1\t2.791005291005291e+28\n10.11\t2.8174603174603175e+28\n10.12\t2.8359788359788364e+28\n10.13\t2.8518518518518524e+28\n10.14\t2.8333333333333335e+28\n10.15\t2.843915343915344e+28\n10.16\t2.8518518518518524e+28\n10.17\t2.867724867724868e+28\n10.18\t2.8862433862433864e+28\n10.19\t2.9100529100529103e+28\n10.2\t2.9312169312169317e+28\n10.21\t2.9497354497354497e+28\n10.22\t2.9656084656084657e+28\n10.23\t2.986772486772487e+28\n10.24\t3.007936507936508e+28\n10.25\t3.0317460317460316e+28\n10.26\t3.058201058201058e+28\n10.27\t3.0978835978835983e+28\n10.28\t3.1746031746031747e+28\n10.29\t3.1481481481481483e+28\n10.3\t3.1031746031746033e+28\n10.31\t3.1005291005291004e+28\n10.32\t3.08994708994709e+28\n10.33\t3.0476190476190475e+28\n10.34\t2.984126984126984e+28\n10.35\t2.933862433862434e+28\n10.36\t2.9021164021164023e+28\n10.37\t2.8703703703703704e+28\n10.38\t2.8412698412698414e+28\n10.39\t2.8201058201058205e+28\n10.4\t2.798941798941799e+28\n10.41\t2.7830687830687835e+28\n10.42\t2.7645502645502646e+28\n10.43\t2.7328042328042327e+28\n10.44\t2.6904761904761903e+28\n10.45\t2.648148148148148e+28\n10.46\t2.6026455026455027e+28\n10.47\t2.564814814814815e+28\n10.48\t2.505820105820106e+28\n10.49\t2.4560846560846564e+28\n10.5\t2.4171957671957672e+28\n10.51\t2.3875661375661375e+28\n10.52\t2.358730158730159e+28\n10.53\t2.3291005291005292e+28\n10.54\t2.298941798941799e+28\n10.55\t2.2685185185185188e+28\n10.56\t2.2380952380952383e+28\n10.57\t2.210582010582011e+28\n10.58\t2.192857142857143e+28\n10.59\t2.1846560846560847e+28\n10.6\t2.187301587301587e+28\n10.61\t2.1896825396825398e+28\n10.62\t2.1891534391534394e+28\n10.63\t2.201058201058201e+28\n10.64\t2.188095238095238e+28\n10.65\t2.145238095238095e+28\n10.66\t2.095767195767196e+28'
num_na_bcc='1'
vol_na_bcc='3.7800e-29'
button_na_bcc = Button(
    description='Na bcc',
    disabled=False,
    button_style='', # 'success', 'info', 'warning', 'danger' or ''
    tooltip='Na bcc',
    icon='' # (FontAwesome names without the `fa-` prefix)
)

DOS_pt_fcc='-10.683\t0\n-10.6694\t0\n-10.65579\t0\n-10.64218\t0\n-10.62858\t0\n-10.61497\t0\n-10.60137\t0\n-10.58776\t0\n-10.57415\t0\n-10.56055\t0\n-10.54694\t4.610004958992666e+21\n-10.53334\t7.601603921743227e+22\n-10.51973\t4.563904909402739e+23\n-10.50613\t1.801138745999624e+24\n-10.49252\t5.421463916987269e+24\n-10.47891\t1.335881351904181e+25\n-10.46531\t2.748798829229487e+25\n-10.4517\t4.8013986329603765e+25\n-10.4381\t7.2613267046424315e+25\n-10.42449\t9.754603748368263e+25\n-10.41089\t1.2005531850547731e+26\n-10.39728\t1.397115949689269e+26\n-10.38367\t1.5757869908222788e+26\n-10.37007\t1.7452546965233245e+26\n-10.35646\t1.9043528336229942e+26\n-10.34286\t2.0464155311210073e+26\n-10.32925\t2.1675988295632595e+26\n-10.31564\t2.271514226451668e+26\n-10.30204\t2.3668452055951603e+26\n-10.28843\t2.4628019683905333e+26\n-10.27483\t2.5643152584396708e+26\n-10.26122\t2.671633231328663e+26\n-10.24762\t2.7822409822245623e+26\n-10.23401\t2.8924622773856012e+26\n-10.2204\t2.9982118677364175e+26\n-10.2068\t3.0959488771276565e+26\n-10.19319\t3.184188295451252e+26\n-10.17959\t3.2642199432436025e+26\n-10.16598\t3.3390226683899126e+26\n-10.15238\t3.4115507974724134e+26\n-10.13877\t3.483855292271797e+26\n-10.12516\t3.5572877670079554e+26\n-10.11156\t3.6329212738990034e+26\n-10.09795\t3.711581690429083e+26\n-10.08435\t3.793525999853356e+26\n-10.07074\t3.8783294932043235e+26\n-10.05713\t3.9649161757075145e+26\n-10.04353\t4.051620560464977e+26\n-10.02992\t4.13621611316673e+26\n-10.01632\t4.216234029029416e+26\n-10.00271\t4.289868559302075e+26\n-9.98911\t4.357049082632144e+26\n-9.9755\t4.4197019925812115e+26\n-9.96189\t4.4807178603437766e+26\n-9.94829\t4.542404630955693e+26\n-9.93468\t4.6057107884159705e+26\n-9.92108\t4.670535304956359e+26\n-9.90747\t4.736477012060214e+26\n-9.89387\t4.803334835043154e+26\n-9.88026\t4.871194108039526e+26\n-9.86665\t4.94029415896635e+26\n-9.85305\t5.010848813585554e+26\n-9.83944\t5.0828727846789226e+26\n-9.82584\t5.156102223026462e+26\n-9.81223\t5.2300035450754705e+26\n-9.79862\t5.303707715848574e+26\n-9.78502\t5.375997497866174e+26\n-9.77141\t5.445553645028303e+26\n-9.75781\t5.5115100649139414e+26\n-9.7442\t5.573919723537513e+26\n-9.7306\t5.6336712729187724e+26\n-9.71699\t5.6919682186076504e+26\n-9.70338\t5.749889497934977e+26\n-9.68978\t5.8082639309412515e+26\n-9.67617\t5.867718282130473e+26\n-9.66257\t5.928630179568431e+26\n-9.64896\t5.9910584743822615e+26\n-9.63535\t6.0547765897324924e+26\n-9.62175\t6.119430438004186e+26\n-9.60814\t6.1846982997023326e+26\n-9.59454\t6.250393812924335e+26\n-9.58093\t6.316475781881198e+26\n-9.56733\t6.383038368376338e+26\n-9.55372\t6.450228700227596e+26\n-9.54011\t6.51816055628077e+26\n-9.52651\t6.586788817338387e+26\n-9.5129\t6.65578882134908e+26\n-9.4993\t6.724475933533833e+26\n-9.48569\t6.791906574154229e+26\n-9.47208\t6.857232306127395e+26\n-9.45848\t6.920195165346044e+26\n-9.44487\t6.981317945989575e+26\n-9.43127\t7.041580519324797e+26\n-9.41766\t7.101833284138832e+26\n-9.40406\t7.162469562131369e+26\n-9.39045\t7.223532510795643e+26\n-9.37684\t7.284998589680799e+26\n-9.36324\t7.346981577632635e+26\n-9.34963\t7.40970903234274e+26\n-9.33603\t7.473415377467544e+26\n-9.32242\t7.538226162078267e+26\n-9.30882\t7.604100190385914e+26\n-9.29521\t7.670873660086627e+26\n-9.2816\t7.738361190129923e+26\n-9.268\t7.806420556958557e+26\n-9.25439\t7.874973292403015e+26\n-9.24079\t7.943989970899731e+26\n-9.22718\t8.013480400969891e+26\n-9.21358\t8.083444582613497e+26\n-9.19997\t8.153857013675455e+26\n-9.18636\t8.224588221676068e+26\n-9.17276\t8.295298831782183e+26\n-9.15915\t8.365439566807198e+26\n-9.14555\t8.43446801552934e+26\n-9.13194\t8.502157601109135e+26\n-9.11833\t8.568757459984795e+26\n-9.10473\t8.634839428941658e+26\n-9.09112\t8.701009674589224e+26\n-9.07752\t8.76774194850094e+26\n-9.06391\t8.835318736087059e+26\n-9.05031\t8.903854797045496e+26\n-9.0367\t8.973312858995732e+26\n-9.02309\t9.043577181387731e+26\n-9.00949\t9.114528100262986e+26\n-8.99588\t9.186109707050714e+26\n-8.98228\t9.258350446462368e+26\n-8.96867\t9.331357231378908e+26\n-8.95506\t9.405257572575799e+26\n-8.94146\t9.480127976518315e+26\n-8.92785\t9.555977270875529e+26\n-8.91425\t9.632757393893612e+26\n-8.90064\t9.710394781663643e+26\n-8.88704\t9.788812927720345e+26\n-8.87343\t9.867931402189968e+26\n-8.85982\t9.947680564572065e+26\n-8.84622\t1.0027987831809837e+27\n-8.83261\t1.0108761003804101e+27\n-8.81901\t1.0189823527173452e+27\n-8.8054\t1.0270909590993658e+27\n-8.7918\t1.0351714150255728e+27\n-8.77819\t1.0432080268620637e+27\n-8.76458\t1.0512148207941387e+27\n-8.75098\t1.0592315213326151e+27\n-8.73737\t1.0673026591636923e+27\n-8.72377\t1.0754580521917859e+27\n-8.71016\t1.0837131978803752e+27\n-8.69655\t1.0920791798584043e+27\n-8.68295\t1.1005686511182072e+27\n-8.66934\t1.1091923029478803e+27\n-8.65574\t1.1179511161995425e+27\n-8.64213\t1.1268360670336997e+27\n-8.62853\t1.1358339139467465e+27\n-8.61492\t1.1449343579914336e+27\n-8.60131\t1.1541343585261926e+27\n-8.58771\t1.1634396044933134e+27\n-8.5741\t1.1728635335668252e+27\n-8.5605\t1.1824209566137241e+27\n-8.54689\t1.1921237419446491e+27\n-8.53329\t1.2019754206272283e+27\n-8.51968\t1.2119712845712908e+27\n-8.50607\t1.2221026041929783e+27\n-8.49247\t1.2323601594823727e+27\n-8.47886\t1.2427348285147677e+27\n-8.46526\t1.25321915681406e+27\n-8.45165\t1.2638061803302043e+27\n-8.43804\t1.2744862867124358e+27\n-8.42444\t1.285246528712784e+27\n-8.41083\t1.2960739590832796e+27\n-8.39723\t1.3069661256936245e+27\n-8.38362\t1.3179436264383168e+27\n-8.37002\t1.329049324554954e+27\n-8.35641\t1.3403332435016016e+27\n-8.3428\t1.3518345192778052e+27\n-8.3292\t1.3635723765850956e+27\n-8.31559\t1.37555338713267e+27\n-8.30199\t1.387785103481844e+27\n-8.28838\t1.4002787073467738e+27\n-8.27477\t1.413044988100767e+27\n-8.26117\t1.42608580936285e+27\n-8.24756\t1.439392931975224e+27\n-8.23396\t1.4529546837976734e+27\n-8.22035\t1.4667646892914255e+27\n-8.20675\t1.4808294220804645e+27\n-8.19314\t1.495166929843779e+27\n-8.17953\t1.5098029109068858e+27\n-8.16593\t1.5247557072044082e+27\n-8.15232\t1.540029340230034e+27\n-8.13872\t1.555614982314693e+27\n-8.12511\t1.5714960570575752e+27\n-8.11151\t1.5876579497621084e+27\n-8.0979\t1.604089380628925e+27\n-8.08429\t1.6207882898685747e+27\n-8.07069\t1.6377589932303812e+27\n-8.05708\t1.6550162034961287e+27\n-8.04348\t1.6725816955828574e+27\n-8.02987\t1.6904827371794733e+27\n-8.01626\t1.7087611125862437e+27\n-8.00266\t1.727489306774757e+27\n-7.98905\t1.7467838449767438e+27\n-7.97545\t1.7667942090551288e+27\n-7.96184\t1.787663995760124e+27\n-7.94824\t1.8094949194564637e+27\n-7.93463\t1.832338671050815e+27\n-7.92102\t1.8562073150242414e+27\n-7.90742\t1.8810951624344524e+27\n-7.89381\t1.906998093702549e+27\n-7.88021\t1.933921601600397e+27\n-7.8666\t1.9618770640125762e+27\n-7.85299\t1.990867423495443e+27\n-7.83939\t2.0208801251418755e+27\n-7.82578\t2.0518920208418666e+27\n-7.81218\t2.083889182495328e+27\n-7.79857\t2.1168750430846752e+27\n-7.78497\t2.1508704947600414e+27\n-7.77136\t2.185892604348297e+27\n-7.75775\t2.2219628525108457e+27\n-7.74415\t2.2591840325497524e+27\n-7.73054\t2.297901502496094e+27\n-7.71694\t2.338997735001276e+27\n-7.70333\t2.3841475350583789e+27\n-7.68972\t2.4356434483249885e+27\n-7.67612\t2.4955878332328296e+27\n-7.66251\t2.564887683736281e+27\n-7.64891\t2.6432314812023685e+27\n-7.6353\t2.731098666146828e+27\n-7.6217\t2.8336456762441107e+27\n-7.60809\t2.96532909470477e+27\n-7.59448\t3.151055503214488e+27\n-7.58088\t3.420665561958037e+27\n-7.56727\t3.783414003018412e+27\n-7.55367\t4.2022789555072734e+27\n-7.54006\t4.59672883130725e+27\n-7.52646\t4.888308604321968e+27\n-7.51285\t5.053092446899466e+27\n-7.49924\t5.126700788420549e+27\n-7.48564\t5.160608355746058e+27\n-7.47203\t5.181737577836513e+27\n-7.45843\t5.190968965639078e+27\n-7.44482\t5.185185763460628e+27\n-7.43122\t5.171627444620594e+27\n-7.41761\t5.164459279250208e+27\n-7.404\t5.172643018904539e+27\n-7.3904\t5.197643664308428e+27\n-7.37679\t5.234892406291877e+27\n-7.36319\t5.280566373721339e+27\n-7.34958\t5.336837859784617e+27\n-7.33597\t5.41267008731496e+27\n-7.32237\t5.518367692503474e+27\n-7.30876\t5.656706584931951e+27\n-7.29516\t5.818495101308646e+27\n-7.28155\t5.988154563598944e+27\n-7.26795\t6.154103364238101e+27\n-7.25434\t6.312950010854475e+27\n-7.24073\t6.46546280491283e+27\n-7.22713\t6.611895296685908e+27\n-7.21352\t6.751821502098459e+27\n-7.19992\t6.885930567849242e+27\n-7.18631\t7.015539091737507e+27\n-7.1727\t7.140865803785774e+27\n-7.1591\t7.261130141877797e+27\n-7.14549\t7.377120809202409e+27\n-7.13189\t7.492671858607315e+27\n-7.11828\t7.613559430135709e+27\n-7.10468\t7.745080909911531e+27\n-7.09107\t7.890819546895675e+27\n-7.07746\t8.05344875162351e+27\n-7.06386\t8.235977680310713e+27\n-7.05025\t8.440547925473767e+27\n-7.03665\t8.664194174986709e+27\n-7.02304\t8.894485991861069e+27\n-7.00944\t9.111089723160061e+27\n-6.99583\t9.294852956153731e+27\n-6.98222\t9.437041006552545e+27\n-6.96862\t9.540312375939661e+27\n-6.95501\t9.612152143005093e+27\n-6.94141\t9.660051761977628e+27\n-6.9278\t9.692626939784778e+27\n-6.91419\t9.722187762860016e+27\n-6.90059\t9.761895501105635e+27\n-6.88698\t9.823092630339778e+27\n-6.87338\t9.916583628993362e+27\n-6.85977\t1.0053825144071177e+28\n-6.84617\t1.024187832997743e+28\n-6.83256\t1.0474576471355173e+28\n-6.81895\t1.0731702930925404e+28\n-6.80535\t1.098961279708303e+28\n-6.79174\t1.1232150356491865e+28\n-6.77814\t1.1452634338773362e+28\n-6.76453\t1.1650212383436167e+28\n-6.75093\t1.18274708994327e+28\n-6.73732\t1.1989972102959012e+28\n-6.72371\t1.2145769868848891e+28\n-6.71011\t1.2301796859878962e+28\n-6.6965\t1.246147654419995e+28\n-6.6829\t1.26245636106969e+28\n-6.66929\t1.2788580132661757e+28\n-6.65568\t1.295042190930851e+28\n-6.64208\t1.3107142264701458e+28\n-6.62847\t1.3256325458156878e+28\n-6.61487\t1.3396931001747002e+28\n-6.60126\t1.3529552703344633e+28\n-6.58766\t1.3654903936695874e+28\n-6.57405\t1.3771599150097516e+28\n-6.56044\t1.3875421856460686e+28\n-6.54684\t1.3960855547298069e+28\n-6.53323\t1.4023862642947285e+28\n-6.51963\t1.4063256410429633e+28\n-6.50602\t1.4080403667172845e+28\n-6.49241\t1.4077538990474286e+28\n-6.47881\t1.4056566998978496e+28\n-6.4652\t1.40194918678201e+28\n-6.4516\t1.3969968742420302e+28\n-6.43799\t1.3913341207037851e+28\n-6.42439\t1.3854372671903136e+28\n-6.41078\t1.3794593952918185e+28\n-6.39717\t1.3732570161518202e+28\n-6.38357\t1.3666816483765547e+28\n-6.36996\t1.3598086998769257e+28\n-6.35636\t1.3528962230369036e+28\n-6.34275\t1.3461761011059257e+28\n-6.32915\t1.3396736891112664e+28\n-6.31554\t1.3332126690760265e+28\n-6.30193\t1.3265414131976137e+28\n-6.28833\t1.3195237105422723e+28\n-6.27472\t1.312271917720226e+28\n-6.26112\t1.3051192792388826e+28\n-6.24751\t1.2984277981897776e+28\n-6.2339\t1.2923723997398018e+28\n-6.2203\t1.2868484367763857e+28\n-6.20669\t1.281546038498116e+28\n-6.19309\t1.2761174830203088e+28\n-6.17948\t1.27034130374303e+28\n-6.16588\t1.2642275642090199e+28\n-6.15227\t1.2580127969067595e+28\n-6.13866\t1.2520291870233686e+28\n-6.12506\t1.2465281367654508e+28\n-6.11145\t1.2415781586535143e+28\n-6.09785\t1.23708747435479e+28\n-6.08424\t1.2329027864916097e+28\n-6.07064\t1.228889276940226e+28\n-6.05703\t1.2249654565065975e+28\n-6.04342\t1.2211213695417174e+28\n-6.02982\t1.2174350232146042e+28\n-6.01621\t1.2140699942331328e+28\n-6.00261\t1.2112427076173464e+28\n-5.989\t1.209152168453655e+28\n-5.97539\t1.207925495176673e+28\n-5.96179\t1.2076365655679984e+28\n-5.94818\t1.2084013850077377e+28\n-5.93458\t1.2105225561831034e+28\n-5.92097\t1.2144232285067248e+28\n-5.90737\t1.2203020637667712e+28\n-5.89376\t1.22754859922146e+28\n-5.88015\t1.2344883143248252e+28\n-5.86655\t1.2388388054301903e+28\n-5.85294\t1.2387439766473313e+28\n-5.83934\t1.233541792030053e+28\n-5.82573\t1.2236278096208795e+28\n-5.81213\t1.2095457451748988e+28\n-5.79852\t1.1913825904665397e+28\n-5.78491\t1.1691903698921907e+28\n-5.77131\t1.144003548947607e+28\n-5.7577\t1.1181185476562446e+28\n-5.7441\t1.0941036782489278e+28\n-5.73049\t1.0733268567077648e+28\n-5.71688\t1.0554098370301312e+28\n-5.70328\t1.0389711086235502e+28\n-5.68967\t1.0228486755997616e+28\n-5.67607\t1.006755589671372e+28\n-5.66246\t9.91022280300207e+27\n-5.64886\t9.757725310236772e+27\n-5.63525\t9.603287397724586e+27\n-5.62164\t9.434825261615871e+27\n-5.60804\t9.245019881484351e+27\n-5.59443\t9.039476827189738e+27\n-5.58083\t8.834628902791813e+27\n-5.56722\t8.644841079913222e+27\n-5.55362\t8.471409554629138e+27\n-5.54001\t8.305239866092797e+27\n-5.5264\t8.140160394686652e+27\n-5.5128\t7.982714502981329e+27\n-5.49919\t7.848047724715717e+27\n-5.48559\t7.748161962587529e+27\n-5.47198\t7.685133190106486e+27\n-5.45837\t7.654175143187825e+27\n-5.44477\t7.650364434620551e+27\n-5.43116\t7.674095857382539e+27\n-5.41756\t7.735084261285774e+27\n-5.40395\t7.855578413029263e+27\n-5.39035\t8.069244394146833e+27\n-5.37674\t8.410175643440534e+27\n-5.36313\t8.898355061129418e+27\n-5.34953\t9.526831936757871e+27\n-5.33592\t1.025450758569041e+28\n-5.32232\t1.100257877932844e+28\n-5.30871\t1.1667242722606806e+28\n-5.2951\t1.2158207367972617e+28\n-5.2815\t1.244496419303332e+28\n-5.26789\t1.257342453143116e+28\n-5.25429\t1.2633025520012163e+28\n-5.24068\t1.270045253147972e+28\n-5.22708\t1.2801549645974794e+28\n-5.21347\t1.291213542578323e+28\n-5.19986\t1.299012081988506e+28\n-5.18626\t1.301037139464737e+28\n-5.17265\t1.2979156560643972e+28\n-5.15905\t1.292070611159848e+28\n-5.14544\t1.28559649674882e+28\n-5.13184\t1.2790678960025854e+28\n-5.11823\t1.271883919296042e+28\n-5.10462\t1.2633948109515232e+28\n-5.09102\t1.25365938286208e+28\n-5.07741\t1.2433814062315697e+28\n-5.06381\t1.2331444782622363e+28\n-5.0502\t1.2229755920043937e+28\n-5.03659\t1.2129220049131318e+28\n-5.02299\t1.2039774673127493e+28\n-5.00938\t1.1980533755359352e+28\n-4.99578\t1.196757591418653e+28\n-4.98217\t1.2005958226963831e+28\n-4.96857\t1.2090827143151131e+28\n-4.95496\t1.2214727401962834e+28\n-4.94135\t1.2371284053137131e+28\n-4.92775\t1.254827361948265e+28\n-4.91414\t1.272377121167006e+28\n-4.90054\t1.2866405353612564e+28\n-4.88693\t1.2947404023508972e+28\n-4.87332\t1.2955551471634901e+28\n-4.85972\t1.290343487514743e+28\n-4.84611\t1.2820453216522173e+28\n-4.83251\t1.2738141479894147e+28\n-4.8189\t1.2677173575800197e+28\n-4.8053\t1.2642566758999097e+28\n-4.79169\t1.2630374865245954e+28\n-4.77808\t1.2635346510381197e+28\n-4.76448\t1.2655177280436606e+28\n-4.75087\t1.2689912686950496e+28\n-4.73727\t1.2736385264175194e+28\n-4.72366\t1.2785744685356341e+28\n-4.71006\t1.2825409756534785e+28\n-4.69645\t1.2844787961422516e+28\n-4.68284\t1.284212082834071e+28\n-4.66924\t1.2825987282262413e+28\n-4.65563\t1.2813116050331694e+28\n-4.64203\t1.2823727104724753e+28\n-4.62842\t1.2874460405468891e+28\n-4.61481\t1.2969215526333358e+28\n-4.60121\t1.3094597166100285e+28\n-4.5876\t1.3228540173587333e+28\n-4.574\t1.3356329314880189e+28\n-4.56039\t1.3476967259544312e+28\n-4.54679\t1.3597890534089835e+28\n-4.53318\t1.372327923599202e+28\n-4.51957\t1.3850762057168127e+28\n-4.50597\t1.3973588871420867e+28\n-4.49236\t1.40853894365786e+28\n-4.47876\t1.4182352063221942e+28\n-4.46515\t1.4264117759475356e+28\n-4.45155\t1.4332812129965792e+28\n-4.43794\t1.4392603796198714e+28\n-4.42433\t1.4448664300971209e+28\n-4.41073\t1.4502623624334524e+28\n-4.39712\t1.4545760225417513e+28\n-4.38352\t1.4559274602082617e+28\n-4.36991\t1.452752432090749e+28\n-4.3563\t1.4454794724799762e+28\n-4.3427\t1.4366706848128542e+28\n-4.32909\t1.4292819748435258e+28\n-4.31549\t1.4248283471378549e+28\n-4.30188\t1.4230689534580372e+28\n-4.28828\t1.4229673469870367e+28\n-4.27467\t1.4237092439127565e+28\n-4.26106\t1.4249810560042516e+28\n-4.24746\t1.4268591327904606e+28\n-4.23385\t1.429648068088397e+28\n-4.22025\t1.433852637824028e+28\n-4.20664\t1.4400955850076655e+28\n-4.19304\t1.4488761927934103e+28\n-4.17943\t1.4601786792706695e+28\n-4.16582\t1.4732958696787328e+28\n-4.15222\t1.4872205465937091e+28\n-4.13861\t1.5015502663911996e+28\n-4.12501\t1.5172404182691312e+28\n-4.1114\t1.5364471505894307e+28\n-4.09779\t1.5611755016365818e+28\n-4.08419\t1.590969473260492e+28\n-4.07058\t1.6217165192713283e+28\n-4.05698\t1.6470470448598572e+28\n-4.04337\t1.6616515405699458e+28\n-4.02977\t1.6640629164617406e+28\n-4.01616\t1.6570404174395376e+28\n-4.00255\t1.64579896938964e+28\n-3.98895\t1.635732523327099e+28\n-3.97534\t1.630375521011368e+28\n-3.96174\t1.6306119456061158e+28\n-3.94813\t1.6359224064888035e+28\n-3.93452\t1.6461835418884318e+28\n-3.92092\t1.6619055028005804e+28\n-3.90731\t1.6830870043089732e+28\n-3.89371\t1.708239220790801e+28\n-3.8801\t1.7350199950883015e+28\n-3.8665\t1.7615985961470473e+28\n-3.85289\t1.7871062734367767e+28\n-3.83928\t1.8110760138381015e+28\n-3.82568\t1.8329066923214112e+28\n-3.81207\t1.852019056859348e+28\n-3.79847\t1.8688506557736474e+28\n-3.78486\t1.88587154933838e+28\n-3.77126\t1.907046626265394e+28\n-3.75765\t1.9368540453718545e+28\n-3.74404\t1.9787729577832717e+28\n-3.73044\t2.0320019680843905e+28\n-3.71683\t2.087995814146883e+28\n-3.70323\t2.1313809925823744e+28\n-3.68962\t2.148451350519465e+28\n-3.67601\t2.1372965509457537e+28\n-3.66241\t2.1093258166660827e+28\n-3.6488\t2.080518817678329e+28\n-3.6352\t2.0621126862830684e+28\n-3.62159\t2.05823563287847e+28\n-3.60799\t2.068471393633782e+28\n-3.59438\t2.091710104950865e+28\n-3.58077\t2.1275537468483762e+28\n-3.56717\t2.1771652764496525e+28\n-3.55356\t2.2425219150730844e+28\n-3.53996\t2.321760789140306e+28\n-3.52635\t2.4047324332654297e+28\n-3.51274\t2.470635818476998e+28\n-3.49914\t2.4943195522089627e+28\n-3.48553\t2.4585895616464715e+28\n-3.47193\t2.3646394359245365e+28\n-3.45832\t2.232784260449331e+28\n-3.44472\t2.0917978029388185e+28\n-3.43111\t1.9645221671557916e+28\n-3.4175\t1.859935347566409e+28\n-3.4039\t1.775827523580796e+28\n-3.39029\t1.7057314957953631e+28\n-3.37669\t1.6446976392049367e+28\n-3.36308\t1.5912255443231822e+28\n-3.34947\t1.5453532191697085e+28\n-3.33587\t1.5077155693211022e+28\n-3.32226\t1.4778114578127568e+28\n-3.30866\t1.453634296613841e+28\n-3.29505\t1.43193176645987e+28\n-3.28145\t1.4082514264762368e+28\n-3.26784\t1.3776539309879744e+28\n-3.25423\t1.3364151708613902e+28\n-3.24063\t1.2847355636099463e+28\n-3.22702\t1.228169596315e+28\n-3.21342\t1.1753897083906202e+28\n-3.19981\t1.133648516574633e+28\n-3.18621\t1.106406006142144e+28\n-3.1726\t1.0941179496472582e+28\n-3.15899\t1.095872782364723e+28\n-3.14539\t1.1101578341567172e+28\n-3.13178\t1.1348336899984628e+28\n-3.11818\t1.167334166108234e+28\n-3.10457\t1.2044572118926415e+28\n-3.09096\t1.2414954924369305e+28\n-3.07736\t1.272790452249925e+28\n-3.06375\t1.2940225853446975e+28\n-3.05015\t1.303896931519745e+28\n-3.03654\t1.3035335160011587e+28\n-3.02294\t1.2947943001748327e+28\n-3.00933\t1.2792030672330959e+28\n-2.99572\t1.2580738255255996e+28\n-2.98212\t1.2328654846855266e+28\n-2.96851\t1.2053807037796606e+28\n-2.95491\t1.1779459561403816e+28\n-2.9413\t1.1530256130994702e+28\n-2.92769\t1.1323616287860696e+28\n-2.91409\t1.11636734409162e+28\n-2.90048\t1.1043111414206082e+28\n-2.88688\t1.0950661001565476e+28\n-2.87327\t1.0876880324327095e+28\n-2.85967\t1.0815816492895914e+28\n-2.84606\t1.0764392181833987e+28\n-2.83245\t1.072140643580689e+28\n-2.81885\t1.0687038162241115e+28\n-2.80524\t1.0662260170268227e+28\n-2.79164\t1.0648573948311884e+28\n-2.77803\t1.0646766237856686e+28\n-2.76443\t1.0654526641736484e+28\n-2.75082\t1.066481627089017e+28\n-2.73721\t1.0666079019908084e+28\n-2.72361\t1.0645364305923092e+28\n-2.71\t1.0593179932554204e+28\n-2.6964\t1.050897750538172e+28\n-2.68279\t1.0403890774892879e+28\n-2.66918\t1.0298929201134414e+28\n-2.65558\t1.0215768635082662e+28\n-2.64197\t1.0167052358635904e+28\n-2.62837\t1.0152786060736423e+28\n-2.61476\t1.0164572274053176e+28\n-2.60116\t1.0193896319426905e+28\n-2.58755\t1.023689491461676e+28\n-2.57394\t1.0292326398925381e+28\n-2.56034\t1.0357827507257411e+28\n-2.54673\t1.0428279368574554e+28\n-2.53313\t1.0500855755581305e+28\n-2.51952\t1.0579376694940072e+28\n-2.50592\t1.067313674132988e+28\n-2.49231\t1.0788555081443091e+28\n-2.4787\t1.0925759127969965e+28\n-2.4651\t1.1084394793295556e+28\n-2.45149\t1.1271133735447649e+28\n-2.43789\t1.150128519238379e+28\n-2.42428\t1.1784661706787009e+28\n-2.41067\t1.211019377398386e+28\n-2.39707\t1.244117692683169e+28\n-2.38346\t1.2730672192923248e+28\n-2.36986\t1.2948392035848374e+28\n-2.35625\t1.309259416798821e+28\n-2.34265\t1.3179296492956222e+28\n-2.32904\t1.3224888559233752e+28\n-2.31543\t1.3241233773199315e+28\n-2.30183\t1.3239048336593116e+28\n-2.28822\t1.3228204624077447e+28\n-2.27462\t1.3215847750997896e+28\n-2.26101\t1.3206237558106998e+28\n-2.24741\t1.3207735417377824e+28\n-2.2338\t1.3232330970856594e+28\n-2.22019\t1.328844640334775e+28\n-2.20659\t1.3372144868701525e+28\n-2.19298\t1.346675962962777e+28\n-2.17938\t1.3552334759340703e+28\n-2.16577\t1.3617205670186317e+28\n-2.15216\t1.3663408022652249e+28\n-2.13856\t1.3707278987716685e+28\n-2.12495\t1.3777700344532928e+28\n-2.11135\t1.3917006847576734e+28\n-2.09774\t1.4171466174065159e+28\n-2.08414\t1.4581151527743336e+28\n-2.07053\t1.5154155429018533e+28\n-2.05692\t1.5851639468878146e+28\n-2.04332\t1.6568967127955926e+28\n-2.02971\t1.7142773170093989e+28\n-2.01611\t1.740237736020186e+28\n-2.0025\t1.7256455107701051e+28\n-1.9889\t1.6754280793893995e+28\n-1.97529\t1.6058452432411145e+28\n-1.96168\t1.5343879496509392e+28\n-1.94808\t1.4713809520869368e+28\n-1.93447\t1.4190315895831209e+28\n-1.92087\t1.375703359421655e+28\n-1.90726\t1.3390494159716494e+28\n-1.89365\t1.3075048194858648e+28\n-1.88005\t1.2795222757466818e+28\n-1.86644\t1.2540040739137162e+28\n-1.85284\t1.2301275340807325e+28\n-1.83923\t1.2073909013462902e+28\n-1.82563\t1.1856549339435846e+28\n-1.81202\t1.1651988510453132e+28\n-1.79841\t1.1466836194688627e+28\n-1.78481\t1.1309993134695602e+28\n-1.7712\t1.119081204968373e+28\n-1.7576\t1.1119307930213398e+28\n-1.74399\t1.110823842553995e+28\n-1.73038\t1.1175187173514314e+28\n-1.71678\t1.1333987621995888e+28\n-1.70317\t1.157464734002302e+28\n-1.68957\t1.1848587860871666e+28\n-1.67596\t1.2081222835372948e+28\n-1.66236\t1.2211177501973985e+28\n-1.64875\t1.2222297226275922e+28\n-1.63514\t1.2140841381206878e+28\n-1.62154\t1.2008423108338713e+28\n-1.60793\t1.18598922796276e+28\n-1.59433\t1.1717240580432167e+28\n-1.58072\t1.1590571572259135e+28\n-1.56712\t1.147981277013692e+28\n-1.55351\t1.1378051422586906e+28\n-1.5399\t1.1279233219904966e+28\n-1.5263\t1.1182924233113682e+28\n-1.51269\t1.1092970187200976e+28\n-1.49909\t1.1013561772844998e+28\n-1.48548\t1.0946440002556852e+28\n-1.47187\t1.0891014403360942e+28\n-1.45827\t1.084566676543145e+28\n-1.44466\t1.0808355445082815e+28\n-1.43106\t1.0776580642604717e+28\n-1.41745\t1.074751259963403e+28\n-1.40385\t1.071888427266826e+28\n-1.39024\t1.0690279388068135e+28\n-1.37663\t1.0663186290838924e+28\n-1.36303\t1.0639533140076026e+28\n-1.34942\t1.0620081273194164e+28\n-1.33582\t1.060410790026689e+28\n-1.32221\t1.059020059424294e+28\n-1.30861\t1.057688856736997e+28\n-1.295\t1.0562655029931263e+28\n-1.28139\t1.0545657451221398e+28\n-1.26779\t1.0524099596754968e+28\n-1.25418\t1.0497049853189414e+28\n-1.24058\t1.0464903209673028e+28\n-1.22697\t1.0429235895560939e+28\n-1.21336\t1.0392059050037808e+28\n-1.19976\t1.0355307796249082e+28\n-1.18615\t1.0320551301414635e+28\n-1.17255\t1.0288668899459087e+28\n-1.15894\t1.0259199884142182e+28\n-1.14534\t1.0230423056165605e+28\n-1.13173\t1.0200952863826156e+28\n-1.11812\t1.0171773788395606e+28\n-1.10452\t1.0146411208559831e+28\n-1.09091\t1.012886641245281e+28\n-1.07731\t1.0121218218055417e+28\n-1.0637\t1.0123191986774352e+28\n-1.0501\t1.0133066421226088e+28\n-1.03649\t1.0148631661586675e+28\n-1.02288\t1.0167494330600695e+28\n-1.00928\t1.0187606899469873e+28\n-0.99567\t1.0207802448428312e+28\n-0.98207\t1.02278425323259e+28\n-0.96846\t1.0247577375044077e+28\n-0.95485\t1.0266358142906167e+28\n-0.94125\t1.0283476170256236e+28\n-0.92764\t1.029931742240309e+28\n-0.91404\t1.0315895294491262e+28\n-0.90043\t1.0336069853214357e+28\n-0.88683\t1.036159142917861e+28\n-0.87322\t1.0391373826747518e+28\n-0.85961\t1.042170344171358e+28\n-0.84601\t1.0448672559234957e+28\n-0.8324\t1.0471020784338824e+28\n-0.8188\t1.04904282186197e+28\n-0.80519\t1.0509456945897454e+28\n-0.79158\t1.0529743714102954e+28\n-0.77798\t1.0553638841083593e+28\n-0.76437\t1.0585016104197887e+28\n-0.75077\t1.0627221974705218e+28\n-0.73716\t1.067957937038789e+28\n-0.72356\t1.0738198231742203e+28\n-0.70995\t1.0799763670947006e+28\n-0.69634\t1.0863171837027653e+28\n-0.68274\t1.0926804520158325e+28\n-0.66913\t1.0987151544860988e+28\n-0.65553\t1.1040852413690962e+28\n-0.64192\t1.1086540407305724e+28\n-0.62832\t1.1124248089995623e+28\n-0.61471\t1.115539034094222e+28\n-0.6011\t1.118383740643641e+28\n-0.5875\t1.1216385120384229e+28\n-0.57389\t1.1259579003230964e+28\n-0.56029\t1.1317026236729209e+28\n-0.54668\t1.138902499992312e+28\n-0.53307\t1.1474333534030127e+28\n-0.51947\t1.1571849263183337e+28\n-0.50586\t1.168225731258782e+28\n-0.49226\t1.180860244339118e+28\n-0.47865\t1.1955326640584428e+28\n-0.46505\t1.212503877463351e+28\n-0.45144\t1.2315332226779415e+28\n-0.43783\t1.2518459638475515e+28\n-0.42423\t1.2724127849500504e+28\n-0.41062\t1.29230434821979e+28\n-0.39702\t1.310928895764896e+28\n-0.38341\t1.328079124490031e+28\n-0.36981\t1.3439493411999565e+28\n-0.3562\t1.359245690760657e+28\n-0.34259\t1.3753115384257042e+28\n-0.32899\t1.3940323173721988e+28\n-0.31538\t1.4173232982986996e+28\n-0.30178\t1.446329998777868e+28\n-0.28817\t1.4812839489523786e+28\n-0.27456\t1.5216901814174536e+28\n-0.26096\t1.5675827415501406e+28\n-0.24735\t1.619944963025236e+28\n-0.23375\t1.6794546833165712e+28\n-0.22014\t1.743810313310024e+28\n-0.20654\t1.806350180052384e+28\n-0.19293\t1.8586219081109862e+28\n-0.17932\t1.8953978009049389e+28\n-0.16572\t1.9172552566510956e+28\n-0.15211\t1.9286576036825834e+28\n-0.13851\t1.934314158235437e+28\n-0.1249\t1.9371786289550522e+28\n-0.11129\t1.9386540169038326e+28\n-0.09769\t1.9398632702471823e+28\n-0.08408\t1.9418256512730135e+28\n-0.07048\t1.9452213122661592e+28\n-0.05687\t1.949647113197216e+28\n-0.04327\t1.9537216513674399e+28\n-0.02966\t1.9556298991648272e+28\n-0.01605\t1.9543419520559754e+28\n-0.00245\t1.9488707197024733e+28\n0.01116\t1.9361258215246726e+28\n0.02476\t1.909971429198845e+28\n0.03837\t1.8645175846019148e+28\n0.05197\t1.7997058289475938e+28\n0.06558\t1.7230368855171926e+28\n0.07919\t1.6450461948139211e+28\n0.09279\t1.5731471646634627e+28\n0.1064\t1.5094961297896466e+28\n0.12\t1.4529635997434347e+28\n0.13361\t1.401642258536953e+28\n0.14722\t1.354291279197143e+28\n0.16082\t1.3100528869289541e+28\n0.17443\t1.2683279478325778e+28\n0.18803\t1.2283162238982596e+28\n0.20164\t1.1890423067363253e+28\n0.21524\t1.1499233151665767e+28\n0.22885\t1.111263136792502e+28\n0.24246\t1.074042103881413e+28\n0.25606\t1.0391212476573953e+28\n0.26967\t1.006561135738793e+28\n0.28327\t9.758144526432406e+27\n0.29688\t9.464539882303359e+27\n0.31049\t9.186168950518698e+27\n0.32409\t8.928156781485068e+27\n0.3377\t8.695179195338642e+27\n0.3513\t8.490356380754961e+27\n0.36491\t8.314913716286213e+27\n0.37851\t8.17264847282564e+27\n0.39212\t8.068031276246135e+27\n0.40573\t7.997342637227484e+27\n0.41933\t7.9365459899135e+27\n0.43294\t7.834111189298624e+27\n0.44654\t7.632674080059082e+27\n0.46015\t7.280119635070795e+27\n0.47376\t6.738792352976591e+27\n0.48736\t6.000955174177101e+27\n0.50097\t5.124967916982027e+27\n0.51457\t4.2491434812386983e+27\n0.52818\t3.5323674533926075e+27\n0.54178\t3.061104890284199e+27\n0.55539\t2.813295741162151e+27\n0.569\t2.7078533536949856e+27\n0.5826\t2.669441419183692e+27\n0.59621\t2.655196896201252e+27\n0.60981\t2.6493072715678973e+27\n0.62342\t2.644111305553053e+27\n0.63702\t2.6394910016468115e+27\n0.65063\t2.6353664204014795e+27\n0.66424\t2.63174805693473e+27\n0.67784\t2.628762048829057e+27\n0.69145\t2.6266437025077944e+27\n0.70505\t2.625634601847834e+27\n0.71866\t2.6258333224871304e+27\n0.73227\t2.627093521289537e+27\n0.74587\t2.629071605757793e+27\n0.75948\t2.631382689520427e+27\n0.77308\t2.6337370288615055e+27\n0.78669\t2.6359825917025943e+27\n0.80029\t2.6380732779941036e+27\n0.8139\t2.640016247956501e+27\n0.82751\t2.6418373960857275e+27\n0.84111\t2.6435574183614906e+27\n0.85472\t2.6451868099014646e+27\n0.86832\t2.646728415176795e+27\n0.88193\t2.648182136102267e+27\n0.89553\t2.649544932036315e+27\n0.90914\t2.6508150374451233e+27\n0.92275\t2.6519910791357263e+27\n0.93635\t2.653073743704606e+27\n0.94996\t2.6540723492468936e+27\n0.96356\t2.6550082783387807e+27\n0.97717\t2.655915958889643e+27\n0.99078\t2.6568314862574564e+27\n1.00438\t2.6577827166423993e+27\n1.01799\t2.6587856379340104e+27\n1.03159\t2.65984240800695e+27\n1.0452\t2.6609523402647365e+27\n1.0588\t2.6621052338453324e+27\n1.07241\t2.663229486544055e+27\n1.08602\t2.6641025430151186e+27\n1.09962\t2.664321567293277e+27\n1.11323\t2.663358959023755e+27\n1.12683\t2.6607204668238205e+27\n1.14044\t2.656140770195303e+27\n1.15405\t2.649832321707163e+27\n1.16765\t2.642655034412071e+27\n1.18126\t2.6359656229609366e+27\n1.19486\t2.6310339965921457e+27\n1.20847\t2.6284431738051914e+27\n1.22207\t2.627943625821018e+27\n1.23568\t2.6288225674047955e+27\n1.24929\t2.630386536108437e+27\n1.26289\t2.6321982680573206e+27\n1.2765\t2.634053942181133e+27\n1.2901\t2.635883525638582e+27\n1.30371\t2.6376701477732213e+27\n1.31731\t2.6394173396526796e+27\n1.33092\t2.6411198046755145e+27\n1.34453\t2.6427707749621054e+27\n1.35813\t2.6443610305025336e+27\n1.37174\t2.6458822340537896e+27\n1.38534\t2.6473268330545566e+27\n1.39895\t2.6486919830336897e+27\n1.41256\t2.649973466327078e+27\n1.42616\t2.651165495907219e+27\n1.43977\t2.652260224957162e+27\n1.45337\t2.653249120063472e+27\n1.46698\t2.6541316908000893e+27\n1.48058\t2.65490980078604e+27\n1.49419\t2.655592375775607e+27\n1.5078\t2.656190499397733e+27\n1.5214\t2.6567128031510655e+27\n1.53501\t2.657165662574377e+27\n1.54861\t2.657541230850718e+27\n1.56222\t2.657823618175759e+27\n1.57582\t2.6579890879282233e+27\n1.58943\t2.65802155413336e+27\n1.60304\t2.657917779979177e+27\n1.61664\t2.657693262929153e+27\n1.63025\t2.6573822347222386e+27\n1.64385\t2.657046390956715e+27\n1.65746\t2.656785876633926e+27\n1.67106\t2.656749977446373e+27\n1.68467\t2.657127311256527e+27\n1.69828\t2.658092273571135e+27\n1.71188\t2.659706461903266e+27\n1.72549\t2.661839815261949e+27\n1.73909\t2.664199647374893e+27\n1.7527\t2.66646423874709e+27\n1.76631\t2.6684557608893745e+27\n1.77991\t2.670207072347732e+27\n1.79352\t2.671878836699244e+27\n1.80712\t2.673618966443446e+27\n1.82073\t2.675470520988359e+27\n1.83434\t2.677381613256891e+27\n1.84794\t2.679260337405499e+27\n1.86155\t2.6810230267484363e+27\n1.87515\t2.6826153420783145e+27\n1.88876\t2.6840128601773725e+27\n1.90236\t2.685212540404042e+27\n1.91597\t2.6862195812745516e+27\n1.92958\t2.687036631089624e+27\n1.94318\t2.687656627714002e+27\n1.95679\t2.688066721984929e+27\n1.97039\t2.688261715386173e+27\n1.984\t2.688255241762188e+27\n1.9976\t2.6881009537238803e+27\n2.01121\t2.6878805562527557e+27\n2.02482\t2.6876594721851476e+27\n2.03842\t2.6874309336414355e+27\n2.05203\t2.687095678387184e+27\n2.06563\t2.6865071671158233e+27\n2.07924\t2.685535535006807e+27\n2.09284\t2.6841122204970207e+27\n2.10645\t2.682236144649134e+27\n2.12006\t2.6799581156029085e+27\n2.13366\t2.6773895581590546e+27\n2.14727\t2.6747151667715677e+27\n2.16087\t2.6721775061694604e+27\n2.17448\t2.6700035455330535e+27\n2.18809\t2.668310790946196e+27\n2.20169\t2.6670657953516323e+27\n2.2153\t2.6661415383999603e+27\n2.2289\t2.6653981505790197e+27\n2.24251\t2.6647398026367906e+27\n2.25612\t2.664118628989869e+27\n2.26972\t2.6635150125958766e+27\n2.28333\t2.6629265994097285e+27\n2.29693\t2.6623609419927385e+27\n2.31054\t2.661826868013979e+27\n2.32414\t2.6613308510974334e+27\n2.33775\t2.660872793157891e+27\n2.35136\t2.660448966957299e+27\n2.36496\t2.660055154831547e+27\n2.37857\t2.659687433372158e+27\n2.39217\t2.6593436447044717e+27\n2.40578\t2.659022121379885e+27\n2.41938\t2.6587233538244575e+27\n2.43299\t2.6584509711910297e+27\n2.4466\t2.658210073910619e+27\n2.4602\t2.6579937960183943e+27\n2.47381\t2.6577540757605264e+27\n2.48741\t2.6573845887673236e+27\n2.50102\t2.656743209566752e+27\n2.51462\t2.6557084105812767e+27\n2.52823\t2.654234876443001e+27\n2.54184\t2.652374298058594e+27\n2.55544\t2.6502487915168627e+27\n2.56905\t2.6480008746306883e+27\n2.58265\t2.6457468764613765e+27\n2.59626\t2.6435568298502195e+27\n2.60986\t2.6414532943959524e+27\n2.62347\t2.639425480725267e+27\n2.63708\t2.6374503388133684e+27\n2.65068\t2.6355192371616097e+27\n2.66429\t2.6336402187573665e+27\n2.67789\t2.6318305465979327e+27\n2.6915\t2.6300994406932244e+27\n2.70511\t2.6284484704066335e+27\n2.71871\t2.626876360630406e+27\n2.73232\t2.625380855404666e+27\n2.74592\t2.6239476342884787e+27\n2.75953\t2.622548056399971e+27\n2.77314\t2.6211480861706154e+27\n2.78674\t2.6197213386784135e+27\n2.80035\t2.6182652637078546e+27\n2.81395\t2.6167986936196233e+27\n2.82756\t2.6153479152505076e+27\n2.84116\t2.6139235218033906e+27\n2.85477\t2.612514821990177e+27\n2.86838\t2.6110920959916623e+27\n2.88198\t2.609625525903431e+27\n2.89559\t2.60809471000141e+27\n2.90919\t2.6064893493383496e+27\n2.9228\t2.604806109017046e+27\n2.9364\t2.6030444005262275e+27\n2.95001\t2.601204223865894e+27\n2.96362\t2.5992872464846483e+27\n2.97722\t2.5972965090240583e+27\n2.99083\t2.595238288937687e+27\n3.00443\t2.5931227870875684e+27\n3.01804\t2.5909693262604475e+27\n3.03164\t2.58880154499239e+27\n3.04525\t2.5866392564961986e+27\n3.05886\t2.584493642486029e+27\n3.07246\t2.582363525939339e+27\n3.08607\t2.5802410600391764e+27\n3.09967\t2.578123792655244e+27\n3.11328\t2.576002405692412e+27\n3.12689\t2.5738451195420274e+27\n3.14049\t2.5715650307063524e+27\n3.1541\t2.5690332552169577e+27\n3.1677\t2.566135229546354e+27\n3.18131\t2.562861047088138e+27\n3.19492\t2.559335374146628e+27\n3.20852\t2.555744866880056e+27\n3.22213\t2.552229492885794e+27\n3.23573\t2.548798864514608e+27\n3.24934\t2.545349501867951e+27\n3.26294\t2.5417607601351933e+27\n3.27655\t2.538007431416878e+27\n3.29016\t2.534199371150326e+27\n3.30376\t2.53052058719305e+27\n3.31737\t2.527104867774072e+27\n3.33097\t2.5239787939858157e+27\n3.34458\t2.5210872419391963e+27\n3.35818\t2.518347035374529e+27\n3.37179\t2.5156872586836136e+27\n3.3854\t2.5130701490598724e+27\n3.399\t2.510494823736398e+27\n3.41261\t2.50799757424159e+27\n3.42621\t2.505614594018639e+27\n3.43982\t2.503355299247885e+27\n3.45342\t2.5011872237241916e+27\n3.46703\t2.499050045042245e+27\n3.48064\t2.4968868737791465e+27\n3.49424\t2.494666518837514e+27\n3.50785\t2.492384958723661e+27\n3.52145\t2.4900522962144106e+27\n3.53506\t2.4876803996204026e+27\n3.54867\t2.4852755463951987e+27\n3.56227\t2.482842248458546e+27\n3.57588\t2.4803812904921386e+27\n3.58948\t2.4778974786713607e+27\n3.60309\t2.4753958153420178e+27\n3.61669\t2.4728751234815677e+27\n3.6303\t2.4703229462681e+27\n3.64391\t2.467713977716946e+27\n3.65751\t2.4650130052370356e+27\n3.67112\t2.4621830507034853e+27\n3.68472\t2.4591889015252258e+27\n3.69833\t2.4560028976725025e+27\n3.71194\t2.4526053240177246e+27\n3.72554\t2.4489761711776666e+27\n3.73915\t2.4450917025310498e+27\n3.75275\t2.4409370091256668e+27\n3.76636\t2.4365219975679183e+27\n3.77996\t2.431899535787015e+27\n3.79357\t2.4271642760124343e+27\n3.80718\t2.4224240138920472e+27\n3.82078\t2.4177477033298147e+27\n3.83439\t2.4131439758243832e+27\n3.84799\t2.4085654562184082e+27\n3.8616\t2.4039386786881817e+27\n3.87521\t2.3991953759262261e+27\n3.88881\t2.3942975889555378e+27\n3.90242\t2.389251399059255e+27\n3.91602\t2.3841052603320525e+27\n3.92963\t2.3789250860363233e+27\n3.94323\t2.3737662943167868e+27\n3.95684\t2.3686652747870553e+27\n3.97045\t2.363653610885359e+27\n3.98405\t2.3587810318141277e+27\n3.99766\t2.3541135489209653e+27\n4.01126\t2.3445480828866914e+27\n4.02487\t2.3200213852266718e+27\n4.03847\t2.253304510693223e+27\n4.05208\t2.0988844496896002e+27\n4.06569\t1.813798604298713e+27\n4.07929\t1.4009325433692554e+27'
num_pt_fcc='10'
vol_pt_fcc='1.0195e-28'
button_pt_fcc = Button(
    description='Pt fcc',
    disabled=False,
    button_style='', # 'success', 'info', 'warning', 'danger' or ''
    tooltip='Pt fcc',
    icon='' # (FontAwesome names without the `fa-` prefix)
)

DOS_w_bcc='-10.23143\t0\n-10.21782\t0\n-10.20421\t0\n-10.19061\t0\n-10.177\t0\n-10.1634\t0\n-10.14979\t0\n-10.13618\t0\n-10.12258\t0\n-10.10897\t0\n-10.09537\t0\n-10.08176\t0\n-10.06816\t0\n-10.05455\t0\n-10.04094\t0\n-10.02734\t0\n-10.01373\t0\n-10.00013\t0\n-9.98652\t0\n-9.97292\t0\n-9.95931\t0\n-9.9457\t0\n-9.9321\t0\n-9.91849\t0\n-9.90489\t0\n-9.89128\t0\n-9.87768\t0\n-9.86407\t0\n-9.85046\t0\n-9.83686\t0\n-9.82325\t0\n-9.80965\t0\n-9.79604\t0\n-9.78243\t0\n-9.76883\t0\n-9.75522\t0\n-9.74162\t0\n-9.72801\t0\n-9.71441\t1.3378193880153395e+23\n-9.7008\t7.087815902142979e+23\n-9.68719\t2.5563045360899e+24\n-9.67359\t7.203397493029017e+24\n-9.65998\t1.6482854259367394e+25\n-9.64638\t3.135441483085516e+25\n-9.63277\t5.0880948922297005e+25\n-9.61916\t7.255840763569029e+25\n-9.60556\t9.387701928322394e+25\n-9.59195\t1.1332502919319532e+26\n-9.57835\t1.301818349308677e+26\n-9.56474\t1.440380224843688e+26\n-9.55114\t1.549698644457362e+26\n-9.53753\t1.6387142945226213e+26\n-9.52392\t1.7222557677792763e+26\n-9.51032\t1.8117376844895867e+26\n-9.49671\t1.910499902312273e+26\n-9.48311\t2.0151415830414757e+26\n-9.4695\t2.1198601930763007e+26\n-9.4559\t2.219549315215508e+26\n-9.44229\t2.3111796235096584e+26\n-9.42868\t2.3932650689330738e+26\n-9.41508\t2.465482923667046e+26\n-9.40147\t2.5283407334962296e+26\n-9.38787\t2.5840394270912303e+26\n-9.37426\t2.636839199291443e+26\n-9.36065\t2.6919581086074858e+26\n-9.34705\t2.7536732367995008e+26\n-9.33344\t2.8238881151005047e+26\n-9.31984\t2.9020811252918897e+26\n-9.30623\t2.9861554747143177e+26\n-9.29263\t3.0729364222674784e+26\n-9.27902\t3.1581806600327225e+26\n-9.26541\t3.236926247797417e+26\n-9.25181\t3.3051494076126177e+26\n-9.2382\t3.3620358146334435e+26\n-9.2246\t3.4106260527565e+26\n-9.21099\t3.4558661134359365e+26\n-9.19738\t3.5018914159300774e+26\n-9.18378\t3.550667410181343e+26\n-9.17017\t3.602365779883989e+26\n-9.15657\t3.656426442166595e+26\n-9.14296\t3.712395326493537e+26\n-9.12936\t3.770017252729092e+26\n-9.11575\t3.82927908660157e+26\n-9.10214\t3.8902380560090546e+26\n-9.08854\t3.952995482476024e+26\n-9.07493\t4.0176320479571546e+26\n-9.06133\t4.083959181837446e+26\n-9.04772\t4.151173817219185e+26\n-9.03411\t4.217721419231443e+26\n-9.02051\t4.28155773230165e+26\n-9.0069\t4.340867412449576e+26\n-8.9933\t4.3948858574303164e+26\n-8.97969\t4.444322317915217e+26\n-8.96609\t4.490974312801499e+26\n-8.95248\t4.536713475805216e+26\n-8.93888\t4.582631827801296e+26\n-8.92527\t4.628896361672677e+26\n-8.91166\t4.675340084536421e+26\n-8.89806\t4.722137494573575e+26\n-8.88445\t4.77008602970827e+26\n-8.87085\t4.8203583927701144e+26\n-8.85724\t4.873888055211475e+26\n-8.84363\t4.930830751968121e+26\n-8.83003\t4.990481923180029e+26\n-8.81642\t5.051609761794976e+26\n-8.80282\t5.1129083459419154e+26\n-8.78921\t5.173324119398725e+26\n-8.77561\t5.232248214856276e+26\n-8.762\t5.289581187114617e+26\n-8.74839\t5.345618557286807e+26\n-8.73479\t5.400610814697253e+26\n-8.72118\t5.454449132523365e+26\n-8.70758\t5.506721657531387e+26\n-8.69397\t5.557130992283729e+26\n-8.68036\t5.605898543074622e+26\n-8.66676\t5.653787035824442e+26\n-8.65315\t5.701738385445929e+26\n-8.63955\t5.750563164134907e+26\n-8.62594\t5.800737958321328e+26\n-8.61234\t5.8523415736353414e+26\n-8.59873\t5.9050728599903045e+26\n-8.58512\t5.9583942504091264e+26\n-8.57152\t6.011755981805287e+26\n-8.55791\t6.06479498538274e+26\n-8.54431\t6.1174108777792694e+26\n-8.5307\t6.1697378161985854e+26\n-8.51709\t6.222113539055612e+26\n-8.50349\t6.274993993210502e+26\n-8.48988\t6.328825743900768e+26\n-8.47628\t6.38388085818288e+26\n-8.46267\t6.440170594004003e+26\n-8.44907\t6.497464163447269e+26\n-8.43546\t6.555440715018496e+26\n-8.42185\t6.613836625121593e+26\n-8.40825\t6.672483962711357e+26\n-8.39464\t6.731233559987862e+26\n-8.38104\t6.789790834000311e+26\n-8.36743\t6.847577876794275e+26\n-8.35382\t6.903826333475796e+26\n-8.34022\t6.957911387977258e+26\n-8.32661\t7.009803019106223e+26\n-8.31301\t7.060149496986899e+26\n-8.2994\t7.109919943237672e+26\n-8.2858\t7.160014055469415e+26\n-8.27219\t7.211112001323303e+26\n-8.25858\t7.263754162263216e+26\n-8.24498\t7.31832330849274e+26\n-8.23137\t7.374967669649535e+26\n-8.21777\t7.433546521394049e+26\n-8.20416\t7.493683660658545e+26\n-8.19056\t7.554826509869712e+26\n-8.17695\t7.61627519997884e+26\n-8.16334\t7.677259499767443e+26\n-8.14974\t7.737087983647188e+26\n-8.13613\t7.795374128765433e+26\n-8.12253\t7.852188297291954e+26\n-8.10892\t7.90799769403407e+26\n-8.09531\t7.963415877112228e+26\n-8.08171\t8.019005743884641e+26\n-8.0681\t8.075306737652928e+26\n-8.0545\t8.132944612646965e+26\n-8.04089\t8.192636124836212e+26\n-8.02729\t8.254959182175094e+26\n-8.01368\t8.319988837644709e+26\n-8.00007\t8.387100275177443e+26\n-7.98647\t8.455088894426722e+26\n-7.97286\t8.522573720540401e+26\n-7.95926\t8.588443031236016e+26\n-7.94565\t8.652208043974183e+26\n-7.93204\t8.714102361158561e+26\n-7.91844\t8.7748765126001e+26\n-7.90483\t8.835403927366288e+26\n-7.89123\t8.896291596441733e+26\n-7.87762\t8.957778751203671e+26\n-7.86402\t9.019852257380415e+26\n-7.85041\t9.082459577885194e+26\n-7.8368\t9.145692652619851e+26\n-7.8232\t9.209826363127648e+26\n-7.80959\t9.275190004363134e+26\n-7.79599\t9.341957136345095e+26\n-7.78238\t9.410004859816986e+26\n-7.76878\t9.479014199609154e+26\n-7.75517\t9.548697139906648e+26\n-7.74156\t9.61888856415106e+26\n-7.72796\t9.689469325734904e+26\n-7.71435\t9.760250854043173e+26\n-7.70075\t9.831024877053335e+26\n-7.68714\t9.901694764052225e+26\n-7.67353\t9.972328062722833e+26\n-7.65993\t1.004311897265374e+27\n-7.64632\t1.0114300158086341e+27\n-7.63272\t1.0186101468775238e+27\n-7.61911\t1.0258733991229757e+27\n-7.60551\t1.0332460410883736e+27\n-7.5919\t1.0407691642808667e+27\n-7.57829\t1.0484951181547684e+27\n-7.56469\t1.0564596466923254e+27\n-7.55108\t1.0646382638584554e+27\n-7.53748\t1.0729316182694341e+27\n-7.52387\t1.0812081795758928e+27\n-7.51027\t1.0893761016922167e+27\n-7.49666\t1.0974258153633163e+27\n-7.48305\t1.1054143608548236e+27\n-7.46945\t1.1134166035153807e+27\n-7.45584\t1.1214832041072267e+27\n-7.44224\t1.1296345207514834e+27\n-7.42863\t1.137866519350417e+27\n-7.41502\t1.1461625944319604e+27\n-7.40142\t1.1545007929991433e+27\n-7.38781\t1.1628658230070675e+27\n-7.37421\t1.1712691300353501e+27\n-7.3606\t1.1797589356243444e+27\n-7.347\t1.1884076659008073e+27\n-7.33339\t1.1972798664284798e+27\n-7.31978\t1.2064099677624394e+27\n-7.30618\t1.215794873967216e+27\n-7.29257\t1.2254009050175434e+27\n-7.27897\t1.2351719588100529e+27\n-7.26536\t1.245043489781003e+27\n-7.25175\t1.2549599587243838e+27\n-7.23815\t1.2648949094643593e+27\n-7.22454\t1.2748532204447002e+27\n-7.21094\t1.2848594715167157e+27\n-7.19733\t1.2949404003049202e+27\n-7.18373\t1.305122087720245e+27\n-7.17012\t1.315439808663804e+27\n-7.15651\t1.3259535117042467e+27\n-7.14291\t1.3367502582996437e+27\n-7.1293\t1.3479189862325914e+27\n-7.1157\t1.359491030122698e+27\n-7.10209\t1.371392931864716e+27\n-7.08849\t1.383467174014573e+27\n-7.07488\t1.3955482647489552e+27\n-7.06127\t1.4075502684045084e+27\n-7.04767\t1.4194908224317903e+27\n-7.03406\t1.4314537985371744e+27\n-7.02046\t1.4435249447515613e+27\n-7.00685\t1.4557550156534165e+27\n-6.99325\t1.4681535804978298e+27\n-6.97964\t1.4807272064206465e+27\n-6.96603\t1.4935104177931707e+27\n-6.95243\t1.5065794872074397e+27\n-6.93882\t1.5200278556249167e+27\n-6.92522\t1.533925603766699e+27\n-6.91161\t1.5482988125437172e+27\n-6.898\t1.5631346291329586e+27\n-6.8844\t1.578395620860102e+27\n-6.87079\t1.5940224020538566e+27\n-6.85719\t1.6099212503040797e+27\n-6.84358\t1.6259798675878088e+27\n-6.82998\t1.6421050005760327e+27\n-6.81637\t1.6582707559902745e+27\n-6.80276\t1.6745361442369198e+27\n-6.78916\t1.6910523032566478e+27\n-6.77555\t1.7080486137229303e+27\n-6.76195\t1.7257882301507305e+27\n-6.74834\t1.7444643201501418e+27\n-6.73473\t1.764089736544176e+27\n-6.72113\t1.7844684034197231e+27\n-6.70752\t1.80530667598825e+27\n-6.69392\t1.8263773313494917e+27\n-6.68031\t1.8476106640472563e+27\n-6.66671\t1.8690713134615119e+27\n-6.6531\t1.8908858376816295e+27\n-6.63949\t1.91320818913508e+27\n-6.62589\t1.936228814761392e+27\n-6.61228\t1.9601731549525282e+27\n-6.59868\t1.9852659933868679e+27\n-6.58507\t2.0116715084605562e+27\n-6.57147\t2.039464940787141e+27\n-6.55786\t2.0686413181066244e+27\n-6.54425\t2.0991496043918614e+27\n-6.53065\t2.13096146714249e+27\n-6.51704\t2.1641840444890215e+27\n-6.50344\t2.1991238340430032e+27\n-6.48983\t2.23618499610763e+27\n-6.47622\t2.2755873421012838e+27\n-6.46262\t2.3171712906229114e+27\n-6.44901\t2.3605624211130763e+27\n-6.43541\t2.405599463478651e+27\n-6.4218\t2.4526333842224795e+27\n-6.4082\t2.502449518975494e+27\n-6.39459\t2.5560107974851396e+27\n-6.38098\t2.614519474692331e+27\n-6.36738\t2.682278619451912e+27\n-6.35377\t2.769396742522641e+27\n-6.34017\t2.8966157672085644e+27\n-6.32656\t3.0990427573952774e+27\n-6.31295\t3.413880256200546e+27\n-6.29935\t3.8508970658274456e+27\n-6.28574\t4.365836788730015e+27\n-6.27214\t4.8709610827650024e+27\n-6.25853\t5.283059927403514e+27\n-6.24493\t5.56471359496374e+27\n-6.23132\t5.724532351069334e+27\n-6.21771\t5.792209781895748e+27\n-6.20411\t5.800789463429604e+27\n-6.1905\t5.781451030872031e+27\n-6.1769\t5.76152380767777e+27\n-6.16329\t5.758366047314431e+27\n-6.14969\t5.775283739783016e+27\n-6.13608\t5.804904524566807e+27\n-6.12247\t5.834507390451362e+27\n-6.10887\t5.852711209567233e+27\n-6.09526\t5.854462007983723e+27\n-6.08166\t5.842087178644581e+27\n-6.06805\t5.821942958518729e+27\n-6.05445\t5.800371136876227e+27\n-6.04084\t5.782327274426312e+27\n-6.02723\t5.771773699489663e+27\n-6.01363\t5.771574621457309e+27\n-6.00002\t5.782389380768169e+27\n-5.98642\t5.801999505117306e+27\n-5.97281\t5.826093294557047e+27\n-5.9592\t5.849508698863916e+27\n-5.9456\t5.867174575737791e+27\n-5.93199\t5.875446070968026e+27\n-5.91839\t5.873983851263847e+27\n-5.90478\t5.867308263860366e+27\n-5.89118\t5.864788547652561e+27\n-5.87757\t5.877530761334161e+27\n-5.86396\t5.913276338456422e+27\n-5.85036\t5.972095078291761e+27\n-5.83675\t6.046750090954337e+27\n-5.82315\t6.127681972058323e+27\n-5.80954\t6.208097113387474e+27\n-5.79593\t6.285094623406243e+27\n-5.78233\t6.357765610513576e+27\n-5.76872\t6.425797009962079e+27\n-5.75512\t6.489404129991268e+27\n-5.74151\t6.549340690163789e+27\n-5.72791\t6.606064701296771e+27\n-5.7143\t6.658647476565393e+27\n-5.70069\t6.704919703367335e+27\n-5.68709\t6.742594517368639e+27\n-5.67348\t6.770966045282107e+27\n-5.65988\t6.791870739738902e+27\n-5.64627\t6.809336412785706e+27\n-5.63267\t6.828036238290389e+27\n-5.61906\t6.851615539544726e+27\n-5.60545\t6.881743963929396e+27\n-5.59185\t6.918015193367999e+27\n-5.57824\t6.958611726107099e+27\n-5.56464\t7.001131866751657e+27\n-5.55103\t7.043391948816724e+27\n-5.53742\t7.084099184702938e+27\n-5.52382\t7.123214359227678e+27\n-5.51021\t7.161734645061014e+27\n-5.49661\t7.200769325263529e+27\n-5.483\t7.240612044623757e+27\n-5.4694\t7.280538635690359e+27\n-5.45579\t7.319449197025389e+27\n-5.44218\t7.35675099771065e+27\n-5.42858\t7.392733085539587e+27\n-5.41497\t7.428147022301635e+27\n-5.40137\t7.463563210653115e+27\n-5.38776\t7.499058767532104e+27\n-5.37415\t7.534492311885463e+27\n-5.36055\t7.569849771279237e+27\n-5.34694\t7.605363247057463e+27\n-5.33334\t7.641482400393124e+27\n-5.31973\t7.678833923678361e+27\n-5.30613\t7.717959793252906e+27\n-5.29252\t7.759011428506119e+27\n-5.27891\t7.801673044020043e+27\n-5.26531\t7.845481562901321e+27\n-5.2517\t7.890254606405894e+27\n-5.2381\t7.93626067657363e+27\n-5.22449\t7.984053945853685e+27\n-5.21089\t8.034100774707339e+27\n-5.19728\t8.086353598307823e+27\n-5.18367\t8.140069767407204e+27\n-5.17007\t8.194020195623826e+27\n-5.15646\t8.247092222512961e+27\n-5.14286\t8.299072697608298e+27\n-5.12925\t8.351106272687757e+27\n-5.11564\t8.40538224320988e+27\n-5.10204\t8.463976762264197e+27\n-5.08843\t8.527642611251093e+27\n-5.07483\t8.595543137063812e+27\n-5.06122\t8.666212273532893e+27\n-5.04762\t8.738803798296491e+27\n-5.03401\t8.81367468209594e+27\n-5.0204\t8.892054949475155e+27\n-5.0068\t8.975423237977934e+27\n-4.99319\t9.065099166644376e+27\n-4.97959\t9.162492980989251e+27\n-4.96598\t9.269999152558163e+27\n-4.95237\t9.391577289001225e+27\n-4.93877\t9.533478084032693e+27\n-4.92516\t9.703330391732176e+27\n-4.91156\t9.906663552849382e+27\n-4.89795\t1.0138716581528562e+28\n-4.88435\t1.03774967027195e+28\n-4.87074\t1.0588192186017206e+28\n-4.85713\t1.074067939166455e+28\n-4.84353\t1.0826189410799097e+28\n-4.82992\t1.0857421207822088e+28\n-4.81632\t1.0853808814025766e+28\n-4.80271\t1.0829047991216546e+28\n-4.78911\t1.0790392422384786e+28\n-4.7755\t1.0743931718784068e+28\n-4.76189\t1.069585822043585e+28\n-4.74829\t1.064996229051787e+28\n-4.73468\t1.0605764059032258e+28\n-4.72108\t1.0560614061930137e+28\n-4.70747\t1.0512512700162685e+28\n-4.69386\t1.046136822146052e+28\n-4.68026\t1.0409261938805622e+28\n-4.66665\t1.0360627137975042e+28\n-4.65305\t1.0321972694937997e+28\n-4.63944\t1.0299787408991272e+28\n-4.62584\t1.0297084282060914e+28\n-4.61223\t1.0312059415746313e+28\n-4.59862\t1.0340685373265692e+28\n-4.58502\t1.037886004012109e+28\n-4.57141\t1.0422968770926745e+28\n-4.55781\t1.0464866534725575e+28\n-4.5442\t1.0483574709874406e+28\n-4.5306\t1.0439408938803117e+28\n-4.51699\t1.0284397419952872e+28\n-4.50338\t9.991884899455393e+27\n-4.48978\t9.584222155080719e+27\n-4.47617\t9.126839719033736e+27\n-4.46257\t8.687418868606142e+27\n-4.44896\t8.296776639284154e+27\n-4.43535\t7.944783317841853e+27\n-4.42175\t7.606043789963539e+27\n-4.40814\t7.267681215682777e+27\n-4.39454\t6.936033913069247e+27\n-4.38093\t6.626710556785016e+27\n-4.36733\t6.351221928724371e+27\n-4.35372\t6.111582357083671e+27\n-4.34011\t5.9021831325857e+27\n-4.32651\t5.715085995236286e+27\n-4.3129\t5.543858060209561e+27\n-4.2993\t5.384731011140982e+27\n-4.28569\t5.23639010743422e+27\n-4.27209\t5.098871655968881e+27\n-4.25848\t4.971833039886264e+27\n-4.24487\t4.85347082986689e+27\n-4.23127\t4.7405281956123727e+27\n-4.21766\t4.6300507703381413e+27\n-4.20406\t4.52139234787697e+27\n-4.19045\t4.4163343107351436e+27\n-4.17684\t4.317295616493349e+27\n-4.16324\t4.2255342469309623e+27\n-4.14963\t4.1410246840344104e+27\n-4.13603\t4.0633623922355925e+27\n-4.12242\t3.992462843114551e+27\n-4.10882\t3.928233440055859e+27\n-4.09521\t3.8699684974047733e+27\n-4.0816\t3.816140780812241e+27\n-4.068\t3.764984762714231e+27\n-4.05439\t3.715413863576944e+27\n-4.04079\t3.6674363392283007e+27\n-4.02718\t3.6215837524069045e+27\n-4.01358\t3.5779439151006374e+27\n-3.99997\t3.535777743078166e+27\n-3.98636\t3.494003816698142e+27\n-3.97276\t3.4519665481707013e+27\n-3.95915\t3.4098641711821614e+27\n-3.94555\t3.3685399059751217e+27\n-3.93194\t3.329056971843017e+27\n-3.91833\t3.2923348616204867e+27\n-3.90473\t3.259004395613631e+27\n-3.89112\t3.2294448728256586e+27\n-3.87752\t3.2038139045168684e+27\n-3.86391\t3.1820287447756044e+27\n-3.85031\t3.16379837566767e+27\n-3.8367\t3.1486630976838604e+27\n-3.82309\t3.1361482007187505e+27\n-3.80949\t3.1257453884578753e+27\n-3.79588\t3.116884727326046e+27\n-3.78228\t3.108987371206569e+27\n-3.76867\t3.101810992786734e+27\n-3.75506\t3.095829926907061e+27\n-3.74146\t3.092172219873404e+27\n-3.72785\t3.0920428472972414e+27\n-3.71425\t3.101100522504445e+27\n-3.70064\t3.134588130690468e+27\n-3.68704\t3.2328000225292765e+27\n-3.67343\t3.47910007716101e+27\n-3.65982\t3.991746837674906e+27\n-3.64622\t4.8693450044495776e+27\n-3.63261\t6.112794650360806e+27\n-3.61901\t7.58974519077276e+27\n-3.6054\t9.085574370416856e+27\n-3.59179\t1.0405330851288329e+28\n-3.57819\t1.1449568026193135e+28\n-3.56458\t1.2223151298446973e+28\n-3.55098\t1.2789000678037107e+28\n-3.53737\t1.3210797493627787e+28\n-3.52377\t1.3534240942510293e+28\n-3.51016\t1.3800162942335688e+28\n-3.49655\t1.4056862807109052e+28\n-3.48295\t1.4349618030184146e+28\n-3.46934\t1.469767801251972e+28\n-3.45574\t1.5087512765581353e+28\n-3.44213\t1.549073790863257e+28\n-3.42853\t1.5887810771190992e+28\n-3.41492\t1.6280960426795133e+28\n-3.40131\t1.6687114512433574e+28\n-3.38771\t1.7127985292639695e+28\n-3.3741\t1.7620567483003926e+28\n-3.3605\t1.8173497336244622e+28\n-3.34689\t1.8779170953398389e+28\n-3.33328\t1.9427945715086617e+28\n-3.31968\t2.010948438659066e+28\n-3.30607\t2.0786153620681274e+28\n-3.29247\t2.1351680835350058e+28\n-3.27886\t2.1645979429165144e+28\n-3.26526\t2.1557553883163744e+28\n-3.25165\t2.111649744064564e+28\n-3.23804\t2.047234613022531e+28\n-3.22444\t1.9790364552316575e+28\n-3.21083\t1.9163894692263693e+28\n-3.19723\t1.860124951206895e+28\n-3.18362\t1.8060945071308025e+28\n-3.17001\t1.750253513083646e+28\n-3.15641\t1.691311264186293e+28\n-3.1428\t1.6318839760169919e+28\n-3.1292\t1.5761714914367152e+28\n-3.11559\t1.5271443230025927e+28\n-3.10199\t1.4854259733550693e+28\n-3.08838\t1.4497538918645454e+28\n-3.07477\t1.4180952310115772e+28\n-3.06117\t1.3882861289165968e+28\n-3.04756\t1.3585250138214035e+28\n-3.03396\t1.32799880863693e+28\n-3.02035\t1.2972492739255859e+28\n-3.00675\t1.2677145092397523e+28\n-2.99314\t1.2406966556565564e+28\n-2.97953\t1.2166096209851134e+28\n-2.96593\t1.195104024216805e+28\n-2.95232\t1.1756238071963212e+28\n-2.93872\t1.1576845967469217e+28\n-2.92511\t1.1408544817256513e+28\n-2.9115\t1.1248197594347783e+28\n-2.8979\t1.1095488888589983e+28\n-2.88429\t1.0953675342649038e+28\n-2.87069\t1.0826729604630527e+28\n-2.85708\t1.0716314473330604e+28\n-2.84348\t1.0619877959759595e+28\n-2.82987\t1.0531290299319029e+28\n-2.81626\t1.0444066914442313e+28\n-2.80266\t1.0356285604467385e+28\n-2.78905\t1.0273391463172674e+28\n-2.77545\t1.02060596513242e+28\n-2.76184\t1.0163171000542465e+28\n-2.74824\t1.0144998516046202e+28\n-2.73463\t1.0141700406608213e+28\n-2.72102\t1.0138769212431558e+28\n-2.70742\t1.012643575604824e+28\n-2.69381\t1.0104665419270744e+28\n-2.68021\t1.007956676423037e+28\n-2.6666\t1.0056246395760812e+28\n-2.65299\t1.0035293573579889e+28\n-2.63939\t1.0014948117648476e+28\n-2.62578\t9.995344091354052e+27\n-2.61218\t9.979404995942718e+27\n-2.59857\t9.972903812904057e+27\n-2.58497\t9.980928196194037e+27\n-2.57136\t1.000295465126952e+28\n-2.55775\t1.0030663555176147e+28\n-2.54415\t1.0051950738387848e+28\n-2.53054\t1.0059211176146511e+28\n-2.51694\t1.0052679878099184e+28\n-2.50333\t1.0035844931542254e+28\n-2.48973\t1.001103823259834e+28\n-2.47612\t9.980344377817346e+27\n-2.46251\t9.948684309720983e+27\n-2.44891\t9.922658562731634e+27\n-2.4353\t9.90841829154738e+27\n-2.4217\t9.909340880317488e+27\n-2.40809\t9.928473010993276e+27\n-2.39448\t9.970456804271686e+27\n-2.38088\t1.0040535461412003e+28\n-2.36727\t1.0141783152519873e+28\n-2.35367\t1.0273765039386074e+28\n-2.34006\t1.0434296798812066e+28\n-2.32646\t1.06214448783724e+28\n-2.31285\t1.083365568135841e+28\n-2.29924\t1.1068936363489575e+28\n-2.28564\t1.1325332076057053e+28\n-2.27203\t1.1603814473717344e+28\n-2.25843\t1.1908341756877163e+28\n-2.24482\t1.2248025169808968e+28\n-2.23122\t1.2635904980345536e+28\n-2.21761\t1.3083973622887328e+28\n-2.204\t1.3594369356865737e+28\n-2.1904\t1.4155633374575885e+28\n-2.17679\t1.475010974366389e+28\n-2.16319\t1.536713381078108e+28\n-2.14958\t1.6004741533228433e+28\n-2.13597\t1.6658730131697094e+28\n-2.12237\t1.7310145351076465e+28\n-2.10876\t1.792056531875467e+28\n-2.09516\t1.8441696349700204e+28\n-2.08155\t1.8837212425798266e+28\n-2.06795\t1.9098239282564202e+28\n-2.05434\t1.9248875681697746e+28\n-2.04073\t1.9326446315043403e+28\n-2.02713\t1.934838439523365e+28\n-2.01352\t1.9291206219748816e+28\n-1.99992\t1.910476166807002e+28\n-1.98631\t1.875872258106665e+28\n-1.9727\t1.8281998897975306e+28\n-1.9591\t1.7752046045815658e+28\n-1.94549\t1.724309752094521e+28\n-1.93189\t1.6783133825245924e+28\n-1.91828\t1.6350413798786704e+28\n-1.90468\t1.5903125801064524e+28\n-1.89107\t1.5415282080661716e+28\n-1.87746\t1.4893013715603914e+28\n-1.86386\t1.4370396354184024e+28\n-1.85025\t1.3887688227828854e+28\n-1.83665\t1.3469105556153561e+28\n-1.82304\t1.3116255504932064e+28\n-1.80944\t1.2815968058490518e+28\n-1.79583\t1.2552465110062038e+28\n-1.78222\t1.231390874057099e+28\n-1.76862\t1.2092905199401042e+28\n-1.75501\t1.1884368239839625e+28\n-1.74141\t1.1684543430323696e+28\n-1.7278\t1.1490909928850731e+28\n-1.71419\t1.1302840386315007e+28\n-1.70059\t1.1121148939928946e+28\n-1.68698\t1.0947098168467019e+28\n-1.67338\t1.078189717545466e+28\n-1.65977\t1.06267112522396e+28\n-1.64617\t1.0482690116675977e+28\n-1.63256\t1.0349984625255795e+28\n-1.61895\t1.0226389533762034e+28\n-1.60535\t1.0107276793931713e+28\n-1.59174\t9.987342130142176e+27\n-1.57814\t9.863460617709312e+27\n-1.56453\t9.73617929904908e+27\n-1.55093\t9.608947233907693e+27\n-1.53732\t9.48576587197222e+27\n-1.52371\t9.37019000387599e+27\n-1.51011\t9.264890389951264e+27\n-1.4965\t9.171202316547947e+27\n-1.4829\t9.088052713668834e+27\n-1.46929\t9.012343112805651e+27\n-1.45568\t8.940636650321612e+27\n-1.44208\t8.870669915939353e+27\n-1.42847\t8.799910246811827e+27\n-1.41487\t8.722442529866498e+27\n-1.40126\t8.627175904638303e+27\n-1.38766\t8.497225514337887e+27\n-1.37405\t8.314384912995038e+27\n-1.36044\t8.062735644768224e+27\n-1.34684\t7.733176972802336e+27\n-1.33323\t7.325495746631067e+27\n-1.31963\t6.851474064675361e+27\n-1.30602\t6.340109771975923e+27\n-1.29242\t5.837063413538772e+27\n-1.27881\t5.393590734110548e+27\n-1.2652\t5.047454359680435e+27\n-1.2516\t4.808379561722474e+27\n-1.23799\t4.6584251127384e+27\n-1.22439\t4.5667962116876454e+27\n-1.21078\t4.5062806177659786e+27\n-1.19717\t4.4587266736793893e+27\n-1.18357\t4.4147104456729305e+27\n-1.16996\t4.3691567573487444e+27\n-1.15636\t4.321019276334143e+27\n-1.14275\t4.2722130732579863e+27\n-1.12915\t4.225110385220229e+27\n-1.11554\t4.180966379513457e+27\n-1.10193\t4.139821303298781e+27\n-1.08833\t4.10132231374883e+27\n-1.07472\t4.065259731597669e+27\n-1.06112\t4.03142068782767e+27\n-1.04751\t3.9988935701672084e+27\n-1.0339\t3.96587964010812e+27\n-1.0203\t3.930326949147273e+27\n-1.00669\t3.8916191246774253e+27\n-0.99309\t3.851757079174566e+27\n-0.97948\t3.81461167013866e+27\n-0.96588\t3.7835118725461693e+27\n-0.95227\t3.7592528727317926e+27\n-0.93866\t3.7400413735284967e+27\n-0.92506\t3.7231678685025306e+27\n-0.91145\t3.706718788084656e+27\n-0.89785\t3.690137426787601e+27\n-0.88424\t3.673627459638814e+27\n-0.87064\t3.657490318173614e+27\n-0.85703\t3.642032124738644e+27\n-0.84342\t3.6275684771194064e+27\n-0.82982\t3.61420613818151e+27\n-0.81621\t3.6013704835384457e+27\n-0.80261\t3.5876673102501513e+27\n-0.789\t3.571536735920798e+27\n-0.77539\t3.552164998602864e+27\n-0.76179\t3.530083473402501e+27\n-0.74818\t3.5070717603176945e+27\n-0.73458\t3.4854476830371055e+27\n-0.72097\t3.467137663952984e+27\n-0.70737\t3.453102287407119e+27\n-0.69376\t3.443317911710465e+27\n-0.68015\t3.437073691315828e+27\n-0.66655\t3.4334163595470773e+27\n-0.65294\t3.4313856135111035e+27\n-0.63934\t3.4301783863101933e+27\n-0.62573\t3.4292739040717746e+27\n-0.61213\t3.428479562083112e+27\n-0.59852\t3.427808494615898e+27\n-0.58491\t3.427200659285256e+27\n-0.57131\t3.4263859591754714e+27\n-0.5577\t3.4251081821723326e+27\n-0.5441\t3.4233339296992507e+27\n-0.53049\t3.421087969239988e+27\n-0.51688\t3.4181158711886324e+27\n-0.50328\t3.414040212866504e+27\n-0.48967\t3.408949087710163e+27\n-0.47607\t3.4036144156301685e+27\n-0.46246\t3.398941523210978e+27\n-0.44886\t3.3953532401848344e+27\n-0.43525\t3.3928432808645706e+27\n-0.42164\t3.3915314485712595e+27\n-0.40804\t3.391931293328042e+27\n-0.39443\t3.3945922029565325e+27\n-0.38083\t3.39951474035409e+27\n-0.36722\t3.406009168624452e+27\n-0.35361\t3.412988626785139e+27\n-0.34001\t3.4194744239626754e+27\n-0.3264\t3.4249745878659835e+27\n-0.3128\t3.429607983653873e+27\n-0.29919\t3.4339078627570224e+27\n-0.28559\t3.438486188420033e+27\n-0.27198\t3.44377479673288e+27\n-0.25837\t3.4500659252407015e+27\n-0.24477\t3.4576918710172945e+27\n-0.23116\t3.4670903805748946e+27\n-0.21756\t3.478664206973302e+27\n-0.20395\t3.492647234064853e+27\n-0.19034\t3.508979982362031e+27\n-0.17674\t3.5272912210570944e+27\n-0.16313\t3.546926019073766e+27\n-0.14953\t3.5669248240487474e+27\n-0.13592\t3.58620227605918e+27\n-0.12232\t3.6038907626436095e+27\n-0.10871\t3.619818131026649e+27\n-0.0951\t3.6347876357384654e+27\n-0.0815\t3.6500881240969103e+27\n-0.06789\t3.6665934004343797e+27\n-0.05429\t3.684477306218335e+27\n-0.04068\t3.704205545196469e+27\n-0.02708\t3.7279013662039547e+27\n-0.01347\t3.759755540072675e+27\n0.00014\t3.8046553292990725e+27\n0.01374\t3.865897905158869e+27\n0.02735\t3.9436457573561353e+27\n0.04095\t4.0349441438413936e+27\n0.05456\t4.1355323068778905e+27\n0.06817\t4.242265432741527e+27\n0.08177\t4.354457912450001e+27\n0.09538\t4.4731170508258327e+27\n0.10898\t4.5989551006596104e+27\n0.12259\t4.731660592079792e+27\n0.13619\t4.8701502291204997e+27\n0.1498\t5.015411146115581e+27\n0.16341\t5.171169723576399e+27\n0.17701\t5.340983472806844e+27\n0.19062\t5.522385777583235e+27\n0.20422\t5.70349406230619e+27\n0.21783\t5.867355171973551e+27\n0.23143\t6.00107059507059e+27\n0.24504\t6.101324584708762e+27\n0.25865\t6.173134995571616e+27\n0.27225\t6.225498522319215e+27\n0.28586\t6.267251433864533e+27\n0.29946\t6.304280886044647e+27\n0.31307\t6.339255293786159e+27\n0.32667\t6.371998564032174e+27\n0.34028\t6.402095747613463e+27\n0.35389\t6.429984778674717e+27\n0.36749\t6.456057433777251e+27\n0.3811\t6.480006933860837e+27\n0.39471\t6.499861449479664e+27\n0.40831\t6.51229275618708e+27\n0.42192\t6.513729364061461e+27\n0.43552\t6.502813939939708e+27\n0.44913\t6.482971714246536e+27\n0.46273\t6.461690160008418e+27\n0.47634\t6.446090491704084e+27\n0.48995\t6.439218640755042e+27\n0.50355\t6.440163088705894e+27\n0.51716\t6.446393049034123e+27\n0.53076\t6.455133156315068e+27\n0.54437\t6.46370157990176e+27\n0.55797\t6.469730210608202e+27\n0.57158\t6.473260327573997e+27\n0.58519\t6.477842874967194e+27\n0.59879\t6.489236855659653e+27\n0.6124\t6.511553015242163e+27\n0.626\t6.544071970890932e+27\n0.63961\t6.581811611904655e+27\n0.65321\t6.619062470379e+27\n0.66682\t6.652466769756007e+27\n0.68043\t6.681626729235876e+27\n0.69403\t6.70789517880284e+27\n0.70764\t6.733518266548615e+27\n0.72124\t6.76081334708073e+27\n0.73485\t6.791219842760358e+27\n0.74846\t6.824729216310898e+27\n0.76206\t6.860084424115239e+27\n0.77567\t6.895846137628436e+27\n0.78927\t6.931201439249003e+27\n0.80288\t6.9660925381815e+27\n0.81648\t7.000917684306859e+27\n0.83009\t7.036456865731109e+27\n0.8437\t7.073183197683827e+27\n0.8573\t7.111786792326179e+27\n0.87091\t7.152280971562309e+27\n0.88451\t7.192953026363635e+27\n0.89812\t7.229800662697047e+27\n0.91173\t7.258495481326581e+27\n0.92533\t7.278309186886936e+27\n0.93894\t7.293642135659705e+27\n0.95254\t7.310743238850841e+27\n0.96615\t7.333406518470914e+27\n0.97975\t7.361885465963574e+27\n0.99336\t7.394559406018302e+27\n1.00697\t7.42962331443977e+27\n1.02057\t7.466074483400548e+27\n1.03418\t7.503161538743653e+27\n1.04778\t7.540840199210238e+27\n1.06139\t7.579234677484014e+27\n1.07499\t7.618424248276264e+27\n1.0886\t7.658365380857952e+27\n1.10221\t7.698982553166852e+27\n1.11581\t7.740274170327115e+27\n1.12942\t7.782318944152665e+27\n1.14302\t7.825288089256625e+27\n1.15663\t7.869468495659228e+27\n1.17023\t7.915198370856534e+27\n1.18384\t7.962707001705788e+27\n1.19745\t8.011951889456444e+27\n1.21105\t8.062696523401827e+27\n1.22466\t8.114704955732621e+27\n1.23827\t8.168024094562011e+27\n1.25187\t8.223163455815402e+27\n1.26547\t8.281066267832705e+27\n1.27908\t8.342827553608093e+27\n1.29269\t8.409337910578482e+27\n1.30629\t8.481194197576031e+27\n1.3199\t8.558880506328799e+27\n1.33351\t8.642822481055821e+27\n1.34711\t8.733273425568293e+27\n1.36072\t8.830499496500421e+27\n1.37432\t8.935246720484287e+27\n1.38793\t9.049662175676565e+27\n1.40153\t9.17656438296604e+27\n1.41514\t9.318606559050645e+27\n1.42875\t9.474301341477531e+27\n1.44235\t9.637619067561766e+27\n1.45596\t9.797372433757582e+27\n1.46956\t9.938670365718405e+27\n1.48317\t1.0045385854131484e+28\n1.49677\t1.0105628349018192e+28\n1.51038\t1.0119380963457781e+28\n1.52399\t1.0100853947442072e+28\n1.53759\t1.0070711450623443e+28\n1.5512\t1.0045068192389e+28\n1.5648\t1.0030741797908938e+28\n1.57841\t1.0027515270251672e+28\n1.59201\t1.0030949882299024e+28\n1.60562\t1.0034923468566863e+28\n1.61923\t1.0033960538819417e+28\n1.63283\t1.0027371074711743e+28\n1.64644\t1.0018278593684558e+28\n1.66004\t1.000880043415077e+28\n1.67365\t9.997071998611309e+27\n1.68726\t9.980404795467128e+27\n1.70086\t9.959973216239908e+27\n1.71447\t9.940729256622288e+27\n1.72807\t9.927715820230256e+27\n1.74168\t9.92245610731513e+27\n1.75528\t9.921108437223347e+27\n1.76889\t9.915219123613061e+27\n1.7825\t9.897114843513366e+27\n1.7961\t9.865551969027521e+27\n1.80971\t9.827863833122072e+27\n1.82331\t9.794285692277604e+27\n1.83692\t9.77169784090353e+27\n1.85053\t9.761768894402042e+27\n1.86413\t9.741562098853201e+27\n1.87774\t9.667205703239159e+27\n1.89134\t9.421989319838208e+27\n1.90495\t8.809357165542233e+27\n1.91855\t7.640282397041644e+27\n1.93216\t5.919571125797073e+27'
num_w_bcc='6'
vol_w_bcc='1.0659e-28'
button_w_bcc = Button(
    description='W bcc',
    disabled=False,
    button_style='', # 'success', 'info', 'warning', 'danger' or ''
    tooltip='W bcc',
    icon='' # (FontAwesome names without the `fa-` prefix)
)
###################################################################################################
















###########################################DEFINE TEXT INPUT/OUTPUT AREAS WITH DEFAULT##############################


# input for DOS and E
default_input_free_e='-0.39280212388434976\t0\n0\t0\n0.031424169910747986\t1.2075842267210155e+27\n0.06284833982149597\t1.7077819911366868e+27\n0.09427250973224395\t2.091597235099573e+27\n0.12569667964299194\t2.415168453442031e+27\n0.15712084955373992\t2.700240419504709e+27\n0.1885450194644879\t2.957965176899883e+27\n0.21996918937523588\t3.1949675510680467e+27\n0.2513933592859839\t3.4155639822733735e+27\n0.28281752919673186\t3.6227526801630466e+27\n0.31424169910747984\t3.8187166229315745e+27\n0.3456658690182278\t4.0051037827850755e+27\n0.3770900389289758\t4.183194470199146e+27\n0.40851420883972384\t4.3540068488841527e+27\n0.43993837875047176\t4.5183664420623854e+27\n0.4713625486612198\t4.676953599233255e+27\n0.5027867185719678\t4.830336906884062e+27\n0.5342108884827157\t4.97899731860057e+27\n0.5656350583934637\t5.12334597341006e+27\n0.5970592283042117\t5.263737610090615e+27\n0.6284833982149597\t5.400480839009418e+27\n0.6599075681257076\t5.533846126983768e+27\n0.6913317380364556\t5.664072088326441e+27\n0.7227559079472038\t5.791370501563861e+27\n0.7541800778579516\t5.915930353799766e+27\n0.7856042477686995\t6.037921133605077e+27\n0.8170284176794477\t6.157495536357312e+27\n0.8484525875901955\t6.274791705298719e+27\n0.8798767575009435\t6.389935102136093e+27\n0.9113009274116917\t6.503040079388747e+27\n0.9427250973224396\t6.61421121062533e+27\n0.9741492672331874\t6.72354442265292e+27\n1.0055734371439355\t6.831127964546747e+27\n1.0369976070546836\t6.937043241370055e+27\n1.0684217769654314\t7.041365534984202e+27\n1.0998459468761794\t7.144164630094183e+27\n1.1312701167869275\t7.245505360326093e+27\n1.1626942866976755\t7.345448086477744e+27\n1.1941184566084233\t7.444049116963491e+27\n1.2255426265191713\t7.54136107877022e+27\n1.2569667964299194\t7.637433245863149e+27\n1.2883909663406674\t7.732311830858938e+27\n1.3198151362514152\t7.826040244866269e+27\n1.3512393061621635\t7.918659329639829e+27\n1.3826634760729113\t8.010207565570151e+27\n1.4140876459836593\t8.100721258514126e+27\n1.4455118158944076\t8.190234708039085e+27\n1.476935985805155\t8.278780359291667e+27\n1.5083601557159032\t8.366388940398292e+27\n1.5397843256266512\t8.45308958704711e+27\n1.571208495537399\t8.538909955683433e+27\n1.6026326654481473\t8.623876326565394e+27\n1.6340568353588953\t8.708013697768305e+27\n1.6654810052696432\t8.791345871090832e+27\n1.696905175180391\t8.873895530699649e+27\n1.7283293450911392\t8.955684315248981e+27\n1.759753515001887\t9.036732884124771e+27\n1.791177684912635\t9.117060978388123e+27\n1.8226018548233833\t9.196687476927374e+27\n1.8540260247341311\t9.275630448271329e+27\n1.8854501946448792\t9.35390719846651e+27\n1.916874364555627\t9.431534315377798e+27\n1.9482985344663748\t9.508527709733739e+27\n1.979722704377123\t9.584902653204139e+27\n2.011146874287871\t9.660673813768124e+27\n2.042571044198619\t9.73585528860462e+27\n2.073995214109367\t9.810460634714148e+27\n2.105419384020115\t9.884502897460315e+27\n2.136843553930863\t9.95799463720114e+27\n2.168267723841611\t1.0030947954164257e+28\n2.199691893752359\t1.0103374511705361e+28\n2.231116063663107\t1.0175285558076634e+28\n2.262540233573855\t1.024669194682012e+28\n2.293964403484603\t1.0317604155890734e+28\n2.325388573395351\t1.0388032305604323e+28\n2.3568127433060986\t1.0457986175497866e+28\n2.3882369132168466\t1.052747522018123e+28\n2.4196610831275946\t1.0596508584253365e+28\n2.4510852530383427\t1.0665095116349439e+28\n2.4825094229490907\t1.0733243382380093e+28\n2.5139335928598388\t1.0800961678018836e+28\n2.545357762770587\t1.086825804048914e+28\n2.576781932681335\t1.093514025969865e+28\n2.6082061025920824\t1.1001615888764142e+28\n2.6396302725028304\t1.1067692253967536e+28\n2.671054442413579\t1.1133376464180056e+28\n2.702478612324327\t1.1198675419788887e+28\n2.7339027822350745\t1.1263595821158055e+28\n2.7653269521458226\t1.1328144176652881e+28\n2.796751122056571\t1.1392326810255224e+28\n2.8281752919673186\t1.1456149868794726e+28\n2.8595994618780667\t1.1519619328819455e+28\n2.891023631788815\t1.1582741003127723e+28\n2.9224478016995623\t1.164552054698121e+28\n2.95387197161031\t1.170796346401828e+28\n2.9852961415210584\t1.17700751118849e+28\n3.0167203114318064\t1.1831860707599532e+28\n3.048144481342554\t1.189332533266719e+28\n3.0795686512533025\t1.1954473937956808e+28\n3.1109928211640505\t1.2015311348355228e+28\n3.142416991074798\t1.2075842267210153e+28\n3.1738411609855466\t1.2136071280573655e+28\n3.2052653308962946\t1.2196002861257048e+28\n3.236689500807042\t1.2255641372707326e+28\n3.2681136707177907\t1.2314991072714623e+28\n3.2995378406285387\t1.2374056116959638e+28\n3.3309620105392863\t1.2432840562409366e+28\n3.3623861804500343\t1.249134837056901e+28\n3.393810350360782\t1.2549583410597437e+28\n3.42523452027153\t1.260754946229313e+28\n3.4566586901822784\t1.2665250218957113e+28\n3.488082860093026\t1.272268929013904e+28\n3.519507030003774\t1.2779870204272187e+28\n3.5509311999145226\t1.2836796411202813e+28\n3.58235536982527\t1.2893471284619003e+28\n3.613779539736018\t1.2949898124383843e+28\n3.6452037096467667\t1.3006080158777494e+28\n3.6766278795575142\t1.3062020546652458e+28\n3.7080520494682623\t1.3117722379506145e+28\n3.7394762193790108\t1.3173188683474542e+28\n3.7709003892897583\t1.322842242125066e+28\n3.8023245592005055\t1.328342649393117e+28\n3.833748729111254\t1.3338203742794527e+28\n3.865172899022002\t1.339275695101361e+28\n3.8965970689327496\t1.344708884530584e+28\n3.928021238843498\t1.3501202097523543e+28\n3.959445408754246\t1.3555099326187156e+28\n3.9908695786649937\t1.360878309796379e+28\n4.022293748575742\t1.3662255929093494e+28\n4.05371791848649\t1.371552028676549e+28\n4.085142088397238\t1.3768578590446478e+28\n4.116566258307986\t1.3821433213163044e+28\n4.147990428218734\t1.387408648274011e+28\n4.179414598129482\t1.392654068299724e+28\n4.21083876804023\t1.3978798054904531e+28\n4.242262937950978\t1.4030860797699765e+28\n4.273687107861726\t1.4082731069968404e+28\n4.305111277772474\t1.41344109906879e+28\n4.336535447683222\t1.4185902640237746e+28\n4.36795961759397\t1.4237208061376698e+28\n4.399383787504718\t1.4288329260188366e+28\n4.430807957415466\t1.4339268206996492e+28\n4.462232127326214\t1.4390026837251062e+28\n4.493656297236962\t1.444060705238638e+28\n4.52508046714771\t1.4491010720652186e+28\n4.556504637058458\t1.4541239677918866e+28\n4.587928806969206\t1.4591295728457683e+28\n4.619352976879954\t1.4641180645697013e+28\n4.650777146790702\t1.4690896172955488e+28\n4.68220131670145\t1.4740444024152854e+28\n4.713625486612197\t1.478982588449942e+28\n4.745049656522945\t1.483904341116483e+28\n4.776473826433693\t1.4888098233926982e+28\n4.807897996344441\t1.4936991955801714e+28\n4.839322166255189\t1.4985726153654036e+28\n4.870746336165937\t1.5034302378791503e+28\n4.902170506076685\t1.508272215754044e+28\n4.933594675987433\t1.5130986991805483e+28\n4.965018845898181\t1.5179098359613198e+28\n4.9964430158089295\t1.5227057715640192e+28\n5.0278671857196775\t1.5274866491726298e+28\n5.0592913556304255\t1.5322526097373378e+28\n5.090715525541174\t1.5370037920230178e+28\n5.1221396954519225\t1.5417403326563753e+28\n5.15356386536267\t1.5464623661717877e+28\n5.184988035273417\t1.5511700250558925e+28\n5.216412205184165\t1.555863439790958e+28\n5.247836375094914\t1.560542738897082e+28\n5.279260545005661\t1.5652080489732539e+28\n5.310684714916409\t1.5698594947373202e+28\n5.342108884827158\t1.574497199064885e+28\n5.373533054737905\t1.5791212830271848e+28\n5.404957224648654\t1.5837318659279658e+28\n5.436381394559402\t1.5883290653393993e+28\n5.467805564470149\t1.592912997137064e+28\n5.499229734380897\t1.5974837755340233e+28\n5.530653904291645\t1.6020415131140302e+28\n5.562078074202394\t1.6065863208638823e+28\n5.593502244113142\t1.611118308204956e+28\n5.62492641402389\t1.6156375830239445e+28\n5.656350583934637\t1.6201442517028252e+28\n5.687774753845385\t1.6246384191480765e+28\n5.719198923756133\t1.6291201888191722e+28\n5.750623093666882\t1.6335896627563696e+28\n5.78204726357763\t1.638046941607817e+28\n5.813471433488377\t1.6424921246559987e+28\n5.844895603399125\t1.646925309843537e+28\n5.876319773309873\t1.651346593798372e+28\n5.90774394322062\t1.6557560718583333e+28\n5.93916811313137\t1.6601538380951306e+28\n5.970592283042117\t1.664539985337765e+28\n6.002016452952865\t1.6689146051953947e+28\n6.033440622863613\t1.6732777880796585e+28\n6.064864792774361\t1.677629623226476e+28\n6.096288962685108\t1.6819701987173442e+28\n6.127713132595858\t1.6862996015001354e+28\n6.159137302506605\t1.690617917409422e+28\n6.190561472417353\t1.694925231186327e+28\n6.221985642328101\t1.699221626497932e+28\n6.253409812238849\t1.7035071859562355e+28\n6.284833982149596\t1.7077819911366866e+28\n6.316258152060345\t1.7120461225963046e+28\n6.347682321971093\t1.716299659891388e+28\n6.379106491881841\t1.7205426815948358e+28\n6.410530661792589\t1.7247752653130788e+28\n6.441954831703337\t1.7289974877026443e+28\n6.473379001614084\t1.7332094244863512e+28\n6.504803171524833\t1.7374111504691582e+28\n6.536227341435581\t1.741602739553661e+28\n6.567651511346329\t1.7457842647552622e+28\n6.599075681257077\t1.7499557982170081e+28\n6.630499851167825\t1.7541174112241115e+28\n6.661924021078573\t1.7582691742181663e+28\n6.6933481909893215\t1.7624111568110568e+28\n6.724772360900069\t1.7665434277985755e+28\n6.756196530810817\t1.770666055173757e+28\n6.787620700721564\t1.7747791061399298e+28\n6.819044870632312\t1.7788826471234976e+28\n6.85046904054306\t1.782976743786457e+28\n6.881893210453809\t1.7870614610386546e+28\n6.913317380364557\t1.7911368630497962e+28\n6.944741550275304\t1.7952030132612074e+28\n6.976165720186052\t1.7992599743973551e+28\n7.0075898900968\t1.8033078084771402e+28\n7.039014060007548\t1.8073465768249541e+28\n7.070438229918297\t1.811376340081523e+28\n7.101862399829045\t1.8153971582145291e+28\n7.133286569739792\t1.819409090529022e+28\n7.16471073965054\t1.8234121956776245e+28\n7.196134909561288\t1.8274065316705394e+28\n7.227559079472036\t1.8313921558853536e+28\n7.258983249382785\t1.8353691250766581e+28\n7.290407419293533\t1.8393374953854748e+28\n7.3218315892042805\t1.8432973223485044e+28\n7.3532557591150285\t1.8472486609071935e+28\n7.3846799290257765\t1.8511915654166301e+28\n7.416104098936525\t1.8551260896542658e+28\n7.4475282688472735\t1.859052286828475e+28\n7.4789524387580215\t1.8629702095869477e+28\n7.510376608668769\t1.8668799100249295e+28\n7.541800778579517\t1.870781439693302e+28\n7.573224948490265\t1.8746748496065116e+28\n7.604649118401011\t1.8785601902503553e+28\n7.63607328831176\t1.882437511589616e+28\n7.667497458222508\t1.8863068630755595e+28\n7.698921628133256\t1.890168293653296e+28\n7.730345798044004\t1.8940218517689987e+28\n7.761769967954751\t1.897867585376999e+28\n7.793194137865499\t1.9017055419467477e+28\n7.824618307776248\t1.9055357684696525e+28\n7.856042477686996\t1.9093583114657872e+28\n7.887466647597744\t1.9131732169904889e+28\n7.918890817508492\t1.9169805306408278e+28\n7.950314987419239\t1.9207802975619684e+28\n7.981739157329987\t1.9245725624534133e+28\n8.013163327240736\t1.9283573695751399e+28\n8.044587497151484\t1.9321347627536248e+28\n8.076011667062232\t1.935904785387768e+28\n8.10743583697298\t1.9396674804547078e+28\n8.138860006883728\t1.9434228905155378e+28\n8.170284176794476\t1.947171057720924e+28\n8.201708346705225\t1.9509120238166239e+28\n8.233132516615973\t1.9546458301489124e+28\n8.26455668652672\t1.9583725176699106e+28\n8.295980856437469\t1.9620921269428295e+28\n8.327405026348217\t1.9658046981471203e+28\n8.358829196258965\t1.9695102710835364e+28\n8.390253366169713\t1.9732088851791135e+28\n8.42167753608046\t1.976900579492063e+28\n8.453101705991209\t1.9805853927165845e+28\n8.484525875901957\t1.984263363187599e+28\n8.515950045812703\t1.9879345288853993e+28\n8.547374215723451\t1.991598927440228e+28\n8.5787983856342\t1.9952565961367784e+28\n8.610222555544947\t1.9989075719186163e+28\n8.641646725455695\t2.002551891392538e+28\n8.673070895366443\t2.0061895908328515e+28\n8.704495065277191\t2.0098207061855887e+28\n8.73591923518794\t2.013445273072649e+28\n8.767343405098687\t2.017063326795876e+28\n8.798767575009435\t2.0206749023410723e+28\n8.830191744920183\t2.0242800343819415e+28\n8.861615914830931\t2.0278787572839772e+28\n8.89304008474168\t2.0314711051082817e+28\n8.924464254652428\t2.035057111615327e+28\n8.955888424563176\t2.0386368102686584e+28\n8.987312594473924\t2.0422102342385377e+28\n9.018736764384672\t2.0457774164055283e+28\n9.05016093429542\t2.049338389364024e+28\n9.081585104206168\t2.0528931854257267e+28\n9.113009274116916\t2.0564418366230636e+28\n9.144433444027664\t2.0599843747125593e+28\n9.175857613938412\t2.0635208311781468e+28\n9.20728178384916\t2.0670512372344337e+28\n9.238705953759908\t2.0705756238299183e+28\n9.270130123670656\t2.074094021650154e+28\n9.301554293581404\t2.0776064611208646e+28\n9.332978463492152\t2.081112972411017e+28\n9.3644026334029\t2.0846135854358405e+28\n9.395826803313646\t2.08810832985981e+28\n9.427250973224394\t2.091597235099573e+28\n9.458675143135142\t2.095080330326843e+28\n9.49009931304589\t2.0985576444712418e+28\n9.52152348295664\t2.102029206223106e+28\n9.552947652867386\t2.105495044036246e+28\n9.584371822778134\t2.10895518613067e+28\n9.615795992688883\t2.1124096604952606e+28\n9.64722016259963\t2.1158584948904207e+28\n9.678644332510379\t2.119301716850673e+28\n9.710068502421128\t2.1227393536872264e+28\n9.741492672331875\t2.126171432490503e+28\n9.772916842242623\t2.129597980132629e+28\n9.80434101215337\t2.1330190232698877e+28\n9.835765182064119\t2.136434588345143e+28\n9.867189351974867\t2.1398447015902194e+28\n9.898613521885617\t2.1432493890282547e+28\n9.930037691796363\t2.1466486764760185e+28\n9.961461861707111\t2.1500425895461926e+28\n9.992886031617859\t2.1534311536496236e+28\n10.024310201528607\t2.156814393997546e+28\n10.055734371439355\t2.1601923356037672e+28\n10.087158541350105\t2.1635650032868235e+28\n10.118582711260851\t2.1669324216721126e+28\n10.150006881171599\t2.170294615193988e+28\n10.181431051082347\t2.173651608097828e+28\n10.212855220993095\t2.177003424442076e+28\n10.244279390903845\t2.180350088100253e+28\n10.275703560814591\t2.1836916227629384e+28\n10.30712773072534\t2.18702805193973e+28\n10.338551900636087\t2.1903593989611713e+28\n10.369976070546834\t2.193685686980657e+28\n10.401400240457582\t2.197006938976309e+28\n10.43282441036833\t2.2003231777528284e+28\n10.46424858027908\t2.203634425943323e+28\n10.495672750189827\t2.206940706011109e+28\n10.527096920100576\t2.2102420402514894e+28\n10.558521090011322\t2.213538450793507e+28\n10.58994525992207\t2.2168299596016772e+28\n10.621369429832818\t2.2201165884776923e+28\n10.652793599743568\t2.22339835906211e+28\n10.684217769654316\t2.226675292836011e+28\n10.715641939565064\t2.229947411122646e+28\n10.74706610947581\t2.2332147350890473e+28\n10.778490279386558\t2.2364772857476327e+28\n10.809914449297308\t2.2397350839577775e+28\n10.841338619208054\t2.2429881504273727e+28\n10.872762789118804\t2.24623650571436e+28\n10.904186959029552\t2.2494801702282495e+28\n10.935611128940298\t2.252719164231611e+28\n10.967035298851048\t2.2559535078415563e+28\n10.998459468761794\t2.259183221031193e+28\n11.029883638672544\t2.262408323631066e+28\n11.06130780858329\t2.2656288353305763e+28\n11.092731978494037\t2.2688447756793844e+28\n11.124156148404788\t2.2720561640887955e+28\n11.155580318315534\t2.2752630198331235e+28\n11.187004488226284\t2.278465362051045e+28\n11.21842865813703\t2.2816632097469275e+28\n11.24985282804778\t2.28485658179215e+28\n11.281276997958527\t2.2880454969263965e+28\n11.312701167869275\t2.291229973758945e+28\n11.344125337780023\t2.2944100307699294e+28\n11.37554950769077\t2.297585686311595e+28\n11.406973677601517\t2.3007569586095306e+28\n11.438397847512267\t2.303923865763891e+28\n11.469822017423015\t2.307086425750601e+28\n11.501246187333765\t2.3102446564225485e+28\n11.53267035724451\t2.313398575510756e+28\n11.56409452715526\t2.3165482006255446e+28\n11.595518697066007\t2.3196935492576814e+28\n11.626942866976753\t2.3228346387795136e+28\n11.658367036887503\t2.3259714864460847e+28\n11.68979120679825\t2.329104109396242e+28\n11.721215376708997\t2.3322325246537312e+28\n11.752639546619745\t2.335356749128272e+28\n11.784063716530493\t2.338476799616627e+28\n11.81548788644124\t2.341592692803656e+28\n11.846912056351991\t2.344704445263354e+28\n11.87833622626274\t2.347812073459881e+28\n11.909760396173487\t2.35091559374858e+28\n11.941184566084234\t2.35401502237698e+28\n11.972608735994983\t2.357110375485787e+28\n12.00403290590573\t2.3602016691098666e+28\n12.03545707581648\t2.363288919179213e+28\n12.066881245727226\t2.3663721415199064e+28\n12.098305415637974\t2.3694513518550584e+28\n12.129729585548722\t2.3725265658057476e+28\n12.16115375545947\t2.3755977988919487e+28\n12.192577925370216\t2.378665066533438e+28\n12.224002095280968\t2.3817283840507043e+28\n12.255426265191716\t2.3847877666658377e+28\n12.286850435102464\t2.387843229503413e+28\n12.31827460501321\t2.3908947875913616e+28\n12.34969877492396\t2.393942455861835e+28\n12.381122944834706\t2.3969862491520575e+28\n12.412547114745456\t2.400026182205166e+28\n12.443971284656202\t2.4030622696710455e+28\n12.47539545456695\t2.406094526107154e+28\n12.506819624477698\t2.409122965979334e+28\n12.538243794388444\t2.4121476036626195e+28\n12.569667964299192\t2.4151684534420307e+28\n12.601092134209942\t2.418185529513363e+28\n12.63251630412069\t2.4211988459839643e+28\n12.663940474031438\t2.4242084168735027e+28\n12.695364643942186\t2.427214256114731e+28\n12.726788813852933\t2.430216377554238e+28\n12.758212983763682\t2.43321479495319e+28\n12.789637153674429\t2.436209521988072e+28\n12.821061323585178\t2.4392005722514095e+28\n12.852485493495925\t2.442187959252493e+28\n12.883909663406675\t2.445171696418088e+28\n12.91533383331742\t2.4481517970931386e+28\n12.946758003228169\t2.451128274541465e+28\n12.978182173138919\t2.4541011419464505e+28\n13.009606343049667\t2.4570704124117254e+28\n13.041030512960415\t2.4600360989618386e+28\n13.072454682871163\t2.4629982145429247e+28\n13.103878852781909\t2.4659567720233637e+28\n13.135303022692659\t2.468911784194434e+28\n13.166727192603405\t2.471863263770955e+28\n13.198151362514155\t2.4748112233919275e+28\n13.229575532424901\t2.4777556756211666e+28\n13.26099970233565\t2.480696632947922e+28\n13.292423872246397\t2.4836341077875e+28\n13.323848042157145\t2.4865681124818733e+28\n13.355272212067895\t2.4894986593002857e+28\n13.386696381978643\t2.492425760439852e+28\n13.418120551889391\t2.4953494280261487e+28\n13.449544721800137\t2.498269674113802e+28\n13.480968891710885\t2.501186510687065e+28\n13.512393061621633\t2.504099949660394e+28\n13.543817231532381\t2.5070100028790158e+28\n13.575241401443128\t2.5099166821194875e+28\n13.606665571353878\t2.512819999090256e+28\n13.638089741264624\t2.515719965432203e+28\n13.669513911175374\t2.5186165927191975e+28\n13.70093808108612\t2.521509892458626e+28\n13.732362250996871\t2.5243998760919334e+28\n13.763786420907618\t2.527286554995144e+28\n13.795210590818368\t2.530169940479389e+28\n13.826634760729114\t2.5330500437914227e+28\n13.858058930639862\t2.5359268761141324e+28\n13.889483100550608\t2.538800448567047e+28\n13.920907270461358\t2.5416707722068354e+28\n13.952331440372104\t2.544537858027808e+28\n13.983755610282854\t2.547401716962403e+28\n14.0151797801936\t2.5502623598816757e+28\n14.04660395010435\t2.553119797595778e+28\n14.078028120015096\t2.5559740408544374e+28\n14.109452289925848\t2.5588251003474262e+28\n14.140876459836594\t2.56167298670503e+28\n14.172300629747342\t2.564517710498511e+28\n14.20372479965809\t2.5673592822405626e+28\n14.235148969568838\t2.570197712385767e+28\n14.266573139479584\t2.5730330113310408e+28\n14.297997309390334\t2.5758651894160802e+28\n14.32942147930108\t2.5786942569238006e+28\n14.360845649211827\t2.581520224080773e+28\n14.392269819122577\t2.5843431010576554e+28\n14.423693989033323\t2.5871628979696183e+28\n14.455118158944073\t2.5899796248767686e+28\n14.48654232885482\t2.5927932917845696e+28\n14.51796649876557\t2.5956039086442515e+28\n14.549390668676317\t2.5984114853532285e+28\n14.580814838587067\t2.601216031755499e+28\n14.612239008497813\t2.604017557642052e+28\n14.643663178408561\t2.6068160727512657e+28\n14.675087348319309\t2.6096115867693003e+28\n14.706511518230057\t2.6124041093304915e+28\n14.737935688140803\t2.615193650017737e+28\n14.769359858051553\t2.617980218362879e+28\n14.8007840279623\t2.620763823847086e+28\n14.83220819787305\t2.623544475901229e+28\n14.863632367783797\t2.626322183906253e+28\n14.895056537694547\t2.629096957193546e+28\n14.926480707605293\t2.6318688050453078e+28\n14.957904877516043\t2.6346377366949085e+28\n14.98932904742679\t2.63740376132725e+28\n15.020753217337537\t2.640166888079119e+28\n15.052177387248285\t2.642927126039542e+28\n15.083601557159033\t2.645684484250132e+28\n15.11502572706978\t2.648438971705435e+28\n15.14644989698053\t2.651190597353271e+28\n15.177874066891276\t2.653939370095076e+28\n15.209298236802022\t2.656685298786234e+28\n15.240722406712774\t2.6594283922364134e+28\n15.27214657662352\t2.662168659209895e+28\n15.30357074653427\t2.664906108425898e+28\n15.334994916445016\t2.6676407485589055e+28\n15.366419086355766\t2.6703725882389844e+28\n15.397843256266512\t2.673101636052102e+28\n15.42926742617726\t2.675827900540444e+28\n15.460691596088008\t2.678551390202722e+28\n15.492115765998756\t2.681272113494486e+28\n15.523539935909502\t2.6839900788284297e+28\n15.554964105820252\t2.686705294574694e+28\n15.586388275730998\t2.689417769061168e+28\n15.61781244564175\t2.692127510573785e+28\n15.649236615552496\t2.69483452735682e+28\n15.680660785463246\t2.697538827613184e+28\n15.712084955373992\t2.7002404195047086e+28'
DOS_input = Textarea(
    value=default_input_free_e,
    placeholder='Insert DOS and E',
    description='',
    disabled=False,
    layout=Layout(width='280px')
)


# output of Entropy and T
default_output_free_e='4.714212308302336e+29\t0.0\n4.714212214355608e+29\t2.0\n4.714211751345443e+29\t4.0\n4.714211138978883e+29\t6.0\n4.714210476842126e+29\t8.0\n4.714209792275503e+29\t10.0\n4.714209096418591e+29\t12.0\n4.714208394275212e+29\t14.0\n4.714207687653443e+29\t16.0\n4.714206978253402e+29\t18.0\n4.714206267085662e+29\t20.0\n4.714205554283321e+29\t22.0\n4.714204840408659e+29\t24.0\n4.714204125843628e+29\t26.0\n4.7142034104439765e+29\t28.0\n4.714202694467196e+29\t30.0\n4.714201978060546e+29\t32.0\n4.7142012609923346e+29\t34.0\n4.7142005433123326e+29\t36.0\n4.714199824970865e+29\t38.0\n4.71419910563425e+29\t40.0\n4.714198385141995e+29\t42.0\n4.7141976631955634e+29\t44.0\n4.7141969395184324e+29\t46.0\n4.7141962135426704e+29\t48.0\n4.71419548489951e+29\t50.0\n4.714194753150632e+29\t52.0\n4.714194017649423e+29\t54.0\n4.714193277898833e+29\t56.0\n4.714192533318652e+29\t58.0\n4.714191783344175e+29\t60.0\n4.71419102730528e+29\t62.0\n4.714190264625854e+29\t64.0\n4.714189494696856e+29\t66.0\n4.7141887169323894e+29\t68.0\n4.714187930721941e+29\t70.0\n4.71418713545742e+29\t72.0\n4.714186330594759e+29\t74.0\n4.714185515606964e+29\t76.0\n4.714184689914527e+29\t78.0\n4.71418385303176e+29\t80.0\n4.714183004469247e+29\t82.0\n4.714182143771545e+29\t84.0\n4.714181270468574e+29\t86.0\n4.7141803841506825e+29\t88.0\n4.7141794844246016e+29\t90.0\n4.714178570906303e+29\t92.0\n4.7141776432283636e+29\t94.0\n4.714176701072264e+29\t96.0\n4.7141757441072065e+29\t98.0\n4.7141747720457636e+29\t100.0\n4.714173784617247e+29\t102.0\n4.714172781550801e+29\t104.0\n4.714171762616125e+29\t106.0\n4.7141707275789484e+29\t108.0\n4.71416967623479e+29\t110.0\n4.714168608392844e+29\t112.0\n4.7141675238690554e+29\t114.0\n4.71416642249048e+29\t116.0\n4.714165304109009e+29\t118.0\n4.714164168575684e+29\t120.0\n4.7141630157620454e+29\t122.0\n4.714161845542856e+29\t124.0\n4.7141606578026206e+29\t126.0\n4.714159452439979e+29\t128.0\n4.7141582293572285e+29\t130.0\n4.71415698846297e+29\t132.0\n4.7141557296784645e+29\t134.0\n4.714154452925369e+29\t136.0\n4.7141531581389694e+29\t138.0\n4.7141518452487616e+29\t140.0\n4.714150514202251e+29\t142.0\n4.714149164940012e+29\t144.0\n4.7141477974154185e+29\t146.0\n4.71414641158465e+29\t148.0\n4.7141450074031184e+29\t151.0\n4.714143584835712e+29\t153.0\n4.71414214384462e+29\t155.0\n4.7141406844007895e+29\t157.0\n4.7141392064721215e+29\t159.0\n4.714137710035397e+29\t161.0\n4.7141361950619475e+29\t163.0\n4.714134661532919e+29\t165.0\n4.714133109425027e+29\t167.0\n4.7141315387220154e+29\t169.0\n4.714129949405875e+29\t171.0\n4.714128341459872e+29\t173.0\n4.714126714871777e+29\t175.0\n4.714125069627994e+29\t177.0\n4.714123405715301e+29\t179.0\n4.714121723124976e+29\t181.0\n4.714120021846183e+29\t183.0\n4.714118301869868e+29\t185.0\n4.714116563188541e+29\t187.0\n4.714114805793572e+29\t189.0\n4.714113029678865e+29\t191.0\n4.714111234838197e+29\t193.0\n4.7141094212658505e+29\t195.0\n4.7141075889568176e+29\t197.0\n4.714105737906482e+29\t199.0\n4.7141038681105406e+29\t201.0\n4.7141019795650894e+29\t203.0\n4.7141000722666824e+29\t205.0\n4.714098146212815e+29\t207.0\n4.7140962013996176e+29\t209.0\n4.714094237823778e+29\t211.0\n4.7140922554850034e+29\t213.0\n4.7140902543797364e+29\t215.0\n4.714088234505345e+29\t217.0\n4.7140861958622696e+29\t219.0\n4.7140841384472016e+29\t221.0\n4.714082062258094e+29\t223.0\n4.714079967295813e+29\t225.0\n4.714077853557518e+29\t227.0\n4.714075721042656e+29\t229.0\n4.714073569749931e+29\t231.0\n4.714071399677538e+29\t233.0\n4.7140692108269985e+29\t235.0\n4.714067003195856e+29\t237.0\n4.7140647767827905e+29\t239.0\n4.714062531589555e+29\t241.0\n4.714060267613874e+29\t243.0\n4.714057984854567e+29\t245.0\n4.7140556833136425e+29\t247.0\n4.7140533629888654e+29\t249.0\n4.714051023879159e+29\t251.0\n4.714048665987442e+29\t253.0\n4.714046289310301e+29\t255.0\n4.714043893847904e+29\t257.0\n4.7140414796004975e+29\t259.0\n4.714039046568407e+29\t261.0\n4.714036594750848e+29\t263.0\n4.714034124147184e+29\t265.0\n4.714031634757726e+29\t267.0\n4.714029126582902e+29\t269.0\n4.714026599622014e+29\t271.0\n4.714024053874395e+29\t273.0\n4.7140214893413475e+29\t275.0\n4.714018906021394e+29\t277.0\n4.714016303915397e+29\t279.0\n4.714013683021477e+29\t281.0\n4.714011043342402e+29\t283.0\n4.714008384876296e+29\t285.0\n4.714005707623071e+29\t287.0\n4.714003011583048e+29\t289.0\n4.7140002967566075e+29\t291.0\n4.7139975631432866e+29\t293.0\n4.713994810742641e+29\t295.0\n4.713992039555005e+29\t297.0\n4.71398924958153e+29\t299.0\n4.713986440820681e+29\t301.0\n4.7139836132713484e+29\t303.0\n4.713980766936652e+29\t305.0\n4.713977901814531e+29\t307.0\n4.71397501790485e+29\t309.0\n4.713972115208111e+29\t311.0\n4.7139691937247914e+29\t313.0\n4.713966253454386e+29\t315.0\n4.7139632943963935e+29\t317.0\n4.713960316551265e+29\t319.0\n4.713957319920208e+29\t321.0\n4.7139543045016884e+29\t323.0\n4.713951270295151e+29\t325.0\n4.7139482173014746e+29\t327.0\n4.713945145521697e+29\t329.0\n4.7139420549547724e+29\t331.0\n4.713938945599818e+29\t333.0\n4.7139358174577276e+29\t335.0\n4.713932670529609e+29\t337.0\n4.713929504814379e+29\t339.0\n4.7139263203110616e+29\t341.0\n4.7139231170217414e+29\t343.0\n4.7139198949448376e+29\t345.0\n4.7139166540812596e+29\t347.0\n4.713913394429862e+29\t349.0\n4.7139101159913964e+29\t351.0\n4.713906818766703e+29\t353.0\n4.7139035027549364e+29\t355.0\n4.713900167955377e+29\t357.0\n4.713896814368769e+29\t359.0\n4.713893441996013e+29\t361.0\n4.713890050836236e+29\t363.0\n4.713886640888597e+29\t365.0\n4.713883212155063e+29\t367.0\n4.7138797646339676e+29\t369.0\n4.7138762983259096e+29\t371.0\n4.7138728132308986e+29\t373.0\n4.713869309348942e+29\t375.0\n4.713865786680015e+29\t377.0\n4.7138622452241855e+29\t379.0\n4.713858684981439e+29\t381.0\n4.713855105951781e+29\t383.0\n4.7138515081352244e+29\t385.0\n4.71384789153178e+29\t387.0\n4.713844256142026e+29\t389.0\n4.713840601964399e+29\t391.0\n4.713836929000874e+29\t393.0\n4.713833237250487e+29\t395.0\n4.7138295267123304e+29\t397.0\n4.7138257973872784e+29\t399.0\n4.713822049276438e+29\t401.0\n4.713818282378787e+29\t403.0\n4.713814496693354e+29\t405.0\n4.713810692221101e+29\t407.0\n4.71380686896312e+29\t409.0\n4.71380302691834e+29\t411.0\n4.7137991660864394e+29\t413.0\n4.713795286467812e+29\t415.0\n4.713791388062281e+29\t417.0\n4.71378747087003e+29\t419.0\n4.713783534891247e+29\t421.0\n4.7137795801257426e+29\t423.0\n4.7137756065733876e+29\t425.0\n4.713771614234362e+29\t427.0\n4.713767603108859e+29\t429.0\n4.7137635731967176e+29\t431.0\n4.713759524497703e+29\t433.0\n4.713755457012622e+29\t435.0\n4.713751370740705e+29\t437.0\n4.7137472656817205e+29\t439.0\n4.713743141836733e+29\t441.0\n4.7137389992051584e+29\t443.0\n4.713734837786397e+29\t445.0\n4.713730657581093e+29\t447.0\n4.713726458589864e+29\t449.0\n4.713722240812098e+29\t452.0\n4.713718004247196e+29\t454.0\n4.713713748895762e+29\t456.0\n4.713709474759047e+29\t458.0\n4.713705181835606e+29\t460.0\n4.7137008701244804e+29\t462.0\n4.7136965396268465e+29\t464.0\n4.713692190344085e+29\t466.0\n4.713687822274828e+29\t468.0\n4.713683435417909e+29\t470.0\n4.7136790297745296e+29\t472.0\n4.713674605346129e+29\t474.0\n4.7136701621313135e+29\t476.0\n4.7136657001288034e+29\t478.0\n4.7136612193398455e+29\t480.0\n4.7136567197666304e+29\t482.0\n4.713652201405782e+29\t484.0\n4.713647664258617e+29\t486.0\n4.7136431083251404e+29\t488.0\n4.713638533605376e+29\t490.0\n4.713633940099299e+29\t492.0\n4.713629327806977e+29\t494.0\n4.713624696728411e+29\t496.0\n4.7136200468636e+29\t498.0\n4.713615378212556e+29\t500.0\n4.713610690775269e+29\t502.0\n4.713605984552416e+29\t504.0\n4.713601259542809e+29\t506.0\n4.713596515747179e+29\t508.0\n4.7135917531650845e+29\t510.0\n4.7135869717968486e+29\t512.0\n4.713582171642756e+29\t514.0\n4.7135773527025746e+29\t516.0\n4.713572514975977e+29\t518.0\n4.713567658463283e+29\t520.0\n4.713562783164831e+29\t522.0\n4.713557889080315e+29\t524.0\n4.7135529762093894e+29\t526.0\n4.713548044553e+29\t528.0\n4.713543094110513e+29\t530.0\n4.713538124881496e+29\t532.0\n4.713533136867011e+29\t534.0\n4.7135281300665285e+29\t536.0\n4.7135231044795845e+29\t538.0\n4.713518060106679e+29\t540.0\n4.713512996948375e+29\t542.0\n4.713507915004158e+29\t544.0\n4.713502814273491e+29\t546.0\n4.7134976947568896e+29\t548.0\n4.713492556455615e+29\t550.0\n4.713487399368264e+29\t552.0\n4.713482223493784e+29\t554.0\n4.713477028833417e+29\t556.0\n4.7134718153886285e+29\t558.0\n4.7134665831579865e+29\t560.0\n4.713461332140241e+29\t562.0\n4.713456062336666e+29\t564.0\n4.713450773748788e+29\t566.0\n4.713445466375141e+29\t568.0\n4.713440140214344e+29\t570.0\n4.713434795269153e+29\t572.0\n4.7134294315377046e+29\t574.0\n4.713424049020578e+29\t576.0\n4.713418647717792e+29\t578.0\n4.7134132276293526e+29\t580.0\n4.713407788755255e+29\t582.0\n4.7134023310955646e+29\t584.0\n4.713396854650272e+29\t586.0\n4.713391359419391e+29\t588.0\n4.713385845402944e+29\t590.0\n4.713380312600935e+29\t592.0\n4.7133747610133695e+29\t594.0\n4.713369190640906e+29\t596.0\n4.713363601482364e+29\t598.0\n4.713357993538334e+29\t600.0\n'
DOS_output = Textarea(
    value=default_output_free_e,
    placeholder='Press Calc-Button',
    description='',
    disabled=False,
    layout=Layout(width='280px')
)


default_num_electrons='1' # default number of electrons per unitcell
num_electrons=Text(
    value=default_num_electrons,
    placeholder='Type number of electrons',
    description='',
    disabled=False,
    layout=Layout(width='auto')
)

default_T_min='0'
input_T_min=Text(
    value=default_T_min,
    placeholder='Type T_min',
    description='',
    disabled=False,
    layout=Layout(width='auto')
)

default_T_max='600'
input_T_max=Text(
    value=default_T_max,
    placeholder='Type T_min',
    description='',
    disabled=False,
    layout=Layout(width='auto')
)

default_volume_unitcell='1e-29' # default volume of primitive unitcell
vol_unitcell=Text(
    value=default_volume_unitcell,
    placeholder='Type volume of unitcell',
    description='',
    disabled=False,
    layout=Layout(width='auto')
)
############################################################################################################

#initialize output widgets for Plots
out1 =Output()
out2 =Output()

#############################generate default arrays for first plot without calculation#######################
DOS_free=default_input_free_e.split('\n')[:]
DOS_default=[]
E_default=[]
for i in range(len(DOS_free)-1):
    row=DOS_free[i].split('\t')
    DOS_default.append(np.float(row[1]))
    E_default.append(np.float(row[0]))

    
Entropy_free=default_output_free_e.split('\n')[:]
Ent_default=[]
T_default=[]
for i in range(len(Entropy_free)-1):
    row=Entropy_free[i].split('\t')
    Ent_default.append(np.float(row[0]))
    T_default.append(np.float(row[1]))

#############################################################################################################



##################################DEFINE ROUTINE IF BUTTON CALCULATE IS CLICKED#############################
def on_button_calc_clicked(b): 
    global DOS_unit
    global vol_unit
    global f_unit
    label_unit_vol.value = '$~$'+vol_unit
    label_unit_DOS.value = DOS_unit
    label_unit_f.value = f_unit
    
    DOS_free_e=DOS_input.value
    DOS_free=DOS_free_e.split('\n')[:]
    DOS_list=[]
    E_list=[]
    for i in range(len(DOS_free)-1):
        row=DOS_free[i].split('\t')
        DOS_list.append(np.float(row[1]))
        E_list.append(np.float(row[0]))
    DOS_array=np.array(DOS_list)
    E_array=np.array(E_list)
    global DOS
    global E
    DOS=DOS_array
    E=E_array
    num_elec=np.float(num_electrons.value)    #get number of electrons from input
    vol_unit=np.float(vol_unitcell.value)     #get volume of unitcell from input
    T_min=np.float(input_T_min.value)    #get T_min from input        
    T_max=np.float(input_T_max.value)    #get T_max from input
    
    global f
    global T
    [f,T]=calcutlation(DOS,E,num_elec,vol_unit,T_min,T_max)
    t=np.round(T)
    out=''
    for i in range(np.size(t)):
        out=out+str(f[i])+'\t'+str(t[i])+'\n'
    DOS_output.value=out
    with out1:
        clear_output(True)
        plt.figure(figsize=(7.5,7))
        plt.plot(E,DOS)
        min_DOS=np.min(DOS)
        max_DOS=np.max(DOS)
        min_E=np.min(E)
        max_E=np.max(E)       
        plt.ylim([min_DOS-min_DOS/10,max_DOS+max_DOS/10])
        plt.xlim([min_E-min_E/10,max_E+max_E/10])
        plt.xlabel('E [eV]')
        plt.ylabel(r'D(E)'+DOS_unit)
        plt.title('Density of states')
        plt.show()
    with out2:
        clear_output(True)
        plt.figure(figsize=(7.5,7))
        plt.plot(T,f)
        plt.ylim([np.min(f[~np.isnan(f)]),np.max(f[~np.isnan(f)])])
        plt.xlim([np.min(T[~np.isnan(T)]),np.max(T[~np.isnan(T)])])
        plt.xlabel('T [K]')
        plt.ylabel(r'f(T)'+f_unit)
        plt.title('Helmholz free energy density')
        plt.show()
        
button_calc.on_click(on_button_calc_clicked)    # if button clicked perform on_button_clicked
#############################################################################################################   
    
######################################DEFINE FUNCTION OF BUTTONS FOR PREDEFINED DOS##########################
#free electron model
def on_button_1dime_clicked(b):
    DOS_input.value=DOS_free_e_1
    vol_unitcell.value=vol_free_e_1
    num_electrons.value=num_free_e_1
    global DOS_unit
    global vol_unit
    global f_unit
    DOS_unit=DOS_unit_1d
    vol_unit=vol_unit_1d
    f_unit=f_unit_1d
button_1dime.on_click(on_button_1dime_clicked)     #if button 1dim is clicked perform on_button_1dime_clicked

def on_button_2dime_clicked(b):
    DOS_input.value=DOS_free_e_2
    vol_unitcell.value=vol_free_e_2
    num_electrons.value=num_free_e_2
    global DOS_unit
    global vol_unit
    global f_unit
    DOS_unit=DOS_unit_2d
    vol_unit=vol_unit_2d
    f_unit=f_unit_2d
button_2dime.on_click(on_button_2dime_clicked)       

def on_button_3dime_clicked(b):
    DOS_input.value=DOS_free_e_3
    vol_unitcell.value=vol_free_e_3
    num_electrons.value=num_free_e_3
    global DOS_unit
    global vol_unit
    global f_unit
    DOS_unit=DOS_unit_3d
    vol_unit=vol_unit_3d
    f_unit=f_unit_3d
button_3dime.on_click(on_button_3dime_clicked)     

#tight binding
def on_button_2d_square_clicked(b):
    DOS_input.value=DOS_2d_square
    vol_unitcell.value=vol_2d_square
    num_electrons.value=num_2d_square
    global DOS_unit
    global vol_unit
    global f_unit
    DOS_unit=DOS_unit_2d
    vol_unit=vol_unit_2d
    f_unit=f_unit_2d
button_2d_square.on_click(on_button_2d_square_clicked)     

def on_button_2d_hexagonal_clicked(b):
    DOS_input.value=DOS_2d_hexagonal
    vol_unitcell.value=vol_2d_hexagonal
    num_electrons.value=num_2d_hexagonal
    global DOS_unit
    global vol_unit
    global f_unit
    DOS_unit=DOS_unit_2d
    vol_unit=vol_unit_2d
    f_unit=f_unit_2d
button_2d_hexagonal.on_click(on_button_2d_hexagonal_clicked)     

def on_button_graphene_clicked(b):
    DOS_input.value=DOS_graphene
    vol_unitcell.value=vol_graphene
    num_electrons.value=num_graphene
    global DOS_unit
    global vol_unit
    global f_unit
    DOS_unit=DOS_unit_2d
    vol_unit=vol_unit_2d
    f_unit=f_unit_2d
button_graphene.on_click(on_button_graphene_clicked)     

def on_button_simple_cubic_clicked(b):
    DOS_input.value=DOS_simple_cubic
    vol_unitcell.value=vol_simple_cubic
    num_electrons.value=num_simple_cubic
    global DOS_unit
    global vol_unit
    global f_unit
    DOS_unit=DOS_unit_3d
    vol_unit=vol_unit_3d
    f_unit=f_unit_3d
button_simple_cubic.on_click(on_button_simple_cubic_clicked)     

def on_button_al_fcc_clicked(b):
    DOS_input.value=DOS_al_fcc
    vol_unitcell.value=vol_al_fcc
    num_electrons.value=num_al_fcc
    global DOS_unit
    global vol_unit
    global f_unit
    DOS_unit=DOS_unit_3d
    vol_unit=vol_unit_3d
    f_unit=f_unit_3d
button_al_fcc.on_click(on_button_al_fcc_clicked)    

def on_button_au_fcc_clicked(b):
    DOS_input.value=DOS_au_fcc
    vol_unitcell.value=vol_au_fcc
    num_electrons.value=num_au_fcc
    global DOS_unit
    global vol_unit
    global f_unit
    DOS_unit=DOS_unit_3d
    vol_unit=vol_unit_3d
    f_unit=f_unit_3d
button_au_fcc.on_click(on_button_au_fcc_clicked)     

def on_button_cu_fcc_clicked(b):
    DOS_input.value=DOS_cu_fcc
    vol_unitcell.value=vol_cu_fcc
    num_electrons.value=num_cu_fcc
    global DOS_unit
    global vol_unit
    global f_unit
    DOS_unit=DOS_unit_3d
    vol_unit=vol_unit_3d
    f_unit=f_unit_3d
button_cu_fcc.on_click(on_button_cu_fcc_clicked)   

def on_button_na_bcc_clicked(b):
    DOS_input.value=DOS_na_bcc
    vol_unitcell.value=vol_na_bcc
    num_electrons.value=num_na_bcc
    global DOS_unit
    global vol_unit
    global f_unit
    DOS_unit=DOS_unit_3d
    vol_unit=vol_unit_3d
    f_unit=f_unit_3d
button_na_bcc.on_click(on_button_na_bcc_clicked)     

def on_button_pt_fcc_clicked(b):
    DOS_input.value=DOS_pt_fcc
    vol_unitcell.value=vol_pt_fcc
    num_electrons.value=num_pt_fcc
    global DOS_unit
    global vol_unit
    global f_unit
    DOS_unit=DOS_unit_3d
    vol_unit=vol_unit_3d
    f_unit=f_unit_3d
button_pt_fcc.on_click(on_button_pt_fcc_clicked)     

def on_button_w_bcc_clicked(b):
    DOS_input.value=DOS_w_bcc
    vol_unitcell.value=vol_w_bcc
    num_electrons.value=num_w_bcc
    global DOS_unit
    global vol_unit
    global f_unit
    DOS_unit=DOS_unit_3d
    vol_unit=vol_unit_3d
    f_unit=f_unit_3d
button_w_bcc.on_click(on_button_w_bcc_clicked)     

#################################################################################################################

##########Define unit labels

label_unit_vol=Label(value='$~$'+vol_unit)
label_unit_DOS=Label(value=DOS_unit)
label_unit_f=Label(value=f_unit)

###############################################LAYOUT OF GUI#####################################################
box_input= HBox(
    children=(Label('$E~[eV]~~/~~D(E)~$'),label_unit_DOS,Label('$~$'), DOS_input,Label('$~~~~~~~~f(T)~$ '),label_unit_f,Label('$~~ /~~ T ~[K]$'),DOS_output)
)
figures = HBox(
    children=(out1,out2)
)
box_T = HBox(
    children = (Label('$T_{min}$:$~$'),input_T_min,Label('$~[K]~~~~~~T_{max}$:'),input_T_max,Label('$~[K]$'))
)
box_parameters= HBox(
    children = (Label('Number of electrons per primitive unitcell:$~$'),num_electrons,Label('$~~~~~~~~$Volume of primitive unitcell: '),vol_unitcell,label_unit_vol)
)
box_predefined_e = HBox(
    children = (Label('Free electron model: '),button_1dime,button_2dime,button_3dime)
) 
box_predefined_tb_r1 = HBox(
    children = (Label('Tight binding: '),button_2d_square,button_2d_hexagonal,button_graphene,button_simple_cubic)
)
box_predefined_tb_r2 = HBox(
    children = (Label('               '),button_al_fcc,button_au_fcc,button_cu_fcc,button_na_bcc,button_pt_fcc,button_w_bcc)
)

box = VBox(
    children=(figures,box_parameters,box_T,button_calc,box_input,box_predefined_e,box_predefined_tb_r1,box_predefined_tb_r2),
    layout=Layout(border='solid 1px gray', width='960px')
)

display(box) #display layout


#define default plots
with out1: 
    plt.figure(figsize=(7.5,7))
    plt.plot(E_default,DOS_default)
    min_DOS=np.min(DOS_default)
    max_DOS=np.max(DOS_default)
    min_E=np.min(E_default)
    max_E=np.max(E_default)       
    plt.ylim([min_DOS-min_DOS/10,max_DOS+max_DOS/10])
    plt.xlim([min_E-min_E/10,max_E+max_E/10])
    plt.xlabel('E [eV]')
    plt.ylabel(r'D(E)'+ DOS_unit)
    plt.title('Density of states')
    plt.show()
with out2:
    plt.figure(figsize=(7.5,7))
    plt.plot(T_default,Ent_default)
    plt.ylim([np.min(Ent_default),np.max(Ent_default)])
    plt.xlim([np.min(T_default),np.max(T_default)])
    plt.xlabel('T [K]')
    plt.ylabel(r'f(T)'+f_unit)
    plt.title('Helmholz free energy density')
    plt.show()
    
    
    
    
    

In [4]:
HTML('''<script>
code_show=true; 
function code_toggle() {
 if (code_show){
 $('div.input').hide();
 } else {
 $('div.input').show();
 }
 code_show = !code_show
} 
$( document ).ready(code_toggle);
</script>
The raw code for this IPython notebook is by default hidden for easier reading.
To toggle on/off the raw code, click <a href="javascript:code_toggle()">here</a>.''')